In [ ]:
#From https://github.com/gabrielo/Allegheny-County-Property-Assessments

In [1]:
import json, os, re, sqlite3, thread, urllib, urllib2
def exec_ipynb(filename_or_url):
    nb = (urllib2.urlopen(filename_or_url) if re.match(r'https?:', filename_or_url) else open(filename_or_url)).read()
    jsonNb = json.loads(nb)
    #check for the modified formatting of Jupyter Notebook v4
    if(jsonNb['nbformat'] == 4):
        exec '\n'.join([''.join(cell['source']) for cell in jsonNb['cells'] if cell['cell_type'] == 'code']) in globals()
    else:
        exec '\n'.join([''.join(cell['input']) for cell in jsonNb['worksheets'][0]['cells'] if cell['cell_type'] == 'code']) in globals()

exec_ipynb('timelapse-utilities.ipynb')

In [2]:
# assessments/cd/AC Property Assessments_10012017.xls (which is actually TDF) from Amy Gottsegen and Randy Sargent buying a CD from the county assessors office
# assessments/Allegheny_County_Parcel_Boundaries.geojson from https://data.wprdc.org/dataset/allegheny-county-parcel-boundaries
import array, csv, datetime, json, math, numpy, os, random, re 
from dateutil.parser import parse
from shapely.geometry import mapping, shape
from PIL import Image
import matplotlib.colors as colors
import matplotlib.pyplot as plt
import pandas,numbers
from operator import itemgetter, attrgetter
import string
import calendar,time
from IPython.core.display import HTML

# Use geopandas.  Boilerplate from https://docs.google.com/document/d/1utZuLHcKQEZNXTQLOysTNCxTHrqxczAUymmtplpn27Q/edit#heading=h.f50xoxwmcir
import pandas as pd
import geopandas as gpd
from geopandas import GeoSeries, GeoDataFrame
%matplotlib inline

pd.options.display.max_colwidth = 300
pd.options.display.max_rows = 100
pd.set_option('display.max_columns', 500)

# Built-in time handling fails for times before 1900.  Use arrow instead.  
# See https://arrow.readthedocs.io/en/latest/ for info
import arrow

def LonLatToPixelXY(lonlat):
    (lon, lat) = lonlat
    x = (lon + 180.0) * 256.0 / 360.0
    y = 128.0 - math.log(math.tan((lat + 90.0) * math.pi / 360.0)) * 128.0 / math.pi
    return [x, y]

# This does the same as above, but takes a GeoJSON point (which is what centroid returns)
def PointToPixelXY(point):
    lon=point.x
    lat=point.y
    x = (lon + 180.0) * 256.0 / 360.0
    y = 128.0 - math.log(math.tan((lat + 90.0) * math.pi / 360.0)) * 128.0 / math.pi
    return [x, y]

def GetCentroid(geometry):
    s = shape(geometry)
    return (s.centroid.x, s.centroid.y)   

def GetEpoch(date):
    return (date - datetime.datetime(1970, 1, 1)).total_seconds()

def HexToRgb(hex_string):
    rgb = colors.hex2color(hex_string)
    r,g,b = tuple([int(255*x) for x in rgb])
    return (r,g,b)

In [61]:
from shapely.geometry import Point

# Google geocoding API to geocode an address
# Assumes key is in google_api_key.txt
# Use as second level lookup only for those which fail census lookup

re_noalnum = re.compile('^([^\w]+)$')

def geocode_address_google(address):
    if(pandas.isnull(address) or re_noalnum.match(address)):
        #print "Skipping address lookup for %r, no alphanumeric characters" %(address)
        return None

    try:
        geocode_address_google.conn
    except:
        geocode_address_google.conn = sqlite3.connect('geocoding_cache')
        geocode_address_google.cur = geocode_address_google.conn.cursor()
        geocode_address_google.cur.execute(('CREATE TABLE IF NOT EXISTS kvs'
                                     ' (key PRIMARY KEY, value)'
                                     ' WITHOUT ROWID;'))
        geocode_address_google.conn.commit()

    geocode_address_google.cur.execute('SELECT value FROM kvs WHERE key=?', (address,))
    rows = geocode_address_google.cur.fetchall()
    if rows:
        #print "Google: Found %r in cache" % (address)
        return json.loads(rows[0][0])
        
    #print "Google: %r not found in cache, fetching" % (address)

    api_key = open('google-api-key-do-not-commit.txt').read()
    payload = {'address':address, 'key':api_key}
    result = json.load(urllib2.urlopen('https://maps.googleapis.com/maps/api/geocode/json?%s' % urllib.urlencode(payload)))
    
    geocode_address_google.cur.execute(('INSERT OR REPLACE INTO kvs (key, value)'
                                 ' VALUES (?, ?);'),
                                 (address, json.dumps(result)))
    geocode_address_google.conn.commit()
    
    # If the result succeeded and generated a formatted address, cache under that key too
    try:
        if(result['status']=='OK'):
            if(len(result['results'])== 1):
                canonical = result['results'][0]['formatted_address']
                #print "Google: Storing canonical addr of %r for %r" % (canonical, address)
                geocode_address_google.cur.execute(('INSERT OR REPLACE INTO kvs (key, value)'
                                                     ' VALUES (?, ?);'),
                                                     (canonical, json.dumps(result)))
                geocode_address_google.conn.commit()
            else:
                print "Google: Fetch %r seemed to succeed, but results empty or non-unique" % (address)

        else:
            print "Google: Fetch %r failed" % (address)

    except:
        #pass
        raise
    
    return result

def get_canonical_address_google(raw_addr):
    if(pandas.isnull(raw_addr) or re_noalnum.match(raw_addr)):
        #print "Skipping address lookup for %r, no alphanumeric characters" %(raw_addr)
        return None

    try:
        result=geocode_address_google(raw_addr)
        if(result['status']=='OK' and len(result['results'])== 1):
            return(result['results'][0]['formatted_address'])
        else:
            return None
    except:
        return None

def get_canonical_zip_google(addr):
    if(pandas.isnull(addr) or re_noalnum.match(addr)):
        #print "Skipping address lookup for %r, no alphanumeric characters" %(addr)
        return None

    try:
        result=geocode_address_google(addr)
        if(result['status']=='OK' and len(result['results'])== 1):
            addr_comps = result['results'][0]['address_components']
            for i in range(0, len(addr_comps)):
                if('postal_code' in addr_comps[i]['types']):
                    return addr_comps[i]['short_name']
        
        return None
    except:
        return None
    
def get_canonical_coords_google(addr):
    if(pandas.isnull(addr) or re_noalnum.match(addr)):
        #print "Skipping address lookup for %r, no alphanumeric characters" %(addr)
        return None

    try:
        result=geocode_address_google(addr)
        if(result['status']=='OK' and len(result['results'])== 1):
            latlon = ['results'][0]['geometry']['location']
            if(latlon):
                return(Point(latlon['lng'], latlon['lat']))
        return None
    except:
        return None


In [52]:
geocode_address_google(apd_2017.iloc[170]['owner_address_raw'])

{u'results': [{u'address_components': [{u'long_name': u'313',
     u'short_name': u'313',
     u'types': [u'street_number']},
    {u'long_name': u'Gist Street',
     u'short_name': u'Gist St',
     u'types': [u'route']},
    {u'long_name': u'Uptown',
     u'short_name': u'Uptown',
     u'types': [u'neighborhood', u'political']},
    {u'long_name': u'Pittsburgh',
     u'short_name': u'Pittsburgh',
     u'types': [u'locality', u'political']},
    {u'long_name': u'Allegheny County',
     u'short_name': u'Allegheny County',
     u'types': [u'administrative_area_level_2', u'political']},
    {u'long_name': u'Pennsylvania',
     u'short_name': u'PA',
     u'types': [u'administrative_area_level_1', u'political']},
    {u'long_name': u'United States',
     u'short_name': u'US',
     u'types': [u'country', u'political']},
    {u'long_name': u'15219',
     u'short_name': u'15219',
     u'types': [u'postal_code']},
    {u'long_name': u'5905',
     u'short_name': u'5905',
     u'types': [u'postal_

In [57]:
get_canonical_address_google(apd_2017.iloc[174]['owner_address_raw'])

In [25]:
apd_2017.iloc[175]['owner_address_raw']

' '

In [30]:
apd_2017.iloc[175]['CHANGENOTICEADDRESS4']

''

In [31]:
apd_2017[apd_2017.owner_address_raw==' ']

PROPERTYOWNER  \
PARID                                                                                  
0011J00246000000                                                     BROWN WILLIAM H   
0011J00258000000                                                       DAVIES DAPHNE   
0011K00271001000                                         HOFF MILTON J & HELEN A (W)   
0025N00080000000  OTTO MILK FACTORY CONDOMINIUMS UNITOWNERS WITH PERCENTAGE INTEREST   
0009N00079000000       LENFANT LOFTS AT 806 PENN UNIT OWNERSWITH PERCENTAGE INTEREST   
0009N00039000000      KEYSTONE LOFTS CONDOMINIUM UNIT OWNERSWITH PERCENTAGE INTEREST   
0025P00076000000                                                   LEMPICKI MARTHA P   
0009S00214000000                            SECURITY PACIFIC NATIONAL BANK (TRUSTEE)   
0009M00257000A00                                         WILLIS I V & ROBERT E JONES   
0009S00108000000                                        ABRAHAM MIKE  & HOFFEEZA (W)   
0009M00200000A00                                                       WILLIS KATE S   
0010N00140000000                                          JONES LOVE  & MARGARET (W)   
0011E00201000000                                                       MORGAN DENNIS   
0011E00204000000                                                        RAY HAROLD M   
0011E00207000000                                      BROWN WILLIE MAY & MAXINE CARR   
0011E00161000000                                                     OKOBI RAPHAEL I   
0011A00059000000                                                    WILLIAMS IRWIN O   
0009M00270000000                                                       RECK TILLIE I   
0009M00278000000                                       KEYSTONE INTER STATE DEV CORP   
0011H00002000000                                    RATTLIFF WILLIAM J & DIANE C (W)   
0011E00207000D00                                         DENHAM ALBERT  & AMANDA (W)   
0011E00232000000                                                       GADSEN ROBERT   
0011F00186000000                                                   THOMPSON ALFRED S   
0011K00045000000                                             HINTON BILL  & GLORIA L   
0011M00201000000                                            KING LUTHER  & MARIE (W)   
0028N00175000000                                                       DEAN HERMON L   
0029C00168000000                                             NATL COUNCIL JR O U A M   
0029B00250000000                                         SCHUYLKILL IMP LAND CO(B&O)   
0029C00013000000                                                          MIKOS MARY   
0029M00242000000                                                          PAGE SALLY   
0029M00246000000                                                      PACELLI NICK S   
0010D00049000000                                         WILSON DOUGLAS W & RUBY (W)   
0010D00050000B00                                    YOUNG LOUIS A & LAURA LOIS SWOPE   
0010F00123000000                              WOODS BETTY LOU & WILLA MAE WOODS KING   
0010D00265000000                                             WILSON R HENRY & LOUISA   
0010D00272000000                                                        HUNTER HELEN   
0010D00280000000                                        EVANS AUGUSTUS  & BESSIE LEE   
0010D00067000000                                                    KELLEY WILLIAM F   
0010D00156000000                                                    OGBURN CORETTA M   
0010D00161000000                                                         WOOD HOWARD   
0010C00076000000                                      FERGUSON WILLIAM A & CLARA (W)   
0010D00360000000                                    BATTLES CLYDE  & JEANNETTE I (W)   
0010F00069000000                                    SUPPLES JOSEPH E & SUSANNA RESSA   
0010D00174000000                                                       FOSTER MOLLIE   
0010D00170000000       

In [34]:
geocode_address_census(apd_2017.iloc[175]['owner_address_raw'])

Skipping address lookup for ' ', no alphanumeric characters


In [37]:
cache_canonical_addresses(['3634 frazier st pittsburgh', apd_2017.iloc[175]['owner_address_raw'], ', -'])

Skipping address lookup for ' ', no alphanumeric characters
Skipping address lookup for ', -', no alphanumeric characters
SimpleThreadPoolExecutor succeeded: all 1 jobs completed


In [43]:
get_canonical_address('3634 frazier st pittsburgh')

u'3634 FRAZIER ST, PITTSBURGH, PA, 15213'

In [46]:
apd_2017.iloc[170]['owner_address_raw']

'313 GIST ST PITTSBURGH PA 15219'

In [48]:
get_canonical_zip(apd_2017.iloc[170]['owner_address_raw'])

u'15219'

In [35]:
geocode_address_census(', -')

Skipping address lookup for ', -', no alphanumeric characters


In [396]:
# Uses Census geocoding API to geocode an address
# Assumes key is in google_api_key.txt

import sqlite3
import urllib,urllib2
import json
from shapely.geometry import Point

# Match if the string contains no alphanumerics
re_noalnum = re.compile('^([^\w]+)$')

def geocode_address_census(address):
    if(pandas.isnull(address) or re_noalnum.match(address)):
        #print "Skipping address lookup for %r, no alphanumeric characters" %(address)
        return None

    try:
        geocode_address_census.sqlite
    except:
        geocode_address_census.sqlite = {}
    
    tpid = '%d.%s' % (os.getpid(), thread.get_ident())
    if not tpid in geocode_address_census.sqlite:
        conn = sqlite3.connect('geocoding_cache_census')
        cur = conn.cursor()
        geocode_address_census.sqlite[tpid] = { 'conn': conn, 'cur': cur }

        cur.execute(('CREATE TABLE IF NOT EXISTS kvs'
                     ' (key PRIMARY KEY, value)'
                     ' WITHOUT ROWID;'))
        conn.commit()
    else:
        conn = geocode_address_census.sqlite[tpid]['conn']
        cur = geocode_address_census.sqlite[tpid]['cur']

    cur.execute('SELECT value FROM kvs WHERE key=?', (address,))
    rows = cur.fetchall()
    if rows:
        return json.loads(rows[0][0])
    
    payload = {'address':address, 'benchmark':4, 'format':'json'}
    result = json.load(urllib2.urlopen('https://geocoding.geo.census.gov/geocoder/locations/onelineaddress?%s' % urllib.urlencode(payload)))
    
    cur.execute(('INSERT OR REPLACE INTO kvs (key, value)'
                 ' VALUES (?, ?);'),
                (address, json.dumps(result)))
    conn.commit()
    
    if len(result['result']['addressMatches']) == 1:
        canonical = result['result']['addressMatches'][0]['matchedAddress']
        cur.execute(('INSERT OR REPLACE INTO kvs (key, value)'
                     ' VALUES (?, ?);'),
                     (canonical, json.dumps(result)))
        conn.commit()
    
    return result

def cache_canonical_addresses(addrs):
    t = SimpleThreadPoolExecutor(25)
    for addr in addrs:
        if(not (pandas.isnull(addr) or re_noalnum.match(addr))):
            t.submit(geocode_address_census, addr)
        else:
            #print "Skipping address lookup for %r, no alphanumeric characters" %(addr)
            pass
    t.shutdown()

def get_canonical_address(raw_addr):
    if(pandas.isnull(raw_addr) or re_noalnum.match(raw_addr)):
        #print "Skipping address lookup for %r, no alphanumeric characters" %(raw_addr)
        return None

    try:
        result=geocode_address_census(raw_addr)
        if len(result['result']['addressMatches']) == 1:
            return(result['result']['addressMatches'][0]['matchedAddress'])
        else:
            return None
    except:
        return None

def get_canonical_zip(addr):
    if(pandas.isnull(addr) or re_noalnum.match(addr)):
        #print "Skipping address lookup for %r, no alphanumeric characters" %(addr)
        return None

    try:
        result=geocode_address_census(addr)
        if len(result['result']['addressMatches']) == 1:
            return(result['result']['addressMatches'][0]['addressComponents']['zip'])
        else:
            return None
    except:
        return None
    
def get_canonical_coords(addr):
    if(pandas.isnull(addr) or re_noalnum.match(addr)):
        #print "Skipping address lookup for %r, no alphanumeric characters" %(addr)
        return None

    try:
        result=geocode_address_census(addr)
        if len(result['result']['addressMatches']) == 1:
            coords = result['result']['addressMatches'][0]['coordinates']
            return(Point(coords['x'], coords['y']))
        else:
            return None
    except:
        return None


def canonicalize_addr_colset(df, col_arr, out_colname):
    for  col_name in col_arr:
        df[col_name]=df[col_name].astype(basestring)
        df[col_name].fillna('', inplace=True)

    df[out_colname] = df[col_arr].apply(lambda x: get_canonical_address(' '.join(x)), axis=1)
    
    

# Create structures to populate with sale and ownership information

In [5]:
# Read in 2017 data to harvest list of residential parcel IDs
# We need to do this before loading the older ADB files because they're missing some of the columns we need.

In [9]:
# For each residential PARID, we want to generate a sorted list of who bought it when.
# For each owner name, we want to generate a sorted list of PARIDs they bought and when they bought it.
# For each change address, we want to generate a sorted list of PARIDs they bought and when they bought it.
# Each of the following is a map indexed on PARID, owner name, or change address.  

# The map indexed on PARID builds up a history of a given property.
#   Each record contains a a list of maps containing a list of date, event_type, owner name, and change address
#   event_type is either PURCHASE or FORECLOSURE

# Each map indexed on owner name or change address builds a history of a given owner/change address.
#   Each record contains a list of maps containing date, event_type, and PARID
#   event_type is either PURCHASE or SALE


# To start with, clear the maps
property_map = {}
owner_map = {}
changeaddr_map = {}

# Also create a map to cache lookups for owner and changeaddress PARID sets at various times
# to speed up runtime
owned_parids_cache={}

# TODO: Create a map of owner and changeaddress to inferred owner type
# 'GOVERNMENT'
# 'INVESTOR' 

# Create a global map of PARIDs to canonical property addresses.  Not all versions of the db have valid 
# property addresses, but at least one hopefully should!
canonical_property_address_map={}

# Create a global map of PARIDs to raw property addresses.  We might have conflicts, but at least we'll have something
# to fall back on if canonical resolution fails
raw_property_address_map={}

In [346]:
# Create functions to update the above maps with info from a given row of an assessment spreadsheet/database.  
# The first argument should be a pandas table, the second an index into the table.
# We expect the index to be PARID
# We expect the following columns to exist and be valid:
#   PROPERTYOWNER
#   CHANGENOTICEADDRESS1 - CHANGENOTICEADDRESS4
#   SALEDATE


# In 2017 the date format is MM-DD-YYYY
# In 2009, an example is 09/16/96 00:00:00

# Setup regular expression for parsing various sorts of dates
re_MDY = re.compile('(\d\d)-(\d\d)-(\d\d\d\d)')
re_YMD = re.compile('(\d\d\d\d)-(\d\d)-(\d\d)')
re_MDY_HMS = re.compile('(\d+)/(\d+)/(\d+) (\d+):(\d+):(\d+)')

# Setup this year to use for dealing with 2-digit dates
this_year = datetime.datetime.now().year
this_date = arrow.now().format('YYYY-MM-DD')

# Utility function to normalize SALEDATE format
# SALEDATE field is in '%m-%d-%Y' format (ex 10-26-2012) when present
def SaledateToEpoch(datestr):
    if(re_YMD.match(datestr)!=None):
        return calendar.timegm(time.strptime(datestr, '%Y-%m-%d'))
    elif(re_MDY.match(datestr)!=None):
        return calendar.timegm(time.strptime(datestr, '%m-%d-%Y'))

# Built-in time handling fails for times before 1900.  Use arrow instead.  
# See https://arrow.readthedocs.io/en/latest/ for info
def SaledateToYMD(datestr):
    # Check which format and parse accordingly
    if(re_YMD.match(datestr)!=None):
        # Already like we want it
        return datestr
    if(re_MDY.match(datestr)!=None):
        return arrow.get(datestr, 'MM-DD-YYYY').format('YYYY-MM-DD')
    elif(re_MDY_HMS.match(datestr)!=None):
        # Some of the 2-digit years are farther back than python's default pivot year of 1969
        # If the year we parse is > this_year, set it back by 100 years
        ad=arrow.get(datestr, 'MM/DD/YY HH:mm:ss')
        if(ad.year>this_year):
            ad = ad.replace(year=(ad.year-100))
        return ad.format('YYYY-MM-DD')
    else:
        raise Exception('Unrecognized saledate format %r' % (datestr))

def merge_dwelling_col(df):
    r_df = pd.merge(df,dwelling_col.to_frame(),on='PARID', left_on=None, right_on=None,
                    left_index=False, right_index=False, sort=False,
                    suffixes=('_x', '_y'), copy=True, indicator=False,
                    validate=None)
    print "After merge, size = %d" % (len(r_df))

    r_df = r_df[r_df.is_dwelling]
    print "After filtering to only include dwellings, size = %d" % (len(r_df))
    return(r_df)

# find_event_by_date takes a list of maps containng 'date' fields and looks for one the the last one that's before
# search_date or the first which is simultaneous (in case of multiple simultaneous records).  
# Returns -1 if the search_date is earlier than any existing item.  It assumes that each map in the event list 
# contains a 'date' field and that they're in sorted order from earliest to latest.
def find_event_index_by_date(event_list, search_date):
    match_index=-1
    for i in range(0,len(event_list)):
        if(event_list[i]['date']<search_date):
            # This happened before the date we're looking for, update match_index
            match_index=i
        elif(event_list[i]['date']==search_date):
            # This is the first exact match, return i
            return(i)
        else:
            # This happened after the date we're looking for, return match_index
            return match_index
    # If we get to here, there is no event after this date.  Return match_index
    return match_index

# This takes an existing event list and either inserts a given event_map and returns True, or 
# decides that the event is a duplicate and returns false
def insert_event(event_list, event_map):
    # Find the index of the element already in the list which precedes the date in event_map.  
    # If not found, match_index is -1, so we should insert it at the beginning of event_list and return True
    # If found, check if the record matches what we already have (TODO: see if we need something
    # more sophisticated than ==).  If it matches what we already have, return False and do not modify the list.
    # If it doesn't match what we have insert it.  Note that list.insert takes the arg of the element to insert
    # before, so we use match_index+1
    match_index = find_event_index_by_date(event_list, event_map['date'])
    if(match_index==-1):
        #print "No match, insert at beginning"
        # No match.  Insert at the beginning, return True
        event_list.insert(0, event_map)
        return True
    # We've got a matching or preceeding event, compare it with this and any other potentially 
    # simultaneous events
    #print "Time match at %d" % (match_index)
    for i in range(match_index, len(event_list)):
        if(event_map == event_list[i]):
            # This is a duplicate, ignore it
            #print "Found duplicate match at %d (%r)" % (i,event_list[i])
            return False
        elif(event_map['date']<event_list[i]['date']):
            # We're past any simultaneous events that might have matched, continue
            #print "Hit a later item at %d (%r)" % (i,match_index)
            break
        #print "Didn't match at %d (%r), keep trying" % (i,event_list[i])
        match_index=i
    # We've got a preceeding or simultaneous event that doesnt match.  Insert this 
    # new item just past match_index
    #print "Inserting after %d" % (match_index)
    event_list.insert(match_index+1, event_map)
    return True

# Create 'property_address_raw' and 'owner_address_raw' columns.  Call once per dataframe before calling
# canonicalize_addrs
def merge_addr_colset(df, col_arr, out_colname):
    for  col_name in col_arr:
        df[col_name]=df[col_name].astype(basestring)
        df[col_name].fillna('', inplace=True)

    df[out_colname] = df[col_arr].apply(lambda x: ' '.join(x), axis=1)
    # Fix up PGH to be PITTSBURGH
    df[out_colname] = df[out_colname].str.replace('\s*PGH\s*,', ' PITTSBURGH,', regex=True)
    # Fix up to make sure there aren't differences in whitespace that could be avoided
    df[out_colname] = df[out_colname].str.replace('\s\s+', ' ', regex=True)
    
def merge_addrs(df):
    property_addr_cols=['PROPERTYHOUSENUM', 'PROPERTYADDRESS', 
                        'PROPERTYCITY' ,'PROPERTYSTATE', 'PROPERTYZIP']
    owner_addr_cols=['CHANGENOTICEADDRESS1', 'CHANGENOTICEADDRESS2',
                     'CHANGENOTICEADDRESS3', 'CHANGENOTICEADDRESS4']
    merge_addr_colset(df, property_addr_cols, 'property_address_raw')
    merge_addr_colset(df, owner_addr_cols, 'owner_address_raw')

# This assumes that merge_addrs has already been called to create the columns 'property_address_raw' and 
# 'owner_address_raw'
def canonicalize_cache_addr_col(df, colname):
    chunk_size=100
    total_len = len(df)
    next_i=0
    chunk_start_time=arrow.now()
    print_subset=10
    print_count=0
    retry_num=0
    while(next_i<total_len):
        u_addrs = df[colname][next_i:next_i+chunk_size].unique()
        if((print_count % print_subset) == 0):
            print "Processing %s for rows %d-%d, %d unique addresses (p=%d)" % (colname, next_i,next_i+chunk_size-1, len(u_addrs),print_count)
        try:
            cache_canonical_addresses(u_addrs)
            if((print_count % print_subset) == 0):
                print "   %s time elapsed" % (arrow.now()-chunk_start_time)
            next_i=next_i+chunk_size
            print_count=print_count+1
            chunk_start_time=arrow.now()
            retry_num = 0
        except:
            print "Error while processing %s for rows %d-%d, %d unique addresses (p=%d), retry %d: %s" % (colname, next_i,next_i+chunk_size-1, len(u_addrs),print_count, retry_num, sys.exc_info()[0])
            if(retry_num>=5):
                # Give up on that block
                print "   Giving up on that block"
                next_i=next_i+chunk_size
                print_count=print_count+1
                chunk_start_time=arrow.now()
            else:
                # Try again
                retry_num = retry_num+1
                
  
def canonicalize_addrs(df):
    if(not 'property_address_raw' in list(df) or not 'owner_address_raw' in list(df)):
        print "ERROR: No 'property_address_raw' or 'owner_address_raw' column, make sure merge_addrs has been run on this dataframe"
        raise
        
    # First make sure all the addresses are in the cache
    canonicalize_cache_addr_col(df, 'property_address_raw')
    canonicalize_cache_addr_col(df, 'owner_address_raw')
    print "* Address canonicalization cacheing complete.  Harvesting property addresses"
    # Harvest results.  They should all be in the cache
    df['property_address'] = df['property_address_raw'].apply(get_canonical_address)
    print "* Harvesting owner addresses"
    df['owner_address'] = df['owner_address_raw'].apply(get_canonical_address)
    print "* Done"

# Clean up multiple whitespace to a single space
def cleanup_str(str_in):
    str_out = re.sub( '\s+', ' ', str_in).strip()
    return(str_out)

# Try to normalize changeaddr to be more likely to match
re_zp4 = re.compile('(.+) (\d\d\d\d\d)-(\d\d\d\d)?')
re_cscz = re.compile('(.+) (\w\w), (\d\d\d\d\d)')
# Check for change address with no alphanumerics in it
re_noalnum = re.compile('^([^\w]+)$')

# The raw_owner_changeaddr is the one that should be used for detecting multiple ownership since it
# preserves unit number.  The canonical version loses it.
def get_raw_owner_changeaddr(apd, i):
    try:
        return(apd['owner_address_raw'].iloc[i])
    except:
        print "ERROR: No 'owner_address_raw' column, make sure merge_addrs has been run on this dataframe"
        raise

def get_canonical_owner_changeaddr(apd, i):
    try:
        return(apd['owner_address'].iloc[i])
    except:
        print "ERROR: No 'owner_address' column, make sure canonicalize_addrs has been run on this dataframe"
        raise

def update_property_address(apd, i):
    parid=apd.index[i]
    # Check if the canonical property address is cached
    if(parid in canonical_property_address_map and canonical_property_address_map[parid]):
        return canonical_property_address_map[parid]
    # Not cached, try to retrieve from data frame
    try:
        ret=apd['property_address'].iloc[i]
        raw_addr=apd['property_address_raw'].iloc[i]
        if(ret):
            # If this is a valid property address, cache it for next time
            canonical_property_address_map[parid]=ret
            # Also cache the raw address
            if(raw_addr):
                raw_property_address_map[parid]=raw_addr
                #print "Cacheing raw address for %r: %r" % (parid, raw_addr)
        else:
            # Don't have a valid canonical address, only cache the raw address if we don't have 
            # anything in there yet.  Return None
            if(raw_addr and parid not in raw_property_address_map):
                raw_property_address_map[parid]=raw_addr
                #print "Cacheing raw address for %r (can't canonicalize): %r" % (parid, raw_addr)
            return None
    except:
        #print "ERROR: No 'property_address' column, make sure canonicalize_addrs has been run on this dataframe"
        #raise
        # It's ok to not have a property_address, as some of the old versions are hopelessly messed up for that
        pass

def get_canonical_property_addr(parid):
    # Check if the canonical property address is cached
    if(parid in canonical_property_address_map.keys()):
        return canonical_property_address_map[parid]
    # Nope.  Return None
    return None

# First arg is a pandas table, second is an index for what to process.
# This updates property_map, owner_map, and changeaddr_map appropriately
# Returns True on success, False on failure
def process_assessment_record(apd, i, asofdate):
    # Extract PARID, saledate, owner_name, and changeaddr from the record
    par_id = apd.index[i]
    
    # Process saledate
    saledate_raw = apd['SALEDATE'].iloc[i]
    # If saledate is valid, keep it.  Otherwise return False
    if(saledate_raw == '' or (isinstance(saledate_raw, numbers.Number) and math.isnan(saledate_raw))):
        #print "%s: Missing saledate" % (par_id)
        return False
    
    # Convert saledatet YMD so it sorts properly 
    saledate = SaledateToYMD(saledate_raw)
    
    owner_name = cleanup_str(apd['PROPERTYOWNER'].iloc[i])
    # Use the raw changeaddr for computing multiple ownership since it preserves
    # unit number.  Canonical doesn't 
    owner_changeaddr = get_raw_owner_changeaddr(apd,i)
        
    # If owner_changaddr is None or doesn't contain alphanumeric characters, skip 
    # TODO: Consider including entries with an empy changeaddr since it could help with accuracy 
    # of SALE calculations for the owners 
    if(pandas.isnull(owner_changeaddr) or re_noalnum.match(owner_changeaddr)):
        #print "%s: Missing owner_changeaddr" % (par_id)
        # skip this one
        return False
    
    # We have valid par_id, owner_name, and owner_changeaddr.  Update the maps.
    property_event={'date': saledate, 'asofdate': asofdate, 
                    'event_type':'PURCHASE', 'ownername':owner_name, 'changeaddr': owner_changeaddr}
    owner_event={'date':saledate, 'event_type':'PURCHASE', 'parid':par_id}

    # Check for nice-to-have columns, if valid value, add to property_event
    try:
        saledesc = apd['SALEDESC'].iloc[i]
        if(saledesc != '' and not (isinstance(saledesc, numbers.Number) and math.isnan(saledesc))):
            property_event['saledesc']=saledesc
    except:
        pass
 
    try:
        homesteadflag = apd['HOMESTEADFLAG'].iloc[i]
        if(homesteadflag != '' and not (isinstance(homesteadflag, numbers.Number) and math.isnan(homesteadflag))):
            property_event['homesteadflag']=homesteadflag
    except:
        pass

    try:
        ownerdesc = apd['OWNERDESC'].iloc[i]
        if(ownerdesc != '' and not (isinstance(ownerdesc, numbers.Number) and math.isnan(ownerdesc))):
            property_event['ownerdesc']=ownerdesc
    except:
        pass
    
    try:
        fm_total = apd['FAIRMARKETTOTAL'].iloc[i]
        if(fm_total != '' and not (isinstance(fm_total, numbers.Number) and math.isnan(fm_total))):
            property_event['fm_total']=fm_total
    except:
        pass
    
    try:
        # TODO: change update_property_address to happen globally using pandas apply
        # Cache the canonical address for this property if available
        update_property_address(apd, i)
        # Store the canonical owner address with this property record if available
        canonical_owner_addr=get_canonical_owner_changeaddr(apd, i)
        if(canonical_owner_addr):
            property_event['canonical_owner_address']=canonical_owner_addr
    except:
        pass

    #print "-------\nProcessing %s: %r %r %r" % (par_id, saledate, owner_name, owner_changeaddr)

    if(not property_map.has_key(par_id)):
        # We don't have an entry for this property yet, create an empty list
        property_map[par_id]=[]
    
    # Insert the property event
    pret = insert_event(property_map[par_id], property_event)
 
    if(not owner_map.has_key(owner_name)):
        # We don't have an entry for this owner name yet, create an empty list
        owner_map[owner_name]=[]
    
    # Insert the owner event to owner map
    oret = insert_event(owner_map[owner_name], owner_event)
   
    if(not changeaddr_map.has_key(owner_changeaddr)):
        # We don't have an entry for this changeaddr yet, create an empty list
        changeaddr_map[owner_changeaddr]=[]
    
    # Insert the owner event
    cret = insert_event(changeaddr_map[owner_changeaddr], owner_event)
    
    # Print diagnostics
    #print "%s: %r %r %r = %r %r %r" % (par_id, saledate, owner_name, owner_changeaddr, pret, oret, cret)
    return(pret or oret or cret)

# Clear out the cache that stores what sets of properties are associated with each owner changeaddr at a given time.  
# We need to do this whenever we process in a new dataset.
def reset_cache():
    owned_parids_cache={}
    
# For a common parcel id, check if two events are both for the same transaction.  
# This happens when the dates are the same and/or when the set of owner names overlap
def is_same_transaction(e1,e2):
    if(e1['event_type']!='PURCHASE' or e2['event_type']!='PURCHASE'):
        return False
    if(e1['date']==e2['date']):
        return True
    if((e1['ownername'] in e2['ownername']) or (e2['ownername'] in e1['ownername'])):
        return True
    return False
    
def register_sale_dates(parid):
    prop_ev_list = property_map[parid]
    if(len(prop_ev_list)<2):
        # No sales have happened that we know about, only purchases
        return

    # Keep a list of the equivalent transactions so any subsequent sale can 
    # be applied to all.  Seed it with the 0'th item in prop_ev_list
    equiv_transactions=[prop_ev_list[0]]
    #print "Starting with %r" %(equiv_transactions)
    for i in range(1,len(prop_ev_list)):
        # See if this new transaction is equivalent to the last item in the current list
        if(is_same_transaction(prop_ev_list[i],equiv_transactions[-1])):
            equiv_transactions.append(prop_ev_list[i])
            #print "  %d still equivalent %r" %(i, equiv_transactions)
        else:
            #print "  %d not equivalent %r, record sale date" %(i,prop_ev_list[i])
            sell_event={'date':prop_ev_list[i]['date'],'event_type':'SALE','parid':parid}
            
            for j in range(0,len(equiv_transactions)):
                    dup_o = insert_event(owner_map[equiv_transactions[j]['ownername']], sell_event)
                    dup_c = insert_event(changeaddr_map[equiv_transactions[j]['changeaddr']], sell_event)
                    #print "    %d %r: %r %r" % (j, equiv_transactions[j], dup_o, dup_c)
            # Reset equiv_transactions and keep going if any more transactions are left
            equiv_transactions=[prop_ev_list[i]]
        
# This needs to be called once after imports are complete and before get_owned_parids
def register_all_sales():
    # Reset the owner and changeaddr caches since this will change the results
    reset_cache()
    
    # Add SALE records each time a property goes into different hands
    for parid in property_map.keys():
        register_sale_dates(parid)
   
def get_next_sale_date(parid, start_date):
    event_list = property_map[parid]
    # Get the index of the first transaction at or before this date
    start_index=find_event_index_by_date(event_list, start_date)

    # Starting with the transaction at or before the initial start date, 
    # go past all the equivalent transactions to the next one that's a real transfer.
    # If no future transfers, then return None
    equiv_transactions=[event_list[start_index]]

    for i in range(start_index,len(event_list)):
        # See if this new transaction is equivalent to the last item in the current list
        if(is_same_transaction(event_list[i],equiv_transactions[-1])):
            equiv_transactions.append(event_list[i])
            #print "  %d still equivalent %r" %(i, equiv_transactions)
        else:
            # This is a real tranfer, return the event date
            return event_list[i]['date']
    # If we get to here, there is no event after this date.  Return None
    return None

    
def get_owned_parids(name, event_list, eval_date):
    # Check if this name:date pair is in the cache.  If so, return the 
    # stored map of {'parids':owned_parids,'next_date':next_date}
    name_date_str=u"%s:%s"%(name,eval_date)
    if(name_date_str in owned_parids_cache):
        return(owned_parids_cache[name_date_str])

    # Return value wasn't in the cache, compute it
    
    # Use a set for accumulating parids since we don't want duplicates
    owned_parids=set()
    
    # In case eval_date is at or after the last date in the list, 
    # default next_date to today
    next_date = this_date
    for i in range(0,len(event_list)):
        if(event_list[i]['date']<= eval_date):
            # This event happened on or before the date we're asking about, process the event
            if(event_list[i]['event_type']=='PURCHASE'):
                # Add purchased property to owned_parids
                owned_parids.add(event_list[i]['parid'])
            else:
                # This must be a sale, remove it from owned_parids
                # Note that this can potentially fail in the case where 
                # two subsequent sales of the same property involve the same 
                # change address if the transactions happen as (add, 
                # (add, remove) from the same day, remove).  This actually 
                # happens with PARID == '0104R00158000000'.  So, we put this
                # in a try/catch block.  Bleh...
                try:
                    owned_parids.remove(event_list[i]['parid'])
                except:
                    pass
        else:
            # This and subsequent events happened after the date we're looking for.
            # Set next_date and return owned_parids
            next_date = event_list[i]['date']
            break

    ret_val = {'parids':owned_parids,'next_date':next_date}
    # Store in cache for next time
    owned_parids_cache[name_date_str]=ret_val
    return ret_val

# For a given parid and eval_date, get a map back containing:
#   'parids' = the set of parids owned by the same owners/changeaddrs as of eval_date, and
#   'next_date' = the next date that something changes within that set of owners/changeaddrs
# When the last of the related events is complete, 'next_date'==this_date
def get_related_parids(parid, eval_date):
    prop_ev_list = property_map[parid]
    parid_set = set()
    start_date = eval_date
    next_date = this_date

    # Keep a list of the equivalent transactions so we can accumulate the 
    # parids for all.  Seed it with the 0'th item in prop_ev_list
    equiv_transactions=[prop_ev_list[0]]
    # If date of the first event is later than eval_date, set eval_date to 
    # the first event.  We don't want to iterate over the earlier purchases by
    # the original owners we know about.  Just start at the first purchase
    # of this parcel we know about.
    if(eval_date<prop_ev_list[0]['date']):
        eval_date=prop_ev_list[0]['date']
        start_date=eval_date
    #print "%s: starting with %r" %(parid, equiv_transactions)
    for i in range(1,len(prop_ev_list)):
        # See if this new transaction is equivalent to the last item in the current list
        if(is_same_transaction(prop_ev_list[i],equiv_transactions[-1]) and 
           prop_ev_list[i]['date']<=eval_date):
            equiv_transactions.append(prop_ev_list[i])
            #print "  %d still equivalent %r" %(i, equiv_transactions)
        elif(prop_ev_list[i]['date']>eval_date):
            #print "  %d after timespan (%r), process current set" %(i,prop_ev_list[i])
            break
        else:
            # We haven't hit the end of the timespan yet, but the ownership has changed.
            # Reset equiv_transactions starting from the current event
            equiv_transactions=[prop_ev_list[i]]
            
    # We've got all the equivalent transactions, process them
    changeaddr_set=set()
    owner_set=set()
    for j in range(0,len(equiv_transactions)):
        owner_set.add(equiv_transactions[j]['ownername'])
        changeaddr_set.add(equiv_transactions[j]['changeaddr'])

    #print "    Owner set= %r\n    Changeaddr set= %r" % (owner_set, changeaddr_set)
    
    for owner in owner_set:
        ret_map=get_owned_parids(owner, owner_map[owner],eval_date)
        parid_set = parid_set.union(ret_map['parids'])
        if(ret_map['next_date']<next_date):
            next_date = ret_map['next_date']
    for changeaddr in changeaddr_set:
        ret_map=get_owned_parids(changeaddr, changeaddr_map[changeaddr],eval_date)
        parid_set = parid_set.union(ret_map['parids'])
        if(ret_map['next_date']<next_date):
            next_date = ret_map['next_date']

    ret_val={"parids":parid_set, "parcount":len(parid_set), "start_date":start_date, "next_date":next_date}
    #print "    Returning %r" % (ret_val)
    return ret_val

# Call this once for each assessment spreadsheet/database file.  It adds PURCHASE records if they don't already exist.
# It's safe to call multiple times on the same input file if necessary, but takes a lot of processing time
# asofdate, in format YYYY-MM-DD, is used to disambiguate earlier vs later versions of addresses or values
def process_all_assessment_records(apd, asofdate):
    start=arrow.now()
    addcnt=0
    chunk_start_time=arrow.now()
    chunk_size=10000

    # Clear the owner and changeaddr caches as this will cause changes in the ownership profiles
    reset_cache()
    
    # Iterate over each record in the data frame and add to the maps
    for i in range(0,len(apd)):
        if(process_assessment_record(apd,i, asofdate)):
            addcnt=addcnt+1
        if((i%chunk_size)==0 and i>0):
            print "%d-%d: %d added, %s time elapsed" %(i-(chunk_size-1), i, addcnt, arrow.now()-chunk_start_time)
            #break
            addcnt=0
            chunk_start_time=arrow.now()
    end=arrow.now()
    print "Processing took %s" % (str(end-start))

# The next section is a failed attempt to speed up update_property_address, ignore it

In [316]:
def update_property_address_info(parid, raw_addr, property_address):
    # Check if the canonical property address is cached
    if(parid in canonical_property_address_map and canonical_property_address_map[parid]):
        return False
    # Not cached, see if we should add it
    if(property_address):
        # If this is a valid property address, cache it for next time
        canonical_property_address_map[parid]=property_address
        # Also cache the raw address
        raw_property_address_map[parid]=raw_addr
        #print "Cacheing raw address for %r: %r" % (parid, raw_addr)
    else:
        # Don't have a valid canonical address, only cache the raw address if we don't have 
        # anything in there yet.  
        if(raw_addr and parid not in raw_property_address_map):
            raw_property_address_map[parid]=raw_addr
            #print "Cacheing raw address for %r (can't canonicalize): %r" % (parid, raw_addr)
    return True

In [335]:
test_parids=[]
for parid in noprop_parids_2004[0:400]:
    if parid in raw_property_address_map:
        print "%s: %r" % (parid, raw_property_address_map[parid])
        if(raw_property_address_map[parid]==apd_2004.loc[parid]['property_address_raw']):
            test_parids.append(parid)
        if parid in canonical_property_address_map:
            print "                  %r" % (canonical_property_address_map[parid])

0553N00123000000: ' SCHWEITZER RD  '
0295B00162000000: ' VERONA RD  '
0878N00067000000: ' REED ST CLAIRTON       PA 15025'
0188M00010000000: ' IDA ST PITTSBURGH     PA 15227'
0032E00295000000: ' ST LUCAS ST PGH            PA 15210'
0887H00134000000: ' ROOSEVELT AVE  '
0876R00369000000: '128 PIERCE RD ELIZABETH      PA 15037'
                  u'128 PIERCE RD, ELIZABETH, PA, 15037'
0163K00059000000: ' EVERGREEN RD                PA '
0177D00218000000: '121 EDGEWOOD AVE PITTSBURGH     PA 15218'
0355M00371000000: '1491 HIGHLAND AVE GLENSHAW       PA 15116'
                  u'1491 HIGHLAND AVE, GLENSHAW, PA, 15116'
8000T02674000000: '99 GRACE LANE  '
0237D00012000000: '617 MARGARETTA ST BRADDOCK       PA 15104'
                  u'617 MARGARETTA ST, BRADDOCK, PA, 15104'
1210M00159000000: ' HARDIES  '
0094N00272000000: ' NICE WAY                PA '
8000T02126000000: '404 RICHMOND RD IMPERIAL       PA 15126'
                  u'404 RICHMOND RD, IMPERIAL, PA, 15126'
8000T00242000000: '525 4

8000T02579000000: '214 VALLEY VIEW DR  '
0284L00130000000: ' ARGONNE AVE  '
0090H00213000000: '463 8TH AVE W                PA '
0051K00109000000: ' POWHATTAN ST PGH            PA 15224'
0564C00217000000: ' WILHELM AVE  '
0395L00104000000: ' TRUXTON DR  '
0652E00167000000: ' BURNING TREE DR  '
0235P00300000000: '2537 WOODSTOCK AVE  '
0455J00106000000: '221 BROWN AVE TURTLE CREEK   PA 15145'
                  u'221 BROWN AVE, TURTLE CREEK, PA, 15145'
0739J00057000000: '7612 SALTSBURG RD  '
0232S00052000000: ' BESSICA ST PGH            PA 15221'
0006A00102000000: ' MAIN ST S                PA '
0184K00147000000: ' MIFFLIN RD  '
8000T03040000000: '6 SHERYL DR  '
8000T02715000000: '25 SKYVIEW DR  '
0311S00084000000: '412 CURRY HOLLOW RD  '
0178S00120000000: '100 HARRIET ST BRADDOCK       PA 15104'
                  u'100 HARRIET ST, BRADDOCK, PA, 15104'
8000T03284000000: ' TRAILER  '
0102B00258000000: '403 W MAIN ST CARNEGIE       PA 15106'
                  u'403 W MAIN ST, CARNEGIE, PA, 

0849A00036000000: '7191 LEECHBURGH RD  '
0376M00134000000: ' PORTER ST  '
0465M00108000000: ' A ST  '
8000T03090000000: '26 LARRAINE DR  '
8000T01169000000: '128 CLOVERLEAF DR  '
0177H00138000000: ' GORDON ST                PA '
2019F00245000000: ' DONNELLSVILLE RD  '
0074J00066000000: ' ISLAND AVE MCKEES ROCKS   PA 15136'
0355D00220000000: '107 SPENCER LANE                PA '
0029D00160000000: ' JUNO ST PITTSBURGH     PA 15213'
0537M00020000000: ' HERSHEY RD  '
0051A00094000000: '4780 LIBERTY AVE PITTSBURGH     PA 15224'
                  u'4780 LIBERTY AVE, PITTSBURGH, PA, 15224'
0117J00057000000: '3543 FABER TERRACE  '
8000T02545000000: '258 VALLEY VIEW DR  '
8000T00515000000: '32 TRAILER-DEPRETIS  '
0302L00147000000: '1412 BELL AVE N BRADDOCK     PA 15104'
                  u'1412 BELL AVE, BRADDOCK, PA, 15104'
0881K00010000000: ' OAK ST CLAIRTON       PA 15025'
0467M00381000000: ' LIMEKLIN ST  '
0205A00106000000: '5661 STEUBENVILLE PIKE  '
0970G00216000000: ' OLD LEECHBURG RD  '


ValueError: The truth value of a Series is ambiguous. Use a.empty, a.bool(), a.item(), a.any() or a.all().

In [336]:
test_2004 = apd_2004.loc[test_parids]

In [345]:
# Check property map matches test_2004
for parid in test_parids:
    if parid in raw_property_address_map:
        if(raw_property_address_map[parid]!=test_2004.loc[parid]['property_address_raw']):
            print "%s: diff raw %r %r" %(parid, raw_property_address_map[parid], test_2004.loc[parid]['property_address_raw'])
        else:
            print "%s: match raw" % (parid)
        if parid in canonical_property_address_map:
            if(canonical_property_address_map[parid]!=test_2004.loc[parid]['property_address']):
                print "%s: diff can %r %r" %(parid, raw_property_address_map[parid], test_2004.loc[parid]['property_address'])
            else:
                print "%s: match can" % (parid)

0553N00123000000: match raw
0295B00162000000: match raw
0878N00067000000: match raw
0188M00010000000: match raw
0032E00295000000: match raw
0887H00134000000: match raw
0876R00369000000: match raw
0876R00369000000: match can
0163K00059000000: match raw
0177D00218000000: match raw
0355M00371000000: match raw
0355M00371000000: match can
8000T02674000000: match raw
0237D00012000000: match raw
0237D00012000000: match can
1210M00159000000: match raw
0094N00272000000: match raw
8000T02126000000: match raw
8000T02126000000: match can
8000T00242000000: match raw
0747P00108000000: match raw
0747P00108000000: match can
0382F00350000000: match raw
0382F00350000000: match can
0006N00100000000: match raw
0635G00296000000: match raw
0455H00238000000: match raw
0378P00127000000: match raw
0711E00097000000: match raw
0711E00097000000: match can
0382L00054000000: match raw
0382L00054000000: match can
0455R00061000000: match raw
0455R00061000000: match can
0381N00013000000: match raw
0381N00013000000: ma

0050P00214000000: match raw
0050P00214000000: match can
1102F00345000000: match raw
1102F00345000000: match can
8000T00357000000: match raw
0755E00031000000: match raw
0283C00190000000: match raw
0774G00325000000: match raw
1133F00030000000: match raw
0877F00292000000: match raw
0125B00097000001: match raw
0125B00097000001: match can
8000T01602000000: match raw
8000T01602000000: match can
0236K00127000000: match raw
0236C00024000000: match raw
0849A00036000000: match raw
0376M00134000000: match raw
0465M00108000000: match raw
8000T03090000000: match raw
8000T01169000000: match raw
0177H00138000000: match raw
2019F00245000000: match raw
0074J00066000000: match raw
0355D00220000000: match raw
0029D00160000000: match raw
0537M00020000000: match raw
0051A00094000000: match raw
0051A00094000000: match can
0117J00057000000: match raw
8000T02545000000: match raw
8000T00515000000: match raw
0302L00147000000: match raw
0302L00147000000: match can
0881K00010000000: match raw
0467M00381000000: ma

In [343]:
# Reset property map for test_parids
for parid in test_parids:
    if parid in raw_property_address_map:
        del raw_property_address_map[parid]
        if parid in canonical_property_address_map:
            del canonical_property_address_map[parid]
            

In [344]:
%time
for i in range (0,len(test_2004)):
    update_property_address(test_2004, i)

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 16 µs


In [341]:
%time
for parid, row in test_2004[['property_address_raw', 'property_address']].iterrows():
    update_property_address_info(parid, row[0], row[1])

CPU times: user 0 ns, sys: 0 ns, total: 0 ns
Wall time: 23.1 µs


# Support save/restore for dataframes

In [226]:
from pandas import HDFStore
hdf_file_t = 'assessments/apdstore_{}.h5'

# Save this data frame using a key string to get it back with.  
# For example, 1999 is stored with keystr 'tables/apd_1999'
def save_adf(df, keystr):
    hdf_file = hdf_file_t.format(keystr)
    print "Saving to %s, key=%s" % (hdf_file, keystr)
    hdf = HDFStore(hdf_file)
    hdf.put(keystr, df)
    hdf.close()
    
def restore_adf(keystr):
    hdf_file = hdf_file_t.format(keystr)
    print "Restoring from %s, key=%s" % (hdf_file, keystr)
    hdf = HDFStore(hdf_file)
    df = hdf[keystr]
    hdf.close()
    return df

def list_hdfstore(keystr):
    hdf_file = hdf_file_t.format(keystr)
    print "Listing %s" % (hdf_file)
    hdf = HDFStore(hdf_file)
    print hdf.info()
    hdf.close()

# Read in 2017 data and generate series dwelling_col which is True for residental PARIDs

In [ ]:
# Restore apd_2017 from mdf if we don't want to change saved version
apd_2017 = restore_adf('apd_2017')

In [11]:
# Read in assessments data as TDF, set index to PARID
path = "assessments/cd/AC Property Assessments_10012017.xls"
raw_pd_2017 = pd.read_csv(path,sep='\t', index_col='PARID',dtype={'PROPERTYHOUSENUM':numpy.str,'CHANGENOTICEADDRESS4':numpy.str, 'PROPERTYZIP':numpy.str})

/home/rsargent/anaconda2/lib/python2.7/site-packages/IPython/core/interactiveshell.py:2714: DtypeWarning: Columns (20,21,30,31,32,39,48,63,89) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [12]:
# Consider a parcel a dwelling if either residential or apartments (usedesc includes APART)
# dwelling_col is indexed on PARID, has TRUE for dwellings, and FALSE for non-dwellings
#vacant_col = raw_pd_2017.USEDESC.str.contains('VACANT')

# Tried to filter out vacant lots, but it led to less dramatic results
#dwelling_col = ((raw_pd_2017.CLASSDESC == 'RESIDENTIAL') | (raw_pd_2017.USEDESC.str.contains('APART'))) & (~vacant_col.astype('bool'))
dwelling_col = ((raw_pd_2017.CLASSDESC == 'RESIDENTIAL') | (raw_pd_2017.USEDESC.str.contains('APART')))
dwelling_col.name='is_dwelling'

In [13]:
# Only keep the subset that are dwellings
apd_2017 = pd.concat([raw_pd_2017, dwelling_col], axis=1)[dwelling_col]
len(apd_2017)

519728

In [160]:
apd_15213_2017 = apd_2017[apd_2017.PROPERTYZIP=='15213'].copy()

In [10]:
merge_addrs(apd_15213_2017)

In [11]:
canonicalize_addrs(apd_15213_2017)

Processing property_address_raw for rows 0-99, 88 unique addresses (p=0)
SimpleThreadPoolExecutor succeeded: all 88 jobs completed
   0:00:00.066431 time elapsed
SimpleThreadPoolExecutor succeeded: all 48 jobs completed
SimpleThreadPoolExecutor succeeded: all 55 jobs completed
SimpleThreadPoolExecutor succeeded: all 78 jobs completed
SimpleThreadPoolExecutor succeeded: all 18 jobs completed
SimpleThreadPoolExecutor succeeded: all 41 jobs completed
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
SimpleThreadPoolExecutor succeeded: all 34 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
Processing property_address_raw for rows 1000-1099, 100 unique addresses (p=10)
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
   0:00:00.033707 time elapsed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 92 jobs completed
SimpleThreadPoolExecutor succ

In [161]:
process_all_assessment_records(apd_15213_2017,'2017-10-01')

Processing took 0:03:13.759680


In [14]:
# merge property and owner addresses
merge_addrs(apd_2017)

In [63]:
canonicalize_addrs(apd_2017)

Processing owner_address_raw for rows 0-99, 90 unique addresses (p=0)
SimpleThreadPoolExecutor succeeded: all 90 jobs completed
   0:00:00.077237 time elapsed
SimpleThreadPoolExecutor succeeded: all 69 jobs completed
SimpleThreadPoolExecutor succeeded: all 73 jobs completed
SimpleThreadPoolExecutor succeeded: all 82 jobs completed
SimpleThreadPoolExecutor succeeded: all 78 jobs completed
SimpleThreadPoolExecutor succeeded: all 91 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 85 jobs completed
SimpleThreadPoolExecutor succeeded: all 85 jobs completed
SimpleThreadPoolExecutor succeeded: all 77 jobs completed
Processing owner_address_raw for rows 1000-1099, 81 unique addresses (p=10)
SimpleThreadPoolExecutor succeeded: all 80 jobs completed
   0:00:00.028427 time elapsed
SimpleThreadPoolExecutor succeeded: all 83 jobs completed
SimpleThreadPoolExecutor succeeded: all 49 jobs completed
SimpleThreadPoolExecutor succeeded: al

SimpleThreadPoolExecutor succeeded: all 90 jobs completed
   0:00:09.860038 time elapsed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPoolExecutor succeeded: all 88 jobs completed
SimpleThreadPoolExecutor succeeded: all 86 jobs completed
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 95 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPoolExecutor succeeded: all 89 jobs completed
SimpleThreadPoolExecutor succeeded: all 78 jobs completed
Processing owner_address_raw for rows 13000-13099, 77 unique addresses (p=130)
SimpleThreadPoolExecutor succeeded: all 77 jobs completed
   0:00:05.779317 time elapsed
SimpleThreadPoolExecutor succeeded: all 88 jobs completed
SimpleThreadPoolExecutor succeeded: all 76 jobs completed
SimpleThreadPoolExecutor succeeded: all 89 jobs completed
SimpleThreadPoolExecutor succeeded: all 93 jobs

SimpleThreadPoolExecutor succeeded: all 73 jobs completed
   0:00:08.926038 time elapsed
SimpleThreadPoolExecutor succeeded: all 57 jobs completed
SimpleThreadPoolExecutor succeeded: all 68 jobs completed
SimpleThreadPoolExecutor succeeded: all 50 jobs completed
SimpleThreadPoolExecutor succeeded: all 65 jobs completed
SimpleThreadPoolExecutor succeeded: all 51 jobs completed
SimpleThreadPoolExecutor succeeded: all 65 jobs completed
SimpleThreadPoolExecutor succeeded: all 71 jobs completed
SimpleThreadPoolExecutor succeeded: all 55 jobs completed
SimpleThreadPoolExecutor succeeded: all 53 jobs completed
Processing owner_address_raw for rows 25000-25099, 69 unique addresses (p=250)
SimpleThreadPoolExecutor succeeded: all 68 jobs completed
   0:00:10.785508 time elapsed
SimpleThreadPoolExecutor succeeded: all 67 jobs completed
SimpleThreadPoolExecutor succeeded: all 61 jobs completed
SimpleThreadPoolExecutor succeeded: all 51 jobs completed
SimpleThreadPoolExecutor succeeded: all 52 jobs

SimpleThreadPoolExecutor succeeded: all 87 jobs completed
   0:00:04.249414 time elapsed
SimpleThreadPoolExecutor succeeded: all 88 jobs completed
SimpleThreadPoolExecutor succeeded: all 91 jobs completed
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
SimpleThreadPoolExecutor succeeded: all 85 jobs completed
SimpleThreadPoolExecutor succeeded: all 82 jobs completed
SimpleThreadPoolExecutor succeeded: all 95 jobs completed
SimpleThreadPoolExecutor succeeded: all 95 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPoolExecutor succeeded: all 93 jobs completed
Processing owner_address_raw for rows 37000-37099, 92 unique addresses (p=370)
SimpleThreadPoolExecutor succeeded: all 92 jobs completed
   0:00:04.271208 time elapsed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs

SimpleThreadPoolExecutor succeeded: all 83 jobs completed
   0:00:04.513581 time elapsed
SimpleThreadPoolExecutor succeeded: all 83 jobs completed
SimpleThreadPoolExecutor succeeded: all 84 jobs completed
SimpleThreadPoolExecutor succeeded: all 85 jobs completed
SimpleThreadPoolExecutor succeeded: all 88 jobs completed
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
SimpleThreadPoolExecutor succeeded: all 83 jobs completed
SimpleThreadPoolExecutor succeeded: all 73 jobs completed
SimpleThreadPoolExecutor succeeded: all 78 jobs completed
SimpleThreadPoolExecutor succeeded: all 76 jobs completed
Processing owner_address_raw for rows 49000-49099, 88 unique addresses (p=490)
SimpleThreadPoolExecutor succeeded: all 87 jobs completed
   0:00:07.743791 time elapsed
SimpleThreadPoolExecutor succeeded: all 92 jobs completed
SimpleThreadPoolExecutor succeeded: all 88 jobs completed
SimpleThreadPoolExecutor succeeded: all 93 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs

...

SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
Processing owner_address_raw for rows 467000-467099, 97 unique addresses (p=4670)
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
   0:00:09.931111 time elapsed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 93 jobs completed
SimpleThreadPoolExecutor succeeded: all 91 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPool

SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
Processing owner_address_raw for rows 479000-479099, 100 unique addresses (p=4790)
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
   0:00:01.217906 time elapsed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThread

SimpleThreadPoolExecutor succeeded: all 99 jobs completed
   0:00:01.027250 time elapsed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
Processing owner_address_raw for rows 491000-491099, 100 unique addresses (p=4910)
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
   0:00:01.683731 time elapsed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeed

SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
Processing owner_address_raw for rows 502000-502099, 100 unique addresses (p=5020)
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
   0:00:02.207256 time elapsed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 95 jobs completed
Processing owner_address_raw for rows 503000-503099, 99 unique addresses (p=5030)
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
   0:00:01.212955 time elapsed
SimpleThreadP

SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
Processing owner_address_raw for rows 514000-514099, 100 unique addresses (p=5140)
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
   0:00:01.263484 time elapsed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
Pr

In [167]:
# Process entries from apd_2017 into the property, owner, and changeaddr maps
process_all_assessment_records(apd_2017, '2017-10-01')

1-10000: 6093 added, 0:06:19.289246 time elapsed
10001-20000: 9759 added, 0:06:29.803133 time elapsed
20001-30000: 9656 added, 0:06:30.265928 time elapsed
30001-40000: 9796 added, 0:06:23.983966 time elapsed
40001-50000: 9843 added, 0:06:55.865839 time elapsed
50001-60000: 9838 added, 0:06:41.603959 time elapsed
60001-70000: 9863 added, 0:06:59.777201 time elapsed
70001-80000: 9695 added, 0:06:48.254868 time elapsed
80001-90000: 9887 added, 0:06:57.604835 time elapsed
90001-100000: 9480 added, 0:06:45.187511 time elapsed
100001-110000: 9153 added, 0:06:08.624197 time elapsed
110001-120000: 9671 added, 0:06:21.631407 time elapsed
120001-130000: 9847 added, 0:06:28.307381 time elapsed
130001-140000: 9726 added, 0:06:39.904737 time elapsed
140001-150000: 9708 added, 0:07:13.609307 time elapsed
150001-160000: 9590 added, 0:06:18.407208 time elapsed
160001-170000: 9336 added, 0:06:24.632715 time elapsed
170001-180000: 9643 added, 0:06:10.309117 time elapsed
180001-190000: 9429 added, 0:06:2

In [68]:
len(apd_2017)

519728

In [228]:
# Save out apd_2017 to mdf
save_adf(apd_2017, 'apd_2017')

Saving to assessments/apdstore_apd_2017.h5, key=apd_2017


## Process 2018

In [257]:
# Read in assessments data as TDF, set index to PARID
path = "assessments/2018-01-cd/AC Property Assessments_01222018.xls"
raw_pd_2018 = pd.read_csv(path,sep='\t', index_col='PARID',dtype={'PROPERTYHOUSENUM':numpy.str,'CHANGENOTICEADDRESS4':numpy.str, 'PROPERTYZIP':numpy.str})

/home/rsargent/anaconda2/lib/python2.7/site-packages/IPython/core/interactiveshell.py:2714: DtypeWarning: Columns (20,21,30,31,38,39,48,62,63,66,68,69,81,107) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [259]:
# Consider a parcel a dwelling if either residential or apartments (usedesc includes APART)
# dwelling_col is indexed on PARID, has TRUE for dwellings, and FALSE for non-dwellings
dwelling_col_2018 = ((raw_pd_2018.CLASSDESC == 'RESIDENTIAL') | (raw_pd_2018.USEDESC.str.contains('APART')))
dwelling_col_2018.name='is_dwelling'

# Only keep the subset that are dwellings
apd_2018 = pd.concat([raw_pd_2018, dwelling_col_2018], axis=1)[dwelling_col_2018]
len(apd_2018)

520091

In [260]:
# merge property and owner addresses
merge_addrs(apd_2018)
canonicalize_addrs(apd_2018)


Processing property_address_raw for rows 0-99, 18 unique addresses (p=0)
SimpleThreadPoolExecutor succeeded: all 18 jobs completed
   0:00:00.027813 time elapsed
SimpleThreadPoolExecutor succeeded: all 64 jobs completed
SimpleThreadPoolExecutor succeeded: all 39 jobs completed
SimpleThreadPoolExecutor succeeded: all 86 jobs completed
SimpleThreadPoolExecutor succeeded: all 37 jobs completed
SimpleThreadPoolExecutor succeeded: all 22 jobs completed
SimpleThreadPoolExecutor succeeded: all 20 jobs completed
SimpleThreadPoolExecutor succeeded: all 19 jobs completed
SimpleThreadPoolExecutor succeeded: all 24 jobs completed
SimpleThreadPoolExecutor succeeded: all 30 jobs completed
Processing property_address_raw for rows 1000-1099, 60 unique addresses (p=10)
SimpleThreadPoolExecutor succeeded: all 60 jobs completed
   0:00:02.328283 time elapsed
SimpleThreadPoolExecutor succeeded: all 87 jobs completed
SimpleThreadPoolExecutor succeeded: all 54 jobs completed
SimpleThreadPoolExecutor succeed

SimpleThreadPoolExecutor succeeded: all 88 jobs completed
   0:00:00.383295 time elapsed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 93 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 93 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 83 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
Processing property_address_raw for rows 13000-13099, 98 unique addresses (p=130)
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
   0:00:00.029986 time elapsed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 9

SimpleThreadPoolExecutor succeeded: all 83 jobs completed
Processing property_address_raw for rows 24000-24099, 99 unique addresses (p=240)
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
   0:00:00.036299 time elapsed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 90 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 95 jobs completed
SimpleThreadPoolExecutor succeeded: all 93 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
Processing property_address_raw for rows 25000-25099, 94 unique addresses (p=250)
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
   0:00:00.028836 time elapsed
SimpleThreadPoolExecutor succeeded: all 91 jobs completed
SimpleThreadPoolExec

SimpleThreadPoolExecutor succeeded: all 95 jobs completed
Processing property_address_raw for rows 36000-36099, 98 unique addresses (p=360)
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
   0:00:00.027278 time elapsed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 80 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
Processing property_address_raw for rows 37000-37099, 100 unique addresses (p=370)
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
   0:00:00.025542 time elapsed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadP

SimpleThreadPoolExecutor succeeded: all 90 jobs completed
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
Processing property_address_raw for rows 48000-48099, 90 unique addresses (p=480)
SimpleThreadPoolExecutor succeeded: all 90 jobs completed
   0:00:00.032461 time elapsed
SimpleThreadPoolExecutor succeeded: all 88 jobs completed
SimpleThreadPoolExecutor succeeded: all 95 jobs completed
SimpleThreadPoolExecutor succeeded: all 95 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPoolExecutor succeeded: all 92 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
Processing property_address_raw for rows 49000-49099, 91 unique addresses (p=490)
SimpleThreadPoolExecutor succeeded: all 91 jobs completed
   0:00:00.028341 time elapsed
SimpleThreadPoolExec

...

SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
Processing owner_address_raw for rows 469000-469099, 96 unique addresses (p=4690)
SimpleThreadPoolExecutor succeeded: all 95 jobs completed
   0:00:01.231926 time elapsed
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 93 jobs completed
SimpleThreadPoolExecutor succeeded: all 92 jobs completed
Processing owne

SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 95 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
Processing owner_address_raw for rows 481000-481099, 94 unique addresses (p=4810)
SimpleThreadPoolExecutor succeeded: all 93 jobs completed
   0:00:00.998357 time elapsed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPo

SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
Processing owner_address_raw for rows 493000-493099, 100 unique addresses (p=4930)
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
   0:00:00.032846 time elapsed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
S

SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
Processing owner_address_raw for rows 505000-505099, 99 unique addresses (p=5050)
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
   0:00:00.029769 time elapsed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThre

SimpleThreadPoolExecutor succeeded: all 97 jobs completed
   0:00:00.468501 time elapsed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
Processing owner_address_raw for rows 517000-517099, 99 unique addresses (p=5170)
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
   0:00:00.033478 time elapsed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: a

In [261]:
# TODO
# Process entries from apd_2018 into the property, owner, and changeaddr maps
process_all_assessment_records(apd_2018, '2018-01-22')

1-10000: 9750 added, 0:05:54.927791 time elapsed
10001-20000: 9882 added, 0:05:49.093737 time elapsed
20001-30000: 9689 added, 0:06:02.650488 time elapsed
30001-40000: 9784 added, 0:06:00.204636 time elapsed
40001-50000: 9863 added, 0:06:16.588293 time elapsed
50001-60000: 9809 added, 0:06:13.958612 time elapsed
60001-70000: 9894 added, 0:06:25.131962 time elapsed
70001-80000: 9717 added, 0:06:14.873057 time elapsed
80001-90000: 9848 added, 0:06:27.268074 time elapsed
90001-100000: 9851 added, 0:06:21.286542 time elapsed
100001-110000: 8992 added, 0:05:42.141868 time elapsed
110001-120000: 9592 added, 0:05:51.225122 time elapsed
120001-130000: 9744 added, 0:05:55.680995 time elapsed
130001-140000: 9811 added, 0:06:14.700531 time elapsed
140001-150000: 9649 added, 0:06:25.872768 time elapsed
150001-160000: 9608 added, 0:06:04.215834 time elapsed
160001-170000: 9583 added, 0:05:52.469545 time elapsed
170001-180000: 9398 added, 0:05:57.229205 time elapsed
180001-190000: 9726 added, 0:05:4

# Deal with older versions of the assessment database from Kristin

In [188]:
# Original processing of 1999 data is in
#   http://localhost:8815/notebooks/uwsgi/dotmaptiles/data-visualization-tools/examples/lodes/Import%20DBF%20Test.ipynb
#
# It was then pulled into a copy of this notebook and processed:
#  apd_1999 = merge_dwelling_col(apd_1999)
#  pa_2017 = apd_2017[['property_address_raw','property_address']]
#  # Merge property_address_raw and property_address into 1999
#  apd_1999 = pd.merge(adf_1999,pa_2017,on='PARID', left_on=None, right_on=None,
#                left_index=False, right_index=False, sort=False,
#                suffixes=('_x', '_y'), copy=True, indicator=False,
#                validate=None)
#  # After canonicalization cacheing completes
#  apd_1999['owner_address'] = apd_1999['owner_address_raw'].apply(get_canonical_address)
# 
#  Manual fixup of bad addresses and sale dates:
#  apd_1999.set_value('0162H00002000000','property_address_raw','124 MONTVILLE ST PITTSBURGH PA 15214')
#  apd_1999.set_value('0162H00002000000','property_address',get_canonical_address('124 MONTVILLE ST PITTSBURGH PA 15214'))
# 
#  apd_1999.set_value('0232C00201000000','SALEDATE','1970-11-01')
#  The result was saved out using:
#  save_adf(apd_1999, 'apd_1999')
#
apd_1999 = restore_adf('apd_1999')

In [221]:
apd_1999.set_value('0232C00201000000','SALEDATE','1970-11-01')

/home/rsargent/anaconda2/lib/python2.7/site-packages/ipykernel_launcher.py:1: FutureWarning: set_value is deprecated and will be removed in a future release. Please use .at[] or .iat[] accessors instead
  """Entry point for launching an IPython kernel.


AREA   PERIMETER  CITYPROP_  CITYPROP_I  MAP BLOCK  \
PARID                                                                         
0163B00066000000   4534.45409   319.77703          2           2  163     B   
0163B00060000000   5542.02637   325.20027          4           5  163     B   
0163B00014000000   4904.62282   357.33466          6           7  163     B   
0163B00055000000   4661.38813   302.34886          7           8  163     B   
0162D00029000000   4772.31761   304.65658          8           9  162     D   
0162D00029000000  21953.56453   653.52560          9          10  162     D   
0163A00045000000  11411.71715   436.53544         10          11  163     A   
0162D00023000000   8134.89214   361.13825         11          12  162     D   
0163B00048000000   5771.87910   323.39223         12          14  163     B   
0163B00019000000   8783.50113   375.93285         13          15  163     B   
0163A00044000000   7558.31038   353.18811         14          16  163     A   
0162D00020000000   5813.60996   313.08864         16          18  162     D   
0163A00040000000   4448.99170   294.47700         17          19  163     A   
0163A00005000000   5269.18448   314.90696         18          20  163     A   
0163A00011000000   7133.67634   349.33999         19          21  163     A   
0163A00038000000   6761.22675   339.49961         21          23  163     A   
0162D00003000000   2699.24859   247.99305         22          24  162     D   
0163B00024000000  10408.66377   410.03692         23          25  163     B   
0162D00004000000   3169.74070   259.68227         24          26  162     D   
0162D00006000000   3522.44223   266.39647         25          27  162     D   
0162D00008000000   3380.62112   259.57566         26          28  162     D   
0162D00018000000   3602.81200   268.51461         27          29  162     D   
0162D00010000000   1592.42043   215.16823         28          30  162     D   
0163A00014000000   2295.68295   241.85189         29          31  163     A   
0163A00033000000   4117.03536   282.36294         30          32  163     A   
0162D00012000000   3158.99574   259.31424         31          33  162     D   
0163A00015000000   2328.61310   242.64067         32          34  163     A   
0162D00016000000   1754.48291   191.81429         33          35  162     D   
0163A00016000000   3227.66335   261.21121         34          36  163     A   
0163A00031000000   4054.78308   281.18081         35          37  163     A   
0163B00041000000   5009.96793   310.52027         36          38  163     B   
0162D00011000000   2544.98793   209.46839         37          40  162     D   
0163A00018000000   2288.06505   242.05425         38          41  163     A   
0163B00029000000   9774.39239   398.59073         39          42  163     B   
0163A00019000000   2347.07017   243.37390         40          43  163     A   
0163A00030000000   2070.46087   241.67216         41          44  163     A   
0163A00020000000   1684.42713   229.90002         42          45  163     A   
0163A00021000000   2010.37313   236.65117         43          46  163     A   
0163A00001000000   5378.59692   332.19574         44          47  163     A   
0163A00024000000   4709.87045   290.59828         45          48  163     A   
0163B00038000000   5723.37042   343.94021         46          49  163     B   
0163A00029000000   2092.22976   242.23510         47          50  163     A   
0163E00076000000  11194.97533   429.44723         48          51  163     E   
0162H00002000000   3246.89212   286.95076         49          52  162     H   
0162H00004000000   3879.34909   296.79667         50          53  162     H   
0163A00027000000   2921.17142   258.87239         51          54  163     A   
0162H00005000000   2212.56843   266.56219         52          55  162     H   
0162H00006000000   2728.06150   274.76062         53          56  162     H   
0162H00007000000   2842.14040   275.81471         54          57  162     H

In [222]:
apd_1999.loc['0232C00201000000']['SALEDATE']

'1970-11-01'

In [227]:
# Save apd_1999 back out
save_adf(apd_1999, 'apd_1999')

Saving to assessments/apdstore_apd_1999.h5, key=apd_1999


/home/rsargent/anaconda2/lib/python2.7/site-packages/ipykernel_launcher.py:2: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->mixed,key->axis0] [items->None]

  
/home/rsargent/anaconda2/lib/python2.7/site-packages/ipykernel_launcher.py:2: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->unicode,key->block1_items] [items->None]

  
/home/rsargent/anaconda2/lib/python2.7/site-packages/ipykernel_launcher.py:2: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type->unicode,key->block2_items] [items->None]

  
/home/rsargent/anaconda2/lib/python2.7/site-packages/ipykernel_launcher.py:2: PerformanceWarning: 
your performance may suffer as PyTables will pickle object types that it cannot
map directly to c-types [inferred_type

In [192]:
# Try to save out property_map before we start messsing with it
import pickle

with open('assessments/property_map_09_17.pickle', 'wb') as handle:
    pickle.dump(property_map, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [ ]:
# Try to restore property_map 
import pickle

with open('assessments/property_map_09_17.pickle', 'rb') as handle:
    property_map = pickle.load(handle)

In [193]:
len(property_map)

505214

In [201]:
# Process assessment records from apd_1999.  We don't know when it's from exactly, but the most recent 
# SALEDATE in there is '1997-12-01' (apd_1999['SALEDATE'].max()), so '1999-01-01' seems safe
process_all_assessment_records(apd_1999, '1999-01-01')

1-10000: 9550 added, 0:06:19.840404 time elapsed
10001-20000: 9945 added, 0:06:22.275768 time elapsed
20001-30000: 9917 added, 0:06:35.797176 time elapsed
30001-40000: 9915 added, 0:06:30.859224 time elapsed
40001-50000: 9899 added, 0:06:39.305964 time elapsed
50001-60000: 9913 added, 0:06:34.924352 time elapsed
60001-70000: 9942 added, 0:06:27.730443 time elapsed
70001-80000: 9963 added, 0:06:40.150202 time elapsed
80001-90000: 9963 added, 0:06:48.449238 time elapsed
Processing took 1:05:15.371023


## 2004

In [235]:
# Try to save out property_map before we start messsing with it
import pickle

with open('assessments/property_map_99_09_17.pickle', 'wb') as handle:
    pickle.dump(property_map, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [262]:
apd_2004 = restore_adf('apd_2004')

Restoring from assessments/apdstore_apd_2004.h5, key=apd_2004


In [269]:
len(apd_2004)

395103

In [270]:
apd_2004[pd.isnull(apd_2004.property_address)]

OldBlockLot  FAIRMARKETLAND  FAIRMARKETBUILDING  MuniCode  \
PARID                                                                          
0001C01662004200   1-C-1662-42               0               54100       102   
0001C01662004300   1-C-1662-43               0              135300       102   
0001C01662004400   1-C-1662-44               0              106900       102   
0001C01662004600   1-C-1662-46               0               76800       102   
0001C01662004700   1-C-1662-47               0               53500       102   
0001C01662005200   1-C-1662-52               0               53900       102   
0001C01662005300   1-C-1662-53               0              135300       102   
0001C01662005400   1-C-1662-54               0              106900       102   
0001C01662005500   1-C-1662-55               0               77400       102   
0001C01662005700   1-C-1662-57               0               53500       102   
0001C01662006100   1-C-1662-61               0               69700       102   
0001C01662006200   1-C-1662-62               0               53900       102   
0001C01662006300   1-C-1662-63               0              135300       102   
0001C01662006400   1-C-1662-64               0              106900       102   
0001C01662006500   1-C-1662-65               0               77400       102   
0001C01662006600   1-C-1662-66               0               76800       102   
0001C01662006700   1-C-1662-67               0               53500       102   
0001C01662006800   1-C-1662-68               0               71900       102   
0001C01662007200   1-C-1662-72               0               48600       102   
0001C01662007300   1-C-1662-73               0              135300       102   
0001C01662007400   1-C-1662-74               0              106900       102   
0001C01662007500   1-C-1662-75               0               77400       102   
0001C01662008100   1-C-1662-81               0               69700       102   
0001C01662008200   1-C-1662-82               0               53900       102   
0001C01662008300   1-C-1662-83               0              135300       102   
0001C01662008400   1-C-1662-84               0              106900       102   
0001C01662008500   1-C-1662-85               0               77400       102   
0001C01662008700   1-C-1662-87               0               53500       102   
0001C01662009100   1-C-1662-91               0               69700       102   
0001C01662009200   1-C-1662-92               0               53900       102   
0001C01662009300   1-C-1662-93               0              114300       102   
0001C01662009400   1-C-1662-94               0              106900       102   
0001C01662009500   1-C-1662-95               0               77400       102   
0001C01662009600   1-C-1662-96               0               76800       102   
0001C01662009700   1-C-1662-97               0               53500       102   
0001C01662009800   1-C-1662-98               0               71000       102   
0001C01662010200  1-C-1662-102               0               53900       102   
0001C01662010300  1-C-1662-103               0              135300       102   
0001C01662010400  1-C-1662-104               0              105100       102   
0001C01662010500  1-C-1662-105               0               77400       102   
0001C01662010600  1-C-1662-106               0               76800       102   
0001C01662010700  1-C-1662-107               0               53500       102   
0001C01662011100  1-C-1662-111               0               69700       102   
0001C01662011200  1-C-1662-112               0               53900       102   
0001C01662011300  1-C-1662-113               0              130600       102   
0001C01662011400  1-C-1662-114               0              106900       102   
0001C01662011500  1-C-1662-115               0               77400       102   
0001C01662011600  1-C-1662-116               0               76800       102   
0001C01662011700  1

In [237]:
apd_2004['SALEDATE'].max()

'2001-02-15'

In [240]:
# Process assessment records from apd_2004.  We don't know when it's from exactly, but the most recent 
# SALEDATE in there is '2001-02-15' (apd_2004['SALEDATE'].max()), so '2004-01-01' seems safe.
# Actually, comparing the 2004 to 2005 sets, we really need the asofdate to be '2001-02-15'
# instead of '2004-01-01'
process_all_assessment_records(apd_2004, '2001-02-15')

1-10000: 9708 added, 0:05:55.131887 time elapsed
10001-20000: 9831 added, 0:05:51.868352 time elapsed
20001-30000: 9694 added, 0:05:51.064735 time elapsed
30001-40000: 9895 added, 0:05:50.814573 time elapsed
40001-50000: 9690 added, 0:05:52.453277 time elapsed
50001-60000: 9917 added, 0:05:50.446461 time elapsed
60001-70000: 9780 added, 0:05:54.229597 time elapsed
70001-80000: 9798 added, 0:05:54.119624 time elapsed
80001-90000: 9898 added, 0:05:51.770988 time elapsed
90001-100000: 9881 added, 0:05:50.671346 time elapsed
100001-110000: 9795 added, 0:05:54.216169 time elapsed
110001-120000: 9702 added, 0:05:51.360727 time elapsed
120001-130000: 9882 added, 0:05:52.779460 time elapsed
130001-140000: 9821 added, 0:05:58.147278 time elapsed
140001-150000: 9897 added, 0:05:53.616516 time elapsed
150001-160000: 9901 added, 0:05:55.704589 time elapsed
160001-170000: 9809 added, 0:06:00.578988 time elapsed
170001-180000: 9873 added, 0:05:52.383572 time elapsed
180001-190000: 9899 added, 0:05:5

In [290]:
# Rewrite property_map entries with asofdate of '2004-01-01' to '2001-02-15'
bad_asofdate='2004-01-01'
replacement_asofdate='2001-02-15'
count=0
for parid in apd_2004.index:
    for ev in property_map[parid]:
        if(ev['asofdate']==bad_asofdate):
            ev['asofdate']=replacement_asofdate
            if(count % 1000==0):
                print "%s: %s [%s] -> [%s]" % (parid, ev['date'], bad_asofdate, replacement_asofdate)
            count = count+1            

In [271]:
for i in range(0, len(apd_2004)):
    update_property_address(apd_2004, i)

In [278]:
count=0
for parid in noprop_parids_2004:
    if (not parid in canonical_property_address_map):
        print "%s missing from canonical_property_address_map (raw = %s)" % (parid, raw_property_address_map[parid])
    else:
        if((count % 100)==0):
            print "%d: Ok" % (count)
        count = count+1

0553N00123000000 missing from canonical_property_address_map (raw =  SCHWEITZER RD  )
0295B00162000000 missing from canonical_property_address_map (raw =  VERONA RD  )
0878N00067000000 missing from canonical_property_address_map (raw =  REED ST CLAIRTON       PA 15025)
0188M00010000000 missing from canonical_property_address_map (raw =  IDA ST PITTSBURGH     PA 15227)
0032E00295000000 missing from canonical_property_address_map (raw =  ST LUCAS ST PGH            PA 15210)
0887H00134000000 missing from canonical_property_address_map (raw =  ROOSEVELT AVE  )
0: Ok
0163K00059000000 missing from canonical_property_address_map (raw =  EVERGREEN RD                PA )
0177D00218000000 missing from canonical_property_address_map (raw = 121 EDGEWOOD AVE PITTSBURGH     PA 15218)
8000T02674000000 missing from canonical_property_address_map (raw = 99 GRACE LANE  )
1210M00159000000 missing from canonical_property_address_map (raw =  HARDIES  )
0094N00272000000 missing from canonical_property_addre

8000T02772000000 missing from canonical_property_address_map (raw = 108 JOSEPH LANE  )
0472L00148000000 missing from canonical_property_address_map (raw =    )
0141K00070000000 missing from canonical_property_address_map (raw = 748 SHADY DR E  )
8000T02760000000 missing from canonical_property_address_map (raw = 112 JOSEPH LANE  )
0179P00080000000 missing from canonical_property_address_map (raw =  WHITAKER WAY MUNHALL        PA 15120)
8000T02544000000 missing from canonical_property_address_map (raw = 282 VALLEY VIEW DR  )
0887C00269000000 missing from canonical_property_address_map (raw =  ROOSEVELT AVE  )
0319B00085000000 missing from canonical_property_address_map (raw =  CLAIR DR  )
0232F00088000000 missing from canonical_property_address_map (raw = 1703 MAPLEWOOD AVE PGH            PA 15221)
0089K00120000000 missing from canonical_property_address_map (raw =  JOHNSTON AVE PITTSBURGH     PA 15207)
0004J00287000000 missing from canonical_property_address_map (raw = 116 WILBERT ST  

# 2005

In [347]:
# Try to save out property_map before we start messsing with it
import pickle

with open('assessments/property_map_99_04_09_17.pickle', 'wb') as handle:
    pickle.dump(property_map, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [348]:
apd_2005 = restore_adf('apd_2005')

Restoring from assessments/apdstore_apd_2005.h5, key=apd_2005


In [350]:
# Process assessment records from apd_2005.  We don't know when it's from exactly, but the most recent 
# valid-looking SALEDATE in there is '2005-08-28 (apd_2005['SALEDATE'].max())
process_all_assessment_records(apd_2005, '2005-08-28')


1-10000: 8838 added, 0:00:03.088631 time elapsed
10001-20000: 8940 added, 0:00:02.632514 time elapsed
20001-30000: 8778 added, 0:00:02.648495 time elapsed
30001-40000: 9227 added, 0:00:02.924991 time elapsed
40001-50000: 9159 added, 0:00:02.760473 time elapsed
50001-60000: 9049 added, 0:00:03.038509 time elapsed
60001-70000: 8486 added, 0:00:03.333076 time elapsed
70001-80000: 9709 added, 0:00:02.923451 time elapsed
80001-90000: 9495 added, 0:00:02.958425 time elapsed
90001-100000: 9155 added, 0:00:03.243168 time elapsed
100001-110000: 9046 added, 0:00:02.764956 time elapsed
110001-120000: 9442 added, 0:00:03.104817 time elapsed
120001-130000: 9084 added, 0:00:03.406248 time elapsed
130001-140000: 8440 added, 0:00:02.893669 time elapsed
140001-150000: 9212 added, 0:00:02.989249 time elapsed
150001-160000: 8055 added, 0:00:02.959788 time elapsed
160001-170000: 9355 added, 0:00:02.680239 time elapsed
170001-180000: 9887 added, 0:00:03.183450 time elapsed
180001-190000: 9818 added, 0:00:0

# Deal with older versions of the assessment database from the ACCDB files from Bob Gradeck

In [81]:
# From https://stackoverflow.com/questions/17123550/extract-and-sort-data-from-mdb-file-using-mdbtools-in-python?utm_medium=organic&utm_source=google_rich_qa&utm_campaign=google_rich_qa
import sys, subprocess, os, numpy
from io import StringIO
import pandas as pd
import pandas
VERBOSE = True
def mdb_to_pandas(database_path,dtype_map):
    subprocess.call(["mdb-schema", database_path, "mysql"])
    # Get the list of table names with "mdb-tables"
    table_names = subprocess.Popen(["mdb-tables", "-1", database_path],
                                   stdout=subprocess.PIPE).communicate()[0]
    tables = table_names.splitlines()
    sys.stdout.flush()
    # Dump each table as a stringio using "mdb-export",
    out_tables = {}
    for rtable in tables:
        table = rtable.decode()
        if VERBOSE: print('running table:',table)
        if table != '':
            if VERBOSE: print("Dumping " + table)
            contents = subprocess.Popen(["mdb-export", database_path, table],
                                        stdout=subprocess.PIPE).communicate()[0]
            temp_io = StringIO(contents.decode('utf8'))
            print(table, temp_io)
            out_tables[table] = pd.read_csv(temp_io,dtype=dtype_map)
    return out_tables
pd.options.display.max_colwidth = 300
pd.set_option('display.max_columns', 500)


In [241]:
# ACCDB files are from Bob Gradeck
# 2009 is missing YEARBLT, CLASSDESC, and CLASS

# A number of files after 2009 seem to have a common set of column names
post_2009_colmap = {'mapblolot':'PARID',
                    'PropertyHouseNum'    :'PROPERTYHOUSENUM', 
                    'PropertyFraction'    :'PROPERTYFRACTION', 
                    'PropertyAddress'     :'PROPERTYADDRESS',  
                    'PropertyUnit'        :'PROPERTYUNIT',     
                    'PropertyCityState'   :'PROPERTYCITY',     
                    'PropertyLocation2'   :'PROPERTYSTATE',    
                    'PropertyZip'         :'PROPERTYZIP',       
                    'FairMarketTotal':'FAIRMARKETTOTAL',
                    'UseDesc':'USEDESC',
                    'PropertyZip':'PROPERTYZIP',
                    'PropertyOwner2':'PROPERTYOWNER',
                    'ChangeNoticeFullAddress1':'CHANGENOTICEADDRESS1',
                    'ChangeNoticeFullAddress2':'CHANGENOTICEADDRESS2',
                    'ChangeNoticeFullAddress3':'CHANGENOTICEADDRESS3',
                    'ChangeNoticeFullAddress4':'CHANGENOTICEADDRESS4',
                    'HomesteadFlag':'HOMESTEADFLAG',
                    'OwnerDesc':'OWNERDESC',
                    'SaleDate':'SALEDATE',
                    'SalePrice':'SALEPRICE',
                    'SaleCode': 'SALECODE',
                    'SaleDesc': 'SALEDESC'
                    }
post_2009_dtype = {'PropertyHouseNum':numpy.str,'PropertyFraction':numpy.str, 'PropertyZip':numpy.str,
                    'ChangeNoticeFullAddress1':numpy.str,'ChangeNoticeFullAddress2':numpy.str, 
                    'ChangeNoticeFullAddress3':numpy.str,'ChangeNoticeFullAddress4':numpy.str, 
                   }

accdb_info = {'2004':{'fname': 'assessments/kristin/ParcelData_RandySargent/2004/db1.mdb',
                      'tname': 'LandFileAug2001',
                      'col_remap': {'MapBloLot':'PARID',
                                    'CurOwnerName':'PROPERTYOWNER',
                                    'Homestead':'HOMESTEADFLAG',
                                    'SalePrice':'SALEPRICE',
                                    'TotalLandAssess':'FAIRMARKETLAND',
                                    'TotalBuildingAssess':'FAIRMARKETBUILDING'
                        },
                      'dtype':{'MailStreetNumber':numpy.str,'MailZipCode':numpy.str, 
                               'ST_NUMBER':numpy.str, 'ZIPCODE':numpy.str
                              }
                     },
              '2005':{'fname': 'assessments/kristin/ParcelData_RandySargent/2005/AC db 10.20.05.mdb',
                      'tname': 'DS09-21-05',
                      'col_remap': {'Field1':'PARID',
                                    'Field2':'PROPERTYOWNER',
                                    'Field23':'OWNERDESC',
                                    'Field27':'USEDESC',
                                    'Field29':'HOMESTEADFLAG',
                                    'Field31':'SALEDATE_raw',
                                    'Field32':'SALEPRICE',
                                    'Field36':'FAIRMARKETBUILDING',
                                    'Field37':'FAIRMARKETLAND',
                                    'Field38':'FAIRMARKETTOTAL',
                                    'Field57':'SALECODE',
                                    'Field58':'SALEDESC',
                                    'Field62':'YEARRBLT'
                        },
                      'dtype':{'Field45':numpy.str,'Field31':numpy.str, 
                               'Field4' :numpy.str, 'Field5' :numpy.str, 'Field6' :numpy.str, 
                               'Field7' :numpy.str, 'Field8' :numpy.str, 'Field9' :numpy.str, 
                               'Field10':numpy.str, 'Field11':numpy.str
                              }
                     },
              '2009':{'fname':'assessments/gradeck/AssessmentSep09.mdb',
                      'tname':'pncis',
                     'col_remap': {'PIN':'PARID',
                                    'PROPERTYHO':'PROPERTYHOUSENUM', 
                                    'PROPERTYAD':'PROPERTYFRACTION', 
                                    'PROPERTY_1':'PROPERTYADDRESS',  
                                    'PROPERTYUN':'PROPERTYUNIT',     
                                    'PROPERTYLO':'PROPERTYCITY',     
                                    'PROPERTYCI':'PROPERTYSTATE',    
                                    'PROPERTYZI':'PROPERTYZIP',       
                                    'FAIRMARK_2':'FAIRMARKETTOTAL',
                                    'USEDESC':'USEDESC',
                                    'PROPERTYZI':'PROPERTYZIP',
                                    'PROPERTYOW':'PROPERTYOWNER',
                                    'CHANGENOTI':'CHANGENOTICEADDRESS1',
                                    'CHANGENO_1':'CHANGENOTICEADDRESS2',
                                    'CHANGENO_2':'CHANGENOTICEADDRESS3',
                                    'CHANGENO_3':'CHANGENOTICEADDRESS4',
                                    'HOMESTEADF':'HOMESTEADFLAG',
                                    'OWNERDESC':'OWNERDESC',
                                    'SALEDATE':'SALEDATE',
                                    'SALEPRICE':'SALEPRICE'
                                  },
                      'dtype':{'PROPERTYHO':numpy.str,'PROPERTY_1':numpy.str,'PROPERTYUN':numpy.str,
                                'PROPERTYLO':numpy.str,'PROPERTYCI':numpy.str,'PROPERTYZI':numpy.str}
                     },
               '2010':{'fname':'assessments/gradeck/June2010AssessNew.accdb',
                       'tname':'RawDataAssessment',
                       'col_remap': post_2009_colmap,
                       'dtype': post_2009_dtype
                      },
               '2011':{'fname':'assessments/gradeck/AssessMarch2011Data3.mdb.accdb',
                       'tname':'AssessMarch2011',
                       'col_remap': {'PIN':'PARID',
                                    'PropertyOwnerNew':'PROPERTYOWNER',
                                    'CHANGENOTICEFULLADDRESS1':'CHANGENOTICEADDRESS1',
                                    'CHANGENOTICEFULLADDRESS2':'CHANGENOTICEADDRESS2',
                                    'CHANGENOTICEFULLADDRESS3':'CHANGENOTICEADDRESS3',
                                    'CHANGENOTICEFULLADDRESS4':'CHANGENOTICEADDRESS4',
                                    'PROPERTYHOUSENUM'    :'PROPERTYHOUSENUM',
                                    'PROPERTYADDNUMPREFIX':'PROPERTYFRACTION',
                                    'PROPERTYADDRESS'     :'PROPERTYADDRESS',
                                    'PROPERTYUNIT'        :'PROPERTYUNIT',
                                    'PROPERTYLOCATION2'   :'PROPERTYCITY',
                                    'PROPERTYCITYSTATE'   :'PROPERTYSTATE',
                                    'PROPERTYZIP'         :'PROPERTYZIP'       

                                  },
                        'dtype':{'PROPERTYHOUSENUM':numpy.str,'PROPERTYADDRESS':numpy.str,'PROPERTYUNIT':numpy.str,
                                'PROPERTYLOCATION2':numpy.str,'PROPERTYCITYSTATE':numpy.str,'PROPERTYZIP':numpy.str}
                      },
               '2012':{'fname':'assessments/gradeck/AssessNov2012.mdb',
                       'tname':'AssessmentOct2_2012',                       
                       'col_remap': {'SALEDATE':'SALEDATE_raw'},
                       'dtype':{'PROPERTYHOUSENUM':numpy.str,'PROPERTYADDRESS':numpy.str,'PROPERTYUNIT':numpy.str,
                                'PROPERTYLOCATION2':numpy.str,'PROPERTYCITYSTATE':numpy.str,'PROPERTYZIP':numpy.str,
                                'SALEDATE':numpy.str, 'CHANGENOTICEADDRESS1':numpy.str,
                                'CHANGENOTICEADDRESS2':numpy.str, 'CHANGENOTICEADDRESS3':numpy.str,
                                'CHANGENOTICEADDRESS4':numpy.str,}
                      },
               '2013':{'fname':'assessments/gradeck/Dec2013Assess.accdb',
                       'tname':'RawDataAssessment',
                       'col_remap': post_2009_colmap,
                       'dtype': post_2009_dtype
                      },
               '2014':{'fname':'assessments/gradeck/June2014Assess.accdb',
                       'tname':'RawDataAssessment',
                       'col_remap': post_2009_colmap,
                       'dtype': post_2009_dtype
                      },
               '2015':{'fname':'assessments/gradeck/May2015Assess.accdb',
                       'tname':'RawDataAssessment',
                       'col_remap': post_2009_colmap,
                       'dtype': post_2009_dtype
                      }
             }

In [118]:
# Uses accdb_info map to import a file for a given year and return a dataframe.  
# This doesn't remap the column names (we might not know them yet)
def import_accdb_file(year):
    # Import the accdb file for this year.  The returned value is a map of table names to tables
    accdb_table_map = mdb_to_pandas(accdb_info[year]['fname'], accdb_info[year]['dtype'])     
    apd_df = accdb_table_map[accdb_info[year]['tname']]
    return apd_df

# Takes a dataframe imported by import_accdb_file, renames columns, sets the index to PARID, 
# filters out rows that aren't dwellings, sets zipcode to be type string
skip_dwelling_col=False
def cleanup_accdb_import(df, year):
    r_df = df.rename(index=str, columns=accdb_info[year]['col_remap']).set_index('PARID')
    if(not skip_dwelling_col):
        r_df = pd.merge(r_df,dwelling_col.to_frame(),on='PARID', left_on=None, right_on=None,
                         left_index=False, right_index=False, sort=False,
                         suffixes=('_x', '_y'), copy=True, indicator=False,
                         validate=None)
        print "After merge, size = %d" % (len(r_df))

        r_df = r_df[r_df.is_dwelling]
        print "After filtering to only include dwellings, size = %d" % (len(r_df))

    # Change ',  -' in CHANGENOTICEADDRESS3 to nan (that's a common pattern in these accdb files)
    bad_changeaddr = r_df.CHANGENOTICEADDRESS3==',  -'
    r_df.loc[bad_changeaddr,'CHANGENOTICEADDRESS3']= numpy.nan

    # Filter out empty owner names
    empty_owner = r_df.PROPERTYOWNER.isna()

    # Filter out empty change addresses
    p1=pandas.isna(r_df.CHANGENOTICEADDRESS1) 
    p2=pandas.isna(r_df.CHANGENOTICEADDRESS2) 
    p3=pandas.isna(r_df.CHANGENOTICEADDRESS3)
    p4=pandas.isna(r_df.CHANGENOTICEADDRESS4)
    r_df = r_df[~((p1&p2&p3&p4)|empty_owner)]
    print "After filtering to remove empty owner names and change addresses, size = %d" % (len(r_df))

    # Fix up <BR> to be &
    r_df.PROPERTYOWNER = r_df.PROPERTYOWNER.str.replace('\s*<BR>\s*', ' & ', regex=True)
    return r_df

# More cleanup after merge
def cleanup_merged_accdb_import(df, year):
    # A common pattern of bad addresses is ' , -0000 ', get rid of ones like this
    bad_owner_addr = df.owner_address_raw.str.contains('^[\s,]*-\d\d\d\d\s*$',regex=True)
    r_df = df[~(bad_owner_addr)]
    print "After filtering to remove malformed owner_address_raw addresses, size = %d" % (len(r_df))
    return r_df

# Process 2015

In [496]:
apd_2015_raw = import_accdb_file('2015') 

('running table:', u'LandUseCodes')
Dumping LandUseCodes
(u'LandUseCodes', <_io.StringIO object at 0x7f9cf2f4a050>)
('running table:', u'MasterListPotentialREO')
Dumping MasterListPotentialREO
(u'MasterListPotentialREO', <_io.StringIO object at 0x7f9d6aaa8350>)
('running table:', u'Name AutoCorrect Save Failures')
Dumping Name AutoCorrect Save Failures
(u'Name AutoCorrect Save Failures', <_io.StringIO object at 0x7f9d6aaa8750>)
('running table:', u'OwnerCodeDefinition')
Dumping OwnerCodeDefinition
(u'OwnerCodeDefinition', <_io.StringIO object at 0x7f9ccdb652d0>)
('running table:', u'RawDataAssessment')
Dumping RawDataAssessment
(u'RawDataAssessment', <_io.StringIO object at 0x7f9d6aaa8350>)
('running table:', u'RawDataAssessment Table Layout')
Dumping RawDataAssessment Table Layout
(u'RawDataAssessment Table Layout', <_io.StringIO object at 0x7f9ccd3b38d0>)
('running table:', u'SaleDataFull')
Dumping SaleDataFull
(u'SaleDataFull', <_io.StringIO object at 0x7f9c823c1bd0>)
('running tabl

In [497]:
apd_2015 = cleanup_accdb_import(apd_2015_raw, '2015')

After merge, size = 577753
After filtering to only include dwellings, size = 519223
After filtering to remove empty owner names and change addresses, size = 506872


In [ ]:
merge_addrs(apd_2015)
canonicalize_addrs(apd_2015)

In [ ]:
# Save out apd_2015 to mdf
save_adf(apd_2015, 'apd_2015')

In [498]:
process_all_assessment_records(apd_2015, '2015-05-01')

1-10000: 1517 added, 0:00:05.867339 time elapsed
10001-20000: 1407 added, 0:00:04.489289 time elapsed
20001-30000: 1427 added, 0:00:04.819603 time elapsed
30001-40000: 1334 added, 0:00:04.969159 time elapsed
40001-50000: 1274 added, 0:00:05.379638 time elapsed
50001-60000: 1384 added, 0:00:05.167290 time elapsed
60001-70000: 1399 added, 0:00:05.008074 time elapsed
70001-80000: 1293 added, 0:00:04.626940 time elapsed
80001-90000: 1321 added, 0:00:04.544026 time elapsed
90001-100000: 1572 added, 0:00:05.238416 time elapsed
100001-110000: 1307 added, 0:00:05.137790 time elapsed
110001-120000: 1388 added, 0:00:04.622946 time elapsed
120001-130000: 1272 added, 0:00:05.403689 time elapsed
130001-140000: 1098 added, 0:00:05.451560 time elapsed
140001-150000: 1124 added, 0:00:05.181060 time elapsed
150001-160000: 1398 added, 0:00:05.196724 time elapsed
160001-170000: 1300 added, 0:00:04.792961 time elapsed
170001-180000: 1203 added, 0:00:05.596729 time elapsed
180001-190000: 1221 added, 0:00:0

# Process 2014

In [499]:
apd_2014_raw = import_accdb_file('2014') 

('running table:', u'LandUseCodes')
Dumping LandUseCodes
(u'LandUseCodes', <_io.StringIO object at 0x7f9c3dc874d0>)
('running table:', u'MasterListPotentialREO')
Dumping MasterListPotentialREO
(u'MasterListPotentialREO', <_io.StringIO object at 0x7f9c15490250>)
('running table:', u'Name AutoCorrect Save Failures')
Dumping Name AutoCorrect Save Failures
(u'Name AutoCorrect Save Failures', <_io.StringIO object at 0x7f9c15490650>)
('running table:', u'OwnerCodeDefinition')
Dumping OwnerCodeDefinition
(u'OwnerCodeDefinition', <_io.StringIO object at 0x7f9c14e3fad0>)
('running table:', u'RawDataAssessment')
Dumping RawDataAssessment
(u'RawDataAssessment', <_io.StringIO object at 0x7f9c15490250>)
('running table:', u'RawDataAssessment Table Layout')
Dumping RawDataAssessment Table Layout
(u'RawDataAssessment Table Layout', <_io.StringIO object at 0x7f9c14424a50>)
('running table:', u'SaleDataFull')
Dumping SaleDataFull
(u'SaleDataFull', <_io.StringIO object at 0x7f9ab6d1ccd0>)
('running tabl

In [500]:
apd_2014 = cleanup_accdb_import(apd_2014_raw, '2014')

After merge, size = 576705
After filtering to only include dwellings, size = 518307
After filtering to remove empty owner names and change addresses, size = 505834


In [ ]:
merge_addrs(apd_2014)
canonicalize_addrs(apd_2014)

In [501]:
process_all_assessment_records(apd_2014, '2014-06-01')

1-10000: 266 added, 0:00:05.618758 time elapsed
10001-20000: 226 added, 0:00:04.789025 time elapsed
20001-30000: 223 added, 0:00:05.533156 time elapsed
30001-40000: 205 added, 0:00:05.346532 time elapsed
40001-50000: 256 added, 0:00:05.375026 time elapsed
50001-60000: 225 added, 0:00:05.805101 time elapsed
60001-70000: 245 added, 0:00:05.383229 time elapsed
70001-80000: 239 added, 0:00:05.206946 time elapsed
80001-90000: 251 added, 0:00:05.517752 time elapsed
90001-100000: 285 added, 0:00:05.431181 time elapsed
100001-110000: 243 added, 0:00:05.211462 time elapsed
110001-120000: 261 added, 0:00:05.428997 time elapsed
120001-130000: 258 added, 0:00:04.613174 time elapsed
130001-140000: 161 added, 0:00:04.925088 time elapsed
140001-150000: 211 added, 0:00:05.429947 time elapsed
150001-160000: 273 added, 0:00:04.913482 time elapsed
160001-170000: 240 added, 0:00:04.764811 time elapsed
170001-180000: 204 added, 0:00:06.020577 time elapsed
180001-190000: 205 added, 0:00:05.418098 time elaps

# Process 2013

In [502]:
apd_2013_raw = import_accdb_file('2013') 

('running table:', u'Name AutoCorrect Save Failures')
Dumping Name AutoCorrect Save Failures
(u'Name AutoCorrect Save Failures', <_io.StringIO object at 0x7f9c3dc873d0>)
('running table:', u'OwnerCodeDefinition')
Dumping OwnerCodeDefinition
(u'OwnerCodeDefinition', <_io.StringIO object at 0x7f9b2e4ab0d0>)
('running table:', u'RawDataAssessment')
Dumping RawDataAssessment
(u'RawDataAssessment', <_io.StringIO object at 0x7f9b2e4ab750>)
('running table:', u'RawDataAssessment Table Layout')
Dumping RawDataAssessment Table Layout
(u'RawDataAssessment Table Layout', <_io.StringIO object at 0x7f9b2ddff1d0>)
('running table:', u'SaleDataFull')
Dumping SaleDataFull
(u'SaleDataFull', <_io.StringIO object at 0x7f9a4a166bd0>)
('running table:', u'SaleDetails')
Dumping SaleDetails
(u'SaleDetails', <_io.StringIO object at 0x7f9a498b3dd0>)
('running table:', u'tblOwnerAddressCount')
Dumping tblOwnerAddressCount
(u'tblOwnerAddressCount', <_io.StringIO object at 0x7f9a481572d0>)
('running table:', u'Un

In [488]:
apd_2013 = cleanup_accdb_import(apd_2013_raw, '2013')

After merge, size = 575195
After filtering to only include dwellings, size = 517123
After filtering to remove empty owner names and change addresses, size = 504628


In [489]:
merge_addrs(apd_2013)
canonicalize_addrs(apd_2013)

u'ROBERT E KELLY JR REVOCABLE TRUST       ROBERT E KELLY JR \u0393\xc7\xf4 TRUSTEE & BRI'

In [ ]:
# Save out apd_2013 to mdf
save_adf(apd_2013, 'apd_2013')

In [491]:
process_all_assessment_records(apd_2013, '2013-12-01')

1-10000: 9797 added, 0:00:05.047437 time elapsed
10001-20000: 9897 added, 0:00:04.349531 time elapsed
20001-30000: 9805 added, 0:00:04.347125 time elapsed
30001-40000: 9922 added, 0:00:04.748191 time elapsed
40001-50000: 9957 added, 0:00:04.252485 time elapsed
50001-60000: 9881 added, 0:00:04.917269 time elapsed
60001-70000: 9915 added, 0:00:04.663241 time elapsed
70001-80000: 9971 added, 0:00:05.381502 time elapsed
80001-90000: 9901 added, 0:00:05.187847 time elapsed
90001-100000: 9896 added, 0:00:05.320142 time elapsed
100001-110000: 9900 added, 0:00:04.745531 time elapsed
110001-120000: 9980 added, 0:00:04.537871 time elapsed
120001-130000: 9835 added, 0:00:05.404307 time elapsed
130001-140000: 9923 added, 0:00:05.861283 time elapsed
140001-150000: 9873 added, 0:00:04.975491 time elapsed
150001-160000: 9884 added, 0:00:04.953024 time elapsed
160001-170000: 9909 added, 0:00:05.259866 time elapsed
170001-180000: 9938 added, 0:00:05.342598 time elapsed
180001-190000: 9951 added, 0:00:0

# Process 2012

In [ ]:
#  SALEDATE field is MMDDYYYY, so we need to do some more work than usual:
#    9042007  = '2007-09-04'

# Setup regular expression for parsing mmddyyyy date
mmddyyyy_re = re.compile('(\d\d)(\d\d)(\d\d\d\d)')

def mmddyyyy_to_yyyymmdd(datestr_raw):
    # Parse the sections of the date string
    m = mmddyyyy_re.match(str(datestr_raw))
    # The month will be in the first group, the day in the second, the year in the third
    return '%s-%s-%s'%(m.group(3),m.group(1),m.group(2))

In [ ]:
# If we've already processed before and haven't changed process, just reload
apd_2012 = restore_adf('apd_2012')

In [ ]:
# Otherwise, process afresh
apd_2012_raw = import_accdb_file('2012') 

In [291]:
apd_2012 = cleanup_accdb_import(apd_2012_raw, '2012')


After merge, size = 572899
After filtering to only include dwellings, size = 515052
After filtering to remove empty owner names and change addresses, size = 515052


In [ ]:
# Get rid of empty sale dates and convert to yyyy-mm-dd format
apd_2012=apd_2012[~pandas.isna(apd_2012.SALEDATE_raw)].copy()
apd_2012['SALEDATE'] = apd_2012['SALEDATE_raw'].map(mmddyyyy_to_yyyymmdd)

In [ ]:
merge_addrs(apd_2012)
canonicalize_addrs(apd_2012)

In [ ]:
apd_2012=cleanup_merged_accdb_import(apd_2012, '2012')

In [292]:
process_all_assessment_records(apd_2012, '2012-11-01')

TypeError: buffer size mismatch

# Process 2011

In [503]:
apd_2011_raw = import_accdb_file('2011') 

('running table:', u'AssessMarch2011')
Dumping AssessMarch2011
(u'AssessMarch2011', <_io.StringIO object at 0x7f9c23829c50>)
('running table:', u'MasterListPotentialREO')
Dumping MasterListPotentialREO
(u'MasterListPotentialREO', <_io.StringIO object at 0x7f9c39c75550>)
('running table:', u'OwnerCodeDefinition')
Dumping OwnerCodeDefinition
(u'OwnerCodeDefinition', <_io.StringIO object at 0x7f9a29da0ad0>)
('running table:', u'Universe of Potential Public Owners')
Dumping Universe of Potential Public Owners
(u'Universe of Potential Public Owners', <_io.StringIO object at 0x7f9a296b2550>)
('running table:', u'ChangeNoticeCount')
Dumping ChangeNoticeCount
(u'ChangeNoticeCount', <_io.StringIO object at 0x7f9c39c75550>)


In [504]:
apd_2011 = cleanup_accdb_import(apd_2011_raw, '2011')

After merge, size = 566424
After filtering to only include dwellings, size = 509082
After filtering to remove empty owner names and change addresses, size = 508830


In [ ]:
merge_addrs(apd_2011)
canonicalize_addrs(apd_2011)

In [ ]:
# Save out apd_2011 to mdf
save_adf(apd_2011, 'apd_2011')

In [505]:
process_all_assessment_records(apd_2011, '2011-03-01')

1-10000: 9341 added, 0:00:04.501821 time elapsed
10001-20000: 9450 added, 0:00:04.474968 time elapsed
20001-30000: 9756 added, 0:00:04.939104 time elapsed
30001-40000: 9638 added, 0:00:05.174120 time elapsed
40001-50000: 9763 added, 0:00:04.502422 time elapsed
50001-60000: 9632 added, 0:00:04.686311 time elapsed
60001-70000: 9763 added, 0:00:05.465233 time elapsed
70001-80000: 9735 added, 0:00:05.216360 time elapsed
80001-90000: 9644 added, 0:00:05.685269 time elapsed
90001-100000: 9535 added, 0:00:05.639264 time elapsed
100001-110000: 9420 added, 0:00:05.574873 time elapsed
110001-120000: 9681 added, 0:00:04.861739 time elapsed
120001-130000: 9725 added, 0:00:04.739321 time elapsed
130001-140000: 9813 added, 0:00:04.588998 time elapsed
140001-150000: 9708 added, 0:00:04.881982 time elapsed
150001-160000: 9509 added, 0:00:04.705842 time elapsed
160001-170000: 9777 added, 0:00:05.290132 time elapsed
170001-180000: 9580 added, 0:00:05.027809 time elapsed
180001-190000: 9698 added, 0:00:0

# Process 2010

In [506]:
apd_2010_raw = import_accdb_file('2010') 

('running table:', u'LandUseCodes')
Dumping LandUseCodes
(u'LandUseCodes', <_io.StringIO object at 0x7f9c3dc871d0>)
('running table:', u'MasterListPotentialREO')
Dumping MasterListPotentialREO
(u'MasterListPotentialREO', <_io.StringIO object at 0x7f9a2806a6d0>)
('running table:', u'Name AutoCorrect Save Failures')
Dumping Name AutoCorrect Save Failures
(u'Name AutoCorrect Save Failures', <_io.StringIO object at 0x7f9a2806aad0>)
('running table:', u'OwnerCodeDefinition')
Dumping OwnerCodeDefinition
(u'OwnerCodeDefinition', <_io.StringIO object at 0x7f9a27af30d0>)
('running table:', u'RawDataAssessment Table Layout')
Dumping RawDataAssessment Table Layout
(u'RawDataAssessment Table Layout', <_io.StringIO object at 0x7f9a2806a6d0>)
('running table:', u'SaleDataFull')
Dumping SaleDataFull
(u'SaleDataFull', <_io.StringIO object at 0x7f9a27af31d0>)
('running table:', u'SaleDataFullYear2013')
Dumping SaleDataFullYear2013
(u'SaleDataFullYear2013', <_io.StringIO object at 0x7f9a27af3f50>)
('run

In [507]:
apd_2010 = cleanup_accdb_import(apd_2010_raw, '2010')

After merge, size = 564759
After filtering to only include dwellings, size = 507726
After filtering to remove empty owner names and change addresses, size = 500552


In [ ]:
merge_addrs(apd_2010)
canonicalize_addrs(apd_2010)

In [397]:
# Alternatively, load apd_2010 from storage
apd_2010 = restore_adf('apd_2010')

Restoring from assessments/apdstore_apd_2010.h5, key=apd_2010


In [398]:
# Try to save out property_map before we start messsing with it
import pickle

with open('assessments/property_map_99_04_05_09_17.pickle', 'wb') as handle:
    pickle.dump(property_map, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('assessments/owner_map_99_04_05_09_17.pickle', 'wb') as handle:
    pickle.dump(owner_map, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('assessments/changeaddr_map_99_04_05_09_17.pickle', 'wb') as handle:
    pickle.dump(changeaddr_map, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('assessments/canonical_property_address_map_99_04_05_09_17.pickle', 'wb') as handle:
    pickle.dump(canonical_property_address_map, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('assessments/raw_property_address_map_99_04_05_09_17.pickle', 'wb') as handle:
    pickle.dump(raw_property_address_map, handle, protocol=pickle.HIGHEST_PROTOCOL)


In [399]:
process_all_assessment_records(apd_2010, '2010-06-01')

1-10000: 9945 added, 0:00:04.721765 time elapsed
10001-20000: 9731 added, 0:00:04.438478 time elapsed
20001-30000: 9914 added, 0:00:04.944825 time elapsed
30001-40000: 9892 added, 0:00:04.740126 time elapsed
40001-50000: 9781 added, 0:00:04.253693 time elapsed
50001-60000: 9755 added, 0:00:04.450354 time elapsed
60001-70000: 9730 added, 0:00:05.183635 time elapsed
70001-80000: 9800 added, 0:00:04.881873 time elapsed
80001-90000: 9917 added, 0:00:05.012781 time elapsed
90001-100000: 9850 added, 0:00:04.978874 time elapsed
100001-110000: 9948 added, 0:00:05.357415 time elapsed
110001-120000: 9943 added, 0:00:05.137700 time elapsed
120001-130000: 9672 added, 0:00:04.683835 time elapsed
130001-140000: 9949 added, 0:00:04.675560 time elapsed
140001-150000: 9806 added, 0:00:04.532692 time elapsed
150001-160000: 9817 added, 0:00:04.917499 time elapsed
160001-170000: 9726 added, 0:00:04.366502 time elapsed
170001-180000: 9934 added, 0:00:04.611921 time elapsed
180001-190000: 9952 added, 0:00:0

# Process 2009

In [84]:
apd_2009_raw = import_accdb_file('2009') 

('running table:', u'pncis')
Dumping pncis
(u'pncis', <_io.StringIO object at 0x7f542f1d5050>)


/home/rsargent/anaconda2/lib/python2.7/site-packages/IPython/core/interactiveshell.py:2878: DtypeWarning: Columns (3,33,39,43) have mixed types. Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [85]:
apd_2009 = cleanup_accdb_import(apd_2009_raw, '2009')

After merge, size = 562378
After filtering to only include dwellings, size = 505806
After filtering to remove empty owner names and change addresses, size = 500042


In [87]:
merge_addrs(apd_2009)

In [119]:
apd_2009=cleanup_merged_accdb_import(apd_2009, '2009')


After filtering to remove malformed owner_address_raw addresses, size = 495437


In [123]:
canonicalize_addrs(apd_2009)

Processing property_address_raw for rows 0-99, 84 unique addresses (p=0)
SimpleThreadPoolExecutor succeeded: all 84 jobs completed
   0:00:00.082626 time elapsed
SimpleThreadPoolExecutor succeeded: all 91 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 95 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
Processing property_address_raw for rows 1000-1099, 100 unique addresses (p=10)
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
   0:00:00.040441 time elapsed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor suc

SimpleThreadPoolExecutor succeeded: all 100 jobs completed
   0:00:00.053576 time elapsed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
Processing property_address_raw for rows 13000-13099, 100 unique addresses (p=130)
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
   0:00:00.035123 time elapsed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: al

SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
Processing property_address_raw for rows 25000-25099, 98 unique addresses (p=250)
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
   0:00:00.035802 time elapsed
SimpleThreadPoolExecutor succeeded: all 95 jobs completed
SimpleThreadPoolExecutor succeeded: all 95 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoo

SimpleThreadPoolExecutor succeeded: all 89 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
SimpleThreadPoolExecutor succeeded: all 90 jobs completed
SimpleThreadPoolExecutor succeeded: all 87 jobs completed
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
SimpleThreadPoolExecutor succeeded: all 91 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
Processing property_address_raw for rows 37000-37099, 94 unique addresses (p=370)
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
   0:00:11.404039 time elapsed
SimpleThreadPoolExecutor succeeded: all 93 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
SimpleThreadPool

SimpleThreadPoolExecutor succeeded: all 99 jobs completed
   0:00:09.652269 time elapsed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed


...

Error while processing owner_address_raw for rows 478500-478599, 100 unique addresses (p=4785), retry 0: <type 'exceptions.Exception'>
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
Processing owner_address_raw for rows 479000-479099, 96 unique addresses (p=4790)
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
   0:00:12.152494 time elapsed
SimpleThreadPoolExecutor succeeded: all 94 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs comple

SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
Processing owner_address_raw for rows 491000-491099, 97 unique addresses (p=4910)
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
   0:00:02.291054 time elapsed
SimpleThreadPoolExecutor succeeded: all 99 jobs completed
SimpleThreadPoolExecutor succeeded: all 100 jobs completed
SimpleThreadPoolExecutor succeeded: all 97 jobs completed
SimpleThreadPoolExecutor succeeded: all 98 jobs completed
SimpleThreadPoolExecutor succeeded: all 96 jobs completed
SimpleThreadPo

/home/rsargent/anaconda2/lib/python2.7/site-packages/ipykernel_launcher.py:169: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


* Harvesting owner addresses
* Done


/home/rsargent/anaconda2/lib/python2.7/site-packages/ipykernel_launcher.py:171: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [168]:
process_all_assessment_records(apd_2009, '2009-09-01')

1-10000: 9968 added, 0:07:18.401344 time elapsed
10001-20000: 9922 added, 0:06:53.958442 time elapsed
20001-30000: 9903 added, 0:07:03.970188 time elapsed
30001-40000: 9846 added, 0:07:43.233650 time elapsed
40001-50000: 9784 added, 0:06:45.695790 time elapsed
50001-60000: 9936 added, 0:07:31.623767 time elapsed
60001-70000: 9679 added, 0:07:06.624527 time elapsed
70001-80000: 9917 added, 0:06:59.443757 time elapsed
80001-90000: 9921 added, 0:06:49.688077 time elapsed
90001-100000: 9942 added, 0:06:41.422868 time elapsed
100001-110000: 9815 added, 0:06:54.683025 time elapsed
110001-120000: 9860 added, 0:06:34.210066 time elapsed
120001-130000: 9666 added, 0:06:27.519099 time elapsed
130001-140000: 9744 added, 0:06:20.315907 time elapsed
140001-150000: 9895 added, 0:06:30.829366 time elapsed
150001-160000: 9954 added, 0:06:25.956163 time elapsed
160001-170000: 9880 added, 0:06:32.032558 time elapsed
170001-180000: 9903 added, 0:06:34.621421 time elapsed
180001-190000: 9945 added, 0:06:3

In [229]:
len(apd_2009)

495437

In [232]:
# Save out apd_2009 to mdf
save_adf(apd_2009, 'apd_2009')

Saving to assessments/apdstore_apd_2009.h5, key=apd_2009


# After input processing is done, register all sales so we know when owners stop owning given parcels

In [351]:
start=arrow.now()
register_all_sales()
end=arrow.now()
print "Processing took %s" % (str(end-start))

Processing took 0:09:28.117341


# Debugging

In [370]:
# Coords from census
def get_canonical_coords(addr):
    if(pandas.isnull(addr) or re_noalnum.match(addr)):
        #print "Skipping address lookup for %r, no alphanumeric characters" %(addr)
        return None

    try:
        result=geocode_address_census(addr)
        if len(result['result']['addressMatches']) == 1:
            coords = result['result']['addressMatches'][0]['coordinates']
            return(Point(coords['x'], coords['y']))
        else:
            return None
    except:
        return None


In [389]:
def get_canonical_coords_google(addr):
    if(pandas.isnull(addr) or re_noalnum.match(addr)):
        #print "Skipping address lookup for %r, no alphanumeric characters" %(addr)
        return None

    try:
        result=geocode_address_google(addr)
        if(result['status']=='OK' and len(result['results'])== 1):
            latlon = ['results'][0]['geometry']['location']
            if(latlon):
                return(Point(latlon['lng'], latlon['lat']))
        return None
    except:
        return None


In [392]:
def update_centroids(parid_arr):
    for parid in parid_arr:
        # Check if we already know this centroid
        if(parid in parid2centroid):
            continue
        # Don't know the centroid yet.  First try census
        if parid in canonical_property_address_map:
            addr = canonical_property_address_map[parid]
            coords = get_canonical_coords(addr)
            if(coords):
                print "Updating %s from census: %r (%f, %f)" % (parid, addr, coords.x, coords.y)
                parid2centroid[parid]=coords
                continue
        if parid in raw_property_address_map:
            addr = raw_property_address_map[parid]
            coords = get_canonical_coords_google(addr)
            if(coords):
                print "Updating %s from google: %r (%f, %f)" % (parid, addr, coords.x, coords.y)
                parid2centroid[parid]=coords
                continue
            print "Skipping %s: Raw property addr = %r" % (parid, raw_property_address_map[parid])
        else:
            print "Skipping %s: No raw property addr" % (parid)

In [395]:
centroids_missing_arr=['9905X00960000000', '9929X87705000000',
'9946X50077000000', '9923X82120000000', '0008H00207000000',
'9935X83622000000', '9923X88213000000', '9929X86742000000',
'9929X00651000000', '9946X82242000000', '9929X87710000000', 
'8000T03550000000', '0102B00350000001', '9809X00280000000',
'9905X00543000000', '9946X85474000000', '9935X83214000000',
'9935X82985000000', '9946X83796000000', '9910X82175000000',
'0184N00250000000', '9910X84175000000', '9923X00741000000',
'9905X82540000000', '9923X00961000000', '9923X00116000000',
'0334H00209000000', '0773C00150000000', '9935X88055000000',
'0421G00051000100', '9929X85730000000', '9923X00172000000',
'9946X00048000000', '9946X84997000000', '9910X84166000000',
'9946X83232000000','9929X84542000000', '9946X85534000000',
'9929X01588000000', '9910X80010000000', '9923X82186000000',
'9929X00031000000', '9935X01299000000', '0353J00078000000',
'0175P00284000000', '9929X01440000000', '9946X84392000000',
'9929X86606000000', '9929X00211000000', '9935X50292000000',
'9929X01396000000', '9929X85323000000', '9946X88090000000',
'9929X83275000000', '9929X88152000000', '0055S00160000000',
'9935X83607000000', '9809X00150000000', '0666R00162000000',
'9905X83634000000', '9946X84101000000', '9809X00342000000',
'0048N00167000000', '9946X82914000000', '8000T03658000080',
'0381C00095000000', '9923X88163000000', '9935X50106000000',
'9929X86261000000', '9946X84349000000', '0940M00200001900',
'9905X82809000000', '9935X01187000000', '0286C00090000000',
'0083S00153000000', '1095R00098000000', '9905X01709000000',
'9923X88208000000', '0448R00316000000', '9946X88341000000',
'9935X87920000000', '9929X84603000000', '9905X80008000000',
'9946X83694000000', '9935X82587000000', '9905X00752000000',
'9910X01368000000', '9929X82330000000', '9923X00397000000',
'9929X86581000000', '9905X83945000000', '9929X84863000000',
'9929X00828000000', '9929X86843000000', '9908X82859000000',
'9929X82337000000', '9946X00743000000', '9935X00333000000',
'9905X00481000000', '9946X01383000000', '0083L00006000000',
'9946X84293000000', '9923X00541000000', '9905X82248000000',
'0235N00087000000', '9905X84005047C00', '9809X82044000000',
'9844X00641000000', '9946X85496033400', '8000T00350000000',
'9929X84954000000', '9923X00774000000', '9929X88312000000',
'9946X82666000000', '9923X00430000000', '9946X88092000000',
'9935X88285000000', '9946X00664000000', '9935X82575000000',
'9935X83138000000', '9910X01166000000', '8000T02002000000',
'0117N00025000000', '9935X82327000000', '9946X84855000000',
'9946X87860000000', '8000T00496000000', '9946X85477000000',
'9935X82850000000', '0301N00094000000', '9946X83237000000',
'9923X87426000000', '9905X00838000000', '9908X82521000000',
'9935X01147000000', '9905X80001000000', '9905X82215000000',
'9923X87438000000', '9946X01607000000', '9946X83332000000',
'9946X00759000000', '9905X83553000000', '9923X82066000000',
'9946X83799000000', '9946X00631000000', '9946X85100000000',
'9929X87601000000', '9929X85896000000', '9946X84803000000',
'9905X01605000000', '9923X87464000000', '9935X82813000000',
'0178J00009000000', '0260M00024000000', '9929X86804000000',
'9946X87674000000', '9905X82907000000', '9929X86816000000',
'9946X85297000000', '9923X00078000000', '9946X88540000000',
'9946X84989000000', '9910X00965000000', '9910X01582000000',
'9923X82314000000', '9929X00033000000', '0163K00060000000',
'9929X00798000000', '9946X85562000000', '8000T01863000000',
'9946X83304000000', '9946X83024000000', '9908X82865000000',
'8000T02121000000', '9923X00207000000', '9844X00581000000',
'9946X83854000000', '9910X01205000000', '9946X00125000000',
'9929X87712000000', '9809X00276000000', '9923X87579000000',
'9929X85330000000', '1504L00014000000', '0024D00277000000',
'0072H00068000100', '9910X80041000000', '9905X00823000000',
'9946X83693000000', '9929X83065000000', '0564S00027000000',
'9935X83456000000', '9935X01218000000', '9905X00458000000',
'9929X00002000000', '9929X86704000000', '9910X01164000000',
'9929X83940000000', '9910X01490000000', '9946X01316000000',
'9946X82318000000', '9905X82834000000', '9935X88057000000',
'0052H00268000000', '9946X83711000000', '0395M00229000100',
'9935X82735000000', '9929X00892000000', '9946X83079000000',
'9929X87554000000', '9905X83599000000', '9946X82973000000',
'9929X00148000000', '9844X00562000000', '9946X83483000000',
'9905X00826000000', '9923X84562000000', '9923X00880000000',
'9905X84006045F00', '9946X82498000000', '9946X82520000000',
'9910X00207000000', '9923X00139000000', '9910X01293000000',
'9905X82038000000', '0256M00150000000', '0060L00105000000',
'8000T02682000000', '9923X88055000000', '9905X01722000000',
'9929X85966000000', '9905X50097000000', '0024N00055000000',
'9910X82271000000', '9809X82058000000', '9946X87788000000',
'9935X82197000000', '9923X88090000000', '9935X50211000000',
'9929X86116000000', '9946X01628000000', '9929X83817000000',
'9935X00302000000', '9923X87700000000', '9844X00588000000',
'9923X00136000000', '9929X00525000000', '9946X83205000000',
'9935X80011000000', '9841X00039000000', '9929X84353000000',
'9910X50066000000', '9923X00024000000', '9935X87922000000',
'0184K00167000000', '9946X88160000000', '9929X82514000000',
'9923X87779000000', '9923X87461000000', '9905X83394000000',
'9929X01297000000', '9935X88002000000', '9929X00372000000',
'9910X82498000000', '9908X82889000000', '9929X00803000000',
'9929X86321000000', '9923X87984000000', '9905X83782000000',
'9935X82769000000', '0564S00037000000', '0530P00010000000',
'9809X84008000000', '9923X84391000000', '9929X85871000000',
'9923X01032000000', '2008H00326000100', '0073G00288000000',
'9905X82719000000', '9946X85063000000', '9905X82683000000',
'9929X83552000000', '0084E00302041300', '0079R00106000000',
'0350A00029000000', '9905X83001000000', '9929X85089000000',
'0751F00006000000', '0282B00342I22000', '0175C00227000000',
'0225G00175000000', '9923X88559000000', '9910X00720000000',
'9841X00095000000', '9946X88072000000', '9929X86580000000',
'9929X00111000000', '9929X85177000000', '9929X50216000000',
'9923X88206000000', '9946X88474000000', '9929X87713000000',
'9844X00113000000', '9910X00018000000', '9929X00795000000',
'9935X88044000000', '9935X82321000000', '9929X87414000000',
'9923X82033000000', '8000T02865000000', '9844X00756000000',
'9929X88241000000', '9905X83829000000', '9946X85286000000',
'9923X88416000000', '9946X88205000000', '9946X82655000000',
'0175P00285000000', '9841X00032000000', '9929X84358000000',
'9809X84047000000', '9929X85852000000', '9935X82527000000',
'0138F00044000000', '8000T02888000000', '9923X01083000000',
'9923X84497000000', '9923X84387000000', '0766L00207000000',
'9905X50107000000', '9923X82345000000', '0023F00075000000',
'9946X88376000000', '9905X83766000000', '9905X01578000000',
'9910X83811000000', '9910X82182000000', '0060J00081000002',
'9935X82231000000', '9929X88236000000', '9929X85364000000',
'1678P00100000000', '0564S00023000000', '2179J00002000000',
'9935X88043000000', '8000T03067000000', '9929X82868000000',
'9935X50109000000', '9946X83377000000', '9929X00215000000',
'0025A00025000000', '9946X85224000000', '9910X00781000000',
'9929X84504000000', '0662J00200000000', '9905X01031000000',
'9935X83696000000', '8000T01865000000', '9929X87881000000',
'9946X83001000000', '9905X00058000000', '9929X88203000000',
'9929X85493000000', '9946X83146000000', '9946X82551000000',
'0359N00029000000', '9923X88017000000', '9935X82189000000',
'0070K00044000000', '9905X00188000000', '9929X87292000000',
'9935X88262000000', '9910X01634000000', '0281R00110000000',
'9923X01031000000', '9946X82910000000', '9935X82894000000',
'9929X88313000000', '9929X87687000000', '9910X82356000000',
'0775H00099000000', '8000T00355000000', '9935X82219000000',
'9935X83565000000', '9905X01844000000', '0997B00235000001',
'9935X83441000000', '0023F00077000000', '1832J00328000000',
'9935X88266000000', '9935X88542000000', '9905X00621000000',
'9905X01636000000', '9929X87343000000', '9935X87792000000',
'9946X84152000000', '9935X82866000000', '9844X00630000000',
'9929X87425000000', '9910X00240000000', '9929X01872000000',
'0050L00204000000', '9905X01594000000', '9923X88027000000',
'9935X00283000000', '9935X82324000000', '9946X85115000000',
'9929X86526000000', '9946X84130000000', '0222J00048000000',
'9946X88225000000', '9929X84505000000', '9923X84559000000',
'9946X84306000000', '9923X88589000000', '9929X50224000000',
'9908X82522000000', '0083L00291000000', '9905X82768000000',
'9905X83533000000', '9946X85589000000', '9905X01200000000',
'9946X82462000000', '9910X00805000000', '9923X88536000000',
'9910X01656000000', '9923X00990000000', '9929X88220000000',
'9905X83558000000', '9946X82492000000', '9929X87473000000',
'9935X82954000000', '9946X00923000000', '9946X84911000000',
'9935X00138000000', '9905X00269000000', '9844X00364000000',
'9929X85367000000', '9946X50160000000', '9809X00152000000',
'9929X01545000000', '9923X82114000000', '0451R00265000000',
'9929X86127000000', '0141B00128000000', '9841X82024000000',
'9946X85293000000', '9935X82350000000', '9929X86194000000',
'9923X00884000000', '9929X00867000000', '0125S00020000000',
'9923X88129000000', '8000T01860000000', '9935X88079000000',
'1837A00261000000', '0344K00210000000', '9929X87897000000',
'0168D00268000000', '9929X00121000000', '9946X82612000000',
'9935X83594000000', '0139R00076000000', '9809X83037000000',
'9929X85819000000', '9946X00424000000', '9929X84237000000',
'9946X01716000000', '9905X00483000000', '0012L00164000000',
'9946X84715000000', '9946X01230000000', '9929X00723000000',
'9935X00570000000', '9809X00338000000', '9908X82965000000',
'9946X84731000000', '9908X82747000000', '9910X82452000000',
'9910X82366000000', '9935X88194000000', '9946X83116000000',
'9809X82060000000', '9929X85492000000', '9905X50064000000',
'9946X01687000000', '9841X00210000000', '9929X01240000000',
'1674N00009000000', '9946X83190000000', '9923X00816000000',
'0085G00004115900', '9905X83197000000', '9935X00192000000',
'9929X00893000000', '9910X00202000000', '9935X88348000000',
'9946X82867000000', '9923X87561000000', '9905X84089000000',
'9929X87072000000', '9946X82760000000', '9935X00209000000',
'9935X50048000000', '9929X84304000000', '0309G00144000000',
'9946X84157000000', '9946X85498000000', '9935X83088000000',
'9929X83812000000', '9910X01433000000', '9935X00216000000',
'0022P00298000000', '9929X83380000000', '9844X00536000000',
'9929X00812000000', '9841X00046000000', '9929X84296000000',
'9905X00255000000', '9946X01016000000', '0006M00104000000',
'9923X00754000000', '9929X82493000000', '9929X87974000000',
'0374G00316000000', '9905X01189000000', '9929X84350000000',
'9923X84351000000', '9946X82861000000', '9929X00352000000',
'9946X84796000000', '9844X00163000000', '9929X00537000000',
'9935X50243000000', '9929X01080000000', '9905X83308000000',
'9929X00387000000', '9923X88469000000', '9910X82539000000',
'9946X84827000000', '9946X87668000000', '9946X50447000000',
'9905X00881000000', '9946X00537000000', '9929X83163000000',
'9923X87476000000', '9929X01112000000', '0342F00370000000',
'9946X83192000000', '8000T01342000000', '9905X00342000000',
'9935X00261000000', '9935X88487000000', '9929X83736000000',
'0066E00142000000', '9929X84914000000', '9910X00553000000',
'9946X83128000000', '9946X83477000000', '9910X00241000000',
'9946X85466000000', '9946X82571000000', '9935X00562000000',
'9946X01750000000', '8000T00783000000', '9929X86649000000',
'9946X88073000000', '9935X00600000000', '9946X85472000000',
'9946X87955000000', '9841X00023000000', '9841X82010000000',
'9923X82218000000', '9923X87885000000', '8000T00351000000',
'9935X00963000000', '0387M00050000000', '9935X00728000000',
'9946X82799000000', '9935X83684000000', '9935X00677000000',
'9910X84031000000', '9905X82206000000', '9946X83754000000',
'9935X82090000000', '9946X00277000000', '9910X00649000000',
'9929X00832000000', '9946X84898000000', '9946X84920000000',
'9935X87796000000', '9946X82180000000', '9929X50226000000',
'9910X83997000000', '9905X82631000000', '9910X83973000000',
'9935X88122000000', '9923X88549000000', '9844X00315000000',
'9935X82224000000', '9923X82410000000', '8000T00003000000',
'9910X01587000000', '9929X82246000000', '8000T00769000000',
'9905X82180000000', '9905X83909000000', '0141J00095000000',
'9905X50045000000', '9929X85365000000', '9946X87882000000',
'9929X01577000000', '9929X85283000000', '9905X82784000000',
'1001H00219000000', '9923X00623000000', '0299F00066000100',
'9929X85535000000', '9905X00883000000', '9929X87413000000',
'9905X01437000000', '9809X00023000000', '9935X83699000000',
'9935X83209000000', '9929X87020000000', '9946X83045000000',
'8000T00295000000', '9929X86269000000', '9923X84457000000',
'9929X83539000000', '9935X01044000000', '9946X50088000000',
'9905X00178000000', '9844X00481000000', '9946X50015000000',
'9923X87542000000', '0055F00328000000', '8000T00372000000',
'9809X82040000000', '9923X87626000000', '1999P00024000000',
'9905X83543000000', '9929X87549000000', '0726K00150000000',
'9929X01452000000', '1009M00015000000', '9946X01126000000',
'9935X83007000000', '9929X50075000000', '9910X00694000000',
'9946X82479000000', '9946X01668000000', '9946X83868000000',
'9905X82547000000', '9929X87686000000', '9923X87912013500',
'2273L00379000000', '9923X88141000000', '9905X83489000000',
'9844X00458000000', '9923X87936000000', '9946X82089000000',
'9910X84491000000', '0512L00012000100', '9946X83743000000',
'9946X83702000000', '9809X83018000000', '9935X00975000000',
'8000T02016000000', '9935X83625000000', '9946X83147000000',
'9910X01365000000', '9844X00237000000', '9929X87677000000',
'9905X82989000000', '9929X87840000000', '9905X83577000000',
'9923X88418000000', '9929X87424000000', '1909A00288000000',
'9910X00206000000', '0004E00123000000', '9935X01141000000',
'9935X83180000000', '9929X00317000000', '9946X87730000000',
'9946X84878000000', '9929X01983000000', '9923X87841000000',
'9946X82277000000', '0048N00119000000', '9910X84460000000',
'0051N00227000000', '9905X82698000000', '9841X00218000000',
'9905X00096000000', '9935X00851000000', '9946X84801000000',
'9929X84400000000', '0002M00295000000', '9935X82816000000',
'0489B00005000000', '9910X00914000000', '0395H00301000000',
'9905X83200000000', '9929X00973000000', '9935X88125000000',
'9946X82302000000', '9923X87912013600', '9935X82152000000',
'0856A00294000000', '9946X82932000000', '0024D00273000000',
'9935X00597000000', '9844X00255000000', '0256M00006000000',
'9929X87395000000', '9929X00554000000', '9844X00063000000',
'8000T01450000000', '9929X86776000000', '0175B00227000001',
'9910X01236000000', '9923X88050000000', '9929X84153000000',
'9905X00318000000', '9923X84515000000', '9923X88215000000',
'0941S00115000000', '8000T00494000000', '9923X88078000000',
'9946X83423000000', '9905X01620000000', '9946X00463000000',
'9935X83560000000', '9935X50309000000', '0547P00228000000',
'9910X80037000000', '0478H00155000000', '9905X83616000000',
'9905X82826000000', '0222N00031000000', '9905X83796000000',
'9946X88035000000', '9946X83235000000', '9905X50127000000',
'9935X82484000000', '9910X82127000000', '9844X00692000000',
'9929X84817000000', '9946X00614000000', '0851E00022000000',
'9923X88355000000', '0236S00097000000', '0012R00167000000',
'9923X87814000000', '9946X87724000000', '9929X86092000000',
'9946X88345000000', '9935X82027000000', '9923X82295000000',
'9929X87488000000', '9946X81025000000', '9905X82801000000',
'9946X88098000000', '9946X01467000000', '9841X00211000000',
'9929X86623000000', '9923X84335000000', '9946X88387000000',
'9929X01871000000', '9923X00815000000', '9935X00029000000',
'8000T03322000000', '9935X00191000000', '9935X83278000000',
'9910X82460000000', '9929X00377000000', '9910X84462000000',
'9923X00717000000', '0443L00218025900', '0080G00214000000',
'9809X84044000000', '9946X82261000000', '9935X00720000000',
'9946X85436000000', '9923X87731000000', '9905X82281000000',
'0056J00325000A00', '1677K00319000000', '9923X87450000000',
'9946X82831000000', '9946X83548000000', '9905X83233000000',
'9923X88407000000', '9910X01417000000', '9929X85058000000',
'9929X86873000000', '9935X87797000000', '9929X87011000000',
'0048N00166000000', '9946X83115000000', '9910X84447000000',
'9935X50168000000', '9923X88182000000', '9929X01127000000',
'9905X00193000000', '9946X84426000000', '0176H00172000200',
'9844X00166000000', '0026E00269000000', '9946X83949000000',
'9929X86013000000', '9910X00966000000', '9935X00343000000',
'9935X50054000000', '9935X83647000000', '9923X82171000000',
'9946X83405000000', '9910X01016000000', '9935X88374000000',
'9929X87920000000', '9946X83730000000', '9935X83130000000',
'9929X88192000000', '9905X00793000000', '9929X00526000000',
'9929X84403000000', '9929X86543000000', '9946X84963000000',
'9929X85594000000', '9946X82509000000', '9946X85104000000',
'9935X01233000000', '8000T02110000000', '9946X88179000000',
'9929X87684000000', '9929X01428000000', '9946X00532000000',
'9946X85456000000', '9923X87870000000', '9929X00039000000',
'0301L00169000000', '9923X84432000000', '9946X82753000000',
'9935X88643000000', '9905X01759000000', '9929X00720000000',
'9905X84020007D00', '9946X85519000000', '0970P00384000000',
'9935X01159000000', '9905X82213000000', '9946X84824000000',
'9910X84566000000', '9946X88600000000', '9935X00891000000',
'9929X84015000000', '9929X86272000000', '9946X82141000000',
'9935X50260000000', '9929X87478000000', '9923X88124000000',
'9923X50043000000', '9923X88548000000', '8000T02723000000',
'9946X83372000000', '9905X01868000000', '9935X01226000000',
'9946X00393000000', '9946X00750000000', '9905X00488000000',
'9929X82852000000', '9910X82150000000', '9910X82342000000',
'9935X88053000000', '9929X85158000000', '8000T03336000000',
'9929X00046000000', '0115C00313000000', '9905X00029000000',
'9935X82078000000', '8000T01387000000', '9844X00479000000',
'8000T00724000000', '9844X00213000000', '9946X85119000000',
'9844X00566000000', '0124J00127000000', '9946X82536000000',
'9935X88019000000', '9929X00534000000', '9905X82543000000',
'9905X83621000000', '9844X00358000000', '9935X82203000000',
'9946X88087000000', '0008H00205000000', '9923X88211000000',
'9809X00257000000', '9929X87585000000', '0512L00014000100',
'0084J00378000000', '9946X85220000000', '9809X00304000000',
'9935X87855000000', '9935X88354000000', '9946X50560000000',
'0380D00158000000', '9905X00396000000', '9905X82053000000',
'9946X83985000000', '8000T04720000000', '9935X83125000000',
'9946X50371000000', '9935X87926000000', '9946X00952000000',
'9929X01017000000', '9946X82485000000', '9910X83829000000',
'9929X86333000000', '9929X85223000000', '9929X87302000000',
'9946X01073000000', '9946X87854000000', '9905X00106000000',
'9905X83570000000', '9905X00464000000', '9935X01288000000',
'9946X83183000000', '9809X00070000000', '9946X01739000000',
'9929X83469000000', '9946X83625000000', '9935X88401000000',
'9929X50047000000', '9929X85875000000', '9809X00049000000',
'9905X01645000000', '9910X84143000000', '9929X83351000000',
'9935X82582000000', '9910X84536000000', '9946X50161000000',
'0162S00264000100', '9841X00165000000', '9946X83950000000',
'1010H00150000000', '1507N00079000000', '9923X00518000000',
'9929X85500000000', '9844X00079000000', '9935X83120000000',
'0281R00068000000', '9929X84604000000', '9905X82532000000',
'9935X00490000000', '9929X87500000000', '8000T00314000000',
'9946X84710000000', '9905X82869000000', '9935X83681000000',
'9929X00342000000', '9946X82245000000', '9844X00301000000',
'9929X85732000000', '9929X85961000000', '9929X01359000000',
'9910X00065000000', '9946X87841000000', '9910X00964000000',
'9946X84690000000', '9905X81022000000', '9929X87510000000',
'9923X82090000000', '9905X01552000000', '9935X83439000000',
'0092P00098000000', '9923X00962000000', '9905X00065000000',
'9946X82702000000', '0856P00237000000', '9929X88040000000',
'9929X87391000000', '9929X00524000000', '0957C00212000000',
'9946X85581000000', '9929X84170000000', '9905X83461000000',
'9935X88142000000', '9929X82007000000', '9935X88159000000',
'9923X82309000000', '9929X85171000000', '9905X83583000000',
'9935X88534000000', '9923X87993000000', '9923X82291000000',
'9809X83055000000', '9923X84419000000', '9905X01741000000',
'9923X88327000000', '9929X01951000000', '9935X83698000000',
'9905X83155000000', '9946X84094000000', '9929X00548000000',
'9946X85593000000', '9905X82905000000', '9946X87798000000',
'0002M00304000000', '9946X85608000000', '9929X84966000000',
'9905X82139000000', '9910X84274000000', '9935X82163000000',
'9935X82215000000', '9923X84399000000', '9946X01844000000',
'9923X00735000000', '9935X01179000000', '9935X83098000000',
'9946X00998000000', '9929X86603000000', '9935X50024000000',
'9905X01438000000', '9946X83791000000', '9929X00434000000',
'9841X00043000000', '9905X82045000000', '9809X00331000000',
'0418M00018000000', '9929X83199000000', '9929X00678000000',
'9946X88130000000', '8000T01888000000', '0308J00093000000',
'9946X83592000000', '9910X00813000000', '9910X82736000000',
'9946X82041000000', '9946X82648000000', '9929X01211000000',
'9923X88398000000', '9923X88220000000', '9844X00020000000',
'9935X82024000000', '0643L00081000000', '9929X84881000000',
'9935X83690000000', '9946X83179000000', '9946X01677000000',
'9946X84862000000', '9935X83556000000', '9809X00137000000',
'0010J00116000000', '9841X82007000000', '0766B00220000002',
'9935X88010000000', '9929X85615000000', '0079F00009000100',
'9905X83422000000', '9935X83526000000', '9929X86318000000',
'9929X00276000000', '9905X82817000000', '0192K00020000000',
'9923X87743000000', '9910X00756000000', '9946X50043000000',
'9929X85235000000', '9844X00675000000', '9929X86300000000',
'9923X87833000000', '9905X83312000000', '9905X00198000000',
'9910X00777000000', '9844X82061000000', '9910X01229000000',
'9946X82714000000', '9935X88294000000', '9946X88578000000',
'9929X00316000000', '9929X84675000000', '9946X84226000000',
'9946X01499000000', '1735L00142000000', '9923X00255000000',
'9946X87837000000', '1218M00074000000', '9935X83342000000',
'9935X01238000000', '0277D00084000000', '0957C00206000000',
'9923X84437000000', '9946X83531000000', '1078R00197000000',
'9929X85321000000', '9946X84360000000', '9935X83074000000',
'9935X50302000000', '9935X88274000000', '9946X82112000000',
'9935X88260000000', '9910X83801000000', '9929X85610000000',
'9910X00461000000', '8000T01842000000', '0451P00100000000',
'9946X83627000000', '9929X82862000000', '9946X82186000000',
'9929X85873000000', '9929X00888000000', '9935X01189000000',
'9935X82118000000', '9946X82793000000', '9923X88391000000',
'9929X00861000000', '9844X00172000000', '9929X00653000000',
'9935X88176000000', '9905X83537000000', '9929X88187000000',
'9935X83659000000', '9910X00097000000', '0081A00128000000',
'9929X50184000000', '9923X87660000000', '9929X83099000000',
'9946X82142000000', '0025A00024000000', '9929X87813000000',
'9946X85389000000', '9910X00487000000', '9946X50048000000',
'9923X87702000000', '9946X01040000000', '0002K00114000001',
'9910X84219000000', '9946X87706000000', '9946X83443000000',
'9946X01272000000', '9910X82490000000', '9946X01306000000',
'9929X85869000000', '0558L00230000000', '9905X83438000000',
'9946X84675000000', '9929X83359000000', '9910X01532000000',
'9905X00704000000', '9929X85843000000', '9929X00047000000',
'9844X00316000000', '9929X01228000000', '9929X00684000000',
'0718G00281000000', '0625K00031000000', '9929X84026000000',
'9946X83819000000', '9946X88120000000', '9809X00252000000',
'9946X84691000000', '0050K00365000000', '9946X50475000000',
'9946X81011000000', '0018G00070000000', '9935X87861000000',
'9946X84845000000', '9946X84128000000', '9929X00390000000',
'0036A00104000000', '0156M00022000000', '9923X82079000000',
'9844X00400000000', '9935X50150000000', '9910X84100000000',
'9923X87933000000', '9929X85023000000', '9905X00074000000',
'9946X82104000000', '9929X87427000000', '0130R00303000000',
'9905X00037000000', '9929X86290000000', '9923X84326000000',
'9910X00642000000', '9946X83389000000', '9946X82513000000',
'9935X82779000000', '9946X88410000000', '9929X84006000000',
'0236S00212000A00', '9910X00449000000', '9929X85779000000',
'8000T02911000000', '9910X80064000000', '9923X88178000000',
'0003H00068000000', '0235N00039000000', '9923X00363000000',
'9929X86197000000', '9935X82442000000', '9905X00240000000',
'9929X01353000000', '9905X01604000000', '9946X82546000000',
'8000T02587000000', '9935X00088000000', '9935X83639000000',
'9844X00071000000', '0361F00065000100', '9929X85876000000',
'9923X00692000000', '9946X01616000000', '9929X00610000000',
'9923X01037000000', '9935X83356000000', '9923X00910000000',
'9929X87546000000', '9910X82725000000', '9935X87966000000',
'9910X84548000000', '9910X84656000000', '9935X82356000000',
'9946X82668000000', '0275M00076000000', '9923X82168000000',
'9929X87609000000', '8000T01404000000', '9946X50268000000',
'0192H00334000000', '9929X83459000000', '9935X83025000000',
'9929X01632000000', '9929X87354000000', '9923X01067000000',
'8000T02048000000', '9946X82200000000', '9905X01175000000',
'9935X83091000000', '9910X82159000000', '9935X82392000000',
'9910X00767000000', '9929X83937000000', '9929X85237000000',
'9844X82021000000', '9905X01564000000', '9910X82290000000',
'9923X00447000000', '9923X87634000000', '9935X00440000000',
'9923X84553000000', '8000T03413000000', '9910X83967000000',
'9923X00336000000', '9929X00852000000', '9910X00269000000',
'9929X01193000000', '9946X83038000000', '9946X01268000000',
'9929X01118000000', '0008H00199000000', '9929X01550000000',
'9946X01536000000', '9946X82483000000', '9923X84409000000',
'0414C00006000000', '9929X01820000000', '9923X82076000000',
'9908X82954000000', '9929X00327000000', '9923X84382000000',
'9923X00191000000', '8000T00216000000', '9844X82009000000',
'9935X83500000000', '9905X82630000000', '0236S00327000000',
'0367C00225000000', '9910X01526000000', '9929X00353000000',
'9923X88336000000', '0218S00162000000', '9929X85074000000',
'9905X00246000000', '9929X84323000000', '9929X87573000000',
'9935X88018000000', '9905X83809000000', '9910X84148000000',
'9935X00248000000', '9946X87760000000', '9905X01343000000',
'9905X00222000000', '9929X87945000000', '9910X00421000000',
'9923X00614000000', '9923X84330000000', '9935X83046000000',
'9946X84990000000', '9935X01350000000', '9910X82493000000',
'9935X50078000000', '9905X83584000000', '0180C00114000000',
'9935X82996000000', '9935X87790000000', '9905X82028000000',
'9946X50564000000', '0112E00255000000', '9923X84349000000',
'9905X82195000000', '9929X88207000000', '9935X88564000000',
'9929X82509000000', '9946X83470000000', '9929X00507000000',
'9946X88413000000', '9929X00220000000', '0292C00160000000',
'9946X85369000000', '9923X87683000000', '0124N00219000000',
'0086F00290000000', '8000T01836000000', '9809X00294000000',
'9929X86097000000', '9929X87768000000', '9908X82941000000',
'9929X01142000000', '9809X50004000000', '9844X00173000000',
'9935X00603000000', '0167D00310000000', '0426C00062000000',
'0023F00229000100', '9946X84927000000', '9923X87538000000',
'9929X87148000000', '9946X84154000000', '9905X83400000000',
'9905X82078000000', '9905X01265000000', '9923X88324000000',
'8000T01941000000', '9929X84860000000', '9946X00317000000',
'9946X84160000000', '9929X87675000000', '9946X50473000000',
'9923X81014000000', '9946X82859000000', '9844X00666000000',
'0039R00055000000', '9923X82479000000', '0014E00235000000',
'9923X88006000000', '9946X82120000000', '0739M00165000000',
'9923X84398000000', '9946X50216000000', '9910X01628000000',
'9910X83907000000', '9923X00464000000', '9923X87986000000',
'9905X00455000000', '9946X84248000000', '9923X00743000000',
'9910X01654000000', '9929X86868000000', '9946X88645000000',
'9946X82273000000', '9910X84317000000', '9935X83001000000',
'9935X00528000000', '9935X83596000000', '9929X88067000000',
'0026L00206000000', '9946X84123000000', '0023H00114000000',
'0162K00205000000', '0049F00296000000', '0810M00053000000',
'9844X00755000000', '8000T01853000000', '9946X82574000000',
'8000T00163000000', '9905X83764000000', '8000T00215000000',
'0075B00269000000', '0087P00214000100', '0133P00300000002',
'9946X82035000000', '0299F00066000200', '9809X82052000000',
'9905X01510000000', '9923X84577000000', '9946X83766000000',
'9935X83783000000', '9929X86754000000', '9935X83747000000',
'9905X82626000000', '9910X83980000000', '9905X82795000000',
'9946X00932000000', '9923X00313000000', '9929X88341000000',
'9935X83400000000', '9946X50117000000', '9946X00172000000',
'9923X84625000000', '9946X00106000000', '9923X87515000000',
'9929X84126000000', '0414E00263000000', '9910X82432000000',
'0422H00350000000', '9910X00298000000', '9910X00697000000',
'0450P00649000000', '9910X84040000000', '8000T01463000000',
'9905X01228000000', '9929X82676000000', '9929X01711000000',
'9935X82810000000', '9905X01375000000', '9905X00918000000',
'9908X82742000000', '9923X00314000000', '9935X83701000000',
'9946X01855000000', '9929X00363000000', '9905X00810000000',
'0180N00257000000', '9946X84272000000', '1510R00319000000',
'9935X83677000000', '9929X83493000000', '9910X00332000000',
'9935X00671000000', '9946X50471000000', '9935X01294000000',
'9905X01158000000', '8000T03460000000', '9946X85404000000',
'9923X82162000000', '9910X01504000000', '9905X00626000000',
'9946X01041000000', '9946X85324000000', '9929X83861000000',
'9905X83668905C00', '9935X88636000000', '9946X85612000000',
'9935X50266000000', '9929X85992000000', '9946X84783000000',
'9929X85882000000', '9910X84045000000', '9935X83048000000',
'9935X82535000000', '9905X82470000000', '0050K00248000000',
'9905X01196000000', '9908X82866000000', '0046E00059000000',
'9946X84915000000', '0772L00213000000', '9910X84503000000',
'9905X01652000000', '9929X86597000000', '9946X82510000000',
'0023H00370000000', '9929X01358000000', '9910X84243000000',
'9935X82693000000', '9923X87519000000', '9923X87487000000',
'9929X82201000000', '9923X87661000000', '9929X87220000000',
'9946X82045000000', '9905X01786000000', '9929X88062000000',
'9946X87722000000', '9946X87979000000', '0884N00145000000',
'9935X83651000000', '9905X00857000000', '0806B00099000000',
'9935X00116000000', '9935X00056000000', '0723F00283000000',
'0084M00358000000', '9910X00324000000', '9935X50076000000',
'1355H00372000000', '9905X00118000000', '9935X00424000000',
'0829N00041000100', '9923X50013000000', '9935X83551000000',
'9929X86123000000', '9905X82893000000', '8000T00048000000',
'0124N00227000000', '9946X88182000000', '9908X83029000000',
'9935X83632000000', '9929X82521000000', '9935X50190000000',
'9929X85214000000', '9946X82058000000', '9905X83008000000',
'0512L00008000100', '9809X00026000000', '9910X00547000000',
'9809X00174000000', '9923X87545000000', '0167D00312000000',
'9946X85578000000', '0083K00276000000', '9929X01409000000',
'9935X82677000000', '9946X82526000000', '9946X01032000000',
'9935X50153000000', '9910X84547000000', '9929X01638000000',
'9929X87351000000', '9946X84725000000', '0175C00214000000',
'9910X01614000000', '9844X00737000000', '9946X00346000000',
'9844X00730000000', '9910X01391000000', '9910X82173000000',
'9946X88324000000', '9946X82945000000', '9946X50119000000',
'0024H00093000000', '9929X86213000000', '9929X83862000000',
'9929X84864000000', '0382L00212000000', '8000T00119000000',
'9935X88535000000', '9905X01857000000', '9946X01422000000',
'9929X83379000000', '9929X82856000000', '9844X00412000000',
'9910X80063000000', '2195J00295000000', '9935X83490000000',
'9905X82475000000', '9935X88364000000', '9946X82275000000',
'9910X00398000000', '9946X85520000000', '9910X01472000000',
'9946X82905000000', '9935X83080000000', '9929X01981000000',
'9910X83911000000', '9946X83659000000', '0013D00032000000',
'9929X50036000000', '9929X85172000000', '9929X88234000000',
'0163H00085000000', '9910X84177000000', '9910X01570000000',
'9929X83012000000', '9946X83567000000', '9935X01345000000',
'0130P00277000000', '8000T00217000000', '9929X01592000000',
'9929X01965000000', '9929X86585000000', '9929X87180000000',
'9929X01373000000', '9929X01251000000', '9946X85191000000',
'9910X83812000000', '9946X85465000000', '9905X01456000000',
'9929X87551000000', '9929X85892000000', '9946X85070000000',
'9946X50211000000', '9923X87510000000', '9946X83398000000',
'9929X83220000000', '9946X84993000000', '9935X82923000000',
'9910X80025000000', '9923X82284000000', '9946X00444000000',
'9929X01926000000', '8000T01877000000', '9905X82837000000',
'9910X00178000000', '1003L00025000000', '9905X00377000000',
'0525G00048000000', '9923X82264000000', '9935X83164000000',
'9923X87637000000', '9910X00030000000', '9935X82901000000',
'1215R0014800T200', '9946X50334000000', '9946X50363000000',
'9923X87877000000', '9946X83374000000', '9929X01757000000',
'9908X82955000000', '9929X84038000000', '9946X83831000000',
'9910X00693000000', '9946X50177000000', '9935X87959000000',
'9923X87420000000', '9910X84381000000', '9910X00792000000',
'9946X84461000000', '9923X84495000000', '9929X01751000000',
'9929X86699000000', '9946X85125000000', '9946X82897000000',
'9935X82403000000', '9946X82106000000', '9935X82104000000',
'9935X83771000000', '9910X01344000000', '9809X84078000000',
'9841X50010000000', '9935X83306000000', '8000T01996000000',
'9946X87659000000', '9946X83340000000', '9809X00247000000',
'9946X84018000000', '9929X87163000000', '9935X00312000000',
'9946X83901000000', '9929X85496000000', '9929X01959000000',
'9929X00089000000', '9910X00953000000', '9935X88565000000',
'9905X82194000000', '9905X83148000000', '9929X00572000000',
'9929X86599000000', '9923X88123000000', '9946X83329000000',
'9946X88272000000', '9935X83100000000', '0004F00206000100',
'9905X01394000000', '9946X83753000000', '0454B00210000000',
'9929X88185000000', '9923X82208000000', '9929X00673000000',
'0015C00145000000', '9923X00601000000', '9923X00049000000',
'9946X82362000000', '9929X01058000000', '9923X00164000000',
'9910X82351000000', '9929X84952000000', '9910X84347000000',
'9923X00138000000', '0621P00150000000', '9923X00286000000',
'9929X00889000000', '9905X83318000000', '9946X82129000000',
'9905X00463000000', '9929X00752000000', '9946X85354000000',
'9929X86105000000', '0820J00350000000', '9946X85511000000',
'9946X88080000000', '9905X01772000000', '9935X00052000000',
'9905X83172000000', '9910X84639000000', '9929X86755000000',
'8000T02032000000', '9908X82891000000', '9935X00615000000',
'9844X00600000000', '9923X87429000000', '9923X87591000000',
'8000T02758000000', '9946X84263000000', '9929X00139000000',
'9923X88245000000', '9946X84925000000', '9929X50026000000',
'0050K00159000000', '0003N00221000000', '9923X87797000000',
'9929X83108000000', '9946X82252000000', '9929X87249000000',
'9946X01593000000', '9935X82039000000', '9910X84086000000',
'0316A00175000000', '2382R00284000000', '9905X83789000000',
'9935X00674000000', '9905X50098000000', '9929X00831000000',
'9910X01097000000', '9946X82990000000', '9929X85901000000',
'9929X83458000000', '9946X00046000000', '9929X00340000000',
'9905X82104000000', '9946X00176000000', '9905X00375000000',
'9946X84266000000', '9946X00512000000', '0711R00152000000',
'9923X50032000000', '9923X00188000000', '9923X84501000000',
'9910X84144000000', '9923X82428000000', '8000T00483000000',
'9929X87393000000', '9929X00191000000', '0444J00001000000',
'9908X82863000000', '9929X83860000000', '9946X88142000000',
'9929X86118000000', '9929X01210000000', '9946X83331000000',
'8000T03229000000', '0083M00069000000', '8000T00516000000',
'9929X87795000000', '9929X83739000000', '9935X88298000000',
'9946X85188000000', '9929X87068000000', '9946X82270000000',
'9929X01816000000', '9946X82854000000', '9923X87808000000',
'9910X82145000000', '9923X00850000000', '9935X82415000000',
'9946X82197000000', '9929X84707000000', '9946X00308000000',
'9905X00884000000', '0124J00089000000', '1203H00129000000',
'9929X87381000000', '9929X01013000000', '9923X87483000000',
'0125M00372000000', '9946X87825000000', '0050K00218000000',
'9923X87759000000', '9929X50129000000', '9905X01022000000',
'9809X00013000000', '9935X82492000000', '9935X83457000000',
'9844X00122000000', '9844X00446000000', '9929X86303000000',
'9946X88552000000', '9946X83061000000', '9946X01860000000',
'9935X50188000000', '9905X00889000000', '9946X85415000000',
'9923X84694000000', '9935X82715000000', '9935X00656000000',
'9946X01438000000', '9905X01214000000', '9929X87326000000',
'9935X00991000000', '9946X01152000000', '0833F00350000000',
'9905X01748000000', '9929X84345000000', '9929X87508000000',
'0232D00261000000', '9923X84327000000', '9946X84754000000',
'9809X84019000000', '9910X84321000000', '9844X00190000000',
'0505E00195000100', '9905X01714000000', '0999B00035000000',
'9935X50117000000', '9946X50059000000', '9935X83772000000',
'9946X88258000000', '0083S00151000000', '9946X83436000000',
'9935X50060000000', '9929X85236000000', '8000T02366000000',
'9946X01261000000', '9923X87437000000', '9946X00289000000',
'0175C00215000000', '9929X00219000000', '9929X00229000000',
'9946X00347000000', '8000T02006000000', '9946X82572000000',
'9946X85646000000', '9908X82897000000', '9929X87337000000',
'9935X50042000000', '0422K00209000000', '9905X84019006A00',
'9935X88321000000', '9910X50009000000', '9809X84035000000',
'9929X01825000000', '9929X88065000000', '9946X88294000000',
'9905X83202000000', '9809X00289000000', '9929X83266000000',
'9910X01450000000', '9946X84282000000', '9910X82728000000',
'9946X01818000000', '0018A00178000000', '9910X82147000000',
'9935X82048000000', '9929X01982000001', '9905X01917000000',
'9946X83926000000', '8000T00354000000', '9910X84540000000',
'9910X82146000000', '9935X50108000000', '9946X84741000000',
'9946X84212000000', '9929X86780000000', '9929X84444000000',
'9946X87878000000', '9946X88076000000', '9923X84700000000',
'9910X84279000000', '8000T03064000000', '0564S00033000000',
'9935X50189000000', '9935X50187000000', '9946X88611000000',
'8000T02584000000', '0079R00096000000', '9946X83922000000',
'9935X87793000000', '9946X82313000000', '0085G00075000000',
'0235N00041000000', '9946X84326000000', '9929X00311000000',
'9946X88159000000', '9946X00221000000', '9946X50050000000',
'9905X01229000000', '9910X00422000000', '8000T01833000000',
'9935X00122000000', '9935X87837000000', '0012E00110000000',
'9929X85941000000', '9905X82919000000', '0851E00032000000',
'0050K00118000000', '9946X00188000000', '0083S00161000000',
'9935X82477000000', '9929X00695000000', '9844X00682000000',
'9946X82722000000', '1348S00221000000', '9946X85591000000',
'9946X83952000000', '9929X84244000000', '9910X82612000000',
'9910X84276000000', '9946X84689000000', '9946X50145000000',
'9923X82182000000', '9929X85151000000', '9946X00785000000',
'8000T03137000000', '0062P00282000200', '9905X00691000000',
'9809X00052000000', '9929X83241000000', '8000T00345000000',
'9935X01260000000', '9923X87765000000', '9935X88434000000',
'9923X00852000000', '9905X84035000000', '9946X50394000000',
'9935X83571000000', '8000T03272000000', '9946X88251000000',
'0827E00144000000', '9910X83835000000', '9929X00158000000',
'9935X00339000000', '9905X83463000000', '9923X87935000000',
'9910X01554000000', '9929X87347000000', '9910X82352000000',
'9929X50572000000', '9809X00232000000', '9923X00178000000',
'9841X00136000000', '8000T00309000000', '9910X00203000000',
'9905X00185000000', '9946X01746000000', '9946X85438000000',
'0010P00091000000', '0027D00054000000', '9905X82776000000',
'9929X00607000000', '9946X83144000000', '9929X87421000000',
'8000T02213000000', '9946X50419000000', '9809X82039000000',
'9946X82911000000', '0268G00267000000', '9946X88344000000',
'9905X00594000000', '0293A00236000000', '9946X84964000000',
'9905X00438000000', '9935X00541000000', '9946X84358000000',
'9946X01194000000', '0718G00233000000', '9841X00041000000',
'9935X82719000000', '8000T00430000000', '0026F00321000000',
'9946X84860000000', '9923X88339000000', '9910X82138000000',
'9923X84520000000', '9910X82429000000', '9935X00136000000',
'9929X87678000000', '9946X84917000000', '9935X83060000000',
'9935X88267000000', '0004C00013110200', '0079L00160000000',
'0611H00286000000', '9910X01094000000', '9946X84431000000',
'9923X82159000000', '9929X86121000000', '0003G00025000000',
'9929X01468000000', '9946X85617000000', '9905X00272000000',
'9935X88213000000', '9929X83066000000', '9844X00249000000',
'9923X87620000000', '9905X83663000000', '9905X01473000000',
'9923X88177000000', '9935X88302000000', '9946X83018000000',
'9935X83084000000', '9929X00911000000', '9929X86308000000',
'0050F00034000A00', '9946X85594000000', '9946X00107000000',
'9844X00578000000', '9946X50249000000', '9929X85973000000',
'9910X00404000000', '9910X84273000000', '9946X88308000000',
'9910X00596000000', '9923X84402000000', '9929X83921000000',
'9935X82752000000', '9946X84316000000', '9910X84361000000',
'9910X84227000000', '9910X01552000000', '9935X88308000000',
'9946X82855000000', '9946X83174000000', '9946X82100000000',
'9946X01848000000', '9910X82144000000', '9905X83520000000',
'9929X86307000000', '9908X82907000000', '9935X83564000000',
'0286D00152000000', '9905X00022000000', '9923X88577000000',
'9905X83292000000', '9910X01089000000', '9905X83412000000',
'9946X82687000000', '9935X83674000000', '9935X82354000000',
'9946X83450000000', '9844X00512000000', '9946X88651000000',
'8000T01886000000', '9935X83267000000', '8000T02890000000',
'0301N00150000000', '9935X83484000000', '9910X84068000000',
'9910X82181000000', '9935X01123000000', '9923X00573000000',
'9946X87876000000', '9923X00855000000', '9923X00833000000',
'9905X82156000000', '0363P00208000000', '9905X00382000000',
'9946X83526000000', '9905X01507000000', '9905X00948000000',
'9905X00788000000', '0831L00102000000', '9929X83198000000',
'9905X00160000000', '9929X87606000000', '9929X86139000000',
'0935J00189000000', '9929X01122000000', '9929X50145000000',
'9844X00686000000', '9929X85388000000', '9929X00375000000',
'9908X82525000000', '9905X00986000000', '9946X01585000000',
'0029G00040000000', '9905X01906000000', '9923X00883000000',
'9935X00698000000', '9929X85867000000', '0619P00211000100',
'9946X85630000000', '9929X00370000000', '9905X83056000000',
'9935X83101000000', '9809X00214000000', '9929X86345000000',
'9905X00939000000', '0073A00273000000', '9946X84295000000',
'9935X83575000000', '9946X83077000000', '9929X87970000000',
'9910X01249000000', '9929X00882000000', '9923X88007000000',
'9809X00221000000', '0255K00260000000', '8000T02690000000',
'9905X83675000000', '9946X83135000000', '9844X00134000000',
'9935X88397000000', '9946X82347000000', '9935X88429000000',
'9935X83319000000', '1832R00040000000', '0156B00313000000',
'9946X82594000000', '9841X00070000000', '9910X84386000000',
'9935X82188000000', '9929X00347000000', '8000T01767000000',
'9946X00255000000', '9946X00792000000', '9923X87997000000',
'9905X50037000000', '9935X00433000000', '9905X00768000000',
'9905X00592000000', '9946X01331000000', '9935X00080000000',
'9929X88364000000', '9929X83394000000', '9935X83617000000',
'0041K00234000000', '9929X00012000000', '9946X82306000000',
'9923X50029000000', '0651J00284000000', '9935X01293000000',
'9923X84373000000', '9905X83004000000', '9910X01306000000',
'9935X50241000000', '9946X01814000000', '9905X84006045D00',
'9910X82603000000', '0856P00253000000', '9929X01536000000',
'0012S00138000000', '9905X00731000000', '9946X88220000000',
'0702M00201000000', '9905X83726000000', '9905X00274000000',
'9935X01264000000', '9935X80010000000', '9935X88437000000',
'9905X50138000000', '9929X85440000000', '9946X00764000000',
'9908X82746000000', '9809X00258000000', '9946X50233000000',
'9905X83838000000', '9935X82712000000', '9935X00448000000',
'9946X83030000000', '9946X88415000000', '9905X01260000000',
'0024N00051000000', '9910X82137000000', '0160S00088000000',
'9844X00136000000', '9935X82204000000', '9935X00521000000',
'0301N00095000000', '9929X87239000000', '9910X01251000000',
'9905X82762000000', '9905X83196000000', '9905X82638000000',
'9929X84357000000', '9908X82519000000', '9910X82083000000',
'9929X01149000000', '9923X84635000000', '9905X82054000000',
'9910X01638000000', '9946X84039000000', '0120N00257000000',
'9946X50587000000', '9844X00326000000', '9946X84167000000',
'9935X82469000000', '9946X83691000000', '9923X00377000000',
'9905X83946000000', '0255K00258000000', '0361F00076000100',
'9946X87972000000', '9905X01421000000', '9935X83730000000',
'9809X00222000000', '9935X50070000000', '9905X01287000000',
'9935X83408000000', '9946X50169000000', '9946X85005000000',
'9935X82379000000', '9946X83478000000', '9929X88215000000',
'8000T02330000000', '9910X01567000000', '9946X01840000000',
'9929X87811000000', '9946X83025000000', '1355R00273000000',
'0154S00140000000', '9935X00317000000', '9929X50071000000',
'9905X83783000000', '9946X88610000000', '9929X85304000000',
'9946X82995000000', '9946X83188000000', '0050K00064000A00',
'0026F00322000000', '9935X83450000000', '9929X00538000000',
'9935X00522000000', '9923X84643000000', '9923X88457000000',
'9929X00126000000', '9935X83517000000', '9935X83603000000',
'9946X00454000000', '9946X50440000000', '9923X87767000000',
'9929X00416000000', '9946X85074000000', '9905X00271000000',
'9946X83094000000', '9929X87868000000', '9929X88204000000',
'9923X84678000000', '9929X01526000001', '9929X01526000000',
'0121J00211000000', '9929X86113000000', '9929X85991000000',
'9935X82347000000', '9844X00382000000', '9910X84651000000',
'0769R00100000000', '9935X82761000000', '9923X87900000000',
'9809X83009000000', '9946X82723000000', '9929X85240000000',
'9946X83909000000', '9946X00774000000', '9946X85036000000',
'9923X00756000000', '1365G00118000000', '0023J00099000000',
'9923X88452000000', '9929X86193000000', '9946X83829000000',
'9905X01495000000', '9923X88388000000', '9910X82439000000',
'9910X82288000000', '9809X00088000000', '0835E00116000100',
'9935X88145000000', '9910X82065000000', '9905X01127000000',
'9929X88032000000', '0125L00127000000', '9844X00687000000',
'0751G00109000100', '9946X01849000000', '9946X87961000000',
'9946X82029000000', '0033C00302000002', '9946X84914000000',
'0450P00468000000', '9910X82410000000', '0236P00047000000',
'9929X84671000000', '9935X82706000000', '9910X84324000000',
'9844X00171000000', '9910X00492000000', '9946X83905000000',
'9929X86122000000', '9841X00001000000', '9929X01201000000',
'9929X83971000000', '9809X00050000000', '9923X88054000000',
'9946X88588000000', '9946X88597000000', '9923X84340000000',
'9929X82515000000', '9844X00572000000', '9905X01958000000',
'9929X83226000000', '9905X50109000000', '9946X82830000000',
'9910X82028000000', '9929X83396000000', '8000T01052000000',
'0175P00291000A00', '9935X82148000000', '9935X00676000000',
'9910X84114000000', '9923X00429000000', '9935X01122000000',
'9923X87531000000', '9905X83933000000', '0935E00025000000',
'0925B00700000000', '9929X86827000000', '9929X00404000000',
'9935X00953000000', '9905X00898000000', '9946X84892000000',
'0430G00187000000', '0299K00006000000', '9905X83711000000',
'9905X83090000000', '0228S00100000001', '0228S00100000002',
'9935X82312000000', '9946X50500000000', '9905X01403000000',
'0006L00013000000', '9946X82659000000', '9929X86111000000',
'0174P00062000000', '9946X87946000000', '9946X00094000000',
'9946X50515000000', '1666J00102000000', '9929X85033000000',
'9946X81036000000', '9935X01032000000', '9905X00842000000',
'0827S00318000000', '8000T03449000000', '9905X01472000000',
'8000T01732000000', '9910X83919000000', '9905X00722000000',
'9935X83232000000', '9809X83042000000', '9841X00033000000',
'0067P00337000000', '9809X00095000000', '9946X00951000000',
'9929X86779000000', '9910X00741000000', '9923X00089000000',
'9923X87818000000', '9923X84321000000', '0220F00207000000',
'9929X83559000000', '9905X50102000000', '9935X88243000000',
'9910X01239000000', '9923X84662000000', '9923X87861000000',
'9935X00202000000', '9910X00192000000', '9905X83530000000',
'0096M00115000000', '9923X00629000000', '9929X86715000000',
'9929X87983000000', '9946X84978000000', '9923X87718000000',
'9905X01166000000', '9946X84712000000', '9929X00585000000',
'9929X85250000000', '9905X82821000000', '9905X82955000000',
'9910X00004000000', '9935X00383000000', '9929X83864000000',
'9905X83445000000', '9929X87208000000', '9946X01098000000',
'9935X82839000000', '9935X50116000000', '9905X01699000000',
'9935X00419000000', '9910X01289000000', '9923X82420000000',
'9929X83446000000', '9841X00155000000', '9946X83550000000',
'9929X83826000000', '9923X88257000000', '0422H00410000000',
'8000T01765000000', '9946X82268000000', '1357F00153000000',
'9946X85353000000', '9929X85095000000', '9935X88025000000',
'9929X83872000000', '9935X00589000000', '9929X81010000002',
'9929X00564000000', '9935X00035000000', '0010C00013000000',
'9905X82326000000', '9946X84704000000', '9923X88579000000',
'9809X00167000000', '9929X83471000000', '9809X84053000000',
'9935X83053000000', '9946X85111000000', '9946X88297000000',
'9935X00701000000', '9929X00708000000', '9929X00414000000',
'9946X83513000000', '9946X01303000000', '9946X84829000000',
'9905X01481000000', '9923X87629000000', '9923X82337000000',
'9923X84417000000', '9905X83511000000', '8000T02869000000',
'9910X00970000000', '8000T02504000000', '9935X88212000000',
'9905X82380000000', '9935X83749000000', '1067H00047000000',
'9946X83468000000', '9935X88324000000', '8000T00666000000',
'9910X00838000000', '9946X50509000000', '9923X84500000000',
'9935X82259000000', '9929X00530000000', '9923X88217000000',
'0742D00132000000', '9910X82540000000', '0275S00295000000',
'9929X87304000000', '8000T02225000000', '9929X86192000000',
'9929X00325000000', '9923X88104000000', '9946X84202000000',
'9923X84561000000', '9935X82207000000', '0178J00017000000',
'9946X00480000000', '9946X83244000000', '9935X50180000000',
'0253H00168000000', '0362A00021000000', '9844X00168000000',
'9905X83460000000', '9910X84524000000', '9946X01603000000',
'9935X82365000000', '9910X81052000000', '9946X00934000000',
'9905X84014001B00', '0180E00057000000', '9905X00749000000',
'9910X00857000000', '0131C00152000000', '8000T03581000000',
'9946X83318000000', '0307N00157000000', '9929X00681000000',
'9809X00061000000', '9929X86244000000', '9844X00130000000',
'9946X00283000000', '9929X88003000000', '9929X84365000000',
'9905X83940000000', '9946X87799000000', '9929X82523000000',
'9946X82778000000', '9946X84342000000', '9905X83918000000',
'0049K00028000000', '9946X83505000000', '9946X82807000000',
'0617H00163000000', '9935X83657000000', '9935X00534000000',
'9929X87681000000', '0055P00339000000', '9929X86620000000',
'9946X83049000000', '9946X00585000000', '9946X01802000000',
'9935X82238000000', '9929X80120000000', '9946X00997000000',
'9929X87324000000', '9935X88029000000', '9923X87413000000',
'8000T00962000000', '9910X00665000000', '9905X82835000000',
'9946X82754000000', '9929X85305000000', '9910X01360000000',
'9935X01362000000', '9923X87943000000', '9905X01833000000',
'9923X84296000000', '9929X00964000000', '9905X82318000000',
'9929X84049000000', '0174P00063000000', '0050K00154000300',
'0718G00329000000', '1909A00282000000', '9929X84941000000',
'0388A00110030700', '0030E00311000000', '0135M00030000000',
'9910X84467000000', '9946X50339000000', '9905X00559000000',
'9935X83414000000', '0349F00197000000', '0417M00144000000',
'9946X84883000000', '9923X88412000000', '0011A00166000A00',
'9929X01330000000', '9946X50385000000', '9910X82220000000',
'9935X01038000000', '9935X83108000000', '9905X01567000000',
'9946X82352000000', '9929X50085000000', '0254R00037000000',
'9923X00808000000', '9946X83401000000', '9929X87941000000',
'9935X88559000000', '9923X50036000000', '8000T03258000000',
'9935X83380000000', '9946X85019000000', '9935X88350000000',
'9910X83931000000', '0291A00312000000', '9946X83145000000',
'9908X82745000000', '9946X82958000000', '9946X01328000000',
'9905X82301000000', '9929X84379000000', '9929X01906000000',
'9935X82991000000', '0450P00479000000', '9910X84024000000',
'9929X00029000000', '9935X88146000000', '9929X83571000000',
'9905X83405000000', '9905X00194000000', '9946X88088000000',
'9929X87799000000', '9923X88406000000', '9946X88057000000',
'9923X87568000000', '9946X82736000000', '9923X87750000000',
'9935X00046000000', '9946X82243000000', '9910X84237000000',
'9946X84256000000', '9946X01710000000', '9935X00432000000',
'9929X87822000000', '9929X83274000000', '9923X88248000000',
'0124J00101000000', '9946X50568000000', '9946X83827000000',
'9946X82517000000', '9946X82519000000', '9923X00292000000',
'9929X87465000000', '9946X01074000000', '9929X00152000000',
'9935X01068000000', '9929X86107000000', '9946X01546000000',
'9946X82169000000', '0130P00315000001', '9923X82013000000',
'9905X00265000000', '9946X00031000000', '0356L00100000000',
'9929X50182000000', '9929X84161000000', '9908X82861000000',
'9809X00191000000', '9946X84871000000', '9905X82225000000',
'9910X84030000000', '9923X87595000000', '9946X01472000000',
'9935X83397000000', '9929X00915000000', '0024N00050000000',
'9946X82899000000', '1003L00052000000', '9946X84200000000',
'9946X84903000000', '9841X00018000000', '9905X83873000000',
'9946X84120000000', '9841X00186000000', '9935X82029000000',
'9929X50065000000', '9923X84345000000', '9929X84356000000',
'8000T02970000000', '9910X83833000000', '9946X01487000000',
'8000T00458000000', '9929X01712000000', '0023P00009000001',
'9905X01553000000', '9946X84987000000', '9929X85097000000',
'9935X00178000000', '9935X82598000000', '9946X83594000000',
'9929X85906000000', '9946X83839000000', '9946X00215000000',
'9905X83988000000', '1214S00100000000', '9935X83266000000',
'9910X84159000000', '9946X88338000000', '9946X85428000000',
'9929X87018000000', '9929X85282000000', '9905X00977000000',
'9929X87160000000', '9929X00521000000', '0237C00121000001',
'9923X82058000000', '9910X82100000000', '9910X83805000000',
'9935X50182000000', '9935X00523000000', '9946X82935000000',
'0292C00284000000', '9929X00637000000', '9929X01702000000',
'9844X00673000000', '9844X00701000000', '9910X01013000000',
'9946X01608000000', '9929X83005000000', '8000T00436000000',
'0444F00350000000', '9935X82115000000', '9923X82292000000',
'9929X85307000000', '9905X82530000000', '9946X88364000000',
'9923X00317000000', '9935X83686000000', '9923X87704000000',
'9935X88070000000', '9923X00950000000', '9935X83717000000',
'9923X00206000000', '0692A00111000000', '9929X01648000000',
'9910X82492000000', '9946X84232000000', '0222J00056000000',
'9946X82540000000', '9946X00583000000', '9929X87689000000',
'9910X84053000000', '9946X81020000000', '9923X88171000000',
'9929X85101000000', '9946X01044000000', '9905X82160000000',
'0050L00273000000', '9929X87592000000', '9929X01943000000',
'9935X82722000000', '9905X83560000000', '9923X82112000000',
'9910X00704000000', '9910X00517000000', '9935X00583000000',
'9923X82278000000', '9923X84679000000', '9910X00811000000',
'9935X00378000000', '9905X83080000000', '9923X00846000000',
'9923X88159000000', '9910X00771000000', '9929X00699000000',
'0538M00309000000', '9935X00644000000', '9929X83725000000',
'8000T01616000000', '0079L00167000000', '9935X00994000000',
'9935X87838000000', '9929X87305000000', '9929X87223000000',
'9910X82348000000', '9946X84337000000', '9923X87690000000',
'9923X87441000000', '9929X01693000000', '9946X50134000000',
'9910X82435000000', '9929X82855000000', '9923X87662000000',
'9910X00759000000', '9910X84204000000', '9929X86807000000',
'9946X88523000000', '9946X85259000000', '9929X85034000000',
'8000T03139000000', '9946X01563000000', '9905X00575000000',
'9946X01806000000', '9935X83372000000', '9935X87938000000',
'9946X83189000000', '9910X01277000000', '9946X88296000000',
'9946X50258000000', '9905X00608000000', '9929X01006000000',
'9935X83643000000', '9905X83019000000', '9910X00227000000',
'9910X84048000000', '8000T03057000000', '9929X82262000000',
'9946X85464000000', '9905X01315000000', '9923X88214000000',
'9935X83331000000', '9923X00508000000', '9929X82526000000',
'9946X83749000000', '9905X01382000000', '9946X82187000000',
'9844X00568000000', '9923X88138000000', '9929X01083000000',
'0050F00040000000', '0010J00056000000', '9946X82786000000',
'9946X82696000000', '9946X87686000000', '9905X83617000000',
'0131C00149000000', '9905X82092000000', '9929X01095000000',
'9946X83622000000', '9929X86701000000', '9929X82675000000',
'0662H00046000000', '9946X82343000000', '9946X82343000001',
'9923X84609000000', '0076E00037000000', '9946X87853000000',
'9935X87958000000', '9908X82913000000', '8000T00147000000',
'9929X01103000000', '9910X00451000000', '9923X00323000000',
'9905X01562000000', '0011E00280000000', '9935X88109000000',
'9923X82478000000', '8000T00289000000', '9929X50117000000',
'0101L00156000000', '9935X01202000000', '9946X82290000000',
'9946X83714000000', '9946X83675000000', '9946X82145000000',
'9905X83319000000', '1071H00287000000', '9905X00042000000',
'9923X84407000000', '9910X84414000000', '0437D00030000000',
'0745P00214000000', '9929X86664000000', '9929X85104000000',
'0231N00159000000', '9923X87894000000', '9935X83649000000',
'9908X82894000000', '9923X82450000000', '9946X84124000000',
'9910X01209000000', '9946X87962000000', '9929X88231000000',
'9910X01081000000', '9946X50027000000', '1736L00200000000',
'9923X87509000000', '9923X84423000000', '0551E00142000000',
'9935X82596000000', '0850L00225000000', '9935X88278000000',
'9935X83081000000', '1269S00257000000', '9929X83270000000',
'9946X83086000000', '9929X01299000000', '9946X83150000000',
'9935X83455000000', '9923X87726000000', '9946X84962000000',
'9929X85444000000', '9946X00527000000', '0530G00300000000',
'9946X84805000000', '9935X50299000000', '9946X85066000000',
'9905X01736000000', '9910X84208000000', '9935X00741000000',
'9923X00948000000', '0451B00650000000', '1354J00294000000',
'0049S00173000000', '9935X82750000000', '9935X83553000000',
'0025M00274000000', '9946X01711000000', '0660A00044000100',
'9923X87482000000', '9910X00969000000', '9946X85542000000',
'9929X87991000000', '9910X84315000000', '9946X83435000000',
'9935X00307000000', '9935X82665000000', '9905X83787000000',
'9910X84287000000', '8000T03170000000', '9908X82956000000',
'9946X01401000000', '0052J00215000000', '8000T01414000000',
'9841X00077000000', '8000T00432000000', '0010J00336000000',
'9929X01695000000', '0001C01662010500', '9923X87536000000',
'9935X88015000000', '9929X50258000000', '9923X00813000000',
'0473L00077000000', '9946X01463000000', '9929X00742000000',
'8000T01947000000', '9946X84215000000', '9935X50222000000',
'9929X87626000000', '9910X82557000000', '9935X50032000000',
'9841X50017000000', '9946X00636000000', '9923X87498000000',
'9929X00291000000', '9946X84947000000', '9809X00014000000',
'9809X00190000000', '9905X82197000000', '9935X01220000000',
'8000T02634000000', '9905X01276000000', '9935X00182000000',
'9929X87608000000', '9935X83590000000', '0473B00050000100',
'9929X87147000000', '0018G00072000000', '9923X88329000000',
'9905X00111000000', '9923X00263000000', '0231J00151000000',
'9929X87227000000', '8000T02275000000', '8000T00178000000',
'9946X82179000000', '0292C00208000000', '9905X82149000000',
'1067H00105000000', '9880X85658000000', '9905X83949000000',
'9923X87964000000', '9946X88183000000', '9946X86630000000',
'9910X01444000001', '9929X01579000000', '9935X00090000000',
'9929X86530000000', '8000T02321000000', '9935X50278000000',
'9929X87401000000', '9910X00874000000', '9946X01387000000',
'9946X82503000000', '9923X87693000000', '9809X82046000000',
'9905X01342000000', '9946X88551000000', '9844X00182000000',
'9935X82309000000', '9923X88456000000', '0430A00009000000',
'9946X82993000000', '9910X84561000000', '9929X88015000000',
'9929X01340000000', '9946X87759000000', '9946X82630000000',
'9910X82501000000', '9809X00065000000', '9946X83516000000',
'9946X82345000000', '9929X87594000000', '9923X00352000000',
'9905X82642000000', '9841X00212000000', '9929X00506000000',
'9946X01632000000', '9946X83089000000', '9946X82629000000',
'9946X82484000000', '9946X83457000000', '9946X50113000000',
'9946X00487000000', '9905X84001000000', '9946X83647000000',
'9946X00284000000', '9935X50254000000', '9923X88462000000',
'9923X00443000000', '9946X00933000000', '9946X00720000000',
'9905X50071000000', '9935X01302000000', '0362A00027000000',
'9935X00500000000', '9935X82562000000', '9935X00002000000',
'9929X84487000000', '9905X01566000000', '9929X83089000000',
'9905X01155000000', '9946X00316000000', '9946X85080000000',
'9929X84541000000', '9923X87845000000', '0067P00321000000',
'8000T00789000000', '9946X82555000000', '9946X00098000000',
'9905X00806000000', '9923X87667000000', '9946X82194000000',
'0218S00156000000', '9935X01290000000', '9946X50035000000',
'9935X82461000000', '9905X00952000000', '0160C00015000000',
'9923X87707000000', '9946X88178000000', '9929X88219000000',
'9905X00858000000', '9923X82204000000', '9935X01024000000',
'9946X50472000000', '9923X84429000000', '9935X01018000000',
'9935X00091000000', '9923X88046000000', '9935X87834000000',
'9923X87907000000', '9929X85053000000', '9929X00116000000',
'9929X01487000000', '9929X84368000000', '0124J00114000000',
'9929X88189000000', '9929X87463000000', '9844X00424000000',
'8000T01918000000', '9935X00215000000', '9905X83391000000',
'9923X84448000000', '9905X82876000000', '9905X01393000000',
'9809X00129000000', '0188M00283000000', '9910X00597000000',
'9946X50341000000', '9935X82464000000', '9935X82533000000',
'9929X88367000000', '9905X01789000000', '2372M00065000000',
'9935X83236000000', '9946X00121000000', '9929X01941000000',
'9910X01541000000', '9946X88557000000', '9929X00820000000',
'0816L00105000000', '9905X82208000000', '9935X01320000000',
'9946X50241000000', '9905X82583000000', '9929X85566000000',
'0083B00286000A00', '0025G00224000000', '9929X01090000000',
'9946X01226000000', '9923X88227000000', '9929X01290000000',
'9946X00849000000', '9935X83671000000', '9946X01075000000',
'9935X83070000000', '9923X87654000000', '9946X01465000000',
'9946X82999000000', '9844X00503000000', '9923X01077000000',
'9929X86185000000', '9923X87599000000', '9935X00463000000',
'9910X84411000000', '9905X83372000000', '9946X82238000000',
'9935X82371000000', '9946X50470000000', '9929X01070000000',
'0003N00191000000', '9946X82340000000', '9935X01047000000',
'9910X50044000000', '9923X82392000000', '9946X82590000000',
'9905X01209000000', '9910X82261000000', '9910X82685000000',
'9929X84862000000', '9809X00192000000', '9923X87558000000',
'9905X00333000000', '9946X00189000000', '0177H00074000000',
'9946X85264000000', '9946X00582000000', '9946X88043000000',
'9929X87142000000', '0222E00183000000', '0079R00044000000',
'9946X83826000000', '9910X01627000000', '9935X83787000000',
'9929X88069000000', '9905X83084000000', '9908X83040000000',
'9910X84199000000', '9910X84168000000', '9946X88430000000',
'9923X84658000000', '1348L00255000000', '8000T00200000000',
'9946X84313000000', '9910X82411000000', '2016P00185000000',
'9905X00619000000', '9935X82599000000', '9929X84621000000',
'9809X83028000000', '9910X00812000000', '9905X00374000000',
'9929X84559000000', '9935X82109000000', '9905X00798000000',
'9923X84617000000', '9929X87169000000', '9935X00389000000',
'9929X85989000000', '9905X01278000000', '9923X84333000000',
'9946X82824000000', '9929X83009000000', '9910X00829000000',
'9929X01076000000', '9946X83143000000', '9935X82431000000',
'9946X00226000000', '9923X88450000000', '9905X00245000000',
'9946X50055000000', '9935X82307000000', '1067S00215000000',
'9923X84416000000', '9946X88367000000', '9929X01493000000',
'9908X82953000000', '9923X82006000000', '9910X00695000000',
'8000T00136000000', '9905X83694000000', '9946X82734000000',
'9910X84520000000', '1203C00035000300', '9844X00582000000',
'9910X82327000000', '9929X84506000000', '9935X82812000000',
'9946X50367000000', '8000T03171000000', '9905X00470000000',
'0110J00240000000', '9923X00316000000', '9905X00119000000',
'9929X87158000000', '9946X82924000000', '9946X01674000000',
'9929X01696000000', '9946X87928000000', '9946X85279000000',
'9935X82525000000', '9923X82370000000', '0002M00293000000',
'9946X01460000000', '9946X85383000000', '9908X82862000000',
'9923X82301000000', '9910X01506000000', '9905X83642000000',
'9946X83521000000', '9946X88226000000', '9923X87597000000',
'9946X83161000000', '9929X00690000000', '0050L00067000000',
'9935X83260000000', '9929X83551000000', '9935X83761000000',
'9905X83904000000', '9905X01396000000', '9946X84151000000',
'9844X00026000000', '9929X82688000000', '9946X85084000000',
'9946X83509000000', '9929X86259000000', '9929X01897000000',
'9946X85345000000', '9923X87663000000', '9905X00787000000',
'9905X00533000000', '9935X83436000000', '8000T00750000000',
'9910X82615000000', '9935X82062000000', '0131C00033000000',
'9946X00073000000', '9946X50353000000', '9946X50360000000',
'9905X01950000000', '9935X83200000000', '9905X01018000000',
'8000T00018000000', '9946X82845000000', '9946X83326000000',
'0045J00278000000', '9935X83329000000', '9946X50278000000',
'0660P00096000100', '9929X87774000000', '9929X87441000000',
'8000T03167000000', '9946X82611000000', '9946X84802000000',
'9935X83642000000', '9809X00339000000', '9911X85895000000',
'9929X86292000000', '9935X83230000000', '9935X83068000000',
'8000T02036000000', '9844X00594000000', '9946X82296000000',
'0450P00458000000', '9809X83044000000', '9929X87827000000',
'9935X83405000000', '0307N00155000000', '9923X88455000000',
'9935X01281000000', '9946X85133000000', '8000T01650000000',
'9929X00161000000', '9946X83882000000', '0737A00248000000',
'9935X00462000000', '9923X87945000000', '9929X87341000000',
'8000T00165000000', '9946X84994000000', '9929X87523000000',
'8000T00109000000', '9905X01598000000', '9929X88066000000',
'9946X88432000000', '9946X85117000000', '0375N00120000000',
'9935X00352000000', '0110M00208000000', '9935X88102000000',
'9910X82354000000', '9946X83946000000', '9935X00827000000',
'9946X83269000000', '9905X00911000000', '9946X85277000000',
'0281R00013000000', '9929X87761000000', '9841X82015000000',
'9935X88590000000', '9905X01409000000', '9929X82882000000',
'9946X83103000000', '9946X82191000000', '9844X00444000000',
'9929X00261000000', '0128N00187000000', '9923X82092000000',
'9946X85110000000', '9946X00517000000', '9929X88179000000',
'9923X87415000000', '0083L00001000000', '9935X88731000000',
'9935X88425000000', '9935X00672000000', '9946X01877000000',
'0302D00023000000', '9910X00684000000', '9923X01091000000',
'9946X50138000000', '9946X50127000000', '9910X00060000000',
'9946X50212000000', '9905X00771000000', '9929X83495000000',
'0135A00075000000', '9910X82656000000', '9905X01173000000',
'9946X88510000000', '9923X87828000000', '9844X00248000000',
'9929X84233000000', '9935X01130000000', '9935X82433000000',
'9905X01070000000', '9946X82472000000', '9935X83334000000',
'9905X00361000000', '9946X83279000000', '9929X01226000000',
'9946X01611000000', '9935X82844000000', '9946X84204000000',
'8000T00156000000', '1355D00100000000', '9910X84526000000',
'9910X01592000000', '9946X82809000000', '0334C00151000000',
'9935X82829000000', '9946X84756000000', '9929X01117000000',
'9910X00085000000', '9910X82502000000', '9946X01876000000',
'9908X82957000000', '9935X83172000000', '9946X84246000000',
'9923X82442000000', '9905X00895000000', '0362G00327000000',
'9935X83633000000', '9923X87435000000', '0250N00102000001',
'9929X85748000000', '9935X83504000000', '9935X00659000000',
'9910X83905000000', '9935X00069000000', '9946X82709000000',
'9929X84874000000', '9910X82003000000', '9910X84036000000',
'9844X00379000000', '9929X00623000000', '9946X85105000000',
'9910X82262000000', '9929X87172000000', '9946X01578000000',
'9935X00076000000', '9905X00251000000', '9929X01423000000',
'1072R00150000000', '0039G00001000000', '9929X88151000000',
'9946X83124000000', '9946X00732000000', '9923X84563000000',
'9905X83326000000', '9946X01550000000', '9923X87458000000',
'0292C00206000000', '9910X82329000000', '9929X87502000000',
'9929X83574000000', '9923X00054000000', '9946X88066000000',
'9929X86671000000', '9946X83074000000', '9929X87456000000',
'9923X82007000000', '9929X50113000000', '9946X84374000000',
'9929X87511000000', '0382S00375000001', '9923X82065000000',
'9935X88275000000', '9935X83501000000', '9935X00172000000',
'8000T00179000000', '9929X87717000000', '9929X87447000000',
'9905X01802000000', '9841X00131000000', '9908X82893000000',
'8000T00500000000', '9929X87854000000', '9946X00755000000',
'9911X50113000000', '9946X84451000000', '9946X82588000000',
'9929X50081000000', '9935X00666000000', '9929X87708000000',
'9809X00197000000', '9929X85679000000', '9923X84441000000',
'9946X00385000000', '0043K00291000000', '8000T00579000000',
'9929X01264000000', '9929X88034000000', '9923X87819000000',
'9923X88084000000', '9946X87911000000', '0267C00335000000',
'9935X83493000000', '9923X88041000000', '9946X83740000000',
'9935X88323000000', '9929X83156000000', '9946X88493000000',
'2019N00089000000', '9929X01527000000', '9905X83284000000',
'9910X84282000000', '9935X88052000000', '9946X83348000000',
'9946X84449000000', '9935X82308000000', '0167K00126000000',
'9946X82316000000', '9929X87301000000', '1133M00125000100',
'0564S00021000000', '9929X84369000000', '9929X86372000000',
'9935X00960000000', '9946X83529000000', '9929X84978000000',
'9910X84523000000', '9946X83843000000', '0235S00501000000',
'9905X00406000000', '9935X82002000000', '9929X85423000000',
'9946X83083000000', '0072H00070000100', '9923X00419000000',
'9946X01850000000', '9908X82964000000', '9929X00481000000',
'9935X82713000000', '0391S00040000000', '9946X83744000000',
'9929X01729000000', '9910X00309000000', '0048N00164000000',
'9929X84651000000', '9935X87965000000', '9946X84743000000',
'9923X88180000000', '0063M00128000000', '9910X01429000000',
'9929X86115000000', '9905X82867000000', '9935X82194000000',
'9946X83780000000', '9929X82539000000', '9935X82457000000',
'0081S00065000100', '1354C00271000000', '9946X88259000000',
'0112E00249000000', '9809X00195000000', '9910X84338000000',
'9844X00733000000', '9844X00027000000', '9929X83424000000',
'9923X87522000000', '9946X82057000000', '9946X88481000000',
'9923X00483000000', '0507L00020000000', '9923X00169000000',
'9929X87580000000', '9910X82169000000', '8000T01452000000',
'9946X84703000000', '0052J00212000000', '9946X82545000000',
'8000T00302000000', '9929X83248000000', '9946X50046000000',
'9929X86364000000', '8000T00019000000', '9946X01313000000',
'0250D00055000000', '9923X87980000000', '9946X82741000000',
'9935X82768000000', '9929X86570000000', '9929X01224000000',
'1076E00103000000', '0130P00276000000', '9946X85422000000',
'9910X01186000000', '9935X82526000000', '9923X00488000000',
'9929X01672000000', '9946X84873000000', '9929X87641000000',
'9923X88021000000', '9910X82644000000', '9946X82297000000',
'9923X84546000000', '9946X84323000000', '9935X80002000000',
'0025M00025000000', '0544S00157000000', '9935X82317000000',
'9946X87657000000', '0175C00162000000', '9946X84856000000',
'9946X85435000000', '9946X50289000000', '9946X01610000000',
'9809X00038000000', '9946X00045000000', '9935X83072000000',
'9910X84647000000', '9935X00357000000', '9946X87736000000',
'9935X83794000000', '0049A00197000000', '9935X87979000000',
'9946X00841000000', '9935X50233000000', '9910X84405000000',
'9935X00455000000', '9935X83082000000', '0027A00315000000',
'9910X00904000000', '9929X00606000000', '9929X88186000000',
'9946X85150000000', '9946X00666000000', '0135A00030000002',
'9905X83667000000', '9923X88038000000', '9946X82891000000',
'9923X88034000000', '9929X01590000000', '9923X84305000000',
'9923X84517000000', '9929X83432000000', '1345M00055000000',
'9923X82203000000', '9905X83713000000', '9923X82206000000',
'9929X50025000000', '9905X82993000000', '9923X82097000000',
'9910X50011000000', '9929X01780000000', '9946X84346000000',
'9935X00543000000', '9929X84214000000', '9905X83085000000',
'0463N00100000000', '9809X00269000000', '9946X01201000000',
'9935X88001000000', '9935X00170000000', '9929X86044000000',
'9910X82171000000', '9935X82590000000', '9910X84358000000',
'9929X88214000000', '9946X00625000000', '9905X84021000000',
'9935X83547000000', '0824L00046000000', '9923X82325000000',
'9929X87539000000', '9923X87578000000', '9905X50078000000',
'0358F00050000000', '9910X00828000000', '9929X01581000000',
'9905X83658000000', '9946X83761000000', '9923X00790000000',
'9929X01267000000', '9946X84434000000', '9905X01240000000',
'9946X85128000000', '9935X82544000000', '9935X00642000000',
'9929X01416000000', '9910X84402000000', '9929X82626000000',
'9923X01015000000', '9935X88547000000', '8000T01930000000',
'9905X84034210300', '9905X82548000000', '9929X85975000000',
'9935X00881000000', '9946X82768000000', '9923X00177000000',
'0944C00042000000', '0205N00025000000', '9905X01029000000',
'0847C00040000000', '9910X84641000000', '9935X88119000000',
'9935X00538000000', '9905X83872000000', '9929X00403000000',
'9946X83360000000', '9946X00078000000', '9946X50248000000',
'9905X83967000000', '9929X86529000000', '9946X82499000000',
'9905X83980000000', '8000T03004000000', '9946X85075000000',
'9929X86621000000', '9935X82439000000', '9905X82621000000',
'9935X82374000000', '9929X86310000000', '9929X00544000000',
'9844X00081000000', '9946X82927000000', '9946X50514000000',
'0749H00180000000', '0011A00137000000', '9905X83453000000',
'9935X82474000000', '8000T03066000000', '9929X84913000000',
'9923X87642000000', '9946X87774000000', '8000T03580000000',
'9929X00399000000', '9905X01900000000', '9946X87682000000',
'9929X01619000000', '9929X84141000000', '9946X85166000000',
'9935X00137000000', '0382C00156000000', '9935X00186000000',
'9910X82130000000', '9935X82559000000', '9923X84360000000',
'9946X82677000000', '9935X82681000000', '9923X87778000000',
'9946X85233000000', '9905X00253000000', '9946X50190000000',
'9923X01022000000', '9923X00760000000', '9910X01387000000',
'8000T00385000000', '9946X88455000000', '9946X83071000001',
'9929X00014000000', '9910X83840000000', '9923X82402000000',
'9929X00168000000', '9929X85387000000', '9905X00763000000',
'9923X00680000000', '9929X88008000000', '9946X50063000000',
'9935X87824000000', '9946X83375000000', '9923X84615000000',
'9929X01275000000', '9841X00061000000', '9929X83746000000',
'0851K00040000000', '9946X82617000000', '0225S00340000000',
'9946X83618000000', '9929X83400000000', '0011A00142000000',
'9910X84356000000', '9946X82719000000', '9946X00214000000',
'9935X00658000000', '9946X83140000000', '9905X83591000000',
'0141A00038000000', '9935X82692000000', '9929X86299000000',
'9946X00334000000', '9946X84884000000', '9946X00596000000',
'9935X88326000000', '9946X82505000000', '9935X82454000000',
'0615F00227000100', '9910X00744000000', '9910X01244000000',
'9946X85262930200', '9929X00746000000', '9935X82969000000',
'9844X00115000000', '9935X82965000000', '9929X86765000000',
'9905X00023000000', '9946X82295000000', '9929X87824000000',
'9946X85482000000', '9923X88008000000', '9935X87866000000',
'9946X85236000000', '0741F00200000000', '9929X00077000000',
'9923X87610000000', '9946X50012000000', '9910X84329000000',
'9946X83510000000', '9929X85370000000', '9905X00875000000',
'9910X00575000000', '9946X00887000000', '9935X00023000000',
'9935X88217000000', '9929X86803000000', '9946X84995000000',
'9923X88417000000', '9905X83175000000', '9935X82256000000',
'9935X83395000000', '9910X82369000000', '9946X84014000000',
'9923X01063000000', '9929X00467000000', '9929X87848000000',
'9905X01838000000', '8000T01449000000', '9935X00893000000',
'2395S00216000000', '9910X84479000000', '9946X83324000000',
'9844X00363000000', '9841X00171000000', '9923X82458000000',
'9929X00160000000', '1999R00010000000', '9935X83762000000',
'9935X01277000000', '8000T01412000000', '9908X82738000000',
'9923X88510000000', '9905X82394000000', '9946X85013000000',
'9935X87951000000', '9910X82423000000', '9935X88345000000',
'0124J00254000000', '0550F0000100A400', '9910X84214000000',
'9809X84084000000', '9946X82053000000', '9910X01067000000',
'9905X00364000000', '9905X83376000000', '0301N00133000000',
'9929X87953000000', '9923X87788000000', '9946X00382000000',
'8000T02313000000', '9809X00229000000', '9946X00168000000',
'9935X82895000000', '9946X84421000000', '9923X87981000000',
'9809X00037000000', '9905X01881000000', '1202H00199000000',
'9929X86361000000', '9946X84274000000', '9929X86571000000',
'9929X84027000000', '9910X00920000000', '9929X84866000000',
'9935X87858000000', '9935X88428000000', '9946X87693000000',
'9946X00857000000', '9905X83402000000', '9946X84371000000',
'9905X01176000000', '9910X82367000000', '9946X83651000000',
'9946X82581000000', '9929X01187000000', '9935X00450000000',
'9910X82291000000', '0382G00201000000', '9946X82150000000',
'9905X83187000000', '9929X01304000000', '9905X00929000000',
'9935X00358000000', '9905X01381000000', '9946X82658000000',
'9929X50227000000', '9923X00909000000', '9929X86265000000',
'9910X84323000000', '9923X82435000000', '9946X83338000000',
'9929X87164000000', '9929X87485000000', '9905X83600000000',
'0054L00212000000', '9929X50099000000', '9910X82660000000',
'9946X82744000000', '9946X82286000000', '9935X83256000000',
'0711N00100000000', '9929X85360000000', '9929X88142000000',
'9935X00546000000', '9935X82473000000', '9946X84972000000',
'9910X83842000000', '9923X00908000000', '9841X00044000000',
'0739R00250000000', '9910X50012000000', '9946X01038000000',
'8000T01959000000', '0101L00318000000', '9935X82909000000',
'0042D00132000000', '9946X83460000000', '9929X83916000000',
'9929X87607000000', '9841X00129000000', '9923X00579000000',
'0019L00116000100', '0315R00035000000', '9929X88064000000',
'9946X85390000000', '9946X85263000000', '9905X82711000000',
'9929X01779000000', '9929X00454000000', '9809X00205000000',
'0048S00229000000', '0124N00205000000', '9923X84482000000',
'9923X87490000000', '9923X00856000000', '9929X00172000000',
'9935X00835000000', '9923X00295000000', '9905X83094000000',
'0426F00037000001', '8000T00008000000', '9910X82451000000',
'9923X88585000000', '9905X83884000000', '9910X00840000000',
'9935X88722000000', '9935X88322000000', '9923X00861000000',
'9946X50078000000', '9929X00392000000', '9910X00055000000',
'0124J00106000000', '8000T00796000000', '9923X84470000000',
'9946X01861000001', '9929X83236000000', '9946X01004000000',
'9946X84443000000', '9923X88342000000', '9910X84452000000',
'9935X82329000000', '9923X00310000000', '9946X82866000000',
'9929X87396000000', '9929X00400000000', '9905X00278000000',
'9946X82761000000', '9923X82229000000', '9929X00728000000',
'9946X83514000000', '9910X83959000000', '9946X84880000000',
'9844X00144000000', '0083G00274602300', '9946X83866000000',
'9929X84432000000', '9929X86854000000', '9905X01912000000',
'9929X87595000000', '9905X01383000000', '9929X82538000000',
'0051S00026000000', '9929X84295000000', '0131C00202000000',
'9946X84806000000', '9946X88252000000', '8000T01845000000',
'9910X00142000000', '9929X00612000000', '9905X82770000000',
'9844X00506000000', '9935X83722000000', '0011A00252000000',
'9946X84753000000', '9923X01014000000', '9935X82195000000',
'9946X88301000000', '8000T00321000000', '9923X88437000000',
'9929X85391000000', '9935X83606000000', '9946X85399000000',
'0168H00110000000', '9935X88203000000', '9910X82208000000',
'9946X50191000000', '9946X84867000000', '9929X88101000000',
'9905X00315000000', '9910X84004000000', '9946X00639000000',
'9946X85175000000', '9929X85379000000', '9844X00640000000',
'9905X00021000000', '9910X00979000000', '9910X83906000000',
'9935X83430000000', '0004J00070000000', '0617P00090000000',
'9946X83319000000', '0237C00290000000', '9946X84891000000',
'9935X82348000000', '9844X00202000000', '9929X83747000000',
'9923X84531000000', '9929X82677000000', '9946X01655000000',
'0052J00213000000', '9844X00683000000', '9923X87645000000',
'9935X83458000000', '9905X01399000000', '9946X00613000000',
'9923X82426000000', '9929X83101000000', '9923X84361000000',
'9935X88028000000', '9923X00603000000', '9946X01031000000',
'9946X00421000000', '9935X83078000000', '9929X87178000000',
'8000T01928000000', '9946X01786000000', '9905X50030000000',
'8000T00120000000', '9910X00149000000', '9923X84628000000',
'0887J00070000000', '9923X00428000000', '9923X87934000000',
'9946X00886000000', '9905X83989000000', '9929X87457000000',
'9929X00860000000', '9929X00105000000', '1655L0003A000000',
'9905X01207000000', '0775D00116000000', '9841X82016000000',
'0190H00240000000', '9929X01865000000', '9935X00212000000',
'9929X87543000000', '0300S00268000000', '9946X83697000000',
'9923X00830000000', '9946X82821000000', '0048N00136000000',
'0079R00078000000', '9929X01551000000', '8000T03192000000',
'0022R00085000000', '9929X01687000000', '9935X82869000000',
'0083G00037000000', '9905X00921000000', '9923X87990000000',
'9946X01166000000', '9923X87573000000', '9946X83915000000',
'9935X87917000000', '0235N00037000000', '0759F00090000000',
'9910X84014000000', '0564P00275000100', '9946X01266000000',
'9905X82464000000', '9929X86546000000', '9946X88295000000',
'9946X88374000000', '9905X82138000000', '9923X87528000000',
'9946X88441000000', '9929X83271000000', '9844X00128000000',
'9935X83133000000', '9905X00527000000', '9905X83109000000',
'9923X88187000000', '9935X83332000000', '9841X50013000000',
'9844X00344000000', '9929X01831000000', '9809X00112000000',
'9910X00541000000', '9929X87526000000', '9946X01436000000',
'9929X84962000000', '9935X00201000000', '9946X00062000000',
'9905X00387000000', '9946X00838000000', '9923X84300000000',
'0957F00391000000', '9935X00777000000', '9929X00212000000',
'9923X87889000000', '0006M00125000000', '9935X82245000000',
'1832E00099000000', '9905X00738000000', '9929X50177000000',
'9929X00625000000', '9946X01541000000', '9929X85741000000',
'9946X87721000000', '9935X82944000000', '9910X84222000000',
'9935X83154000000', '9923X87652000000', '9910X83903000000',
'9946X83182000000', '2382E00305000000', '9929X86576000000',
'1999L00012000000', '0314N00137000000', '9946X82700000000',
'9844X00611000000', '0764C00324000000', '9905X00462000000',
'1347S00113000000', '9910X84337000000', '9929X84546000000',
'9923X88422000000', '9809X00091000000', '9910X84069000000',
'9905X83401000000', '9929X85529000000', '9923X87881000000',
'9923X82023000000', '9905X00346000000', '9935X83483000000',
'9946X01453000000', '9946X82640000000', '9929X50192000000',
'0250D00062000000', '9946X00889000000', '9905X01597000000',
'9923X88024000000', '9946X00261000000', '9923X88199000000',
'9923X84389000000', '9929X00863000000', '9929X83745000000',
'9935X83262000000', '9844X82027000000', '9935X82367000000',
'0265C00257000000', '9935X00240000000', '9935X83487000000',
'9844X00538000000', '0008H00007000000', '9905X00032000000',
'9935X82441000000', '9910X82030000000', '9923X00684000000',
'9929X87699000000', '1519N00309000000', '9935X82200000000',
'9929X88350000000', '9923X00820000000', '9905X00310000000',
'9946X00615000000', '9929X87956000000', '0587E00014000000',
'9946X85541000000', '9929X01448000000', '9935X82824000000',
'9841X00048000000', '9946X82263000000', '0050K00178000000',
'9946X82955000000', '9929X00127000000', '9923X88001000000',
'0514R00225000000', '9929X85858000000', '0307N00156000000',
'9946X00835000000', '9905X00062000000', '9910X82042000000',
'9946X82784000000', '9935X50084000000', '0124J00105000000',
'9946X50303000000', '9905X01763000000', '9946X83180000000',
'9929X80050000000', '9923X88029000000', '0806B00182000000',
'9946X84262000000', '9929X83075000000', '9935X50069000000',
'9946X50097000000', '9910X00617000000', '9905X00989000000',
'9905X01871000000', '9905X00851000000', '9905X83395000000',
'9905X82375000000', '0085B00062306100', '9946X50474000000',
'9929X00334000000', '9935X50103000000', '9929X00413000000',
'9935X82955000000', '9923X00937000000', '9935X83242000000',
'9905X83743000000', '8000T00599000000', '9935X01155000000',
'9910X00141000000', '9923X84620000000', '9935X88099000000',
'0361K00014000000', '9929X00592000000', '9910X84444000000',
'9929X86842000000', '9929X88171000000', '9905X00558000000',
'9910X83915000000', '9946X00727000000', '0471P00240000000',
'9935X83513000000', '9935X01090000000', '9923X84703000000',
'9809X00218000000', '0454R00062000100', '9844X00419000000',
'9905X01075000000', '9923X00392000000', '9935X88037000000',
'9923X88117000000', '9935X00979000000', '9929X83067000000',
'9929X01198000000', '9935X83201000000', '9946X84697000000',
'9946X84133000000', '0051K00250000000', '9923X88048000000',
'9905X83727000000', '9923X88421000000', '9946X82123000000',
'9946X00593000000', '0381F00021000000', '9910X00636000000',
'9946X87978000000', '9935X00986000000', '9946X00208000000',
'0950A00399000000', '9946X81045000000', '9935X88141000000',
'9946X84383000000', '9910X84154000000', '9905X01348000000',
'0661E00275000000', '9910X01276000000', '9946X82454000000',
'9935X82216000000', '9844X00357000000', '9929X88102000000',
'9946X84201000000', '0301N00127000000', '0010P00093000000',
'9929X86769000000', '9910X82467000000', '9923X84629000000',
'9905X82046000001', '9905X82046000000', '9935X00610000000',
'9946X84986000000', '9929X87069000000', '9946X87852000000',
'0085S00295000000', '1104M00398000000', '9923X84530000000',
'9809X84058000000', '9946X00080000000', '0010J00164000000',
'8000T04680000000', '9905X01199000000', '9923X84329000000',
'9905X01563000000', '0236S00211000000', '9946X82255000000',
'0162K00200000300', '9946X88162000000', '9929X88087000000',
'8000T02968000000', '9841X81004000000', '9844X00603000000',
'9910X00916000000', '9905X83625000000', '9946X00398000000',
'0080K00198000000', '9946X50225000000', '9935X88238000000',
'9946X85039000000', '9923X87668000000', '9905X00993000000',
'1130M00255000000', '9946X85331000000', '9905X01739000000',
'9935X82500000000', '9935X87961000000', '9910X83929000000',
'9905X01043000000', '9923X88591000000', '9935X83094000000',
'9905X83278000000', '0156K00354000000', '9946X88391000000',
'9929X00273000000', '9929X85880000000', '9946X01621000000',
'9935X88013000000', '9809X83022000000', '9910X00859000000',
'9946X01821000000', '0040F00252000000', '8000T00460000000',
'9946X85416000000', '9935X82795000000', '9946X01086000000',
'9929X86267000000', '0050F00011000000', '9923X82210000000',
'9946X50400000000', '8000T03028000000', '9905X00468000000',
'9923X88490000000', '9905X00848000000', '9923X84566000000',
'9910X83921000000', '9946X83782000000', '9929X87872000000',
'9929X83233000000', '9910X82158000000', '9935X88632000000',
'9910X00134000000', '9946X84365000000', '9929X85315000000',
'9946X85545000000', '9929X87756000000', '9905X82838000000',
'9844X50004000000', '9946X83241000000', '9929X87480000000',
'9929X86035000000', '0051K00240000000', '9929X01035000000',
'9905X01477000000', '9910X82505000000', '9910X84508000000',
'9929X84608000000', '9905X83986000000', '9923X84663000000',
'9929X01953000000', '9946X84932000000', '9910X83802000000',
'9908X82929000000', '9910X82289000000', '9929X87217000000',
'0925F00150000000', '9929X86195000000', '9905X83954000000',
'9923X88219000000', '9935X83753000000', '9946X83456000000',
'9923X00747000000', '9935X83689000000', '9910X84482000000',
'9929X00225000000', '9923X87998000000', '9935X82854000000',
'9929X85302000000', '9929X83814000000', '9923X87546000000',
'0255N00137000000', '0094C00208000000', '9946X84957000000',
'9946X85652000000', '9905X82300000000', '9923X00618000000',
'9910X00727000000', '9905X84097000000', '0250N00102000002',
'9935X88097000000', '9935X82764000000', '0646F00171000000',
'0505E00197000100', '9929X00410000000', '2204N00100000000',
'9946X82690000000', '9844X00643000000', '9946X00526000000',
'9929X87862000000', '9935X87862000000', '9946X00260000000',
'0315R00036000000', '9908X82523000000', '9946X88544000000',
'9946X50082000000', '9929X00456000000', '9905X83650000000',
'9946X84913000000', '9910X01160000000', '9929X84905000000',
'9929X00897000000', '9923X88100000000', '0050K00027000A00',
'9905X00344000000', '0189N00125000000', '0054K00166000000',
'8000T03238000000', '9923X87615000000', '9929X00505000000',
'9946X85295000000', '9946X83787000000', '9905X50129000000',
'9929X88339000000', '9908X82890000000', '9905X50015000000',
'9809X83043000000', '9910X00616000000', '8000T00434000000',
'0081S00065000000', '9946X00878000000', '9905X83494081800',
'9946X84370000000', '9929X01843000000', '0050J00023000000',
'8000T00218000000', '9946X88241000000', '9905X50103000000',
'0083R00164000000', '9923X88085000000', '9910X01503000000',
'9923X84647000000', '9910X84480000000', '9946X00446000000',
'9946X84738000000', '9935X82303000000', '9929X87628000000',
'9923X87757000000', '0615G00299000000', '9946X82311000000',
'9910X00502000000', '9935X82551000000', '9929X87342000000',
'9905X00822000000', '9946X50397000000', '9923X87457000000',
'9946X83254000000', '9946X00003000000', '9841X00059000000',
'9935X83018000000', '9935X83368000000', '9946X84304000000',
'9935X88550000000', '9935X88156000000', '9929X86575000000',
'9946X87802000000', '9910X82715000000', '9929X87553000000',
'9929X86088000000', '9923X82241000000', '9923X00261000000',
'9923X87666000000', '9929X87221000000', '9946X88223000000',
'9929X84566000000', '9946X00634000000', '9923X87570000000',
'9923X84406000000', '9946X01535000000', '9929X87008000000',
'9946X84694000000', '9935X50263000000', '9935X87850000000',
'9935X83521000000', '8000T02135000000', '9905X83728000000',
'9905X82911000000', '1354H00102000100', '9946X85033000000',
'9935X00788000000', '9929X83382000000', '9809X00314000000',
'9905X83022000000', '9946X82308000000', '0175C00167000000',
'0649D00209000000', '9929X85821000000', '9923X84691000000',
'9946X83100000000', '9929X00759000000', '9946X82059000000',
'9946X82111000000', '9910X01629000000', '9905X01701000000',
'0010J00270000000', '9841X00145000000', '8000T02280000000',
'9946X84735000000', '9946X88173000000', '9946X82600000000',
'9935X83481000000', '9929X87916000000', '9946X88419000000',
'9910X82464000000', '9935X00623000000', '9923X87781000000',
'9935X01055000000', '9929X85486000000', '9910X84029000000',
'9946X00595000000', '8000T00370000000', '9935X00348000000',
'9910X84391000000', '9929X82498000000', '9905X82529000000',
'0877C00046000000', '9946X88246000000', '9923X87537000000',
'9946X82206000000', '9929X84084000000', '9910X82128000000',
'0887D00088000000', '9929X01851000000', '9929X84469000000',
'9929X84498000000', '9946X83172000000', '9929X87407000000',
'9905X01058000000', '9946X82795000000', '9946X85026000000',
'9935X82352000000', '0049J00306000000', '0255P00189000000',
'1210G00041000000', '9905X00947000000', '8000T00792000000',
'9935X88435000000', '9935X82885000000', '9929X00702000000',
'9929X86186000000', '9935X82501000000', '8000T03309000000',
'8000T00409000000', '9946X01824000000', '9905X00195000000',
'9946X83253000000', '9910X01210000000', '9946X87713000000',
'9946X88390000000', '9946X88342000000', '9910X82655000000',
'1218M00307000000', '9946X01428000000', '0660A00048000100',
'9910X84410000000', '9910X01366000000', '9905X01882000000',
'9935X82922000000', '9905X82287000000', '9923X00122000000',
'9844X00153000000', '9946X00420000000', '9946X50217000000',
'9841X82012000000', '9946X82210000000', '9946X82900000000',
'9946X83842000000', '9905X83261000000', '9905X00299000000',
'9911X50021000000', '9946X00756000000', '9923X50002000000',
'9946X50304000000', '9841X00028000000', '0371K00004000000',
'9910X84152000000', '9905X00775000000', '9935X82675000000',
'9935X50061000000', '9809X84064000000', '9929X87250000000',
'1203F00095000300', '9908X82952000000', '9923X87929000000',
'9946X83249000000', '9910X00618000000', '9946X82788000000',
'9946X50195000000', '0301N00158000000', '9946X87685000000',
'9929X01204000000', '0533S00350000000', '0051M00255000000',
'9910X84408000000', '9935X87889000000', '9910X00002000000',
'9844X00032000000', '9929X86377000000', '9905X00064000000',
'9929X87243000000', '9929X86109000000', '0775H00103000000',
'9946X82082000000', '9935X82517000000', '9929X86342000000',
'9905X00886000000', '9923X82372000000', '0049C00209000000',
'9946X85275000000', '9923X87753000000', '9923X87611000000',
'9905X82193000000', '9935X83366000000', '9905X83539000000',
'9923X88045000000', '9946X88222000000', '9935X00415000000',
'8000T01834000000', '9946X84134000000', '9929X84397000000',
'9905X01896000000', '0139R00093000000', '9844X00742000000',
'9946X83171000000', '9929X83416000000', '9946X01473000000',
'9923X84312000000', '1416G00007000000', '9929X86140000000',
'9923X84568000000', '9946X84769000000', '9929X01561000000',
'9923X01087000000', '0024N00048000000', '9929X87917000000',
'0066E00151000000', '9946X00882000000', '9929X88068000000',
'9946X85043000000', '9929X87216000000', '9946X88192000000',
'9946X87915000000', '0012N0018000P300', '9935X83638000000',
'9935X50234000000', '9905X83204000000', '9946X00471000000',
'9923X82081000000', '9929X87411000000', '9929X84592000000',
'9929X01100000000', '8000T01917000000', '9946X50411000000',
'9946X82810000000', '9946X00199000000', '9935X00009000000',
'9905X01249000000', '9923X84454000000', '0513G00020000000',
'9946X00018000000', '9809X00086000000', '9946X82067000000',
'9946X85067000000', '9935X88486000000', '1078K00200000000',
'9929X82009000000', '9935X88140000000', '9905X83754000000',
'9935X50252000000', '9929X00642000000', '0024D00290000000',
'9929X01064000000', '9929X00424000000', '9946X84121000000',
'9929X87188000000', '9905X83574000000', '9910X00753000000',
'9935X83725000000', '9946X01517000000', '9910X01112000000',
'9946X82991000000', '9905X00046000000', '9923X00427000000',
'9946X00693000000', '0307N00154000000', '8000T01689000000',
'9923X84348000000', '9946X01284000000', '0083S00148000000',
'0004B00051000000', '9935X00089000000', '9905X01539000000',
'9910X83940000000', '9946X85623000000', '0625K00022000000',
'9946X85165000000', '9905X82778000000', '9929X88049000000',
'9929X87588000000', '9935X82597000000', '9946X00081000000',
'9809X00024000000', '9946X82205000000', '9935X88555000000',
'1136B00176000000', '9929X82522000000', '9923X00696000000',
'9910X00127000000', '9946X88257000000', '9946X50017000000',
'9946X50408000000', '9844X00170000000', '9935X88108000000',
'9905X01957000000', '9905X83900000000', '9946X82190000000',
'9910X82506000000', '9929X86216000000', '9844X00368000000',
'9935X50173000000', '9946X85082000000', '9935X83297000000',
'9910X84037000000', '9935X82503000000', '9935X00544000000',
'9946X87753000000', '9946X85421000000', '9946X01675000000',
'9844X00022000000', '9935X82340000000', '9910X82364000000',
'8000T00063000000', '9935X83058000000', '0024D00311000000',
'9946X88392000000', '9844X00679000000', '9905X00472000000',
'9929X01443000000', '9929X01787000000', '9905X01638000000',
'9946X84006000000', '9923X82085000000', '9929X01647000000',
'9910X00355000000', '9905X00709000000', '9935X82476000000',
'9946X84336000000', '9905X01300000000', '9905X82133000000',
'9905X01202000000', '9946X82258000000', '9841X00180000000',
'9935X82120000000', '9935X88389000000', '1367D00384000000',
'1108A00023000000', '9935X83148000000', '9946X82885000000',
'9946X84386000000', '0856K00297000000', '9929X87151000000',
'9946X82584000000', '9946X82989000000', '9935X00769000000',
'9935X82543000000', '9905X01749000000', '9935X82570000000',
'0429K00022000000', '9905X83668905A00', '9935X00199000000',
'2188A00047000000', '9946X82459000000', '0664N00150000000',
'9929X01626000000', '9905X82324000000', '0049R00132000300',
'9935X82349000000', '9910X00742000000', '9946X82605000000',
'9929X87222000000', '9946X85000000000', '9910X01176000000',
'9946X87654000000', '9929X86181000000', '9935X00619000000',
'9946X87897000000', '9905X00750000000', '9935X00347000000',
'9908X82902000000', '9946X85258000000', '9923X82217000000',
'9929X00420000000', '9910X82219000000', '9946X87900000000',
'9929X82123000000', '9844X00383000000', '0006R00295000000',
'9946X83745000000', '9929X01496000000', '9935X00361000000',
'9935X00622000000', '9946X01146000000', '9929X83531000000',
'9935X88007000000', '9923X00768000000', '9905X82154000000',
'9910X84328000000', '9935X83658000000', '0004J00172000000',
'9946X84759000000', '9929X83276000000', '0049N00281000000',
'9929X85531000000', '9910X00677000000', '9946X83173000000',
'9935X00460000000', '9935X01067000000', '9844X00184000000',
'9935X83432000000', '8000T01652000000', '9923X00234000000',
'9946X83495000000', '9935X50176000000', '9935X88073000000',
'9946X84752000000', '9929X83251000000', '9905X83483000000',
'9935X01172000000', '9929X85881000000', '9905X00139000000',
'9946X85486000000', '9905X83189000000', '9946X83359000000',
'2392N00107000000', '9935X00027000000', '0092J00100000000',
'9929X86011000000', '9929X87451000000', '9844X00451000000',
'0444A00026000000', '9929X84737000000', '9935X82934000000',
'9935X01349000000', '9935X83156000000', '9935X87950000000',
'9946X85493000000', '9929X00203000000', '9946X00423000000',
'9910X00041000000', '1368A00194000000', '9923X88362000000',
'9946X85359000000', '9929X86359000000', '9923X82294000000',
'9946X82928000000', '9923X88575000000', '9946X83239000000',
'9905X83521000000', '9946X50151000000', '9946X50382000000',
'8000T03176000000', '1210B00155000000', '9923X00391000000',
'9935X00284000000', '9910X00955000000', '9929X84362000000',
'0523H00359000000', '9935X00616000000', '9946X82844000000',
'1670G00189000000', '9935X87946000000', '9929X86750000000',
'9935X88008000000', '9929X87899000000', '9929X01521000000',
'9935X88423000000', '0236D00281000000', '9841X82002000000',
'9946X00744000000', '9905X00059000000', '9946X82217000000',
'8000T02031000000', '9935X81027000000', '9929X00486000000',
'8000T02325000000', '9946X82203000000', '0174K00381000000',
'9929X84876000000', '9946X85132000000', '9946X50121000000',
'8000T02966000000', '9946X82127000000', '9946X84000000000',
'9929X83090000000', '9935X88295000000', '9910X82727000000',
'0941G00354000000', '9929X84235000000', '9923X87862000000',
'9923X87612000000', '9935X83369000000', '9923X00187000000',
'9946X84053000000', '0075G00064000000', '9923X87582000000',
'9946X01727000000', '9905X82262000000', '9929X86799000000',
'8000T00129000000', '1075C00328000000', '9910X00334000000',
'9844X00198000000', '9935X82331000000', '9929X83838000000',
'9929X86605000000', '9905X83174000000', '9929X01008000000',
'0824L00020000000', '9929X83865000000', '9929X87760000000',
'9929X87838000000', '0073G00290000000', '9935X82449000000',
'0011A00167000000', '9929X88337000000', '0424G00038000000',
'9929X86860000000', '9841X00137000000', '9905X83721000000',
'9905X83276000000', '8000T01576000000', '9923X88010000000',
'9946X83898000000', '0506A00028000000', '9929X01230000000',
'8000T01999000000', '9841X00191000000', '0562N00024000300',
'9946X84966000000', '9946X85365000000', '9935X00971000000',
'9929X01378000000', '9946X00388000000', '9929X84222000000',
'9923X82431000000', '9935X00007000000', '9905X83709000000',
'9910X00717000000', '9809X84057000000', '9905X82275000000',
'9946X83297000000', '9929X00508000000', '9923X82386000000',
'9844X00105000000', '9935X82806000000', '9929X00982000000',
'9905X83757000000', '9929X84520000000', '9809X00041000000',
'9905X83495000000', '9946X50218000000', '8000T02430000000',
'9923X87685000000', '9929X84232000000', '9935X82436000000',
'0520E00201000000', '0004P00131000000', '9923X50040000000',
'9923X88408000000', '9910X00959000000', '9946X00331010300',
'9946X85412000000', '9905X00693000000', '9929X86104000000',
'9905X00063000000', '9905X82991000000', '9946X83274000000',
'9905X01251000000', '9935X00620000000', '9935X87962000000',
'9923X87484000000', '9841X00127000000', '9946X84087000000',
'9946X83122000000', '9946X50285000000', '9929X01003000000',
'9929X88148000000', '9905X83201000000', '9935X87828000000',
'9946X83328000000', '9809X83023000000', '9905X01778000000',
'9910X82333000000', '9946X83410000000', '0649D00213000000',
'1670G00197000000', '9935X82425000000', '0119S00103000000',
'9905X00459000000', '9929X85286000000', '1075M00326000000',
'9946X84047000000', '9935X82402000000', '9935X82037000000',
'9946X85094000000', '8000T03300000000', '9935X50099000000',
'9929X87904000000', '9929X88038000000', '2016P00175000000',
'9946X83233000000', '0374A00098000000', '9910X84137000000',
'9923X88040000000', '9809X82008000000', '9905X01659000000',
'9935X82714000000', '8000T03142000000', '9935X82537000000',
'0301P00225000000', '9935X83428000000', '9809X00196000000',
'9905X01384000000', '9929X85179000000', '9935X00738000000',
'9935X50216000000', '9905X00699000000', '9946X84872000000',
'9923X82320000000', '9946X84190000000', '9946X88485000000',
'9946X83709000000', '9910X82209000000', '9910X82741000000',
'9923X00906000000', '9935X82080000000', '9929X86549000000',
'9929X00890000000', '9923X00780000000', '9905X83891000000',
'9905X83635000000', '0130R00261000000', '9905X83523000000',
'9946X84779000000', '9929X50109000000', '9946X84757000000',
'9910X82166000000', '9905X00290000000', '9935X01073000000',
'9929X00617000000', '0461A00107000000', '9946X84831000000',
'9946X85081000000', '9946X00157000000', '9946X85380000000',
'9929X50274000000', '9929X83103000000', '0082L00297000000',
'8000T00557000000', '9929X86263000000', '9946X84063000000',
'9923X87428000000', '9929X83077000000', '9935X82172000000',
'9935X83268000000', '9929X87392000000', '8000T01121000000',
'0050K00056000B00', '9929X82866000000', '9910X00384000000',
'9841X00168000000', '9946X00410000000', '9935X82208000000',
'9946X00222000000', '9946X00825000000', '9809X00100000000',
'9905X00122000000', '9935X50186000000', '9923X82445000000',
'9905X00128000000', '9929X82869000000', '9923X88142000000',
'9946X82449000000', '9844X00749000000', '9905X01698000000',
'9910X82611000000', '9923X82127000000', '9905X00168000000',
'1002B00035000600', '9923X88413000000', '9946X82569000000',
'9946X85529000000', '9946X84762000000', '9946X87964000000',
'9929X87864000000', '8000T01557000000', '9910X01371000000',
'9946X84788000000', '9929X84965000000', '0050L00274000A00',
'9946X84850000000', '8000T03568000000', '9910X00156000000',
'0775H00097000000', '9935X82853000000', '9923X00989000000',
'0856C00167000000', '0719M00010000000', '9929X83074000000',
'9929X87914000000', '9929X88232000000', '1368C00250000000',
'9946X01788000000', '9923X82107000000', '1834B00027000000',
'9946X01689000000', '9946X83700000000', '8000T01766000000',
'9929X85664000000', '9809X00106000000', '9946X00591000000',
'9841X00217000000', '9935X88327000000', '9923X88232000000',
'9923X84436000000', '9809X83013000000', '9946X82570000000',
'9923X00853000000', '9946X82919000000', '9946X85153000000',
'9910X00786000000', '9923X00175000000', '0066E00162000000',
'9929X87830000000', '9946X83930000000', '9929X01893000000',
'0050K00179000000', '9929X87876000000', '9929X84215000000',
'8000T02426000000', '9946X83300000000', '9946X83848000000',
'9935X87943000000', '9929X87022000000', '9946X85448000000',
'0181S00103000000', '0005D00092000000', '9946X84728000000',
'9929X86782000000', '9844X00478000000', '9929X86285000000',
'8000T03504000000', '9935X88457000000', '9910X01339000000',
'9841X00181000000', '9905X83158000000', '9929X00050000000',
'9946X88373000000', '9905X82058000000', '9946X01191000000',
'9923X88390000000', '9923X88149000000', '9841X00226000000',
'0010L00147000000', '9809X84025000000', '0624H00137000000',
'9844X00439000000', '9946X82124000000', '9935X87874000000',
'9923X00689000000', '9935X00797000000', '9935X88438000000',
'9946X01769000000', '0154S00030000000', '8000T02043000000',
'9946X82698000000', '9929X01886000000', '9844X00631000000',
'9910X82177000000', '9946X00201000000', '9946X01684000000',
'9929X01557000000', '0012J00263000000', '9910X01393000001',
'9946X88111000000', '9946X00344000000', '9905X00825000000',
'9946X88289000000', '9905X83660000000', '9929X84377000000',
'9935X82261000000', '9935X87820000000', '0052J00216000000',
'9929X86370000000', '9844X00112000000', '9935X01091000000',
'9905X84005003F00', '9946X01485000000', '9929X88290000000',
'9946X83809000000', '9935X88696000000', '9946X88292000000',
'9905X83572000000', '9929X00676000000', '9923X88105000000',
'9929X85217000000', '9923X84602000000', '9929X88007000000',
'9923X87951000000', '9905X00479000000', '9935X83778000000',
'9910X01430000000', '0228J00210040800', '9923X84362000000',
'9905X82874000000', '9946X84159000000', '9946X83154000000',
'0624D00053000000', '9946X00022000000', '9935X00457000000',
'9910X84298000000', '9935X82072000000', '9946X88559000000',
'9946X82087000000', '0096M00120000000', '9935X88276000000',
'9809X00040000000', '9946X87879000000', '9935X88269000000',
'9946X87655000000', '8000T03495000000', '9905X01508000000',
'9929X84613000000', '9910X01389000000', '0130R00269000000',
'9910X00779000000', '9841X00134000000', '9910X84165000000',
'9935X83280000000', '9905X82686000000', '0299F00062000000',
'9929X86271000000', '9910X83925000000', '9929X85530000000',
'9905X82607000000', '9929X83532000000', '9946X50432000000',
'9929X87777000000', '9910X00486000000', '9905X82317000000',
'9910X01049000000', '9946X82727000000', '0023M00167000000',
'1211R00073000000', '9935X00547000000', '9946X50024000000',
'9929X85316000000', '9935X83169000000', '9935X83760000000',
'9935X87956000000', '9935X83114000000', '0049J00226000000',
'0925K00239000000', '9946X00418000000', '9910X84495000000',
'9910X82323000000', '9929X87145000000', '9923X88031000000',
'9935X82766000000', '9946X00969000000', '9929X00129000000',
'9923X00068000000', '9905X83389000000', '9929X86958000000',
'9946X50453000000', '9929X84466000000', '8000T00688000000',
'9935X00984000000', '9946X87800000000', '9923X00969000000',
'9929X00696000000', '9946X01811000000', '9923X88414000000',
'9929X88161000000', '9946X88112000000', '9929X00166000000',
'9946X50395000000', '9923X00220000000', '9923X88108000000',
'9929X85178000000', '9923X87416000000', '9946X84322000000',
'9946X50276000000', '9929X87564000000', '9923X88442000000',
'9929X87664000000', '9923X88380000000', '9923X88119000000',
'9946X82573000000', '9809X84074000000', '9935X00598000000',
'9946X88529000000', '9946X85159000000', '9935X83766000000',
'9923X84680000000', '8000T02847000000', '9905X00748000000',
'9910X00788000000', '9935X87798000000', '9946X83833000000',
'9923X87604000000', '9923X84490000000', '9946X00856000000',
'9946X01307000000', '9935X88355000000', '9946X84936000000',
'0027D00052000000', '9923X87664000000', '9910X00827000000',
'9946X83321000000', '9905X83608000000', '9905X83820000000',
'9935X83612000000', '9935X87947000000', '9905X83226000000',
'9935X83723000000', '9905X00450000000', '9923X88367000000',
'0210D00002000000', '9923X87764000000', '9910X83970000000',
'9923X00795000000', '0309M00186000000', '9929X00839000000',
'9923X82377000000', '9946X00140000000', '9910X84354000000',
'9946X82121000000', '8000T02030000000', '9923X87755000000',
'9910X01591000000', '9946X84114000000', '9935X83360000000',
'9929X85371000000', '9946X01451000000', '9809X00108000000',
'9929X84714000000', '9809X00123000000', '9905X82988000000',
'9946X82893000000', '9946X82024000000', '9946X82448000000',
'9844X00748000000', '9935X83308000000', '9905X82136000000',
'9910X82167000000', '9946X00276000000', '9923X87725000000',
'0299F00078000000', '9946X00763000000', '9946X82670000000',
'9935X88104000000', '9923X87822000000', '9946X88467000000',
'9905X82460000000', '0381J00011000001', '9910X84496000000',
'9935X83274000000', '9946X00324000000', '9929X88135000000',
'9935X00449000000', '9910X00558000000', '9905X50028000000',
'9946X83899000000', '0551F00248000000', '9923X84630000000',
'9910X01580000000', '0032F00356000000', '8000T01858000000',
'9910X01431000000', '9935X82690000000', '9923X00378000000',
'9946X82856000000', '9923X82427000000', '9929X83016000000',
'9905X84026000000', '9905X01211000000', '9935X00245000000',
'9929X87567000000', '9910X01207000000', '9929X88143000000',
'9935X00501000000', '9923X82151000000', '9935X88726000000',
'9946X85607000000', '9910X80021000000', '9929X00145000000',
'9935X83516000000', '9923X00946000000', '9946X84462000000',
'9923X88266000000', '9946X88237000000', '9910X84118000000',
'0256H00334000000', '9923X00757000000', '9946X83512000000',
'9929X84644000000', '9910X84198000000', '9946X85444000000',
'9946X82901000000', '9946X50284000000', '9929X86354000000',
'9946X84885000000', '9929X01220000000', '9905X82544000000',
'9910X00442000000', '0718L00291000000', '9923X00872000000',
'9923X00131000000', '9910X00798000000', '0662J00090000000',
'9929X84427000000', '9923X00707000000', '9946X01393000000',
'0141G00060000000', '9935X82409000000', '9844X00324000000',
'9910X84344000000', '9923X01012000000', '9946X87923000000',
'9905X82609000000', '0051K00218000000', '9946X01614000000',
'9946X01768000000', '9929X87821000000', '9946X85599000000',
'9946X87992000000', '9935X83202000000', '9905X00764000000',
'1051S00010000300', '9946X01584000000', '9910X00169000000',
'9905X83142000000', '9908X82920000000', '0603E00065000000',
'1202D00215000000', '9910X84044000000', '0001N00149000100',
'9946X83298000000', '9809X00213000000', '9935X50041000000',
'9946X82345000001', '9910X82692000000', '9923X00765000000',
'9946X83729000000', '9929X00331000000', '9905X00906000000',
'9935X82241000000', '9935X82335000000', '9929X00480000000',
'9844X00461000000', '9929X83815000000', '9910X00913000000',
'0097M00041000000', '0026P00135000000', '9935X82762000000',
'9809X00237000000', '9929X87353000000', '9929X84979000000',
'9910X82135000000', '0732A00337000000', '9935X82186000000',
'9929X84650000000', '9946X82216000000', '9809X00055000000',
'0010K00058000000', '8000T00554000000', '9923X82259000000',
'0010G00022000000', '9929X83407000000', '9910X01315000000',
'1670F00369000000', '9935X83768000000', '0390B00221000200',
'9946X84930000000', '9946X83177000000', '9946X00464000000',
'9935X83009000000', '9929X87535000000', '9935X82738000000',
'9946X83774000000', '9929X85380000000', '9946X88005000000',
'9946X84897000000', '9923X88372000000', '9946X85480000000',
'9923X00772000000', '9910X84339000000', '9929X01583000000',
'9946X85248000000', '8000T00775000000', '9946X82227000000',
'0138B00301000000', '0052E00257000500', '9905X00669000000',
'9905X50034000000', '0508G00027000000', '1361S00112000000',
'9905X83623000000', '9946X87714000000', '9946X82770000000',
'9929X00741000000', '9935X88076000000', '9923X00156000000',
'9946X83966000000', '0049J00269000000', '9946X84355000000',
'9923X84533000000', '9929X87602000000', '9929X87658000000',
'9946X00223000000', '9910X84035000000', '9844X82039000000',
'9935X82136000000', '9935X00732000000', '0027M00246060801',
'8000T02705000000', '9929X88006000000', '9905X83283000000',
'0011A00138000A00', '9905X00057000000', '9910X82488000000',
'9929X88201000000', '9935X82571000000', '9905X00501000000',
'9935X83426000000', '9809X84016000000', '9929X87283000000',
'9946X82865000000', '9935X88284000000', '9935X83805000000',
'9946X82923000000', '0011A00133000000', '9946X82320000000',
'0422K00070000000', '9910X84494000000', '9929X87829000000',
'9905X82462000000', '1421C00007000000', '9905X00891000000',
'9910X00439000000', '9844X00607000000', '8000T01898000000',
'9905X82049000000', '9946X84107000000', '9905X00148000000',
'9923X84548000000', '9910X84145000000', '9946X50273000000',
'8000T02363000000', '9935X83679014800', '0713D00604310500',
'9923X82454000000', '9929X81228000000', '9910X00047000000',
'0975L00054000000', '9929X87937000000', '9946X83282000000',
'9923X87866000000', '0175N00140000000', '9946X83847000000',
'9946X83933000000', '9905X83419000000', '0564C00015000000',
'9923X00499000000', '9946X84834000000', '9946X83613000000',
'9946X00832000000', '9946X87949000000', '9935X87799000000',
'9935X00058000000', '9946X01142000000', '9929X86266000000',
'9910X00071000000', '8000T03222000000', '9935X88169000000',
'9929X85688000000', '9935X83313000000', '9946X01050000000',
'9929X86014000000', '9935X01043000000', '9935X83137000000',
'9946X00772000000', '9923X87592000000', '9910X01447000000',
'0023F00139000000', '9946X85528000000', '9946X81065000000',
'8000T02086000000', '0269E00044000000', '9929X87032000000',
'9809X00245000000', '9929X00208000000', '9946X85147000000',
'9905X82276000000', '9935X83273000000', '0350D00110000000',
'9946X50478000000', '9923X01016000000', '9923X82042000000',
'9929X00581000000', '9905X00054000000', '9923X88223000000',
'9905X01258000000', '9929X85050000000', '9935X83302000000',
'8000T01584000000', '0050F00008000000', '0080F00135000000',
'8000T01903000000', '9935X88105000000', '9905X83661000000',
'0001C01662L02000', '9929X88147000000', '8000T00613000000',
'9910X84064000000', '0701G00041000000', '9929X84009000000',
'9946X01505000000', '9923X87524000000', '0012S00139000000',
'9910X82667000000', '0240N00109000100', '9910X82337000000',
'9946X50378000000', '9905X00926000000', '9935X01329000000',
'9923X82380000000', '9929X87159000000', '0642J00081000000',
'9905X84027000000', '0414S00021000000', '9946X88036000000',
'0351B00248000000', '9946X84045000000', '0450P00471000000',
'9905X84028000000', '9935X82736000000', '0512L00175000000',
'9929X83225000000', '9946X84454000000', '9946X50416000000',
'0229M00100000000', '9946X88585000000', '9929X01181000000',
'9929X00919000000', '9905X00688000000', '9910X84133000000',
'9923X87586000000', '9910X80071000000', '9946X50505000000',
'9910X82328000000', '9929X87616000000', '9935X83002000000',
'9844X00327000000', '9935X82542000000', '9809X83011000000',
'9910X82259000000', '9935X83609000000', '9946X84942000000',
'0353R00295000000', '9935X01121000000', '9923X88033000000',
'0522E00210000000', '9910X00638000000', '9910X01187000000',
'9929X00835000000', '9923X88158000000', '9905X00301000000',
'9910X82522000000', '0010J00120000000', '9946X82994000000',
'0650A00032000000', '9929X00409000000', '0626G00162000000',
'9935X83111000000', '9908X82905000000', '9935X82408000000',
'9905X83527000000', '8000T03002000000', '9946X85561000000',
'0336D00209000000', '9935X88358000000', '8000T02922000000',
'9946X83003000000', '9935X83417000000', '9905X01813000002',
'9946X88105000000', '8000T00652000000', '8000T01677000000',
'9929X00484000000', '1667C00188000000', '8000T02943000000',
'9905X82020000000', '9923X00995000000', '9929X84349000000',
'9929X00749000000', '9910X00543000000', '9929X87207000000',
'9910X83984000000', '9929X87978000000', '0941F00218000000',
'8000T01922000000', '9946X00473000000', '9935X01149000000',
'9844X00668000000', '9946X50305000000', '9935X87826000000',
'9946X50338000000', '9935X82387000000', '0834D00248000000',
'9935X88360000000', '9908X82921000000', '9935X00497000000',
'9905X83568000000', '9923X82470000000', '9946X87684000000',
'9929X84223000000', '9929X87912000000', '9923X88035000000',
'9905X82377000000', '9946X85499000000', '9905X01724000000',
'9929X87039000000', '9946X88228000000', '9809X83045000000',
'9910X83932000000', '9946X84413000000', '9935X83099000000',
'9935X50105000000', '8000T02246000000', '9929X86532000000',
'0062P00061A00300', '9946X00937000000', '9935X83663000000',
'9946X84810000000', '0609L00346000000', '9929X87487000000',
'9910X01177000000', '9929X83406000000', '9923X87640000000',
'9905X83987000000', '9908X82874000000', '9923X88438000000',
'9923X88044000000', '9946X00982000000', '9946X85494000000',
'9923X84453000000', '0667C00166000000', '9910X84412000000',
'9923X84365000000', '9923X84536000000', '9946X84706000000',
'9935X82034000000', '9905X01061000000', '0124J00094000000',
'9929X83734000000', '9929X83541000000', '0362F00112000000',
'9935X83139000000', '9929X01466000000', '9946X82363000000',
'9946X88239000000', '9844X00593000000', '9923X87706000000',
'9929X86281000000', '9923X88236000000', '9929X00578000000',
'9935X82135000000', '9905X00280000000', '9946X83256000000',
'9946X84280000000', '9935X00055000000', '9935X83569000000',
'9935X88041000000', '9929X00108000000', '0775H00067000000',
'9946X81044000000', '9929X85853000000', '9910X00534000000',
'9910X00674000000', '9923X84307000000', '9929X87310000000',
'9946X85010000000', '9946X01319000000', '9905X00056000000',
'9910X00414000000', '9929X84835000000', '9929X00246000000',
'9946X50244000000', '9946X85644000000', '9929X85899000000',
'9935X83012000000', '9905X82022000000', '9935X82580000000',
'9929X83917000000', '9929X88229000000', '9929X00435000000',
'9929X85774000000', '9923X00223000000', '0829N00039000100',
'9946X84205000000', '9905X83239000000', '9929X85054000000',
'9946X85640000000', '9946X82811000000', '9910X82331000000',
'9841X82022000000', '9935X50023000000', '0156P00157000000',
'9905X00928000000', '9844X00259000000', '9946X84068000000',
'9923X00941000000', '0086P00150100400', '9946X88164000000',
'9923X87865000000', '9946X84404000000', '0080N00036000000',
'9910X84286000000', '9935X01014000000', '0004J00127000000',
'9910X00084000000', '9935X01305000000', '9910X84135000000',
'9841X50011000000', '0290P00073000000', '9905X00852000000',
'9923X82323000000', '9946X82972000000', '9935X88228000000',
'0008H00208000000', '9929X88140000000', '9929X84969000000',
'9910X82368000000', '9910X00323000000', '9946X82081000000',
'0017J00240000000', '0125L00217000000', '9946X83962000000',
'0233E00262000300', '9935X00075000000', '9905X82705000000',
'9923X00087000000', '9905X83622000000', '9923X87756000000',
'9935X82845000000', '9946X01080000000', '9935X00736000000',
'0649D00257000000', '8000T00300000000', '0508N00176000000',
'0307N00306000000', '0392D00025000000', '9929X85306000000',
'9910X82373000000', '9923X00997000000', '9946X83859000000',
'9910X83820000000', '9929X87578000000', '9929X01473000000',
'0026P00067000000', '9923X87553000000', '9910X82508000000',
'9923X00405000000', '9929X00652000000', '9923X87565000000',
'9935X50198000000', '9935X83312000000', '9905X00847000000',
'1245J00248000000', '9946X84709000000', '9929X87226000000',
'0124J00118000000', '0250K00160000001', '0004G00134000000',
'9946X82098000000', '9946X84363000000', '9929X83460000000',
'9946X82518000000', '9946X83200000000', '9929X01381000000',
'9905X00475000000', '9929X01223000000', '9929X82865000000',
'9946X83840000000', '9923X82111000000', '9929X84236000000',
'9946X83299000000', '0024N00058000000', '9905X83316000000',
'9929X87215000000', '9923X87923000000', '9809X00006000000',
'9910X82136000000', '9923X82069000000', '9935X82581000000',
'9923X88066000000', '9946X82880000000', '9910X84322000000',
'9929X88368000000', '9929X84289000000', '9929X00887000000',
'1668R00248000000', '9844X00565000000', '9946X87974000000',
'0660A00046000100', '9946X82730000000', '9923X00432000000',
'9923X00925000000', '9910X50014000000', '0039R00075000000',
'9929X87339000000', '9910X01196000000', '9923X84695000000',
'9946X84773000000', '9905X83825000000', '9935X00506000000',
'9946X87981000000', '9910X84269000000', '9929X85576000000',
'9905X00557000000', '9935X50192000000', '9929X85878000000',
'9923X88436000000', '9929X83250000000', '9935X82739000000',
'9929X01235000000', '9929X84748000000', '9946X83042000000',
'9923X88166000000', '0039R00059000000', '0125L00292000000',
'1421C00175000000', '9910X84130000000', '9905X00837000000',
'9844X00185000000', '9844X00655000000', '9844X00633000000',
'9929X00646000000', '9923X88550000000', '8000T00709000000',
'9946X83323000000', '9905X83678000000', '9929X00069000000',
'9929X83748000000', '8000T03563000000', '9905X82243000000',
'9923X84532000000', '9923X88230000000', '9910X84430000000',
'9910X82340000000', '9929X87771000000', '9929X82628000000',
'9929X84818000000', '9910X01435000000', '9929X01119000000',
'9946X83877000000', '9910X80005000000', '9946X83202000000',
'0855K00379000000', '9908X82916000000', '9905X82143000000',
'1510R00332000000', '9946X00029000000', '9923X82302000000',
'9946X83393000000', '9946X88534000000', '9935X82586000000',
'9905X83950000000', '9841X00158000000', '9946X82589000000',
'9946X00584000000', '9905X82310000000', '9929X01476000000',
'9910X82394000000', '9946X85570000000', '9929X86578000000',
'9844X00076000000', '9929X86674000000', '9946X88313000000',
'9905X01465000000', '9946X01182000000', '1365G00112000000',
'9923X88087000000', '9910X00148000000', '9946X82096000000',
'9929X00286000000', '0876G00153000000', '9910X00871000000',
'0051N00225000000', '9923X82009000000', '9946X88250000000',
'9910X83830000000', '0382B00395000000', '9946X01010000000',
'9910X01082000000', '1077E00156000001', '9935X83322000000',
'8000T00380000000', '9946X83595000000', '9844X00646000000',
'9935X87822000000', '0018E00181000000', '9923X00018000000',
'9910X82399000000', '9935X01298000000', '9929X83470000000',
'0024J00053000000', '9935X87978000000', '9935X88098000000',
'9844X00341000000', '8000T00475000000', '9946X50315000000',
'9844X00334000000', '9946X50543000000', '9844X00470000000',
'9923X84624000000', '9946X88434000000', '0098G00208000000',
'9935X87941000000', '9910X82764000000', '0236S00326000000',
'9905X82924000000', '2181M00444000000', '9935X01048000000',
'9946X81040000000', '9935X82868000000', '9809X83007000000',
'9929X01166000000', '9946X88573000000', '9946X83243000000',
'9929X87994000000', '9844X00672000000', '0079R00109000000',
'9946X83041000000', '9946X82085000000', '9929X83526000000',
'9923X84344000000', '0219S00139000000', '9908X82870000000',
'0141B00132000000', '9929X01853000000', '9905X01727000000',
'9929X87948000000', '0167C00024000000', '9923X87786000000',
'9923X88003000000', '9929X01303000000', '0091N00166000000',
'9929X00885000000', '9923X88172000000', '9946X82960000000',
'9923X88170000000', '9929X87820000000', '9923X84430000000',
'0050L00070000000', '9935X00681000000', '9935X83660000000',
'8000T03193000000', '0236S00111000100', '0026P00063000000',
'9929X87992000000', '9929X83511000000', '9946X82117000000',
'9929X85613000000', '9905X00725000000', '9905X83484000000',
'9923X87836000000', '9946X83692000000', '9935X00643000000',
'9946X83409000000', '9923X00141000000', '2204B00032000000',
'9929X84845000000', '9946X00979000000', '9946X82122000000',
'8000T01437000000', '9905X00232000000', '9910X01491000000',
'9929X00859000000', '9935X82058000000', '9929X86015000000',
'9905X00244000000', '9946X83364000000', '9935X00243000000',
'9946X87884000000', '9946X85573000000', '9910X00238000000',
'0189J00180000000', '9910X84290000000', '9923X87575000000',
'8000T03485000000', '9946X82218000000', '9946X85015000000',
'9946X82470000000', '9844X00661000000', '0617H00311000000',
'9946X83945000000', '9905X00994000000', '9929X84925000000',
'9923X88501000000', '9923X82169000000', '9910X00017000000',
'9946X82717000000', '9910X82414000000', '9946X00973000000',
'9910X84093000000', '9923X00086000000', '9929X00162000000',
'9844X82048000000', '9923X87801000000', '9929X84680000000',
'9946X01822000000', '9905X84018000000', '0003H00336000000',
'9935X00278000000', '9905X82803000000', '9905X00181000000',
'9809X00161000000', '9905X83188000000', '9935X83716000000',
'0431L00172000001', '1108S00328000000', '9923X84411000000',
'9946X83204000000', '0079R00085000000', '0444F00303000000',
'9946X84136000000', '9841X00062000000', '9935X83740000000',
'9946X85540000000', '9929X01154000000', '0052E00081050300',
'9905X82273000000', '9946X82315000000', '9935X83038000000',
'9844X82045000000', '9905X83826000000', '9946X01173000000',
'9905X82095000000', '9935X82386000000', '9946X01712000000',
'9946X85058000000', '0250D00068000000', '9929X88083000000',
'9844X00078000000', '9841X00088000000', '9946X82735000000',
'9905X82901000000', '9929X86806000000', '0700S00049000100',
'1008A00267000000', '9841X00230000000', '0188S00179000000',
'9929X84656000000', '9905X83506000000', '9946X82942000000',
'9946X84317000000', '9910X00445000000', '9905X00631000000',
'0299F00062000100', '9910X82141000000', '8000T03811000000',
'9910X84546000000', '9946X82957000000', '9935X50019000000',
'9923X01079000000', '9946X87793000000', '9929X86770000000',
'9935X50033000000', '9844X00211000000', '9923X00117000000',
'9946X00339000000', '9929X87437000000', '9923X88439000000',
'9910X84490000000', '0138N00100000000', '9946X01102000000',
'9908X82850000000', '9946X85621000000', '9946X01782000000',
'9946X83043000000', '9929X01128000000', '9946X83378000000',
'0080K00110000000', '9946X01526000000', '9946X88040000000',
'9935X88210000000', '9905X50059000000', '9929X01202000000',
'9923X87555000000', '9935X00830000000', '9929X00932000000',
'9923X00694000000', '9923X88551000000', '9935X00566000000',
'9929X88235000000', '9923X87481000000', '9935X01026000000',
'9844X00708000000', '9929X00886000000', '1666B00287000000',
'9905X00049000000', '1842G00381000000', '9905X00279000000',
'9929X87561000000', '9905X83510000000', '9935X01351000000',
'9929X86098000000', '9905X01286000000', '9910X84395000000',
'9946X82524000000', '9935X83026000000', '9946X82951000000',
'9905X00266000000', '9946X01852000000', '9929X83076000000',
'9946X84043000000', '9923X82473000000', '9946X00513000000',
'9929X87903000000', '9910X00752000000', '9923X88071000000',
'9946X82114000000', '9929X87744000000', '9946X85269000000',
'9946X01187000000', '8000T01556000000', '9905X01899000000',
'9841X00228000000', '9935X50028000000', '9946X82079000000',
'9923X87691000000', '9905X01921000000', '9910X82657000000',
'9905X00142000000', '9905X82167000000', '9809X00193000000',
'9935X82452000000', '9935X00726000000', '9910X00147000000',
'0564S00025000000', '9929X83113000000', '9946X87936000000',
'0419H00303000000', '9935X00004000000', '9929X00101000000',
'9929X85863000000', '9905X83052000000', '9905X84118000000',
'9809X00337000000', '9946X83048000000', '9946X00186000000',
'9946X82327000000', '1677N00339000000', '9946X84832000000',
'9946X50011000000', '9905X83317000000', '9905X82510000000',
'9946X82968000000', '9929X86260000000', '9923X00663000000',
'9923X82153000000', '9935X82898000000', '9905X00990000000',
'9905X83677000000', '9946X84090000000', '9935X83259000000',
'9946X85501000000', '9929X01723000000', '9905X83011000000',
'9946X84225000000', '9935X82726000000', '9929X01354000000',
'9946X50468000000', '9929X86374000000', '9946X83920000000',
'9929X83507000000', '9946X83650000000', '9905X82895000000',
'9946X00133000000', '9929X00731000000', '0624H00096000000',
'9929X85245000000', '9929X84282000000', '9935X83004000000',
'9841X00022000000', '9935X82579000000', '9929X50406000000',
'9946X80034000000', '0124J00120000000', '0258M00018000000',
'0082L00301000000', '9905X00176000000', '0050K00018000A00',
'9929X01300000000', '9905X83902000000', '9910X00878000000',
'9923X00636000000', '9946X85255000000', '9946X01039000000',
'9929X85018000000', '9929X01028000000', '1846M00066000000',
'9946X00535000000', '8000T03039000000', '9923X87922000000',
'9946X85413000000', '9929X00948000000', '9946X84718000000',
'9946X82603000000', '9929X00015000000', '9841X00058000000',
'9905X82786000000', '9923X82110000000', '9946X01291000000',
'9905X83487000000', '9923X84341000000', '0103P00190000000',
'9910X01189000000', '9929X87385000000', '9935X82422000000',
'9929X87214000000', '9923X87912015300', '9946X84099000000',
'9929X86775000000', '9946X82872000000', '0063E00146000000',
'9905X50060000000', '9946X85342000000', '9946X88397000000',
'9946X83524000000', '9905X01321000000', '9946X50226000000',
'9929X85261000000', '9935X00710000000', '9923X00645000000',
'9935X82730000000', '9923X87574000000', '9910X83972000000',
'9929X86741000000', '9910X01201000000', '0125L00291000000',
'9923X00878000000', '9946X84847000000', '9910X01225000000',
'0337G00282000000', '9946X50558000000', '0023J00050000000',
'9929X85382000000', '9935X01243000000', '9910X84390000000',
'9946X00940000000', '9905X82740000000', '9935X82532000000',
'0029C00060000000', '9935X81025000000', '9923X84301000000',
'9935X82758000000', '9929X00864000000', '0225C00150000000',
'0396M00200000000', '1354A00080000000', '9905X00327000000',
'9935X88088000000', '9935X82044000000', '9946X84325000000',
'9935X00669000000', '9946X00331000000', '9946X83126000000',
'0125L00126000000', '9905X82794000000', '9929X00784000000',
'0831A00053000000', '9929X83942000000', '9946X87727000000',
'9946X82188000000', '9910X82433000000', '9946X82239000000',
'8000T00583000000', '9844X00087000000', '8000T02017000000',
'0450P00477000000', '9929X00292000000', '9946X01525000000',
'9946X01858000000', '0390B00221000100', '0709J00039000000',
'9929X00609000000', '9946X83325000000', '0507L00004000000',
'9910X01478000000', '9929X87958000000', '9946X82077000000',
'9841X00036000000', '9905X00140000000', '9905X00259000000',
'9809X00180000000', '9946X82938000000', '9946X82981000000',
'9929X01266000000', '0190S00306000000', '9905X01893000000',
'9905X82718000000', '9929X50384000000', '9905X00231000000',
'9929X86133000000', '9923X00933000000', '9910X00544000000',
'9844X00517000000', '9905X82789000000', '9905X82091000000',
'9946X00520000000', '9935X83618000000', '9946X82615000000',
'9929X87356000000', '9929X86250000000', '9929X87753000000',
'9809X00305000000', '0007B00262000000', '2013K00133000000',
'9929X87646000000', '9923X88032000000', '9905X00018000000',
'9946X84881000000', '9929X87155000000', '9935X82233000000',
'9946X83320000000', '9935X82432000000', '0119S00224000A00',
'9946X82365000000', '9946X01808000000', '9929X85241000000',
'9905X82063000000', '0773F00108000000', '9929X87436000000',
'9946X84960000000', '0169G00225000000', '9923X84708000000',
'9923X87562000000', '9905X01001000000', '1204B00120000000',
'9844X00533000000', '8000T03172000000', '9946X85096000000',
'9923X82037000000', '9946X85122000000', '9935X50006000000',
'9935X00095000000', '9935X82999000000', '9935X88077000000',
'9929X01462000000', '0050K00059000000', '9929X85820000000',
'9923X82472000000', '9905X83715000000', '9905X01066000000',
'9923X00005000000', '9946X83800000000', '9923X01086000000',
'9946X83400000000', '9923X84392000000', '9929X50157000000',
'9905X82769000000', '9946X82561000000', '9935X00071000000',
'9905X82158000000', '9946X82549000000', '9946X85318000000',
'9946X83995000000', '0601J00016000000', '9910X00446000000',
'9946X81077000000', '9935X88527000000', '9809X00096000000',
'9946X81027000000', '9905X01459000000', '9929X00380000000',
'9809X00335000000', '9905X00786000000', '9910X01434000000',
'9910X84119000000', '9910X82425000000', '9946X83725000000',
'9910X82518000000', '8000T02408000000', '9946X83941000000',
'9923X00993000000', '9905X01953000000', '9946X82857000000',
'9946X82248000000', '2195J00262000000', '9929X87857000000',
'9929X84245000000', '9946X00746000000', '0506M00076000000',
'9923X84666000000', '9929X87296000000', '9946X82576000000',
'9929X87905000000', '9929X01237000000', '9946X87908000000',
'9935X82899000000', '9905X82898000000', '9905X01892000000',
'0155R00121000000', '9910X82654000000', '0002M00291000B00',
'9935X50232000000', '9935X82799000000', '0024N00046000000',
'9946X01868000000', '0604E00106000000', '9905X00323000000',
'9946X00988000000', '9910X82252000000', '9910X00304000000',
'9946X82322000000', '9929X85327000000', '9929X82347000000',
'9910X82164000000', '9946X82567000000', '9935X00143000000',
'9946X82920000000', '9946X82324000000', '9929X85841000000',
'9935X82459000000', '0307N00312000000', '0507L00002000000',
'9946X85492000000', '9905X83475000000', '9946X88030000000',
'0050F00012000000', '9935X01326000000', '9905X00789000000',
'9946X84289000000', '9929X50095000000', '9923X87518000000',
'8000T02524000000', '9905X83575000000', '9929X87056000000',
'0152E00103000000', '9905X82551000000', '9923X82318000000',
'1134A00005000000', '9910X00452000000', '9905X00595000000',
'0763M00274000000', '9929X50165000000', '9946X00597000000',
'9929X01569000001', '9946X83961000000', '9946X85420000000',
'0222J00060000000', '9935X00673000000', '9935X82507000000',
'9910X82078000000', '0222L00209000000', '1421G00224000000',
'9946X85459000000', '9946X85341000000', '9946X88482000000',
'9946X88396000000', '9935X82101000000', '9923X88430000000',
'9905X82157000000', '0011A00150000000', '0011A00181000000',
'9946X83534000000', '9935X50229000000', '9905X01457000000',
'9910X83858000000', '9946X01597000000', '9910X84062000000',
'9946X01088000000', '9946X88219000000', '1224K00145000000',
'9923X82067000000', '9910X01232000000', '0856K00010000000',
'9910X00506000000', '0450P00467000000', '9929X84811000000',
'9910X01136000000', '9905X00393000000', '9946X00528000000',
'9929X01225000000', '9923X84534000000', '9923X82245000000',
'0050K00061000A00', '9929X82503000000', '9946X01631000000',
'9905X00295000000', '9946X83683000000', '8000T01621000000',
'9935X83637000000', '9809X00198000000', '0232D00260000000',
'9946X81028000000', '9923X88344000000', '9905X00292000000',
'9946X01265000000', '9946X01311000000', '9935X00848000000',
'9929X87722000000', '9935X82576000000', '9935X83336000000',
'9946X84868000000', '9946X01435000000', '9841X00183000000',
'9935X88377000000', '9935X82193000000', '9946X83963000000',
'9905X83746000000', '9905X83938000000', '9905X00943000000',
'9946X82916000000', '9935X83093000000', '0746S00052000000',
'9946X85029000000', '9935X82160000000', '9923X00782000000',
'9946X83215000000', '9905X82459000000', '8000T01686000000',
'9923X88093000000', '9929X83431000000', '9910X01479000000',
'9929X01988000000', '9946X01283000000', '9929X87783000000',
'9905X01235000000', '9946X01479000000', '9905X83410000000',
'9923X87448000000', '9905X81016000000', '9946X83167000000',
'9946X00210000000', '9929X01312000000', '9935X00171000000',
'9844X00477000000', '9905X83403000000', '9905X83081000000',
'9946X00521000000', '9946X82097000000', '9929X87911000000',
'0004L00231000B00', '9946X83009000000', '9923X00493000000',
'9935X82878000000', '9910X00761000000', '9946X84716000000',
'9929X84664000000', '9929X88197000000', '9929X87394000000',
'0434P00004000000', '8000T00044000000', '9844X00423000000',
'9905X83548000000', '9935X83421000000', '9946X83424000000',
'9935X00408000000', '9935X83238000000', '9923X87455000000',
'9923X87830000000', '1416E00261000000', '9929X87182000000',
'9923X87475000000', '9905X00785000000', '9929X01814000000',
'9923X88332000000', '9929X85743000000', '0101C00055000000',
'0551E00391000000', '9946X85447000000', '9910X82321000000',
'9923X01001000000', '9935X83284000000', '0115D00170000000',
'8000T03327000000', '9905X82319000000', '9923X84702000000',
'0079R00080000000', '9946X87966000000', '9935X88688000000',
'9929X88005000000', '9905X82781000000', '9935X00539000000',
'9910X84380000000', '9946X00978000000', '0067P00335000000',
'9946X82726000000', '9929X50315000000', '9905X83456000000',
'9905X84032000000', '9946X88334000000', '9946X82926000000',
'9929X00119000000', '9946X85381000000', '0662F00392000000',
'9946X50562000000', '0202A00031000000', '9923X82119000000',
'9929X86663000000', '9935X82453000000', '9946X00645000000',
'9923X00403000000', '9935X01211000000', '9929X00330000000',
'9923X00976000000', '9929X86515000000', '9935X00072000000',
'9910X00654000000', '9935X88598000000', '9935X00336000000',
'9935X83299000000', '9844X00567000000', '9844X00362000000',
'9929X85293000000', '9929X86564000000', '9923X82313000000',
'9929X87190000000', '8000T00524000000', '9935X50311000000',
'9946X83546000000', '9905X82619000000', '0042N00324000000',
'9841X00066000000', '0023M00269000000', '9946X01591000000',
'9929X83272000000', '9905X83632000000', '9929X84298000000',
'9923X87912017300', '9910X84012000000', '9910X82050000000',
'9935X82328000000', '0024H00040000000', '0011A00147000000',
'9929X86961000000', '9946X87844000000', '9946X87892406A00',
'9935X82539000000', '9905X83014000000', '9946X88201000000',
'9929X85578000000', '0084L00068000C00', '9929X83839000000',
'0085B00062318100', '9905X83589000000', '0353C00168000000',
'9929X85605000000', '9910X84239000000', '0010J00119000000',
'9935X83529000000', '9905X00814000000', '9923X87529000000',
'9923X84585000000', '9929X84674000000', '9929X87236000000',
'9905X83612000000', '0618C00067000000', '9929X83260000000',
'9946X80039000000', '9929X00125000000', '0506J00082000000',
'9923X00414000000', '8000T01755000000', '9946X83817000000',
'9935X00486000000', '9905X00876000000', '9905X00402000000',
'9905X83818000000', '9910X82161000000', '9929X83925000000',
'9910X00823000000', '9908X82868000000', '9905X82620000000',
'9946X87797000000', '9809X00307000000', '9946X83238000000',
'8000T00141000000', '1908N00151000000', '9905X01443000000',
'9946X82138000000', '9923X00380000000', '9905X08005000000',
'0222N00027000000', '9905X00186000000', '9923X84555000000',
'9946X82674000000', '9935X00624000000', '9929X00463000000',
'9929X87479000000', '9929X83537000000', '0026D00222000000',
'9929X83724000000', '9946X83047000000', '8000T03138000000',
'9935X82318000000', '9923X87694000000', '9935X82068000000',
'9946X83604000000', '9935X00316000000', '9905X01512000000',
'9923X88242000000', '9929X87631000000', '9905X00650000000',
'9929X84981000000', '9946X01596000000', '9923X82446000000',
'9910X84229000000', '9946X82317000000', '9929X87388000000',
'9929X85275000000', '9929X01840000000', '9905X00539000000',
'9923X84366000000', '9935X83829000000', '9946X83574000000',
'9929X84158000000', '9946X83017000000', '9910X80079000000',
'9946X82564000000', '9923X84443000000', '9910X00488000000',
'9946X00633000000', '9929X84609000000', '9905X01327000000',
'1240K00291000000', '9946X88599000000', '0011A00191000000',
'8000T01791000000', '0010J00125000000', '9929X83239000000',
'9946X83394000000', '8000T02088000000', '9929X00757000000',
'9905X00229000000', '9946X82669000000', '9905X00835000000',
'9935X83376000000', '9905X00817000000', '9910X84443000000',
'1064A00120000000', '9935X00494000000', '0003R00168000000',
'9910X01182000000', '9905X01925000000', '0851E00026000000',
'9923X82239000000', '9923X84343000000', '9946X50376000000',
'9929X01934000000', '9923X88176000000', '9929X87919000000',
'9905X00294000000', '9910X00769000000', '9946X88509000000',
'9946X85651000000', '9923X84438000000', '9946X82544000000',
'8000T01909000000', '9946X50184000000', '9929X01405000000',
'0006G00074000000', '9946X82049000000', '9935X00688000000',
'9946X00948000000', '9910X82738000000', '9929X00329000000',
'9910X00397000000', '9905X00087000000', '9905X83091000000',
'9923X87696000000', '9929X85614000000', '9923X87916000000',
'9905X01755000000', '9946X00860000000', '9935X83183000000',
'9946X84904000000', '9946X00902000000', '9946X01094000000',
'9935X01219000000', '9929X00782000000', '9929X86136000000',
'9946X87993000000', '9905X00389000000', '9935X50053000000',
'9910X84210000000', '9923X00327000000', '9929X83905000000',
'0010P00079000000', '9841X00060000000', '9946X50254000000',
'9929X01002000000', '9935X82548000000', '0362K00114000000',
'9929X00786000000', '9910X00062000000', '9946X80038000000',
'9905X01458000000', '9923X80005000000', '9929X87910000000',
'9910X82693000000', '9929X85026000000', '9946X82506000000',
'9946X82092000000', '9905X00672000000', '9929X83017000000',
'9946X85585000000', '0236S00111000000', '9809X84027000000',
'9929X00668000000', '9935X83105000000', '9905X01475000000',
'0129N00029000000', '9929X00745000000', '9905X00944000000',
'0009A00007000000', '9905X00622000000', '9905X83149000000',
'9935X88721000000', '0098G00210000000', '0352S00135000100',
'9923X00512000000', '9935X00484000000', '9929X87823000000',
'9905X00428000000', '9910X01011000000', '0003R00190000000',
'9841X00021000000', '9923X82188000000', '9809X50011000000',
'9929X87805000000', '8000T00415000000', '9929X01288000000',
'9935X88453000000', '9908X82899000000', '0161A00220000000',
'9935X82772000000', '9946X87656000000', '9908X83034000000',
'9929X01920000000', '9946X82173000000', '9923X88460000000',
'9905X84000000000', '9935X83562000000', '9929X87209000000',
'9905X82291000000', '9809X00334000000', '0003S00012000000',
'9935X00516000000', '9935X82993000000', '9929X85528000000',
'9946X84175000000', '9935X82066000000', '8000T03232000000',
'0011A00056000000', '9929X83355000000', '0237D00366000000',
'9946X01720000000', '0251J00248000000', '9923X82298000000',
'9929X86090000000', '0697A00086000000', '9905X82628000000',
'9910X84003000000', '9946X88442000000', '9923X88103000000',
'9929X00517000000', '9946X50435000000', '0086R00317000000',
'0875G00082000000', '1241J00143000000', '9946X00834000000',
'9929X84287000000', '9923X88492000000', '9905X00164000000',
'9908X82849000000', '9946X88119000000', '9923X87729000000',
'9905X00633000000', '9929X87240000000', '9910X82749000000',
'9910X84205000000', '9929X86761000000', '9923X82055000000',
'9946X82964000000', '9910X00807000000', '9935X82763000000',
'9946X88037000000', '9946X85276000000', '9935X82538000000',
'0137G00265000000', '0025M00121000000', '9929X00574000000',
'9946X82631000000', '9946X83157000000', '8000T03008000000',
'9923X00587000000', '9929X86957000000', '9946X00041000000',
'9910X00766000000', '9946X84367000000', '9910X84586000000',
'8000T03078000000', '0167N00080000000', '9905X00173000000',
'9809X50009000000', '9946X00788000000', '9929X83428000000',
'9935X83789000000', '9910X01422000000', '0026E00268000000',
'9905X01346000000', '9911X85896000000', '0050F00020000A00',
'9910X82471000000', '0011A00149000000', '9809X84065000000',
'8000T00589000000', '8000T00144000000', '9935X82908000000',
'0124J00125000A00', '9935X83401000000', '9929X88061000000',
'9923X00657000000', '9923X84550000000', '9946X87899000000',
'0508N00092000002', '9929X87625000000', '9929X83425000000',
'9946X83163000000', '9935X83533000000', '9946X82071000000',
'9946X82829000000', '9929X83827000000', '9935X50178000000',
'8000T02548000000', '9929X87192000000', '9929X83536000000',
'9923X87770000000', '9929X50323000000', '9923X84494000000',
'9923X84491000000', '9923X88018000000', '9908X82944000000',
'9935X82680000000', '9935X87930000000', '9935X88208000000',
'9929X01298000000', '9946X84765000000', '9935X00117000000',
'0450P00462000000', '9929X83720000000', '9946X50426000000',
'0101K00150000000', '9905X83465000000', '9905X82450000000',
'0356L00150000000', '9946X82288000000', '9935X88637000000',
'9946X82007000000', '9923X50033000000', '9809X00021000000',
'9905X01151000000', '9929X83064000000', '9946X87986000000',
'9935X00239000000', '9935X83049000000', '8000T03340000000',
'9929X83246000000', '9946X00786000000', '9935X82982000000',
'9923X87647000000', '0084M00334000000', '9946X85551000000',
'0048S00264000000', '9910X84218000000', '9905X83409000000',
'9910X01202000000', '0856P00261000000', '9910X00212000000',
'9929X00448000000', '9905X01883000000', '9946X83506000000',
'9923X82476000000', '9946X83148000000', '9935X83499000000',
'9946X84468000000', '9910X84216000000', '8000T00539000000',
'9935X82302000000', '9929X87440000000', '9946X83636000000',
'9929X00326000000', '9946X01229000000', '0612R00034000000',
'9935X82248000000', '9935X82413000000', '9910X82080000000',
'9844X00456000000', '9910X01352000000', '9910X00570000000',
'9946X83220000000', '9929X83007000000', '0011M00188000000',
'9905X01212000000', '9935X00582000000', '9905X00365000000',
'9910X00076000000', '9923X84572000000', '9929X88164000000',
'9929X84315000000', '9923X87854000000', '9910X82201000000',
'9946X84010000000', '9929X83461000000', '9929X85826000000',
'9946X83902000000', '8000T00581000000', '9946X88464000000',
'9929X83994000000', '9910X82724000000', '9946X84158000000',
'9905X01369000000', '9923X87928000000', '9905X01401000000',
'9946X88234000000', '9929X83217000000', '9929X83223000000',
'9946X85284000000', '9910X82485000000', '9935X82491000000',
'9844X00612000000', '9923X87915000000', '1211R00065000000',
'9910X81079000000', '9809X00145000000', '9946X83971000000',
'9923X00665000000', '0512G00060000000', '9841X00049000000',
'9910X00313000000', '9910X84005000000', '9935X00282000000',
'9923X82396000000', '9905X83486000000', '9929X88183000000',
'9929X88353000000', '9935X83433000000', '9935X00185000000',
'9935X88296000000', '9946X50031000000', '9929X00423000000',
'9905X83927000000', '9910X01188000000', '9929X50273000000',
'9905X01239000000', '9946X84786000000', '0746G00016000000',
'9908X83044000000', '9905X01049000000', '9946X85174000000',
'9946X84255000000', '9905X84108000000', '9923X00526000000',
'9929X01605000000', '9923X87502000000', '9910X82583000000',
'9929X85580000000', '9905X01056000000', '9923X84303000000',
'9929X85169000000', '9905X83588000000', '0711R00018000100',
'9929X86959000000', '9905X00484000000', '9929X85425000000',
'9946X85558000000', '9935X83222000000', '0189J00190000000',
'9929X01792000000', '0301P00227000000', '9923X00797000000',
'9923X84653000000', '9910X83862000000', '9905X82802000000',
'9946X01365000000', '9929X83550000000', '9923X87991000000',
'9935X50197000000', '9935X83479000000', '9946X87771000000',
'9844X00399000000', '9923X82155000000', '8000T02813000000',
'9929X83422000000', '9946X01023000000', '9929X83358000000',
'9935X00790000000', '9809X00211000000', '9929X83210000000',
'9923X88489000000', '9923X82353000000', '9905X00914000000',
'9946X83931000000', '9929X87963000000', '0039R00105000000',
'9844X82030000000', '9910X82204000000', '9905X00867000000',
'9809X00308000000', '9929X88366000000', '0421B00133000000',
'9946X87662000000', '0450P00641000000', '8000T03311000000',
'9905X01021000000', '1203F00059000300', '9923X87852000000',
'9923X00142000000', '9935X00981000000', '9923X88590000000',
'9841X82005000000', '9910X84163000000', '9910X00921000000',
'9929X85296000000', '9935X83013000000', '9946X85426000000',
'9946X87742000000', '9946X50441000000', '9929X84638000000',
'9946X82591000000', '9946X83312000000', '9929X87499000000',
'0829D00302000000', '9946X83475000000', '0429P00057000000',
'9929X87700000000', '9929X00561000000', '9905X01664000000',
'9929X86007000000', '9935X81011000000', '0003N00235000000',
'9929X83018000000', '0010P00169000000', '9923X82077000000',
'9946X50133000000', '9910X82270000000', '9935X01142000000',
'9844X00747000000', '9923X88019000000', '9844X00407000000',
'9809X00249000000', '9946X82798000000', '0429P00002000000',
'9929X01301000000', '0454G00010000000', '9946X84065000000',
'9923X87616000000', '9946X88404000000', '9935X88023000000',
'0024G00306000000', '9929X50090000000', '9946X82707000000',
'9935X50166000000', '8000T01505000000', '9929X85684000000',
'9910X84530000000', '9910X01573000000', '9910X00559000000',
'9844X00726000000', '9946X88443000000', '9946X82556000000',
'9929X00103000000', '0050K00061000000', '9946X87711000000',
'9910X00078000000', '9929X88162000000', '9923X00399000000',
'0232D00241000000', '9929X88029000000', '9929X86182000000',
'9946X87743000000', '0052H00270000000', '9844X00030000000',
'9946X50148000000', '9809X00149000000', '0085G00080000000',
'9946X82740000000', '9905X83518000000', '0077B00218000000',
'9923X87882000000', '9910X01274000000', '9923X00402000000',
'1367D00380000000', '9946X83886000000', '9935X83212000000',
'9905X82925000000', '9935X82383000000', '9844X00505000000',
'9910X84013000000', '9923X82015000000', '9929X86043000000',
'9946X88636000000', '0081D00217000000', '9946X83576000000',
'9910X00249000000', '8000T00002000000', '9923X82462000000',
'9923X87520000000', '9923X88186000000', '9935X83118000000',
'9844X00416000000', '0536M00100000000', '9946X83994000000',
'9923X87471000000', '9946X50265000000', '9923X87751000000',
'9935X82936000000', '9946X87661000000', '9923X88578000000',
'9809X84070000000', '8000T02485000000', '9935X87810000000',
'0049R00130000000', '0602P00313000000', '9923X82357000000',
'9923X88580000000', '9929X82012000000', '9929X87505000000',
'9910X84587000000', '9935X82958000000', '9946X84394000000',
'9923X00046000000', '8000T02400000000', '0461F00229000001',
'9910X82668000000', '9946X87950000000', '9946X84106000000',
'9910X01242000000', '9946X83311000000', '0018A00250000000',
'9910X01528000000', '9929X83363000000', '9910X82509000000',
'9935X82981000000', '9935X00154000000', '9929X00917000000',
'9946X87985000000', '0050K00058000000', '9905X01077000000',
'9935X50231000000', '9809X84055000000', '9946X87976000000',
'9946X82742000000', '9935X83203000000', '9908X82900000000',
'9905X82059000000', '9935X83498000000', '9929X00856000000',
'9929X83388000000', '9910X84511000000', '9910X01287000000',
'9905X82553000000', '1214R00332000000', '0278M00260000000',
'9946X83937000000', '9910X82448000000', '9946X84980000000',
'9935X88720000000', '9905X01190000000', '9946X01006000000',
'9946X81003000000', '9905X00681000000', '9908X82898000000',
'8000T03156000000', '9946X84381000000', '9946X84080000000',
'9910X00718000000', '9929X00667000000', '9935X50285000000',
'8000T01429000000', '9844X00174000000', '9929X88167000000',
'9935X88560000000', '9946X88549000000', '9935X82859000000',
'0856P00245000000', '9809X00279000000', '9946X00033000000',
'9908X83039000000', '9923X87543000000', '0024H00038000000',
'9946X85375000000', '9946X88315000000', '9946X82907000000',
'9844X00205000000', '9908X82740000000', '9905X01222000000',
'9910X01343000000', '9946X81075000000', '9929X84711000000',
'9946X83825000000', '9908X82886000000', '9935X00840000000',
'9929X00186000000', '9923X00469000000', '9910X82344000000',
'9935X87933000000', '9929X87054000000', '9905X00706000000',
'9929X86706000000', '9905X83906000000', '9935X83320000000',
'9935X00948000000', '9946X84222000000', '9935X82234000000',
'9946X88244000000', '9929X01380000000', '9905X01313000000',
'9946X87855000000', '0052J00214000000', '9905X01290000000',
'9844X00214000000', '9905X00995000000', '9946X87806000000',
'9946X83029000000', '9905X83653000000', '9946X82161000000',
'9841X00189000000', '9946X82278000000', '9946X88206000000',
'9905X83012000000', '9923X88065000000', '9946X83085000000',
'9910X00967000000', '9946X85031000000', '9905X82241000000',
'9923X87838000000', '9841X00112000000', '9946X82253000000',
'9935X82785000000', '9946X82800000000', '8000T00466000000',
'9809X82057000000', '0876G00122000000', '9946X82083000000',
'9929X00180000000', '9946X01279000000', '9929X86956000000',
'9929X84216000000', '9910X00312000000', '8000T00770000000',
'9905X00762000000', '9929X84474000000', '9946X00105000000',
'9910X83836000000', '9946X84176000000', '9946X84748000000',
'9929X87808000000', '9946X50006000000', '9935X82865000000',
'9935X00416000000', '9935X88234000000', '9946X82465000000',
'9929X87482000000', '9910X83893000000', '9929X87185000000',
'9809X00155000000', '9935X88700000000', '9929X01750000000',
'9844X00632000000', '9935X01154000000', '9923X87844000000',
'9946X87696000000', '9905X01171000000', '9935X82552000000',
'9844X00084000000', '8000T00042000000', '9946X84808000000',
'8000T02689000000', '0066E00156000000', '9929X01735000000',
'9910X01459000000', '9935X82426000000', '9935X01095000000',
'9844X00103000000', '9935X83189000000', '9929X87211000000',
'0361F00065000200', '9905X01012000000', '9946X87663000000',
'9946X00307000000', '9929X86640000000', '9905X82914000000',
'9929X87996000000', '9923X00067000000', '9946X88535000000',
'9946X82783000000', '9923X82361000000', '9929X87507000000',
'9923X82401000000', '9946X85643000000', '9946X01262000000',
'9946X01651000000', '9923X82282000000', '9946X01872000000',
'9935X83043000000', '0301P00351000000', '9935X88288000000',
'9946X82477000000', '9910X84292000000', '9910X84374000000',
'9946X83011000000', '9935X00508000000', '0083B00284000A00',
'9946X00635000000', '9935X82493000000', '9929X87701000000',
'9910X83904000000', '9905X82899000000', '9946X50238000000',
'9910X80034000000', '9946X01222000000', '9935X00063000000',
'9946X83006000000', '9946X00954000000', '9929X87415000000',
'0236S00098000000', '9946X83404000000', '0281M00175000000',
'9935X83781000000', '0609K00025000000', '9946X00552000000',
'9910X01373000000', '1106B00207000000', '8000T01743000000',
'9929X87459000000', '9946X83564000000', '9935X88022000000',
'9935X88531000000', '0275M00077000000', '0023D00038000000',
'9946X82494000000', '9929X85071000000', '9844X00629000000',
'0717J00050000000', '0003K00124000000', '0601J00025000000',
'9946X84156000000', '9844X00571000000', '0856P00134000000',
'9923X88552000000', '9910X82503000000', '0746E00026000000',
'9929X50012000000', '9929X88373000000', '9923X84541000000',
'9905X00613000000', '9923X84475000000', '9935X01262000000',
'9923X00802000000', '9929X83527000000', '9929X82542000000',
'8000T00058000000', '9910X82434000000', '9905X01568000000',
'9923X84676000000', '0738H00044000000', '9935X83371000000',
'9844X82047000000', '9935X00631000000', '9946X00916000000',
'0050J00021000000', '0084A00117000000', '9929X01393000000',
'9946X01846000000', '9946X85431000000', '8000T01706000000',
'9929X87317000000', '9923X88083000000', '9929X00764000000',
'9935X83055000000', '0276G00292000000', '9923X87775000000',
'9929X85674000000', '9935X00795000000', '1999L00010000000',
'9935X82880000000', '9946X88311000000', '9929X86130000000',
'9946X50040000000', '0010D00093001000', '9929X87238000000',
'9923X87883000000', '9844X00738000000', '9929X01343000000',
'8000T02703000000', '9905X00940000000', '9929X84468000000',
'9929X01042000000', '9905X00708000000', '9910X00447000000',
'8000T03310000000', '0083L00309000000', '9929X83243000000',
'9935X00151000000', '0666G00118000000', '9929X87980000000',
'9929X00087000000', '9946X82661000000', '9929X01196000000',
'9929X83360000000', '9905X00676000000', '9929X84904000000',
'9935X88491000000', '9929X84292000000', '0004B00226000C00',
'9905X83581000000', '9905X82302000000', '9929X85212000000',
'9935X83160000000', '9844X00345000000', '9946X83674000000',
'9905X00006000000', '9952X50995000000', '8000T02904000000',
'9910X00906000000', '0024N00056000A00', '9935X00542000000',
'9929X85105000000', '2012F00094000000', '9946X84259000000',
'0393K00012000000', '9923X00562000000', '9929X00880000000',
'9929X83235000000', '9929X01842000000', '9929X00768000000',
'9946X82733000000', '9910X82282000000', '9929X86338000000',
'0046G00182000000', '9935X00114000000', '9946X83988000000',
'9946X88055000000', '9935X82512000000', '9935X00515000000',
'9946X83734000000', '9910X82163000000', '9946X85582000000',
'9946X84351000000', '0103H00284000000', '9929X00957000000',
'9923X88268000000', '9946X88361000000', '9935X88561000000',
'9935X00233000000', '9910X82430000000', '9946X88314000000',
'9946X85272000000', '1076N00100000000', '8000T02107000000',
'9946X50492000000', '0093E00017000100', '0138F00043000000',
'9935X01263000000', '9929X00473000000', '9946X83342000000',
'9910X82716000000', '9910X01331000000', '9923X00143000000',
'8000T01633000000', '8000T03396000000', '9935X87846000000',
'0050K00110000000', '0103A00065000000', '9929X01377000000',
'9929X87706000000', '9946X82750000000', '9935X82662000000',
'9841X00208000000', '9935X00241000000', '9946X83820000000',
'9910X00190000000', '9935X82485000000', '8000T03169000000',
'9923X84697000000', '9905X83595000000', '9946X01817000000',
'9935X83353000000', '0083M00217000000', '9905X00217000000',
'8000T01357000000', '9935X83381000000', '0665M00200000000',
'9946X01431000000', '9929X01352000000', '0451B00643000000',
'1832S00068000000', '9935X01034000000', '9929X85251000000',
'9946X88042000000', '9809X00267000000', '9910X82521000000',
'9935X83630000000', '9905X00197000000', '9946X00461000000',
'9923X87559000000', '9929X84293000000', '9929X87052000000',
'9844X00099000000', '9923X87711000000', '9908X82878000000',
'9929X82244000000', '9946X84981000000', '9946X01181000000',
'9910X82363000000', '9905X82678000000', '9946X82309000000',
'9910X00568000000', '8000T00346000000', '9923X00318000000',
'9935X83576000000', '9905X00769000000', '9905X00326000000',
'9929X00262000000', '0608B00038000000', '9923X88263000000',
'0235G00075000002', '9946X87826000000', '9923X87564000000',
'9946X00248000000', '9946X01013000000', '9910X01508000000',
'9946X85508000000', '9946X84886000000', '9929X01589000000',
'9946X82107000000', '0083M00220000000', '9841X00146000000',
'9905X00030000000', '9935X00260000000', '9929X01847000000',
'9910X00409000000', '8000T02450000000', '9844X00275000000',
'9910X82285000000', '9946X83162000000', '9946X85160000000',
'9910X01279000000', '9929X86535000000', '9929X00635000000',
'9910X82332000000', '9946X85008000000', '9929X85944000000',
'9929X01375000000', '9946X00482000000', '9946X01837000000',
'9905X01944000000', '9946X00538000000', '9929X87446000000',
'9929X83542000000', '9929X87293000000', '2007H00108000001',
'9935X50248000000', '9929X87452000000', '9905X82836000000',
'9946X50071000000', '9946X88379000000', '0002M00292000200',
'9946X84141000000', '9946X84906000000', '8000T00272000000',
'9905X83998000000', '9946X82080000000', '0023G00005000000',
'9905X82165000000', '9946X00173000000', '9946X87795000000',
'9946X00881000000', '9935X00259000000', '9935X88231000000',
'9905X83457000000', '9929X82881000000', '9923X01044000000',
'9929X00147000000', '9946X84699000000', '0124J00160000000',
'9946X83255000000', '9946X50444000000', '9905X82627000000',
'8000T03564000000', '9935X87818000000', '9905X82818000000',
'9946X88388000000', '9935X83422000000', '0035L00161000000',
'9910X84201000000', '9929X87667000000', '9935X83583000000',
'9929X01678000000', '9929X86598000000', '9946X83166000000',
'9946X01223000000', '9935X83446000000', '0003P00047000000',
'9935X82702000000', '9935X88187000000', '9905X83424000000',
'9929X88047000000', '9905X82908000000', '9929X88019000000',
'0852H00085000000', '0562N00024000200', '9905X50077000000',
'9929X88355000000', '0815A00292000000', '9923X88459000000',
'9923X00805000000', '9935X88552000000', '9935X00181000000',
'9905X01608000000', '9929X88002000000', '9905X00695000000',
'9946X82874000000', '9910X82469000000', '9929X86287000000',
'9929X87242000000', '9923X82463000000', '9946X87858000000',
'9946X84148000000', '9946X88558000000', '9935X88575000000',
'9929X85678000000', '9946X01193000000', '9935X88000000000',
'9935X88563000000', '9935X87906000000', '9905X01569000000',
'9929X82516000000', '9946X00515000000', '9905X01407000000',
'9946X85274000000', '9910X82375000000', '9905X82034000000',
'9929X85879000000', '8000T02578000000', '9946X88466000000',
'9841X00051000000', '9905X00719000000', '9929X88050000000',
'9929X80051000000', '9946X01005000000', '9946X00100000000',
'0827L00206000000', '9929X87861000000', '9946X83958000000',
'0023C00062000000', '9923X00842000000', '9929X87967000000',
'9929X84515000000', '9929X01153000000', '0050K00112000000',
'9923X01026000000', '9946X50536000000', '9935X83776000000',
'9935X00549000000', '9929X88193000000', '9935X82929000000',
'9935X83773000000', '9923X01051000000', '9946X00534000000',
'9929X01097000000', '9946X85149000000', '9946X50437000000',
'9946X50014000000', '0157G00002000000', '9929X00258000000',
'1077L00179000000', '9946X84830000000', '9923X84619000000',
'0775L00045000000', '9929X87850000000', '9935X88604000000',
'0083S00150000000', '9905X83480000000', '9841X00114000000',
'9946X00873000000', '9946X00925000000', '0124N00229000000',
'9935X01054000000', '9923X00557000000', '9929X01101000000',
'9923X88468000000', '9809X00094000000', '9910X82226000000',
'9910X01077000000', '9929X83729000000', '9923X82391000000',
'9905X01248000000', '9929X86033000000', '9908X82959000000',
'9946X00021000000', '9929X84445000000', '0292C00222000000',
'9935X00613000000', '0176H00154000000', '9929X50247000000',
'9946X88331000000', '9946X87739000000', '9935X00715000001',
'9923X87648000000', '9935X88263000000', '9923X00561000000',
'9910X82020000000', '9929X86839000000', '1670N00236000000',
'8000T01747000000', '9929X85812000000', '9946X00242000000',
'0094E00046000000', '9929X87166000000', '9935X50207000000',
'9910X84603000000', '9910X82283000000', '0174D00263000000',
'9935X88016000000', '8000T03371000000', '0392D00075000000',
'9946X85392000000', '9946X82738000000', '9929X87247000000',
'9923X82147000000', '9844X82036000000', '9929X01014000000',
'9923X88556000000', '9923X84462000000', '9935X00743000000',
'9910X00126000000', '9910X01662000000', '0363R00093000001',
'0011A00179000A00', '9929X01113000000', '9929X83484000000',
'9946X01665000000', '9946X01875000000', '9946X85271000000',
'9935X82353000000', '9923X00844000000', '9923X88360000000',
'8000T00177000000', '9929X85350000000', '9910X83881000000',
'9923X84642000000', '9923X00616000000', '9923X84347000000',
'9929X00391000000', '0698P00210000000', '9946X83621000000',
'9946X83004000000', '9905X01008000000', '9923X88562000000',
'9946X84005000000', '9946X50535000000', '9935X88219000000',
'9929X86523000000', '9929X83110000000', '9929X83573000000',
'9946X83656000000', '9910X84091000000', '0514R00008000000',
'9946X50141000000', '9946X84078000000', '9905X83315000000',
'9905X00145000000', '9923X87639000000', '9946X84450000000',
'9923X88274000000', '9935X83389000000', '9935X82164000000',
'9929X84394000000', '9929X85984000000', '9910X82413000000',
'9946X82812000000', '9809X84041000000', '9923X00319000000',
'9905X83496000000', '9910X84365000000', '9923X87921000000',
'9844X00336000000', '9905X82615000000', '9935X00187000000',
'9946X83545000000', '9905X01534000000', '9935X01008000000',
'9935X50261000000', '9946X84797000000', '9923X84372000000',
'9910X01509000000', '9935X83610000000', '9935X83028000000',
'9923X84668000000', '0473L00149000000', '9935X88396000000',
'9910X84051000000', '9935X83745000000', '9905X01955000000',
'9910X82659000000', '9929X83116000000', '9923X87856000000',
'9910X00682000000', '9929X01602000000', '9946X82202000000',
'9929X50285000000', '9935X00824000000', '9946X84162000000',
'9910X83899000000', '9946X84052000000', '9929X82687000000',
'9923X87939000000', '9844X00140000000', '9905X00422000000',
'9923X87850000000', '9923X87563000000', '9905X00330000000',
'0176F00112000000', '0301N00037000000', '9929X88078000000',
'9946X83923000000', '9946X83733000000', '9935X82948000000',
'0025K00212000000', '9946X82797000000', '9946X83917000000',
'9929X86752000000', '9935X00972000000', '9923X00800000000',
'9935X83738000000', '9929X50083000000', '9929X00135000000',
'9910X80062000000', '9929X00943000000', '9946X84011000000',
'9935X01304000000', '9946X83881000000', '9905X83892000000',
'9844X00386000000', '9929X01049000000', '9946X00765000000',
'9929X87907000000', '9905X01815000000', '9935X83819000000',
'9946X85317000000', '9905X82767000000', '9809X83012000000',
'0105D00236000000', '0188S00125000000', '9946X87998000000',
'9923X88354000000', '9946X88489000000', '9905X84076000000',
'9946X00618000000', '9910X84636000000', '9929X01683000000',
'0152M00265000000', '9929X00110000000', '9946X01125000000',
'9929X88240000000', '9946X82636000000', '9929X00192000000',
'9935X00493000000', '1664K00138000000', '9929X01652000000',
'9923X00740000000', '9935X82914000000', '9946X82298000000',
'9929X00378000000', '0050K00341000000', '1004N00205000000',
'9935X82563000000', '9935X01248000000', '9946X88224000000',
'9905X00291000000', '9910X82211000000', '1130M00358000000',
'0026P00061000000', '9935X88422000000', '9935X83197000000',
'9905X83525000000', '9935X88024000000', '9844X00577000000',
'9946X84794000000', '9910X84437000000', '9935X00439000000',
'9935X87831000000', '8000T03023000000', '0388K00014000000',
'9923X88064000000', '9905X83882000000', '9946X01498000000',
'9946X83330000000', '0024N00045000000', '9946X01624000000',
'9841X00116000000', '9929X88076000000', '9929X86358000000',
'9946X83278000000', '0881D00150000000', '9929X86853000000',
'9910X84432000000', '9910X84161000000', '9905X01634000000',
'9946X82846000000', '9935X01178000000', '2275L00210000000',
'9905X01452000000', '9923X50001000000', '9929X83909000000',
'8000T01712000000', '0218S00152000000', '9929X00601000000',
'1132K00237000000', '9923X88426000000', '9929X85735000000',
'9923X84320000000', '9910X83875000000', '9946X84822000000',
'9923X87912015600', '9935X00498000000', '8000T01577000000',
'9946X01730000000', '9905X83722000000', '9923X87594000000',
'9923X01085000000', '9935X50047000000', '9935X01271000000',
'9905X84005003E00', '9929X01335000000', '9929X86274000000',
'9946X83811000000', '9908X82923000000', '9946X88370000000',
'9910X82686000000', '9946X83705000000', '9910X00375000000',
'9929X83819000000', '9946X83701000000', '9905X00965000000',
'0014E00158000000', '9929X85152000000', '9929X00971000000',
'8000T03162000000', '9908X82958000000', '9946X85445000000',
'9841X00029000000', '9946X87667000000', '9809X00057000000',
'9946X83568000000', '9905X00776000000', '0717M00015000100',
'9929X86268000000', '9841X00105000000', '9929X85503000000',
'9935X83029000000', '9946X85151000000', '9923X84425000000',
'9929X87972000000', '9923X87988000000', '9905X00696000000',
'9946X82633000000', '9946X83317000000', '9905X83443000000',
'9935X83309000000', '0134G00037000000', '9910X82160000000',
'9946X50157000000', '0080K00200000000', '1210R00015000000',
'0392H00245000000', '9929X85527000000', '9946X00216000000',
'9946X84833000000', '9946X87902000000', '9905X82298000000',
'9905X00567000000', '9946X82174000000', '0830B00102000000',
'9929X86298000000', '8000T02652000000', '9946X83347000000',
'9905X01252000000', '9946X00380000000', '9935X83077000000',
'9946X01314000000', '9935X00609000000', '9923X50035000000',
'9910X00901000000', '9935X82674000000', '9946X00663000000',
'9946X01256000000', '9946X82878000000', '9935X82508000000',
'9946X82759000000', '9929X82880000000', '9905X83504000000',
'9844X00575000000', '9929X87909000000', '0026E00216000000',
'9910X83808000000', '9929X88150000000', '9946X84257000000',
'9910X82740000000', '9946X85072000000', '9946X82602000000',
'9946X50206000000', '9923X88546000000', '9935X00422000000',
'9929X00986000000', '9910X82689000000', '9929X84160000000',
'9923X84672000000', '9905X01014000000', '9946X88094000000',
'9905X83768000000', '9910X00608000000', '9923X84683000000',
'9935X82846000000', '9905X00144000000', '9923X87554000000',
'9910X82694000000', '9929X00061000000', '9923X88233000000',
'9905X84078000000', '9905X01471000000', '9923X88225000000',
'9946X83458000000', '9929X86665000000', '9910X00135000000',
'9935X00480000000', '9923X84638000000', '9905X83919000000',
'9905X01274000000', '9929X87483000000', '9946X50433000000',
'9935X87935000000', '9929X01427000000', '9910X82155000000',
'9946X81057000000', '9946X01064000000', '1738P00316000000',
'9946X00112000000', '9809X00045000000', '9929X88329000000',
'9935X82953000000', '9923X82468000000', '9905X01558000000',
'9946X00123000000', '9910X84221000000', '9910X00560000000',
'9946X85598000000', '9910X84150000000', '9923X00217000000',
'1827C00024000000', '9929X00620000000', '9908X82855000000',
'9910X83968000000', '9841X00110000000', '9923X87773000000',
'9910X01200000000', '9946X81079000000', '9809X84059000000',
'9946X88317000000', '9905X83893000000', '9905X83913000000',
'9809X50002000000', '0371C00078000000', '9929X83533000000',
'9905X01776000000', '0041K00354000000', '9908X82939000000',
'9929X00385000000', '9910X82409000000', '9905X83614000000',
'9946X00032000000', '9929X87878000000', '9929X87867000000',
'9946X82839000000', '9929X83245000000', '9946X87834000000',
'0609K00100000000', '9923X00638000000', '9923X87513000000',
'0301P00343000000', '9929X85324000000', '9929X00951000000',
'9910X82708000000', '9923X88137000000', '9946X85091000000',
'8000T03660000080', '9923X00971000000', '9929X85020000000',
'9905X83481000000', '9946X82196000000', '9929X84556000000',
'9929X88144000000', '9923X00938000000', '9935X01143000000',
'9809X83031000000', '9929X86565000000', '9923X00681000000',
'9905X83472000000', '0450P00476000000', '9923X84456000000',
'9923X82455000000', '9910X01413000000', '9910X82015000000',
'9809X83046000000', '9923X88330000000', '9929X82683000000',
'9946X87738000000', '9946X00865000000', '9905X01946000000',
'9929X88001000000', '9929X86960000000', '9946X83121000000',
'9910X84263000000', '9929X00120000000', '9935X82595000000',
'9905X01266000000', '9844X00294000000', '9923X84418000000',
'9935X82260000000', '9935X00274000000', '9905X84068000000',
'9935X83563000000', '9929X85619000000', '9929X01591000000',
'9905X83844000000', '9923X82322000000', '9905X00264000000',
'0361F00100000000', '9935X00748000000', '9929X84552000000',
'9910X84353000000', '9946X88572000000', '9929X00427000000',
'9946X00030000000', '9910X00762000000', '9946X83111000000',
'9910X83914000000', '9841X00054000000', '9946X00187000000',
'9809X00322000000', '9844X00147000000', '0449A00218000000',
'9946X01547000000', '9946X01695000000', '9935X87868000000',
'9935X87877000000', '9946X88123000000', '9929X01456000000',
'9929X86861000000', '9923X00249000000', '9910X00804000000',
'9923X88139000000', '9929X01947000000', '9844X00055000000',
'9946X85278000000', '9923X88569000000', '9946X88107000000',
'9946X01296000000', '9935X82668000000', '9923X00066000000',
'9929X01713000000', '9929X00131000000', '9935X83277000000',
'9910X82358000000', '9929X01935000000', '9910X83958000000',
'9946X00178000000', '9929X88041000000', '9946X87953000000',
'9923X00135000000', '9946X50142000000', '9929X86313000000',
'9923X87806000000', '0007B00338000000', '1009S00155000000',
'9905X83851000000', '9946X00486000000', '0054F00168000000',
'9929X01612000000', '9929X83518000000', '0029S00128000000',
'9946X88064000000', '8000T00005000000', '9935X00675000000',
'8000T01890000000', '9905X00220000000', '9929X87149000000',
'9946X50340000000', '9923X00398000000', '9929X84976000000',
'9946X00862000000', '9905X82081000000', '0003S00218000002',
'0003S00218000001', '9946X83225000000', '9923X87463000000',
'9946X84959000000', '9946X50257000000', '9946X83572000000',
'9929X84230000000', '9923X84357000000', '9809X00117000000',
'9935X83351000000', '9946X84673000000', '9844X00251000000',
'9923X00945000000', '9923X84420000000', '0187N00036000000',
'9841X00221000000', '9935X83687000000', '9929X83008000000',
'0028E00001000000', '0006R00315000000', '9946X01379000000',
'9841X00099000000', '9946X82101000000', '9946X82496000000',
'9946X50485000000', '9923X82150000000', '9946X00850000000',
'0124J00168000000', '9935X83379000000', '9929X83063000000',
'9905X83083000000', '9935X82384000000', '9946X00822000000',
'9809X84077000000', '9935X00949000000', '9935X82770000000',
'9923X82494000000', '9935X83597000000', '9929X83452000000',
'0322A00065000000', '9935X83811000000', '9910X81046000000',
'9908X82743000000', '9946X50327000000', '9905X83881000000',
'9929X83738000000', '9905X50091000000', '9935X50251000000',
'9905X82922000000', '9946X82177000000', '9929X83154000000',
'9946X82500000000', '9923X87777000000', '9946X88621000000',
'9946X82634000000', '9923X87584000000', '1218B00199000000',
'9923X84660000000', '9905X01805000000', '9905X83097000000',
'9910X82519000000', '9929X00718000000', '9905X82546000000',
'9910X82483000000', '9946X83078000000', '9946X83525000000',
'9946X00815000000', '9910X01525000000', '9929X00032000000',
'0189F00108000000', '9923X84446000000', '9844X00576000000',
'0547P00234000000', '9935X82338000000', '9929X87906000000',
'9935X82947000000', '9935X82242000000', '9929X86749000000',
'9935X82523000000', '9910X01636000000', '9923X87551000000',
'9910X00908000000', '9946X50207000000', '9841X00119000000',
'9946X01681000000', '9910X00875000000', '0173N00380000000',
'9946X50561000000', '9935X82083000000', '9929X87636000000',
'9929X01209000000', '0609R00216000000', '9946X01224000000',
'9905X83508000000', '9905X82996000000', '9946X82148000000',
'8000T03063000000', '9935X00739000000', '9905X83476000000',
'9910X84113000000', '9923X87924000000', '9946X83832000000',
'2007H00108000003', '9905X00020000000', '9929X83353000000',
'9910X84223000000', '9908X82937000000', '9923X00753000000',
'9929X86744000000', '9923X01027000000', '9905X00091000000',
'9905X83827000000', '9929X86548000000', '9946X88440000000',
'9946X87698000000', '9929X00017000000', '9910X00855000000',
'9905X01281000000', '0556B00257000000', '9935X00755000000',
'9908X82873000000', '9929X01785000000', '9946X87744000000',
'9935X83089000000', '9946X83964000000', '9910X84355000000',
'9946X82050000000', '9935X83704000000', '0099C00180014900',
'9946X82785000000', '9923X82189000000', '9929X00393000000',
'9946X83818000000', '9935X83363000000', '9910X01208000000',
'9935X82906000000', '9809X82045000000', '9929X82004000000',
'9809X84004000000', '9946X82226000000', '8000T00602000000',
'1218B00174000000', '0011E00292000000', '9935X00481000000',
'9929X01289000000', '9905X01349000000', '9946X50439000000',
'0004B00226000D00', '9946X84340000000', '9905X01179000000',
'9929X01870000000', '9935X82796000000', '9946X84067000000',
'9923X87533000000', '9946X85489000000', '8000T01408000000',
'9929X87179000000', '9946X87679000000', '9844X00405000000',
'0010P00092000000', '9908X82520000000', '9946X83562000000',
'9844X82014000000', '9905X01559000000', '9929X83466000000',
'9910X82287000000', '9905X82465000000', '9946X84169000000',
'9946X00042000000', '9923X87641000000', '9908X82928000000',
'9923X84412000000', '9935X01031000000', '0459D00201000000',
'9929X86362000000', '0556P00007000000', '9946X01513000000',
'9946X82267000000', '9910X82543000000', '9910X01647000000',
'9923X84556000000', '9923X84549000000', '9929X83512000000',
'9935X88483000000', '9935X82721000000', '9910X00166000000',
'0024G00032000000', '9946X87678000000', '9905X83255000000',
'9923X82317000000', '9929X83197000000', '9946X82887000000',
'9946X50557000000', '9929X00545000000', '9929X00531000000',
'0707P00193000000', '9929X84465000000', '9946X83559000000',
'9946X83932000000', '1846J00100000000', '9929X85426000000',
'9929X88216000000', '9923X00074000000', '9923X00032000000',
'9946X50573000000', '9946X83266000000', '9905X01312000000',
'9923X87792000000', '0775D00090000000', '9923X88160000000',
'9935X82159000000', '1999K00018000000', '9929X84051000000',
'9844X00208000000', '9935X83206000000', '9910X84350000000',
'9946X00327000000', '9923X84390000000', '9929X00774000000',
'0102C00248000000', '0476H00150000000', '9908X82934000000',
'9929X00451000000', '9905X00460000000', '8000T00799000000',
'9946X01373000000', '9929X84710000000', '9905X01516000000',
'9929X01111000000', '9905X01025000000', '2188L00207000000',
'9908X82915000000', '9905X01942000000', '9908X82914000000',
'9929X00320000000', '9946X83969000000', '9844X00054000000',
'9923X87978000000', '9923X88333000000', '9905X00066000000',
'9929X00941000000', '0117A00084000000', '8000T01956000000',
'9923X87659000000', '9946X84347000000', '9946X84155000000',
'0240N00108000100', '9908X82741000000', '9946X00734000000',
'9910X82400000000', '9946X84958000000', '8000T02739000000',
'9929X87598000000', '9946X83489000000', '9844X00295000000',
'9929X83742000000', '9910X01231000000', '9905X83845000000',
'9923X00341000000', '9905X82811000000', '9910X00469000000',
'0651D00300000000', '9935X82717000000', '9923X87809000000',
'9935X82915000000', '0024N00054000000', '9844X00616000000',
'0084M00364000000', '0141A00040000000', '9923X84435000000',
'9946X00867000000', '9946X85491000000', '9929X88052000000',
'0009A00041000000', '9923X00922000000', '9841X00038000000',
'9905X83692000000', '9910X01551000000', '9929X82683000001',
'9929X84352000000', '9935X50191000000', '9923X81021000000',
'9946X50343000000', '9946X82641000000', '8000T00260000000',
'9946X83599000000', '9910X84326000000', '9946X83308000000',
'0435B00100000000', '0997G00225000001', '9935X82366000000',
'9946X50229000000', '9946X01670000000', '9905X83686000000',
'9929X01168000000', '9946X84042000000', '9905X83704000000',
'9910X00311000000', '9946X83775000000', '9946X84789000000',
'9946X82265000000', '9929X84122000000', '9923X00733000000',
'9935X82315000000', '9935X50265000000', '9946X88203000000',
'9844X00545000000', '9923X87581000000', '9929X88356000000',
'9935X83435000000', '9946X87883000000', '9905X83357000000',
'9844X00154000000', '9923X84618000000', '9910X84417000000',
'9910X81043000000', '1067H00040000000', '9946X84269000000',
'9923X88470000000', '9809X83016000000', '9946X82201000000',
'9946X00047000000', '0444J00005000000', '9946X82185000000',
'9946X83959000000', '1997B00118000000', '9923X00329000000',
'9935X83282000000', '9929X00181000000', '9923X84509000000',
'9935X88352000000', '9929X84380000000', '1133P00004000100',
'8000T02518000000', '9809X00250000000', '9935X83589000000',
'0214D00125000000', '9935X82682000000', '9929X87586000000',
'9929X87889000000', '9946X00692000000', '9905X83676000000',
'9905X01062000000', '9905X82463000000', '9908X82879000000',
'9935X81017000000', '0375K00257000000', '9929X85993000000',
'9946X85285000000', '9908X82924000000', '9935X82797000000',
'9905X83488000000', '9923X82399000000', '9935X00792000000',
'9946X01213000000', '9946X00511000000', '9923X00970000000',
'9946X83137000000', '9935X87969000000', '0247J00157000000',
'9910X00039000000', '9910X82381000000', '9910X00044000000',
'9905X00912000000', '9946X00790000000', '0190C00072000002',
'9946X82456000000', '9935X50155000000', '9929X88489000000',
'9929X87233000000', '8000T01379000000', '9935X83129000000',
'0461A00043000000', '0663C00192000000', '9905X00039000000',
'9905X01059000000', '9946X88411000000', '9946X82076000000',
'1075C00315000000', '0067P00324000000', '9910X83986000000',
'9946X85245000000', '9946X82562000000', '9929X83095000000',
'0362A00047000100', '9910X84591000000', '9905X00545000000',
'9929X01684000000', '8000T00435000000', '9929X84426000000',
'9935X88206000000', '9946X84085000000', '0464L00135000000',
'9923X00366000000', '9809X00147000000', '9929X84360000000',
'9910X82274000000', '9910X82225000000', '9910X82584000000',
'9929X85499000000', '0268K00060000000', '9935X82427000000',
'9946X87747000000', '9809X00259000000', '9905X01318000000',
'9844X00254000000', '9946X84403000000', '9844X00374000000',
'8000T00607000000', '9946X85372000000', '9809X00035000000',
'9905X83934000000', '0049G00312000000', '9946X83097000000',
'9844X00592000000', '9910X80031000001', '8000T03376000000',
'9929X84366000000', '9929X88223000000', '9929X85939000000',
'9929X87938000000', '9929X83401000000', '9935X01352000000',
'9910X00248000000', '9946X00863000000', '8000T02005000000',
'9946X82595000000', '9844X00587000000', '0444A00022000000',
'8000T03070000000', '9910X84619000000', '9905X01079000000',
'9929X01480000000', '9946X84044000000', '9935X01064000000',
'9946X80040000000', '9929X87975000000', '9946X84938000000',
'1270D00102000000', '9946X00422000000', '9946X84969000000',
'9929X86356000000', '9935X00001000000', '9910X82196000000',
'9923X00037000000', '9946X00447000000', '9935X82190000000',
'9923X87587000000', '9923X82356000000', '9935X50287000000',
'8000T00138000000', '1735P00025000000', '9809X00163000000',
'9946X01639000000', '8000T02353000000', '9923X82211000000',
'9946X00559000000', '9910X84630000000', '0774L00146000000',
'9946X87665000000', '9946X83368000000', '0461E00154000000',
'9946X84199000000', '9935X82842000000', '9946X83390000000',
'0851E00020000000', '8000T01534000000', '9910X00285000000',
'9946X83341000000', '9929X01748000000', '9935X01058000000',
'0548R00130000000', '9910X00680000000', '9946X88587000000',
'9946X84742000000', '9946X85167000000', '9905X80011000000',
'9923X00146000000', '9809X84050000000', '9905X83306000000',
'9923X00434000000', '0023M00247000000', '9905X50065000000',
'9946X83913000000', '9910X84642000000', '9946X83889000000',
'9935X00193000000', '9905X84091000000', '9935X83315000000',
'9935X50132000000', '9946X85424000000', '9929X87509000000',
'9905X82815000000', '9935X83519000000', '9935X83444000000',
'9905X83597000000', '9935X83752000000', '9946X84792000000',
'0012N00225000000', '9946X01020000000', '9935X50300000000',
'0131E00042000000', '0308F00103000000', '9935X50077000000',
'0010J00187000000', '9910X00655000000', '9946X83789000000',
'0882A00050000000', '1109E00388000000', '9929X87764000000',
'9946X85171000000', '0050K00060000000', '1078E00360000000',
'0141G00058000000', '1202D00218000000', '9929X82494000000',
'9910X00545000000', '9910X01380000000', '9929X83488000000',
'9935X83241000000', '9910X00849000000', '9946X84720000000',
'9946X83984000000', '8000T00133000000', '9910X00314000000',
'9910X00819000000', '9935X50110000000', '9946X85361000000',
'0507L00010000000', '9946X84041000000', '9946X88093000000',
'9946X87982000000', '9935X01242000000', '9946X82482000000',
'9946X50448000000', '9929X86760000000', '9946X87977000000',
'9905X01232000000', '9809X84007000000', '9935X83014000000',
'9935X00418000000', '0450P00639000000', '9844X00608000000',
'9905X00830000000', '9935X00965000000', '9905X83567000000',
'9946X84270000000', '0083M00065000000', '9905X00343000000',
'9929X84557000000', '9929X50039000000', '9905X50094000000',
'9910X01206000000', '9929X84868000000', '9946X85108000000',
'9841X00024000000', '9946X83736000000', '9929X84306000000',
'8000T00603000000', '9946X82983000000', '8000T00521000000',
'9809X00169000000', '9923X87713000000', '9905X84006046A00',
'9929X00575000000', '9910X84413000000', '0235N00028000100',
'9923X50027000000', '9929X84834000000', '9946X82131000000',
'1202H00200000000', '1084E00178000000', '9935X00012000000',
'9905X00705000000', '9841X00190000000', '9946X82679000000',
'9910X84585000000', '9905X01227000000', '9910X84267000000',
'9946X83893000000', '9929X00176000000', '0029G00213000000',
'9946X83633000000', '9946X84329000000', '9935X82556000000',
'0414K00243000000', '9946X82463000000', '9905X00908000000',
'9910X82152000000', '9946X00183000000', '9923X00843000000',
'0450P00470000000', '9935X82420000000', '8000T00768000000',
'9905X01205000000', '9946X01565000000', '9929X83530000000',
'9910X00994000000', '9946X84233000000', '8000T01419000000',
'9905X83941000000', '9923X84431000000', '9935X83163000000',
'9929X87492000000', '9946X88431000000', '9946X84876000000',
'0006P00149000000', '9946X87754000000', '9905X82297000000',
'1669P00397000000', '9929X50200000000', '9946X88176000000',
'9929X85448000000', '9935X88252000000', '0935J00356000000',
'9946X85419000000', '9935X82818000000', '9929X88173000000',
'9935X83027000000', '9910X01061000000', '9946X83216000000',
'9929X85964000000', '0250K00160000002', '9905X50062000000',
'9929X01165000000', '9929X84982000000', '9946X82665000000',
'9946X85406000000', '9841X00052000000', '9844X82058000000',
'0395D00083000000', '9935X82138000000', '9946X01127000000',
'0101A00192000000', '9935X82793000000', '9929X83737000000',
'9905X00442000000', '9946X00553000000', '0010P00166000000',
'9946X83065000000', '9929X00109000000', '9946X84408000000',
'9935X00371000000', '9946X84747000000', '9946X82625000000',
'9923X82415000000', '9905X83519000000', '9929X00608000000',
'0997G00230000001', '9935X82184000000', '9946X83345000000',
'9923X00023000000', '9946X82366000000', '9905X01707000000',
'9935X83675000000', '9905X83724000000', '9946X83224000000',
'9929X86034000000', '9809X00288000000', '9946X83184000000',
'8000T02011000000', '9910X82253000000', '9929X87698000000',
'9929X84667000000', '9905X82247000000', '0851E00028000000',
'9905X01849000000', '9809X00012000000', '9923X00228000000',
'8000T00220000000', '0168A00084000100', '9929X82011000000',
'9935X83486000000', '8000T00551000000', '9844X00415000000',
'9946X88299000000', '9923X87800000000', '9929X01475000000',
'9929X01836000000', '9929X85487000000', '9905X00544000000',
'9946X82701000000', '9946X84034000000', '9929X00205000000',
'9929X01265000000', '9809X82030000000', '9923X87550000000',
'9946X87669000000', '9935X00275000000', '9844X00469000000',
'9946X83052000000', '9935X00605000000', '8000T00347000000',
'9935X83817000000', '9946X50198000000', '9910X82151000000',
'9946X82351000000', '0281L00046000000', '9935X00906000000',
'9841X00140000000', '9946X84217000000', '1206A00293000000',
'9844X00006000000', '9935X83578000000', '9929X00826000000',
'9946X82001000000', '9935X01065000000', '9905X01234000000',
'9923X87954000000', '9844X00519000000', '9946X82475000000',
'9929X87942000000', '9929X00364000000', '9929X87644000000',
'9946X83802000000', '8000T01780000000', '9935X50088000000',
'9935X00369000000', '9935X88301000000', '9929X00914000000',
'9946X82792000000', '9929X86305000000', '9929X86851000000',
'9905X82201000000', '9935X82841000000', '1218L00144000000',
'9929X82629000000', '9809X00238000000', '9935X88403000000',
'9946X85198000000', '9935X00614000000', '9929X00851000000',
'9929X85090000000', '9946X01189000000', '0119S00159000A00',
'9929X00638000000', '9935X80007000000', '9929X86622000000',
'9946X85291000000', '9929X86522000000', '9946X87943000000',
'9935X00569000000', '9923X00801000000', '9946X84283000000',
'9946X00697000000', '9923X01080000000', '9929X85898000000',
'0378N00143000001', '9946X83013000000', '9929X85150000000',
'9946X84181000000', '9929X85606000000', '9946X50398000000',
'9905X00856000000', '9946X01021000000', '9935X82558000000',
'9929X82240000000', '9923X00841000000', '9946X82262000000',
'9935X87836000000', '9935X82759000000', '9910X82339000000',
'0885N00375000000', '9946X81012000000', '0668N00398000000',
'9946X82966000000', '9910X84115000000', '9929X84396000000',
'9905X82806000000', '9935X83145000000', '9946X82954000000',
'9946X00782000000', '9923X82098000000', '9929X85777000000',
'9910X84379000000', '0280P00392000000', '9905X00629000000',
'9844X00107000000', '9935X00281000000', '0175P00305000000',
'9946X85427000000', '9935X01327000000', '9929X86781000000',
'9844X00339000000', '8000T03557000000', '9946X85121000000',
'9905X82467000000', '9923X00075000000', '9946X01523000000',
'0025M00025000A00', '9946X84271000000', '0006K00272000000',
'9929X00833000000', '9935X82481000000', '9935X83646000000',
'8000T00304000000', '9935X82076000000', '9946X82478000000',
'9946X01169000000', '9929X01699000000', '9946X82508000000',
'9946X84714000000', '9910X01291000000', '9929X00037000000',
'9923X00983000000', '9905X83291000000', '9929X86801000000',
'8000T01960000000', '9923X82200000000', '9910X50004000000',
'9935X83616000000', '9946X84900000000', '9929X00547000000',
'9935X88734000000', '9929X84727000000', '9809X00054000000',
'9905X01194000000', '9910X01069000000', '0279S00050000000',
'9946X01037000000', '9923X87912014500', '9905X01746000000',
'9929X86132000000', '0006L00324000000', '9946X88031000000',
'0501P00340000000', '9935X83570000000', '9905X00261000000',
'9935X83449000000', '9935X00346000000', '9929X83079000000',
'9929X83553000000', '9923X00886000000', '0248A00100000000',
'9905X01338000000', '1740A00390000000', '1202H00201000000',
'0011D00161000000', '9923X87860000000', '9910X00205000000',
'0004H00212000000', '9910X01497000000', '9946X00206000000',
'9946X85569000000', '9935X00723000000', '9946X85450000000',
'9910X84264000000', '0233E00259000000', '0220C00078000000',
'9946X00440000000', '9935X82741000000', '9946X82703000000',
'0450P00647000000', '9841X81163000000', '0010J00295000000',
'9929X87286000000', '9946X83936000000', '9946X82140000000',
'0951B00230000100', '9908X82882000000', '9935X83219000000',
'9935X83552000000', '9905X82787000000', '9929X00163000000',
'0772L00301000000', '9905X83936000000', '9923X84670000000',
'9923X00943000000', '9946X83212000000', '0083B00285000B00',
'9946X85240000000', '9929X84140000000', '9946X01699000000',
'0222N00084000000', '0192S00045000000', '9946X01816000000',
'9935X88383000000', '9946X82838000000', '9946X88067000000',
'9946X82099000000', '0362A00047000000', '0273F00165000000',
'8000T01442000000', '9946X87945000000', '9946X85647000000',
'9923X88228000000', '9946X85239000000', '9946X88690000000',
'9935X87989000000', '9923X87884000000', '9923X88250000000',
'9946X01823000000', '9935X83810000000', '9929X01979000000',
'9929X86328000000', '0514R00028000000', '9935X01128000000',
'9910X01173000000', '9844X80004000000', '9946X84685000000',
'9946X01495000000', '9905X00426000000', '9929X83993000000',
'9929X01319000000', '9946X82835000000', '9844X00305000000',
'9923X84378000000', '9929X84500000000', '0222E00185000000',
'9910X82091000000', '9923X87709000000', '9929X88369000000',
'0455L00073000001', '9929X85375000000', '9946X01605000000',
'9929X83572000000', '9935X82218000000', '8000T02446000000',
'9923X00229000000', '9946X82552000000', '1358J00371000100',
'9923X00764000000', '9946X88562000000', '9935X88394000000',
'9910X84442000000', '9935X88388000000', '9905X83002000000',
'9905X83636000000', '0079L00168000000', '8000T01426000000',
'9910X01557000000', '9929X83829000000', '9935X83540000000',
'9946X83064000000', '9935X00372000000', '9929X87156000000',
'0130R00308000000', '9929X87503000000', '9809X84010000000',
'9946X87942000000', '9929X01217000000', '9929X87434000000',
'0222J00050000000', '9923X87583000000', '9923X87926000000',
'9946X82332000000', '9935X00632000000', '9935X82310000000',
'9935X01258000000', '9946X84922000000', '9929X01321000000',
'9905X01533000000', '9923X82316000000', '9935X00711000000',
'9935X83554000000', '9946X87983000000', '9946X85566000000',
'1999P00020000000', '9923X84612000000', '0344C00008000000',
'9946X83643000000', '9935X88315000000', '9929X83387000000',
'9929X00005000000', '9946X85502000000', '9929X00459000000',
'0301L00166000000', '9923X88553000000', '9923X82252000000',
'9905X01017000000', '9946X85227000000', '9923X00934000000',
'0720P00250000000', '9809X83032000000', '0129G00054000000',
'0083S00155000000', '9935X82814000000', '0028H00181000000',
'9923X00401000000', '9929X84128000000', '9905X00267000000',
'9923X87506000000', '9935X82489000000', '0857M00119000000',
'1505P00012000000', '9923X00099000000', '9935X88566000000',
'0062P00061B00300', '9946X84438000000', '9935X83184000000',
'9935X82701000000', '9844X00164000000', '9929X00546000000',
'9946X83023000000', '9929X00926000000', '9935X82100000000',
'9809X00189000000', '9929X88145000000', '9929X87041000000',
'9905X01770000000', '9929X88110000000', '9929X84510000000',
'9905X82771000000', '9929X83920000000', '0954H00275000000',
'9905X00141000000', '9929X01350000000', '9935X82729000000',
'8000T01848000000', '9946X82649000000', '9929X00769000000',
'0083M00067000000', '9923X87607000000', '0767K00290000000',
'9910X82395000000', '9923X84626000000', '9946X82554000000',
'9929X01823000000', '9946X50503000000', '9923X82116000000',
'9923X87585000000', '9809X00144000000', '9946X83682000000',
'8000T01565000000', '9946X01412000000', '9923X00302000000',
'9905X83972000000', '9946X00839000000', '9905X00340000000',
'9929X01167000000', '9935X83325000000', '9929X84564000000',
'9841X00213000000', '9946X83951000000', '9929X84746000000',
'8000T01691000000', '9905X83440000000', '9946X83152000000',
'9844X00068000000', '9929X01348000000', '9946X00051000000',
'9929X83219000000', '9946X83010000000', '9946X00580000000',
'9935X50037000000', '9935X01037000000', '9923X88376000000',
'9910X83897000000', '9946X83704000000', '9905X01405000000',
'9935X50059000000', '9946X84912000000', '9935X82505000000',
'9935X83743000000', '9946X01600000000', '9946X84848000000',
'9935X83676000000', '9905X83718000000', '9935X82210000000',
'9929X87952000000', '9929X83505000000', '9929X50230000000',
'9910X01234000000', '9946X80005000000', '9809X00132000000',
'9929X84226000000', '9910X84363000000', '9905X00262000000',
'9946X01698000000', '9910X84015000000', '9929X01931000000',
'9923X82342000000', '9946X85315000000', '9910X84419000000',
'9910X00112000000', '9923X00423000000', '9946X83737000000',
'9910X84141000000', '9923X88539000000', '9929X00001000000',
'9946X84760000000', '9929X50028000000', '9910X00027000000',
'9935X87955000000', '9923X88441000000', '9935X88067000000',
'9923X82376000000', '9905X01963000000', '9946X88038000000',
'9841X00056000000', '9929X01627000000', '0049G00319000000',
'9946X88694000000', '9905X00878000000', '9929X50244000000',
'0082R00200000000', '9946X83187000000', '9935X83239000000',
'9946X82291000000', '9929X85277000000', '9935X83122000000',
'9935X00976000000', '1218M00295000000', '9929X83069000000',
'9935X82733000000', '9929X86131000000', '9946X84420000000',
'9809X00025000000', '9923X88047000000', '9946X82758000000',
'9946X82976000000', '9923X84567000000', '9946X85332000000',
'9929X87817000000', '9929X85886000000', '9946X85460000000',
'9910X01355000000', '9946X01449000000', '9946X83286000000',
'9923X84610000000', '9923X00248000000', '9929X83569000000',
'9910X01179000000', '9929X83385000000', '8000T03143000000',
'0050F00017000000', '8000T03405000000', '9935X01135000000',
'9935X00200000000', '9929X84224000000', '9935X83509000000',
'9935X50307000000', '9929X00204000000', '9946X83746000000',
'9946X84182000000', '9923X01069000000', '9935X83155000000',
'9929X88060000000', '9946X82272000000', '9929X00471000000',
'0542B00070000001', '9946X82559000000', '9923X82429000000',
'0557F00379000000', '9923X84445000000', '9910X01486000000',
'8000T03419000000', '9929X84050000000', '9935X88599000000',
'9910X84644000000', '0011K00034000000', '9809X00080000000',
'9910X84167000000', '9946X83020000000', '9905X00196000000',
'9946X50467000000', '0154S00042000000', '9935X82483000000',
'0337M00152000000', '1365R00304000000', '9905X01812000000',
'9946X84820000000', '8000T00030000000', '9929X86764000000',
'9910X83935000000', '9929X84879000000', '9910X84320000000',
'9935X83399000000', '9929X86276000000', '9946X83732000000',
'9946X50413000000', '0012L00264000001', '9910X82566000000',
'9935X83221000000', '9923X82185000000', '9946X01734000000',
'9809X83035000000', '8000T02411000000', '9935X87807000000',
'0517E00151000000', '9946X00958000000', '1203F00082000300',
'9929X86835000000', '9946X87712000000', '9929X83498000000',
'9923X82249000000', '9929X86796000000', '9844X00398000000',
'9946X84726000000', '9923X87872000000', '9946X01452000000',
'9929X00980000000', '9910X84060000000', '9935X82153000000',
'0014F00118000001', '9929X88020000000', '9946X83805000000',
'9946X88326000000', '9935X87963000000', '9905X83605000000',
'0609L00354000000', '9923X87505000000', '9923X87423000000',
'9844X00377000000', '0506H00352000000', '9905X01326000000',
'9935X87864000000', '0237D00071000000', '9910X83815000000',
'9935X01306000000', '0083B00284000B00', '9946X84284000000',
'9923X82100000000', '9946X82743000000', '9844X00300000000',
'9929X83506000000', '9923X88144000000', '9946X82637000000',
'9929X83455000000', '9946X01729000000', '9946X83565000000',
'9929X83831000000', '9905X01204000000', '9929X87957000000',
'9905X01208000000', '0124G00264000000', '9946X50332000000',
'0322P00214000000', '0718H00036000000', '9809X84076000000',
'9929X50082000000', '0023B00228000000', '9935X83644000000',
'9935X83636000000', '9929X83109000000', '9929X86179000000',
'9905X01615000000', '9929X00573000000', '9929X86264000000',
'9910X82229000000', '9809X00053000000', '9905X00882000000',
'9923X87418000000', '9905X01333000000', '9929X86119000000',
'9946X81056000000', '9929X85052000000', '9946X01310000000',
'9946X84991000000', '9946X82224000000', '0461A00104000000',
'9905X83455000000', '9905X83502000000', '9929X00680000000',
'9929X82807000000', '0568N00276000000', '9905X82124000000',
'9946X88085000000', '0975H00093000001', '9929X85696000000',
'9905X83629000000', '0023H00368000000', '9923X88401000000',
'9929X00595000000', '0253H00164000000', '0014G00089000000',
'9929X87331000000', '9910X84601000000', '0006M00284000000',
'9946X83127000000', '9923X88533000000', '9905X83473000000',
'9910X84533000000', '9923X87912017200', '9929X84016000000',
'9923X88429000000', '9946X85127000000', '9905X01835000000',
'9929X01252000000', '0064N00175000000', '9929X87327000000',
'9929X87335000000', '9929X85729000000', '9910X00729000000',
'9923X84493000000', '9910X01394000000', '9923X50042000000',
'9929X85572000000', '9929X87029000000', '9935X00350000000',
'9935X00978000000', '9935X83821000000', '0225B00160000000',
'9929X88134000000', '8000T03305000000', '9910X01621000000',
'1357F00154000000', '9905X84015002A00', '9929X84663000000',
'9935X00845000000', '0953M00230000000', '9923X88049000000',
'8000T01968000000', '9946X85298000000', '9946X01171000000',
'9844X00705000000', '9946X84763000000', '9935X82103000000',
'9910X84458000000', '9923X87842000000', '0072C00282000000',
'0281L00015000000', '9905X01885000000', '9935X82798000000',
'9929X85502000000', '9946X01446000000', '9946X01572000000',
'9910X00997000000', '9935X83085000000', '9929X84856000000',
'8000T02601000000', '9905X83541000000', '8000T01854000000',
'9905X82813000000', '9910X00698000000', '8000T00113000000',
'9929X85477000000', '9929X00810000000', '9929X00682000000',
'9946X00023000000', '0499E00318000000', '9929X00136000000',
'0048D00090000000', '9923X84587000000', '9946X82681000000',
'9905X01581000000', '9946X82231000000', '9946X83681000000',
'9935X01061000000', '9905X00345000000', '9946X83580000000',
'9923X88110000000', '0415L00045000000', '9935X82584000000',
'9935X83407000000', '9946X88175000000', '9935X50100000000',
'9946X87849000000', '9905X00068000000', '9905X01294000000',
'0065G00177000000', '0101B00266000000', '9929X50008000000',
'9929X01930000000', '8000T00312000000', '9905X83684000000',
'9929X83082000000', '9910X84046000000', '9905X83355000000',
'9929X83093000000', '9908X82744000000', '9935X83393000000',
'9923X87853000000', '9929X00151000000', '9935X83249000000',
'8000T02374000000', '9935X82339000000', '9910X00095000000',
'9935X82020000000', '9946X85567000000', '9935X88320000000',
'9910X84011000000', '9905X83630000000', '9946X85458000000',
'9946X83670000000', '9935X87949000000', '9929X83562000000',
'9935X82791000000', '0125S00019000100', '9946X82890000000',
'9946X85124000000', '9929X87673000000', '9946X83156000000',
'9946X84722000000', '1134E00230000000', '9929X83114000000',
'9923X88433000000', '9910X00316000000', '9946X00757000000',
'0050F00020000000', '9946X00980000000', '9946X87658000000',
'9923X87747000000', '9946X83109000000', '0661D00004000000',
'1355C00322000000', '9923X00957000000', '0056P00071000A00',
'9935X83488000000', '9923X00205000000', '9946X88407000000',
'9946X84882000000', '9946X50344000000', '9923X82480000000',
'9935X00005000000', '9935X00059000000', '9923X87427000000',
'1203F00137000300', '9905X01223000000', '1832M00075000000',
'9923X01075000000', '9929X85602000000', '9946X01225000000',
'9923X87494000000', '9923X00422000000', '9946X01703000000',
'9910X01172000000', '9929X87064000000', '9905X84034210700',
'9946X00190000000', '9929X86670000000', '9905X01785000000',
'9946X88245000000', '0125M00370000000', '9929X87939000000',
'9910X82227000000', '9946X82909000000', '0372C00144000000',
'9905X82076000000', '9809X84073000000', '9935X82487000000',
'9923X82299000000', '9905X82534000000', '9910X00683000000',
'9929X85258000000', '9905X00616000000', '0010J00130000000',
'9929X82226000000', '9910X82431000000', '9923X82248000000',
'9935X00654000000', '9923X00755000000', '0857C00382000000',
'0299F00076000100', '9905X00444000000', '9844X00296000000',
'9929X87298000000', '9905X01661000000', '9946X50310000000',
'9905X83846000000', '9923X00474000000', '0033B00045000001',
'9946X88570000000', '9905X83733000000', '9935X82191000000',
'9841X00009000000', '9935X83796000000', '0564S00035000000',
'8000T02511000000', '9905X82873000000', '0232P00094000000',
'9946X83155000000', '9935X87871000000', '9910X01613000000',
'0135M00036000000', '0361C00025000000', '0338K00009000000',
'9935X50120000000', '9946X84671000000', '8000T02144000000',
'0454R00124000001', '9929X87332000000', '9946X82091000000',
'9935X83258000000', '9946X82691000000', '9935X83253000000',
'9910X84164000000', '9929X50255000000', '9946X82490000000',
'9929X84665000000', '0314P00076000002', '9929X87542000000',
'0429P00310000000', '9929X87055000000', '9929X87059000000',
'0093M00035000000', '9923X87618000000', '0507D00065000000',
'9841X00130000000', '9905X00894000000', '9910X83928000000',
'9923X81005000000', '9910X84246000000', '9935X00665000000',
'9910X83816000000', '9923X84328000000', '0050F00013000000',
'9946X83055000000', '9929X84681000000', '9929X00143000000',
'9905X82777000000', '9910X83916000000', '0050L00274000B00',
'9910X01122000000', '9923X88053000000', '9923X82281000000',
'9929X83556000000', '9910X82157000000', '9905X82735000000',
'9905X83470000000', '9923X87771000000', '9905X82285000000',
'9929X01537000000', '9910X00637000000', '0350B00002000000',
'0023S00111000000', '9905X01417000000', '0027B00103000000',
'9905X01332000000', '9923X00094000000', '9929X00275000000',
'9910X01145000000', '9923X84426000000', '9923X84439000000',
'0389D00104000002', '9923X00416000000', '9946X88122000000',
'9946X00728000000', '9929X83402000000', '9923X84540000000',
'9935X82071000000', '9923X88002000000', '9946X01097000000',
'9946X82207000000', '2372M00105000000', '9923X88212000000',
'8000T00499000000', '9935X83574000000', '9905X83886000000',
'9946X00643000000', '0124J00126000000', '9905X00368000000',
'0301N00137000000', '9935X83121000000', '9905X00546000000',
'9923X00685000000', '9946X85423000000', '9935X00987000000',
'9935X88399000000', '8000T00369000000', '9929X87330000000',
'0050K00160000000', '9923X82482000000', '9905X82098000000',
'9929X00304000000', '9923X87675000000', '9929X87748000000',
'9946X85126000000', '9946X85246000000', '8000T02574000000',
'9946X82135000000', '9946X82656000000', '9935X82875000000',
'0422D00450000000', '9910X84318000000', '9935X83307000000',
'9929X86201000000', '0051A00006000000', '9929X85883000000',
'9910X01281000000', '0315H00150000000', '9929X84743000000',
'9910X00602000000', '0519M00110000000', '9923X87799000000',
'9929X00701000000', '9946X50165000000', '9946X82193000000',
'9923X87863000000', '9935X83559000000', '9929X84660000000',
'9905X01646000000', '9935X00832000000', '9946X83795000000',
'9929X01641000000', '9929X87299000000', '9809X84069000000',
'9935X83786000000', '9946X82068000000', '9929X87778000000',
'0103K00008000000', '9929X82535000000', '9923X87769000000',
'9905X01884000000', '9946X84285000000', '9935X87880000000',
'0253C00145000000', '9910X82350000000', '0085B00188030100',
'9946X84775000000', '9946X87803000000', '9929X01068000000',
'9910X00739000000', '9946X87792000000', '9935X00485000000',
'9946X85597000000', '9946X00458000000', '9923X00965000000',
'9946X82336000000', '9923X82491000000', '9929X88382000000',
'0072C00285000000', '9923X84659000000', '9935X88390000000',
'9923X84586000000', '9929X00755000000', '9841X00148000000',
'0426H00060000001', '9929X85476000000', '9910X00035000000',
'9910X00666000000', '9905X01262000000', '9923X00334000000',
'9946X84682000000', '9905X08241000000', '9809X00115000000',
'9946X82170000000', '9923X87758000000', '9929X87752000000',
'8000T02130000000', '9929X87014000000', '9929X86651000000',
'9946X00866000000', '9905X83386000000', '9905X01732000000',
'9929X01334000000', '9923X82447000000', '9935X87815000000',
'9935X83365000000', '9929X85079000000', '9935X83193000000',
'9923X88320000000', '0692A00109000000', '9905X83999000000',
'9935X87948000000', '9905X00506000000', '9946X85596000000',
'9910X84271000000', '9905X01117000000', '9923X88101000000',
'9946X82593000000', '8000T00570000000', '9935X82445000000',
'9929X88345000000', '9935X00734000000', '9929X00738000000',
'9910X82472000000', '9905X83534000000', '9910X00505000000',
'1096N00133000000', '0023J00051000000', '9935X00166000000',
'9809X84051000000', '0848F00379000000', '9923X00021000000',
'0069R00229000000', '9929X85817000000', '9929X85601000000',
'9923X87495000000', '9935X00499000000', '9905X50126000000',
'9929X83105000000', '9935X83147000000', '9946X88140000000',
'9923X87412000000', '9908X82949000000', '9905X84099000000',
'9923X84594000000', '9946X50613000000', '0434P00008000000',
'9844X00012000000', '9923X82373000000', '9946X82132000000',
'9905X01514000000', '9923X88573000000', '9910X82228000000',
'9935X00805000000', '9946X01143000000', '9905X01330000000',
'9946X01615000000', '9929X88026000000', '9935X00382000000',
'9923X88136000000', '9905X82171000000', '1274S00302000000',
'0124J00112000000', '9929X87635000000', '9923X87746000000',
'9923X00650000000', '9946X84308000000', '9923X87541000000',
'9935X82390000000', '9935X81016000000', '9910X01374000000',
'0767K00292000000', '9929X84882000000', '9929X87285000000',
'9946X82350000000', '9946X85195000000', '0130R00256000000',
'9946X85586000000', '0395N00398000000', '9905X83564000000',
'9905X50096000000', '9935X88558000000', '9946X84858000000',
'9910X83859000000', '9929X00857000000', '9929X87234000000',
'9946X84889000000', '9923X82045000000', '9929X88338000000',
'9929X85569000000', '9929X01944000000', '9946X85320000000',
'9946X82166000000', '9946X84300000000', '0272R00035000000',
'9935X00968000000', '9935X50095000000', '9905X83974000000',
'0086N00185000100', '9946X82152000000', '9929X83419000000',
'9946X01688000000', '9929X01320000000', '9946X50520000000',
'9929X83371000000', '9905X00565000000', '9935X01165000000',
'9844X00096000000', '9946X82460000000', '9929X00945000000',
'9923X00301000000', '9809X00044000000', '0238J00138000100',
'9844X00308000000', '9910X84464000000', '9905X83546000000',
'9809X00015000000', '9910X83909000000', '9929X87412000000',
'9946X01394000000', '9946X50556000000', '9809X82055000000',
'9946X88053000000', '9905X83973000000', '9923X84592000000',
'9910X01476000000', '9923X88445000000', '9910X00191000000',
'9929X85215000000', '9935X82746000000', '9905X83256000000',
'9946X88401000000', '9946X85083000000', '9935X00034000000',
'9946X83916000000', '9946X82802000000', '0180G00301000001',
'9923X87701000000', '9935X00373000000', '8000T00230000000',
'9908X82896000000', '0052H00245000000', '9929X84476000000',
'9844X00195000000', '9946X87794000000', '9923X00091000000',
'9923X87899000000', '9946X82330000000', '9946X00983000000',
'2018B00130000000', '9946X82577000000', '0743G00091000000',
'9910X84580000000', '9923X84584000000', '9946X00389000000',
'9935X82013000000', '9929X87187000000', '9905X01440000000',
'9935X87794000000', '9946X82493000000', '9908X82935000000',
'9929X85951000000', '9946X82608000000', '9946X00811000000',
'9929X87325000000', '9929X84367000000', '9910X84192000000',
'9923X87893000000', '9923X88371000000', '9929X87380000000',
'9910X84200000000', '9929X87842000000', '0217S00108000000',
'9923X88106000000', '9923X84701000000', '0255K00252000000',
'9946X83139000000', '9935X82156000000', '9929X00332000000',
'9946X00305000000', '1272P00362000000', '9929X85098000000',
'9929X86012000000', '9923X87440000000', '9946X88515000000',
'9935X00272000000', '9923X87670000000', '9935X50157000000',
'9935X83116000000', '9910X84652000000', '0388F00005000000',
'9946X01551000000', '0041D00137000000', '0277A00179000000',
'9929X85959000000', '9923X87772000000', '9905X82181000000',
'0851E00038000000', '9946X88426000000', '9935X88040000000',
'9946X84952000000', '9946X88305000000', '9946X50451000000',
'0629G00062000000', '9946X83248000000', '9935X82972000000',
'9935X88433000000', '9946X83093000000', '9923X00786000000',
'9929X83115000000', '9946X50032000000', '9946X50146000000',
'9923X87867000000', '9935X82470000000', '9923X00036000000',
'0011A00145000000', '9946X82675000000', '9910X01211000000',
'9905X01113000000', '9946X85046000000', '9929X83244000000',
'9809X83040000000', '9809X83059000000', '9929X87300000000',
'0222N00078000000', '9923X87497000000', '9935X83225000000',
'8000T00033000000', '9946X85374000000', '9923X00486000000',
'9929X87566000000', '9910X00662000000', '9946X50274000000',
'8000T01405000000', '9929X82536000000', '9923X82183000000',
'9809X00056000000', '9935X83662000000', '0083S00147000000',
'0083B00212000000', '9946X84208000000', '9935X00524000000',
'9935X82834000000', '9946X82234000000', '9905X50118000000',
'9946X01410000000', '9935X00556000000', '9905X82204000000',
'9929X01133000000', '9923X00656000000', '9946X84088000000',
'9923X82490000000', '0026L00198000000', '9929X86533000000',
'9905X83562000000', '9929X88023000000', '9935X00718000000',
'9946X84070000000', '9946X82072000000', '9844X00513000000',
'9923X82452000000', '9809X00181000000', '0448M00204000000',
'9929X87195000000', '9935X00017000000', '9946X50073000000',
'9809X00182000000', '9905X83828000000', '9946X85251000000',
'9844X00297000000', '9946X84009000000', '9905X82797000000',
'9905X83847000000', '9946X00758000000', '9935X83174000000',
'9905X82209000000', '9946X01093000000', '9809X82037000000',
'9929X86650000000', '9946X88571000000', '9929X83874000000',
'9905X83093000000', '9809X00104000000', '9905X83387000000',
'9905X01288000000', '9923X00612000000', '9905X00600000000',
'9929X86344000000', '9841X00068000000', '9905X82235000000',
'9844X00667000000', '9910X00315000000', '2007H00160000000',
'9905X00273000000', '0532P00088000000', '9946X83929000000',
'8000T02638000000', '9946X01516000000', '9923X84600000000',
'9929X87344000000', '9910X82334000000', '9935X00731000000',
'9905X01245000000', '9935X82667000000', '9923X84339000000',
'9935X50269000000', '9910X00082000000', '9946X85112000000',
'9935X50298000000', '9935X82444000000', '9946X01380000000',
'9929X01654000000', '9946X50260000000', '9935X50226000000',
'9923X00804000000', '9841X82017000000', '9929X87692000000',
'9946X00235000000', '9905X00815000000', '9946X84809000000',
'9929X01614000000', '9929X00133000000', '9910X00686000000',
'9929X84973000000', '0512G00072000000', '9935X00496000000',
'9910X84573000000', '9929X86762000000', '9923X01019000000',
'9923X88576000000', '9910X00419000000', '0851E00024000000',
'9905X01213000000', '9844X00353000000', '2011A00326161800',
'9935X88218000000', '9910X00535000000', '9905X00780000000',
'9935X83192000000', '9946X01554000000', '9923X00409000000',
'9946X88347000000', '0056P00070000000', '9935X82236000000',
'9905X00568000000', '9935X88642000000', '9923X82385000000',
'9910X00496000000', '9946X85302000000', '9946X88059000000',
'9809X84083000000', '9935X50164000000', '0083M00215000000',
'9946X01686000000', '9946X87740000000', '9809X82001000000',
'1078P00170000000', '9929X00853000000', '9946X88235000000',
'9946X88363000000', '9929X00056000000', '9923X00653000000',
'9935X00428000000', '0957F00150000000', '9946X83090000000',
'9935X83595000000', '0187G00040000000', '9946X85139000000',
'9905X00161000000', '9929X86174000000', '9946X01652000000',
'9844X00053000000', '9809X00240000000', '9946X50295000000',
'9946X82833000000', '0189N00140000000', '9905X01654000000',
'9905X01860000000', '9923X82258000000', '9935X82438000000',
'9923X88221000000', '9929X86826000000', '9946X85356000000',
'9923X87674000000', '9929X83264000000', '9841X00122000000',
'9905X00490000000', '9946X83076000000', '9929X86022000000',
'9946X84965000000', '9905X50063000000', '9929X86719000000',
'9946X83335000000', '8000T04710000000', '9946X81022000000',
'1506B00061000000', '9935X83175000000', '0014H00105000000',
'9946X84017000000', '9935X00366000000', '8000T03178000000',
'9841X00045000000', '9905X01057000000', '9946X84811000000',
'0665M00060000000', '9905X83569000000', '9946X01721000000',
'0141G00062000000', '9910X80033000000', '9946X50571000000',
'9935X83223000000', '9929X83086000000', '9844X00639000000',
'9910X82183000000', '0960K00022000002', '9923X88446000000',
'9923X87600000000', '0233E00262000200', '9946X85106000000',
'9946X84278000000', '9905X00505000000', '9935X83061000000',
'9929X85577000000', '9929X85349000000', '9946X85321000000',
'1368C00105000000', '9905X01587000000', '9929X00647000000',
'9910X00530000000', '0508G00031000000', '9929X84151000000',
'9935X01177000000', '9935X00345000000', '9923X87918000000',
'9946X83294000000', '9905X00964000000', '9910X82021000000',
'9929X83868000000', '9844X00736000000', '9923X84690000000',
'0352D00014000000', '1218B00150000003', '0124J00111000000',
'9935X83600000000', '9946X00084000000', '9946X00629000000',
'9946X82171000000', '9946X88221000000', '9905X00451000000',
'9935X88583000000', '9946X87756000000', '8000T03493000000',
'9935X82888000000', '9935X00047000000', '9939X50370000000',
'9929X83492000000', '9946X84982000000', '9946X83973000000',
'9946X00644000000', '9935X82870000000', '9935X00607000000',
'9935X00039000000', '9929X86604000000', '9935X82498000000',
'9935X83758000000', '9929X86188000000', '9946X88327000000',
'9844X00215000000', '9935X82809000000', '9929X85560000000',
'9935X00438000000', '9946X50201000000', '9946X82250000000',
'9910X82641000000', '9809X84031000000', '9809X00159000000',
'9946X50517000000', '0138B00302000000', '9935X88034000000',
'9905X01771000000', '9946X83040000000', '9809X00286000000',
'0240N00125000000', '9946X82447000000', '9935X00310000000',
'9946X82805000000', '9935X82205000000', '9929X83487000000',
'8000T03279000000', '0066E00180000000', '9946X82773000000',
'9910X84531000000', '9905X81004000000', '0769P00100000000',
'2200G00153000000', '9935X87928000000', '9946X50066000000',
'9935X83226000000', '9905X83670000000', '9946X84745000000',
'9929X01104000000', '9905X82055000000', '9946X83343000000',
'9908X82948000000', '9929X86003000000', '9946X84251000000',
'9923X00809000000', '9935X87924000000', '9923X84353000000',
'9923X00887000000', '0773F00112000000', '9946X83433000000',
'9946X00504000000', '9946X00467000000', '9946X88323000000',
'9935X82009000000', '9905X00790000000', '9929X84221000000',
'9910X82266000000', '9923X82051000000', '9935X87904000000',
'9809X80002000000', '9910X84025000000', '9929X01161000000',
'9905X00449000000', '8000T00285000000', '9929X87672000000',
'8000T01671000000', '9946X84977000000', '9946X88369000000',
'9929X00870000000', '9935X87970000000', '9946X87666000000',
'9910X84517000000', '9946X50293000000', '9905X82917000000',
'0050K00064000000', '9929X01313000000', '9911X85899000000',
'9946X88412000000', '9946X85377000000', '9946X88104000000',
'9935X82855000000', '9946X84144000000', '9923X00047000000',
'8000T00339000000', '9929X00287000000', '9929X84649000000',
'9905X83610000000', '9929X01733000000', '9935X88586000000',
'9923X82277000000', '9929X87506000000', '9935X50126000000',
'9946X50423000000', '9946X83316000000', '0352D00012000000',
'9935X00165000000', '9935X83495000000', '9844X00149000000',
'9910X84399000000', '0010P00098000000', '9935X50096000000',
'9905X83939000000', '9935X83008000000', '0361B00056000000',
'9935X50303000000', '9841X00126000000', '9905X00478000000',
'9929X87869000000', '9946X84851000000', '9923X82407000000',
'1136A00064000000', '9923X87835000000', '8000T02147000000',
'9946X85290000000', '0309M00191000000', '9923X00964000000',
'9946X00784000000', '9905X82135000000', '9910X82268000000',
'9923X88567000000', '0660A00042000100', '9910X82086000000',
'9923X88389000000', '9935X00016000000', '0088D00047000000',
'9935X88027000000', '9923X84355000000', '9935X88311000000',
'9935X00611000000', '9946X82599000000', '9929X87334000000',
'9929X86247000000', '9929X01559000000', '9935X88144000000',
'9923X84650000000', '9910X00620000000', '9935X82817000000',
'8000T01992000000', '9935X88038000000', '9809X82029000000',
'9935X82460000000', '0023E00117000000', '9910X00493000000',
'9946X82453000000', '9905X00571000000', '9929X01887000000',
'9844X00120000000', '9905X00756000000', '9929X88182000000',
'9929X87376000000', '9929X85592000000', '0155G00395000000',
'9905X00885000000', '9946X01843000000', '9935X82388000000',
'9929X84614000000', '9929X83258000000', '9946X83296000000',
'9946X84698000000', '8000T01457000000', '9910X82101000000',
'9935X82249000000', '8000T03289000000', '1909E00170000000',
'0545N00014000000', '9946X85190000000', '9905X83418000000',
'9946X00530000000', '0046R00115000000', '9910X84638000000',
'9935X82358000000', '9844X00417000000', '0154S00146000000',
'8000T01879000000', '9946X88157000000', '9935X00041000000',
'9905X82214000000', '9935X80008000001', '0701D00328000000',
'0001C01662009600', '0049E00031000B00', '9844X00378000000',
'9923X00165000000', '9946X85475000000', '9923X88051000000',
'8000T02220000000', '9905X01832000000', '8000T00286000000',
'0314A00180000000', '0152A00180000000', '9910X00584000000',
'0546L00394000000', '9935X87976000000', '8000T03497000000',
'9946X50044000000', '9910X00130000000', '0049N00056000000',
'9946X88492000000', '9929X87173000000', '9929X86852000000',
'8000T01757000000', '0050K00039000000', '0150P00051000000',
'9905X00466000000', '8000T01991000000', '9929X84745000000',
'0029H00086000000', '9946X01538000000', '9935X00262000000',
'9946X83208000000', '9905X00003000000', '1508M00026000100',
'9929X86624000000', '0010J00269000000', '9935X00533000000',
'9946X83053000000', '9935X50008000000', '9946X01397000000',
'9935X83396000000', '9935X82382000000', '9946X84737000000',
'0701C00050000000', '9929X85974000000', '9923X87719000000',
'9929X87665000000', '9935X83524000000', '0946R00054000000',
'0440G00090000000', '0668G00172000000', '9946X50345000000',
'9929X83085000000', '9935X00527000000', '9905X83931000000',
'9841X00050000000', '9929X01900000000', '9809X00231000000',
'9946X01866000000', '9946X82163000000', '9946X83724000000',
'9946X84405000000', '0079L00162000000', '9905X01486000000',
'9905X83554000000', '9929X00255000000', '9929X00328000000',
'9935X88300000000', '9946X84298000000', '9905X00896000000',
'9923X87834000000', '9946X01647000000', '9929X85781000000',
'9929X83919000000', '9929X87481000000', '9946X83334000000',
'9935X00022000000', '9905X00354000000', '9946X87872000000',
'9929X87141000000', '9929X01567000000', '9929X01327000000',
'9905X83225000000', '0450P00457000000', '9905X83730000000',
'9929X83447000000', '9935X88427000000', '0176K00197000001',
'9910X84428000000', '9923X84433000000', '0302A00245000000',
'9923X82390000000', '0004R00313000A00', '9929X85813000000',
'9910X50024000000', '9923X82283000000', '9946X00699000000',
'9935X88730000000', '9929X88500000000', '0361F00078000100',
'9946X01274000000', '9910X00751000000', '9935X88045000000',
'9929X84231000000', '9905X82977000000', '9935X01156000000',
'9935X82177000000', '9935X88737000000', '0027D00051000000',
'9905X84014001A00', '8000T00463000000', '9935X88446000000',
'9809X00170000000', '9946X82034000000', '9910X84565000000',
'9946X87688000000', '9809X82059000000', '9910X00675000000',
'1103P00120000000', '9905X83707000000', '9935X50102000000',
'9910X00072000000', '9905X01854000000', '9935X00651000000',
'9923X01028000000', '9935X88572000000', '9923X00745000000',
'9905X83552000000', '9935X00896000000', '9905X01856000000',
'9946X85002000000', '9946X85337000000', '9935X00303000000',
'9910X80024000000', '0299F00076000000', '9929X85695000000',
'9910X00096000000', '9929X85016000000', '9946X83373000000',
'9910X82072000000', '9935X88124000000', '0086F00288000000',
'9905X83672000000', '9929X86106000000', '9946X83213000000',
'9929X01216000000', '9929X86846000000', '9841X00178000000',
'9905X82177000000', '9935X82079000000', '9923X82083000000',
'9946X82779000000', '9929X84926000000', '9929X01431000000',
'9946X87741000000', '9905X82270000000', '9929X84149000000',
'9910X84094000000', '9923X00542000000', '9809X84052000000',
'9929X82534000000', '0523E00160000000', '9905X82447000000',
'9923X82165000000', '9946X00900000000', '9923X00763000000',
'9910X84211000000', '0175P00309000100', '9923X00232000000',
'9923X84377000000', '0190A00193000000', '9905X83000000000',
'9935X83468000000', '9923X82143000000', '9935X82142000000',
'9946X83091000000', '9923X00322000000', '9923X01035000000',
'9923X87534000000', '8000T02530000000', '9946X00453000000',
'9929X86117000000', '9946X83062000000', '0092H00131000000',
'9929X83247000000', '9905X82877000000', '8000T01993000000',
'9910X84301000000', '0074R00054000000', '9929X01732000000',
'9923X87920000000', '9946X00279000000', '0364G00249000000',
'9929X83259000000', '9923X88246000000', '9929X83395000000',
'9946X82706000000', '9935X01200000000', '9929X84138000000',
'9946X85385000000', '9946X00434000000', '9929X84741000000',
'9905X50249000000', '1834D00046000000', '9923X00347000000',
'0834P00121000000', '9929X87858000000', '9935X00782000000',
'9935X88313000000', '9946X83658000000', '0250D00066000000',
'9929X50045000000', '9923X82486000000', '9905X83293000000',
'9923X82416000000', '9946X83828000000', '9910X84373000000',
'9923X84380000000', '9923X84315000000', '9929X83750000000',
'9935X82421000000', '9946X84902000000', '9910X00646000000',
'9946X85225000000', '9946X82257000000', '9923X00373000000',
'9905X01320000000', '9929X85363000000', '9946X00894000000',
'9844X00518000000', '9929X85015000000', '9929X01079000000',
'0026E00266000000', '9905X00441000000', '0103D00048000000',
'9910X83964000000', '9910X82376000000', '0067P00328000000',
'9910X82544000000', '9923X88088000000', '9809X83029000000',
'9935X82389000000', '9929X01584000000', '9905X83421000000',
'9946X01335000000', '9946X82144000000', '9935X00224000000',
'9905X83679000000', '9929X85347000000', '9946X83021000000',
'9946X82178000000', '0380D00159000000', '9946X01781000000',
'9910X00407000000', '8000T00134000000', '1999P00022000000',
'9929X83741000000', '9929X87927000000', '9929X87303000000',
'9935X83775000000', '9929X00996000000', '9929X00167000000',
'9844X00728000000', '9935X88158000000', '9929X87825000000',
'0050K00062000000', '9946X87769000000', '9923X88118000000',
'9946X01174000000', '9910X82456000000', '9946X82755000000',
'9929X85635000000', '9935X50308000000', '0027D00057000000',
'9809X00154000000', '9929X00632000000', '9910X82325000000',
'9935X01005000000', '9935X88277000000', '9929X00801000000',
'9923X87728000000', '0307N00201000000', '9946X01859000000',
'9905X50014000000', '9946X82357000000', '9935X00530000000',
'9946X50443000000', '0660G00170000000', '9946X84211000000',
'9910X82520000000', '9946X83469000000', '9946X85556000000',
'9946X84875000000', '0514S00198000000', '9905X50114000000',
'9844X00561000000', '9905X82098000001', '0189B00080000000',
'9910X84303000000', '0744D00282000000', '8000T00534000000',
'9929X01623000000', '9929X00677000000', '9910X83966000000',
'0702M00219000000', '0137B00303000000', '9929X87435000000',
'9841X00042000000', '9946X01645000000', '9946X82689000000',
'8000T00263000000', '9923X88125000000', '9905X83655000000',
'0604D00125000000', '9946X82232000000', '9929X86126000000',
'9905X01460000000', '9935X00696000000', '9910X82397000000',
'9910X84212000000', '9910X82286000000', '9946X01604000000',
'9923X87825000000', '8000T02561000000', '9946X00077000000',
'9929X86616000000', '9946X50004000000', '9923X82400000000',
'9910X01350000000', '9923X82180000000', '9905X00367000000',
'9946X00897000000', '0125S00016000000', '9929X88024000000',
'9905X00019000000', '9946X01496000000', '9946X84076000000',
'9929X87031000000', '0624H00114000000', '9929X50234000000',
'9923X87902000000', '0827L00208000000', '9910X84330000000',
'9923X50038000000', '0027B00120000000', '9929X87623000000',
'9929X85248000000', '0224E00128000000', '9910X01060000000',
'9905X00026000000', '9905X00401000000', '9935X50184000000',
'0236A00085000000', '9929X83818000000', '9929X85810000000',
'9841X00053000000', '9929X88202000000', '0749H00184000000',
'8000T03217000000', '9929X85689000000', '9946X83639000000',
'9946X83066000000', '9946X01490000000', '9929X01726000000',
'8000T03578000000', '9923X84359000000', '0006R00313000000',
'9946X88389000000', '9946X50242000000', '9946X85256000000',
'8000T00337000000', '9923X82346000000', '9946X88126000000',
'9946X01828000000', '0507L00014000000', '9923X01041000000',
'9946X82949000000', '9929X86027000000', '9910X01369000000',
'9946X87702000000', '0124N00230000000', '9923X00845000000',
'9935X83196000000', '9946X83303000000', '9946X83217000000',
'0066E00176000000', '9946X82601000000', '9905X01502000000',
'9923X88334000000', '9935X83735000000', '9935X88317000000',
'0052E00081050100', '9923X87879000000', '9910X50018000000',
'9923X84368000000', '9905X01219000000', '9923X88351000000',
'0174E00080000001', '9929X01164000000', '9946X83542000000',
'9946X82715000000', '9929X85017000000', '9929X00475000000',
'9946X83289000000', '9946X50319000000', '9905X82229000000',
'0624H00116000000', '9923X00331000000', '9946X50070000000',
'9905X82327000000', '9935X82368000000', '9929X01624000000',
'0083L00313000000', '9910X84403000000', '9946X01484000000',
'9929X84421000000', '9910X83896000000', '9946X85057000000',
'9905X01905000000', '9946X86631000000', '9929X87582000000',
'9946X88586000000', '9946X01829000000', '9929X84286000000',
'9946X84815000000', '8000T01870000000', '9910X00151000000',
'9905X82290000000', '9935X83742000000', '9935X83062000000',
'9946X82251000000', '9923X82369000000', '9929X82527000000',
'9946X00179000000', '9923X01029000000', '1346N00391000000',
'9923X87669000000', '9935X83673000000', '9905X00624000000',
'9935X00841000000', '8000T01818000000', '9935X82056000000',
'9946X85148000000', '9929X84227000000', '9923X87672000000',
'9910X84510000000', '9946X84033000000', '9935X01007000000',
'9923X87932000000', '9910X84233000000', '9946X82342000001',
'9946X82342000000', '9809X83005000000', '9929X85579000000',
'0003L00018000000', '0506C00257000000', '9905X01535000000',
'9923X84504000000', '9809X00228000000', '9935X83333000000',
'9923X00529000000', '9923X88435000000', '9946X00957000000',
'9946X83026000000', '9946X83206000000', '9935X83621000000',
'9923X00900000000', '9946X82732000000', '0660A00020000100',
'0130L00121000001', '9935X83092000000', '9929X84806000000',
'9946X00113000000', '0546B00359000000', '9929X86521000000',
'9929X00337000000', '9923X84476000000', '9946X82654000000',
'9935X83568000000', '9809X00111000000', '9923X82413000000',
'9935X83419000000', '9946X85526000000', '9946X82538000000',
'9935X83357000000', '9946X85336000000', '9946X83778000000',
'0237D00073000000', '9929X81062000000', '9935X83067000000',
'1999J00009000000', '9935X88387000000', '9910X83917000000',
'0184R00102000000', '9946X01119000000', '9946X80015000000',
'9910X83971000000', '9905X01434000000', '9946X82236000000',
'0020J00098000000', '9946X00895000000', '9946X81035000000',
'9929X85445000000', '9935X88047000000', '1223M00039000000',
'9929X85153000000', '9844X82035000000', '9929X00174000000',
'9946X85185000000', '9929X00658000000', '9923X88089000000',
'9946X84770000000', '9923X82128000000', '9946X00017000000',
'0004K00241000000', '9946X85054000000', '9935X83051000000',
'9809X00282000000', '9946X84072000000', '9905X83856000000',
'9935X88701000000', '9929X87010000000', '9946X84126000000',
'9929X83158000000', '9935X81024000000', '9923X87417000000',
'0218S00158000000', '0084A00119000000', '9946X82360000000',
'9946X83803000000', '0050S00265000000', '1064G00001000000',
'0941H00099000100', '9946X82256000000', '9935X82876000000',
'9905X00932000000', '9935X50044000000', '0051K00249000000',
'9923X00372000000', '0121K00068000000', '9935X50119000000',
'9946X88641000000', '9809X84020000000', '9929X85369000000',
'9929X87012000000', '9929X86363000000', '9809X84068000000',
'9910X00565000000', '0011D00166000000', '9844X00238000000',
'9923X88039000000', '9946X01027000000', '9935X88370000000',
'9935X82783000000', '9844X00176000000', '9946X84369000000',
'9935X83106000000', '9923X82348000000', '9844X00495000000',
'9946X85634000000', '9923X87840000000', '9946X83788000000',
'9929X87669000000', '9905X01420000000', '9923X00869000000',
'9935X00452000000', '0359N00031000000', '9910X82361000000',
'9905X83911000000', '9935X01272000000', '0190K00062000000',
'9946X83544000000', '9935X00764000000', '0124P00311000000',
'9929X87964000000', '9923X82123000000', '9935X82252000000',
'9905X01782000000', '9946X82639000000', '9946X84287000000',
'9844X00411000000', '9946X85463000000', '9946X01556000000',
'9910X84646000000', '9946X87748000000', '9929X86845000000',
'9841X00179000000', '0307N00202000000', '9905X00589000000',
'9923X00395000000', '8000T00112000000', '9935X00093000000',
'9946X84813000000', '9905X01614000000', '9935X50050000000',
'9844X00606000000', '9946X83098000000', '9905X01669000000',
'9910X01585000000', '9910X01180000000', '9910X81048000000',
'9935X82554000000', '9929X86697000000', '9935X87945000000',
'9910X82084000000', '0307E00115000D00', '9929X01308000000',
'9929X01925000000', '9905X01447000000', '0390M00286000000',
'9946X84236000000', '9923X87780000000', '0001C01662M02000',
'0189F00015000000', '0941S00171000100', '9946X82789000000',
'0450P00651000000', '9841X00215000000', '9946X88099000000',
'9946X84429000000', '9910X00706000000', '0056P00285000002',
'9929X87527000000', '9923X84484000000', '9841X00109000000',
'9929X83566000000', '9923X84578000000', '0450P00461000000',
'9910X84631000000', '9935X00140000000', '9905X82325000000',
'9946X83292000000', '9844X00009000000', '0012M00017000000',
'9929X87981000000', '9905X00296000000', '9929X84960000000',
'9929X00674000000', '0609P00236000000', '9910X00566000000',
'9923X00176000000', '9908X83031000000', '9935X82833000000',
'9923X82440000000', '9929X83844000000', '9905X80006000000',
'1233N00354000000', '9905X00679000000', '9929X83257000000',
'9946X87912000000', '0957C00210000000', '9946X82739000000',
'0218C00080L22000', '9910X01633000000', '9923X00346000000',
'9946X84098000000', '9923X82417000000', '9923X87735000000',
'0718H00038000000', '9910X82077000000', '9905X00803000000',
'9946X83118000000', '9929X87197000000', '9946X87683000000',
'9946X00074000000', '9905X82903000000', '9929X85154000000',
'9946X83259000000', '9929X85749000000', '9946X83541000000',
'9935X00767000000', '9923X50037000000', '9841X00087000000',
'0125M00374000000', '9935X88331000000', '8000T01559000000',
'9929X50205000000', '9946X84793000000', '8000T02626000000',
'9929X87460000000', '9905X01804000000', '9935X82026000000',
'9935X01132000000', '9946X01503000000', '9929X00925000000',
'9946X01259000000', '1361S00226000000', '9929X00274000000',
'9946X85507000000', '9946X50528000000', '9929X01586000000',
'9923X87745000000', '0925G00054000000', '0026E00219000000',
'9946X85056000000', '9946X87963000000', '9929X01132000000',
'9946X01081000000', '9910X83861000000', '9946X82771000000',
'9905X82828000000', '8000T03462000000', '9910X00152000000',
'0520E00150000000', '9841X00089000000', '9929X86696000000',
'9910X83819000000', '9946X83440000000', '9935X83672000000',
'0064N00238000000', '1134S00350000000', '9946X50309000000',
'9929X86528000000', '0250A00261000000', '0250D00053000000',
'9905X01000000000', '8000T02046000000', '9910X00679000000',
'9929X87315000000', '0011E00246000000', '9946X83288000000',
'9935X83056000000', '9935X82872000000', '0190S00409000000',
'9923X87439000000', '9946X85425000000', '9905X84019006D00',
'9946X88330000000', '9946X87873000000', '8000T02599000000',
'9946X83629000000', '8000T01538000000', '9929X00846000000',
'9946X84172000000', '9929X50023000000', '8000T03168000000',
'0050J00022000A00', '0256M00147000000', '9905X82109000000',
'9905X01757000000', '9905X82174000000', '9946X01019000000',
'9946X83051000000', '0023M00238000000', '9929X00558000000',
'9946X82873000000', '9935X83126000000', '9844X00580000000',
'9910X00101000000', '9946X83092000000', '0395D00090000100',
'9946X83991000000', '9946X82542000000', '8000T02660000000',
'9923X82487000000', '9809X84056000000', '0124J00095000000',
'0026P00137000000', '0943N00276000000', '9910X82396000000',
'9929X84934000000', '9923X84591000000', '9923X84614000000',
'9946X85530000000', '0084L00068000A00', '9923X00683000000',
'9809X00217000000', '9923X84505000000', '9929X83381000000',
'9929X85109000000', '9946X00093000000', '0083G00274602100',
'9946X00182000000', '9946X85462000000', '9946X83986000000',
'9929X84246000000', '9935X00078000000', '9923X88210000000',
'0055P00336000000', '0160J00060060800', '9809X00081000000',
'9910X84617000000', '9844X00317000000', '9946X01215000000',
'8000T00176000000', '0396D00028000000', '9929X84657000000',
'9946X83247000000', '9923X00375000000', '1269S00242000000',
'1355D00274000000', '9844X00515000000', '8000T00620000000',
'9935X00300000000', '9929X86705000000', '9935X82494000000',
'9910X82322000000', '9929X00446000000', '9929X84980000000',
'0050S00264000000', '9910X01282000000', '9929X00272000000',
'9929X85967000000', '9946X01854000000', '9946X83797000000',
'9935X83653000000', '0026K00232000000', '0159M00045000000',
'0205N00250000000', '9905X00105000000', '9910X84195000000',
'0011A00132000B00', '8000T00577000000', '9929X01384000000',
'9923X88272000000', '9946X82963000000', '9929X01798000000',
'9809X82043000000', '9923X00619000000', '9905X00356000000',
'0011E00270000000', '9946X83357000000', '9946X83876000000',
'9910X00862000000', '0887D00173000000', '9905X82041000000',
'0167A00273000000', '9929X00740000000', '0023L00134000000',
'9929X87493000000', '9923X00053000000', '0174A00109000000',
'9905X83573000000', '9935X82989000000', '9946X83856000000',
'9923X81003000000', '0060E00006000002', '9910X01410000000',
'9935X50305000000', '9923X87588000000', '9910X84650000000',
'0050K00055000000', '9946X88118000000', '9929X00814000000',
'9910X00094000000', '9935X88066000000', '9946X84096000000',
'9910X83969000000', '9946X00342000000', '9929X86324000000',
'9946X85506000000', '9935X88061000000', '9929X85239000000',
'9929X84812000000', '9844X00292000000', '9946X00177000000',
'9923X82397000000', '9923X00260000000', '9935X82861000000',
'9929X82871000000', '9946X88144000000', '9923X84639000000',
'8000T00449000000', '9929X86025000000', '9946X85192000000',
'9946X88574000000', '9910X00177000000', '9841X00104000000',
'9929X84951000000', '8000T02354000000', '2018S00275000000',
'9935X83492000000', '9844X00258000000', '9935X50003000000',
'9910X00730000000', '9946X00737000000', '9946X87892406B00',
'8000T02044000000', '8000T00137000000', '9923X00167000000',
'9929X87875000000', '9946X00273000000', '9929X85325000000',
'9923X87523000000', '9935X01214000000', '9946X82116000000',
'9946X82474000000', '9841X00229000000', '0833A00048000000',
'9910X84645000000', '9929X84909000000', '0124J00159000000',
'9844X00745000000', '9946X83481000000', '9929X86306000000',
'9905X83888000000', '0086S00112000000', '0256M00141000000',
'9946X00321000000', '9844X00459000000', '8000T02028000000',
'9910X00403000000', '9946X50301000000', '9929X87645000000',
'9946X82657000000', '9929X87475000000', '0222N00082000000',
'9923X00219000000', '9929X83207000000', '0541E00255000000',
'0361F00043000000', '9923X00330000000', '9935X83602000000',
'9946X85059000000', '0131C00205000000', '0821S00259000000',
'9929X00260000000', '9946X83014000000', '9923X82489000000',
'0001C01662009700', '9935X88386000000', '9923X88493000000',
'9935X00359000000', '9905X01529000000', '9935X83191000000',
'9910X01522000000', '9905X01139000000', '9910X00337000000',
'9910X82168000000', '9923X84498000000', '9946X84727000000',
'9929X87581000000', '0450P00478000000', '9946X84062000000',
'9905X84090000000', '9929X85839000000', '1136B00186000000',
'9923X87740000000', '9929X86963000000', '9929X01346000000',
'9946X82167000000', '9905X00322000000', '9935X82546000000',
'9844X00203000000', '9946X83108000000', '9910X83874000000',
'9910X00763000000', '9905X50050000000', '9929X87577000000',
'9910X00283000000', '9923X84648000000', '9935X87865000000',
'9946X00269000000', '9946X84339000000', '9946X50320000000',
'9910X83825000000', '9946X82678000000', '9910X80040000000',
'9910X01488000000', '9905X00758000000', '0393D00084000000',
'9923X00254000000', '9923X87671000000', '0175C00225000000',
'0236K00240000000', '9946X00337000000', '9929X86538000000',
'9929X86582000000', '9935X82670000000', '9935X88058000000',
'9905X01490000000', '8000T01669000000', '9946X01506000000',
'9946X88143000000', '9935X00730000000', '9910X01059000000',
'9946X88421000000', '9946X84362000000', '9929X85895000000',
'9935X83506000000', '9841X00153000000', '0434S00110000000',
'9905X00417000000', '9946X88320000000', '9946X88269000000',
'9935X83532000000', '9946X01640000000', '0066E00152000000',
'9935X82583000000', '9910X82634000000', '9929X83218000000',
'9929X00933000000', '9905X83397000000', '9929X86747000000',
'9946X50438000000', '9946X83981000000', '9905X83449000000',
'9946X85496033300', '0256M00144000000', '9929X87984000000',
'9935X82910000000', '8000T00459000000', '9935X00334000000',
'9946X01683000000', '9946X01018000000', '9905X01328000000',
'9910X82184000000', '0023F00076000000', '9923X87703000000',
'0253H00158000000', '9910X00019000000', '9809X00341000000',
'9929X84548000000', '9844X50003000000', '9935X00687000000',
'9946X85181000000', '0222E00181000000', '0050K00057000000',
'9946X85322000000', '9809X50006000000', '9923X84447000000',
'9923X01013000000', '0114F00052000000', '8000T00131000000',
'0157R00196000000', '9910X82499000000', '0180D00279000000',
'0010J00296000000', '9946X85411000000', '9910X00621000000',
'9910X84184000000', '0176H00251000000', '9946X83637000000',
'8000T03184000000', '9905X00550000000', '9929X85491000000',
'0013G00137000000', '9905X00841000000', '9841X00118000000',
'9935X83788000000', '1348P00202000000', '9946X00910000000',
'9923X01018000000', '0887B00040000000', '9946X85496035400',
'0347D00017000000', '9929X01824000000', '9905X00078000000',
'9929X88184000000', '9946X87728000000', '9905X01335000000',
'9946X00169000000', '9935X82896000000', '9929X87600000000',
'9929X00715000000', '9935X82676000000', '9935X82574000000',
'9946X00197000000', '9905X82306000000', '9929X85013000000',
'9946X00271000000', '0132S00070000000', '9946X84939000000',
'0301N00110000000', '8000T00423000000', '9929X00683000000',
'9923X00097000000', '9910X82683000000', '9910X84407000000',
'9929X00431000000', '9923X87802000000', '9929X00543000000',
'8000T00680000000', '9923X01047000000', '9946X85631000000',
'9929X83040000000', '9929X01243000000', '9946X00323000000',
'0468B00146000000', '9844X00263000000', '0774S00200000000',
'9844X00080000000', '9923X88111000000', '9935X88328000000',
'9935X83623000000', '0151M00152000000', '9923X00359000000',
'8000T00469000000', '8000T01746000000', '9905X83273000000',
'8000T00108000000', '8000T00447000000', '9929X87171000000',
'9929X00280000000', '9929X01453000000', '9935X87789000000',
'9905X00284000000', '9935X82351000000', '9935X83402000000',
'1223G00004000000', '9935X83627000000', '9946X88433000000',
'0997B00234000001', '9910X84138000000', '9946X82293000000',
'9929X86357000000', '9905X83542000000', '9935X00558000000',
'9929X83966000000', '9929X88096000000', '9929X88401000000',
'9929X85877000000', '9923X84342000000', '9946X83771000000',
'9946X50162000000', '0125M00371000000', '9935X88485000000',
'8000T00476000000', '9844X00157000000', '9946X00044000000',
'9929X82547000000', '9935X50200000000', '9946X00724000000',
'9844X00234000000', '9935X01205000000', '9935X88645000000',
'9929X01705000000', '9923X87744000000', '9923X88352000000',
'9905X00892000000', '8000T00013000000', '9929X87816000000',
'9946X85592000000', '9910X83863000000', '8000T02322000000',
'9946X84082000000', '9910X82172000000', '9923X82285000000',
'9946X84899000000', '0208J00034000000', '9844X00751000000',
'9946X83007000000', '0255P00191000000', '9905X01167000000',
'9923X00123000000', '9946X50384000000', '0050F00019000000',
'9929X83423000000', '9935X00338000000', '9935X00974000000',
'9923X87896000000', '9905X00236000000', '9946X00475000000',
'9844X00131000000', '9905X00678000000', '9844X00447000000',
'9946X84264000000', '9946X85076000000', '9910X01321000000',
'9905X83358000000', '9935X82718000000', '9910X84629000000',
'9923X88571000000', '0276N00090000002', '9946X83570000000',
'8000T01839000000', '9923X84557000000', '9929X85222000000',
'9929X86527000000', '9935X88268000000', '9946X85211000000',
'9946X00771000000', '9929X87762000000', '8000T01464000000',
'9946X82074000000', '9905X00480000000', '9946X85012000000',
'9946X84260000000', '9935X88667000000', '9935X83127000000',
'0050F00020000B00', '9910X82548000000', '9946X82982000000',
'9935X00139000000', '9935X83194000000', '9910X82513000000',
'9929X00057000000', '9905X83111000000', '9929X85846000000',
'9946X00142000000', '9809X00207000000', '9946X85616000000',
'9929X84317000000', '9929X87814000000', '9905X01913000000',
'9935X83525000000', '9923X87492000000', '9946X85176000000',
'0276P00094000000', '9935X50071000000', '9935X82940000000',
'9841X00214000000', '9929X85972000000', '9946X50028000000',
'9929X84489000000', '9946X00858000000', '9923X82243000000',
'9935X00548000000', '9917X50066000000', '9935X00276000000',
'9935X82462000000', '9923X00725000000', '9905X83935000000',
'9929X87576000000', '9935X00650000000', '9935X83057000000',
'8000T00501000000', '9905X50068000000', '9929X00088000000',
'9935X83780000000', '9929X00310000000', '9929X00827000000',
'9946X88422000000', '8000T00243000000', '9905X83641000000',
'9905X00230000000', '9935X00250000000', '9935X01028000000',
'9935X82378000000', '9946X85546000000', '9929X86573000000',
'9910X84319000000', '0049J00224000000', '9905X00586000000',
'9946X83240000000', '9946X85006000000', '9935X87853000000',
'9905X84019006B00', '9946X88149000000', '9905X00905000000',
'9929X86745000000', '9905X82880000000', '9910X01345000000',
'9809X00175000000', '0322C00075000000', '9910X01361000000',
'0773B00070000100', '9905X00734000000', '9935X83195000000',
'9929X01096000000', '0879E00207000000', '9844X00485000000',
'9946X00456000000', '9910X01626000000', '0051F00133000000',
'0024N00053000000', '9935X83561000000', '8000T00470000000',
'9908X82892000000', '9946X01807000000', '8000T02315000000',
'9929X84364000001', '8000T00572000000', '9946X85433000000',
'9844X00707000000', '9929X84355000000', '9946X83841000000',
'9946X88141000000', '0514S00147000000', '0083L00005000000',
'9929X86805000000', '0079R00092000000', '9929X83969000000',
'9844X00002000000', '9929X84963000000', '9905X83490000000',
'9946X84125000000', '9935X83626000000', '9841X00071000000',
'9910X82081000000', '9946X82220000000', '9929X00589000000',
'8000T00111000000', '9905X82222000000', '9929X85596000000',
'9910X84197000000', '9844X00543000000', '2001G00005000000',
'0414G00034000000', '0175A00028000A00', '9910X84099000000',
'9910X84537000000', '8000T00317000000', '0131B00216000000',
'9946X85086000000', '8000T00697000000', '9935X81018000000',
'9946X00901000000', '9946X88543000000', '8000T00822000000',
'9929X87593000000', '9929X86647000000', '9929X87333000000',
'0048N00123000000', '8000T00308000000', '9809X83001000000',
'9910X01307000000', '0023G00017000000', '9923X00882000000',
'9946X83680000000', '9905X00017000000', '9841X00097000000',
'0002M00291000A00', '9905X83479000000', '9929X83822000000',
'9929X85272000000', '9946X84838000000', '9929X00290000000',
'0096M00121000000', '9929X84129000000', '9809X82042000000',
'9935X82694000000', '9929X87798000000', '9905X84011000000',
'9844X00035000000', '9923X84466000000', '9946X00274000000',
'9946X84341000000', '9946X82984000000', '9946X83673000000',
'8000T03806000000', '9844X00244000000', '8000T00433000000',
'8000T03486000000', '9844X00420000000', '9935X82711000000',
'9809X00146000000', '9923X87712000000', '9935X00280000000',
'9905X01256000000', '0189B00115000000', '9905X83571000000',
'9905X83894000000', '9905X84005003B00', '9929X83560000000',
'9923X00162000000', '9923X50014000000', '9935X82325000000',
'9946X83102000000', '8000T03135000000', '9923X88254000000',
'9946X85326000000', '9905X82761000000', '9946X85614000000',
'9935X00141000000', '0604E00296000000', '8000T02049000000',
'0287K00050000000', '9946X00565000000', '9935X00838000000',
'9946X84352000000', '9946X85030000000', '9929X83918000000',
'9923X84634000000', '9946X00843000000', '9929X01177000000',
'9923X88107000000', '9923X00446000000', '8000T01400000000',
'0315R00050000000', '9946X82481000000', '9946X84261000000',
'9946X85401000000', '9935X00559000000', '0315J00220010200',
'9929X50015000000', '0026E00221000000', '0124J00110000000',
'9946X84437000000', '9923X84599000000', '9841X50006000000',
'9935X83579000000', '0255E00169000001', '9910X84368000000',
'0152P00056000000', '9929X84321000000', '9935X88698000000',
'1243R00157000000', '9946X01841000000', '9929X83816000000',
'9935X83832000000', '9923X82460000000', '9929X87976000000',
'9905X01450000000', '9935X88361000000', '9929X87802000000',
'9929X83941000000', '9935X00513000000', '9935X88456000000',
'9923X87686000000', '9946X00624000000', '9946X01190000000',
'9923X00778000000', '9929X84883000000', '9946X50578000000',
'9905X01319000000', '9935X83124000000', '9946X84901000000',
'9929X82517000000', '9809X84043000000', '9946X87708000000',
'9935X00363000000', '9910X84398000000', '9946X83808000000',
'0088H00151000000', '8000T02854000000', '0066H00126000100',
'9910X00154000000', '9935X83454000000', '9923X01045000000',
'9905X82535000000', '9929X85870000000', '9946X87877000000',
'9910X01193000000', '9910X00586000000', '0430A00008000000',
'9935X83140000000', '9923X88028000000', '0380D00160000000',
'1349P00009000000', '9929X00083000000', '9905X01506000000',
'8000T02517000000', '0079R00102000000', '9946X85077000000',
'9905X83977000000', '9929X87548000000', '9935X82258000000',
'8000T00152000000', '9929X84372000000', '9946X00519000000',
'2021P00176000000', '0049E00034000000', '9929X87804000000',
'9946X00777000000', '9923X87901000000', '0006M00282000000',
'9809X00107000000', '9935X83064000000', '9905X50132000000',
'9946X85178000000', '9929X87691000000', '8000T00375000000',
'9929X87584000000', '8000T01887000000', '8000T03221000000',
'9946X00120000000', '9935X87812000000', '9935X83384000000',
'9844X00066000000', '9923X88109000000', '9841X00031000000',
'9905X50035000000', '9935X82478000000', '9946X80041000000',
'9905X83536000000', '9935X00647000000', '9809X00027000000',
'9935X00092000000', '0083M00216000000', '9923X00121000000',
'9946X01678000000', '9905X83116000000', '9946X82969000000',
'0011M00193000000', '9946X00408000000', '9905X82823000000',
'8000T00139000000', '9923X00621000000', '0120N00255000000',
'8000T00946000000', '9946X82280000000', '9946X84309000000',
'9946X84357000000', '9946X00299000000', '0139R00074000000',
'8000T00400000000', '9946X83426000000', '9935X00682000000',
'9923X82057000000', '9935X00385000000', '9910X80007000000',
'9946X00861000000', '9905X83738000000', '9929X87454000000',
'9946X88501000000', '0046E00064000000', '9923X82439000000',
'0236S00346000000', '8000T01876000000', '9946X88409000000',
'0083M00072000000', '0011A00182000000', '9910X00242000000',
'9910X50028000000', '9905X84067000000', '0888L00089000000',
'9905X00241000000', '9905X01666000000', '9910X00844000000',
'9905X00778000000', '9809X00157000000', '9923X84369000000',
'9935X82573000000', '9923X82365000000', '1224G00081000000',
'9935X00011000000', '9910X00670000000', '2379L00316000000',
'0290G00040000100', '9929X01675000000', '9929X01283000000',
'9946X85351000000', '9905X82741000000', '9929X50077000000',
'9809X00336000000', '9929X00396000000', '0469N00087000000',
'9946X83533000000', '9935X83473000000', '9946X83703000000',
'9905X83087000000', '0119S00158000000', '9946X82271000000',
'9929X01520000000', '9929X83972000000', '9946X88358000000',
'0829N00035000000', '8000T03033000000', '0709J00033000000',
'0767K00291000000', '9809X83030000000', '9946X00278000000',
'9946X82109000000', '9946X82563000000', '9946X88542000000',
'9935X82521000000', '9946X01722000000', '0415B00029000000',
'0024D00281000000', '9946X82491000000', '9929X86375000000',
'9929X83938000000', '9910X84465000000', '8000T00287000000',
'9946X83349000000', '9929X87621000000', '9910X01623000000',
'9946X85158000000', '9935X82057000000', '9905X83668905B00',
'9910X82180000000', '9910X82662000000', '0049F00298000A00',
'0222K00306000100', '9929X00102000000', '9929X85568000000',
'9923X00916000000', '9946X87734000000', '9905X01295000000',
'9935X83830000000', '9935X87894000000', '9935X82928000000',
'9841X00160000000', '9935X83613000000', '9946X88004000000',
'9929X88199000000', '9935X83142000000', '9905X00461000000',
'9946X82737000000', '9910X00895000000', '9905X83203000000',
'9929X88073000000', '9910X00837000000', '9905X82397000000',
'9946X00632000000', '9946X00499000000', '9910X84384000000',
'9946X82184000000', '9905X01954000000', '9905X00360000000',
'9946X83270000000', '9946X00049000000', '9946X84442000000',
'0106L00122000000', '9923X88192000000', '9923X88052000000',
'0178M00318000000', '9946X84354000000', '9935X87878000000',
'9946X85053000000', '9923X84481000000', '9946X00400000000',
'9923X84671000000', '0125L00211000000', '8000T01967000000',
'9910X82534000000', '9910X82148000000', '9946X85145000000',
'9946X88625000000', '9935X83146000000', '9910X00557000000',
'9946X82756000000', '0022M00040000000', '9929X85506000000',
'9946X88215000000', '9923X00041000000', '9844X00573000000',
'9844X00520000000', '9929X83968000000', '9910X00971000000',
'8000T01990000000', '9910X01335000000', '9946X00275000000',
'9923X01072000000', '9905X00041000000', '9923X87941000000',
'9929X87345000000', '9905X83638000000', '9923X88411000000',
'9946X82497000000', '9929X86257000000', '9946X00610000000',
'0256M00142000000', '9935X83211000000', '9946X00338000000',
'9946X50420000000', '9946X85113000000', '9910X82541000000',
'9923X82223000000', '9946X00433000000', '9946X85563000000',
'9946X88161000000', '9935X83416000000', '9923X87969000000',
'9935X82206000000', '9905X83654000000', '9946X83333000000',
'9935X82974000000', '9935X82447000000', '9910X01290000000',
'9929X82204000000', '0423R00104000000', '9946X87812000000',
'9905X01602000000', '9935X83386000000', '9935X01056000000',
'1574M00025000000', '9935X00753000000', '2013S00102000000',
'9946X83210000000', '9929X87943000000', '0222J00055000000',
'0033M00061000000', '9923X87985000000', '9905X01036000000',
'9923X87606000000', '9946X82781000000', '0236S00209000000',
'9946X84955000000', '9935X88356000000', '0541A00245000000',
'9935X00776000000', '9935X82956000000', '9929X01736000000',
'0084K00117000000', '9946X85085000000', '9946X82338000000',
'9929X84706000000', '9946X01326000000', '9923X88059000000',
'9929X84849000000', '9946X01381000000', '9910X84588000000',
'9929X00027000000', '9946X50296000000', '9809X82005000000',
'0741H00008000000', '9946X84174000000', '9905X83098000000',
'0167R00035000000', '9923X82461000000', '9905X01667000000',
'0042D00135000000', '9910X84174000000', '0027D00053000000',
'9929X87668000000', '9929X87565000000', '9910X01165000000',
'0536J00075000000', '9946X87653000000', '9910X01446000000',
'9905X83578000000', '9946X83566000000', '9929X85281000000',
'9946X01701000000', '9923X84696000000', '9905X82257000000',
'9905X01590000000', '9905X01464000000', '0058N00178000000',
'9946X85357000000', '0232A00245000000', '9841X82025000000',
'0022R00248000000', '9910X82156000000', '9910X82450000000',
'9935X83515000000', '9905X00791000000', '9923X82240000000',
'9935X88738000000', '9905X83611000000', '9910X80015000000',
'9946X88101000000', '9910X00089000000', '1136N00301000000',
'9946X83129000000', '9809X00005000000', '9935X83079000000',
'9935X83271000000', '9910X82073000000', '9946X01539000000',
'9929X87954000000', '9946X82274000000', '9935X83350033100',
'9935X00190000000', '9910X84628000000', '0024D00303000000',
'9946X01646000000', '9946X50386000000', '9946X50519000000',
'9905X84005003D00', '9923X80009000000', '9929X84878000000',
'9929X01341000000', '9929X82332000000', '9910X82643000000',
'9809X84037000000', '9946X82959000000', '9923X84308000000',
'9905X83398000000', '0527P00115000000', '0010P00167000000',
'9910X84564000000', '9905X00334000000', '9923X84386000000',
'9935X00749000000', '9935X83718000000', '9946X83491000000',
'9905X01584000000', '9935X88096000000', '9946X01418000000',
'9923X88479000000', '9908X82876000000', '9929X86751000000',
'9929X01238000000', '0067P00333000000', '9946X85292000000',
'9841X00102000000', '9946X82452000000', '9929X86786000000',
'9946X00071000000', '9946X83293000000', '9923X87849000000',
'9929X86962000000', '8000T00207000000', '9910X83976000000',
'9935X00208000000', '9905X83448000000', '9910X84127000000',
'0050L00163000000', '9929X83496000000', '9946X82870000000',
'9946X84356000000', '9809X84082000000', '1364B00279000000',
'9809X00007000002', '9809X82049000000', '9946X00381000000',
'9935X82137000000', '9935X88014000000', '9923X00340000000',
'9923X88425000000', '1133P00002000000', '0154S00034000000',
'9929X00806000000', '9946X83708000000', '1368A00197000000',
'9910X01203000000', '9935X00606000000', '9935X82572000000',
'9923X82364000000', '9923X88013000000', '9929X00825000000',
'0629G00311000000', '9935X82808000000', '9929X87450000000',
'9946X88491000000', '9935X00536000000', '8000T00054000000',
'9905X82162000000', '9905X83013000000', '0023G00006000A00',
'9929X00437000000', '9946X84180000000', '9946X82539000000',
'9905X82212000000', '9946X82929000000', '9923X84538000000',
'9946X83518000000', '9935X00804000000', '9946X87761000000',
'9905X01237000000', '9929X84857000000', '9935X01112000000',
'0124J00119000000', '9905X00282000000', '9923X88419000000',
'8000T01614000000', '9910X82222000000', '9923X00241000000',
'0079L00165000000', '9935X82226000000', '9935X00996000000',
'9929X01861000000', '9923X88357000000', '9905X83545000000',
'9946X82879000000', '9910X00173000000', '9946X01324000000',
'9946X84307000000', '9946X82276000000', '9946X01540000000',
'9923X88325000000', '9946X50290000000', '9929X00025000000',
'9929X00817000000', '9935X00850000000', '0392C00200000000',
'9935X87814000000', '9910X00601000000', '9923X82044000000',
'9844X00183000000', '0001P00032000000', '8000T01982000000',
'0007N00148000000', '0019J00168000000', '0003S00240000100',
'9910X84026000000', '9923X00040000000', '9844X00425000000',
'9935X83641000000', '9910X00681000000', '9910X84394000000',
'0609L00312000000', '0507L00018000000', '9929X86541000000',
'9905X01635000000', '9910X82143000000', '9910X83872000000',
'9929X86800000000', '9910X00948000000', '9929X88129000000',
'9910X83981000000', '9929X87688000000', '9946X85144000000',
'9905X82253000000', '9929X86330000000', '9929X01478000000',
'0344K00097000000', '9905X83615000000', '9923X82341000000',
'9910X01228000000', '9910X82653000000', '0049E00032000000',
'9923X84646000000', '9935X82213000000', '9929X00269000000',
'0658H00315000000', '9910X80011000000', '9946X82048000000',
'0249B001530B2400', '9910X00772000000', '9929X85683000000',
'9946X84705000000', '9844X82055000000', '9905X82221000000',
'9929X00698000000', '8000T03586000000', '9809X00048000000',
'8000T00057000000', '9929X83227000000', '9946X01253000000',
'0233E00262000700', '9946X82147000000', '0827E00168000000',
'9905X82808000000', '9946X83271000000', '9923X87805000000',
'9905X50049000000', '9844X82053000000', '9946X50404000000',
'9935X88030000000', '9923X87593000000', '9905X83741000000',
'9923X87425000000', '9929X00621000000', '9935X83279000000',
'9929X00743000000', '9929X01105000000', '9844X80002000000',
'9946X85468000000', '9946X83313000000', '9946X87909000000',
'9923X84711000000', '9923X82456000000', '9905X82625000000',
'9946X83612000000', '9929X00518000000', '9905X83579000000',
'9929X01143000000', '1222D00050000000', '9910X00455000000',
'9946X88339000000', '0723F00298000000', '9841X00199000000',
'9905X83117000000', '9935X82594000000', '9935X00592000000',
'9929X82779000000', '9929X86814000000', '9935X01116000000',
'9929X87863000000', '9929X00095000000', '9929X88168000000',
'9946X82056000000', '9929X85986000000', '9923X82124000000',
'9946X83596000000', '1203F00145000300', '9946X83874000000',
'0829N00047000100', '9946X84110000000', '9905X00101000000',
'9905X50057000000', '0415R00345000000', '9929X00972000000',
'9923X82349000000', '9929X84029000000', '9946X84292000000',
'9946X87874000000', '9935X83683000000', '9809X00329000000',
'9929X85170000000', '9809X00319000000', '0023G00004000000',
'9910X84171000000', '0102G00122000000', '9946X01719000000',
'9905X82921000000', '9844X00375000000', '9946X85473000000',
'0362F00091000000', '0006L00318000000', '9910X01192000000',
'9929X86577000000', '9923X82366000000', '9905X01744000000',
'9923X87516000000', '9929X87444000000', '9935X87808000000',
'9923X82170000000', '9905X00766000000', '0126D00127000000',
'9905X01221000000', '9910X82549000000', '8000T02658000000',
'9841X00075000000', '9935X87852000000', '9923X87456000000',
'9929X01474000000', '9923X82038000000', '9908X82912000000',
'9905X83910000000', '9946X00819000000', '9929X01907000000',
'9929X86625000000', '9946X87831000000', '9935X82343000000',
'0049J00317000000', '9946X83302000000', '9905X01540000000',
'9905X00839000000', '9946X01366000000', '9905X01133000000',
'9946X85514000000', '9923X88135000000', '0084M00362000000',
'9910X01303000000', '9935X83527000000', '0505A00151000000',
'9935X00436000000', '9929X84977000000', '0002M00297000000',
'0079L00163000000', '9929X85690000000', '9946X83640000000',
'9841X00161000000', '9923X84689000000', '9946X00935000000',
'9923X00709000000', '9905X82894000000', '9910X00932000000',
'9905X83309000000', '9809X00316000000', '9923X88440000000',
'9935X82980000000', '9905X00869000000', '9946X50458000000',
'9929X01984000000', '9923X82250000000', '9946X00753000000',
'9923X00831000000', '9935X88074000000', '0087F00067000200',
'0140F00260000000', '9908X82877000000', '9946X83227000000',
'9946X84841000000', '9905X01108000000', '0154S00084000000',
'9923X88127000000', '9905X00163000000', '9929X84915000000',
'9905X00199000000', '9910X00968000000', '8000T00568000000',
'9935X82890000000', '9935X00633000000', '9929X83524000000',
'9910X01583000000', '9946X50282000000', '9923X82253000000',
'9946X84419000000', '9910X80020000000', '9923X88189000000',
'0004B00224000100', '9946X82501000000', '9923X88237000000',
'9935X83497000000', '9809X82048000000', '9929X01245000000',
'9910X80069000000', '9946X82300000000', '9923X84371000000',
'9910X84558000000', '9809X00256000000', '9929X00245000000',
'9929X87682000000', '9946X87829000000', '9946X82529000000',
'9946X00842000000', '9946X82683000000', '9923X88394000000',
'1210F00065000000', '9905X81023000000', '9946X87921000000',
'9935X88365000000', '9929X00927000000', '9946X83369000000',
'9905X01717000000', '9929X83088000000', '9929X50271000000',
'9844X82051000000', '9905X83854000000', '9935X87848000000',
'9905X01918000000', '9905X83737000000', '9946X82149000000',
'9910X82131000000', '9946X82978000000', '9923X00244000000',
'1210S00118000000', '9910X82688000000', '9946X82182000000',
'9844X00073000000', '9946X00318000000', '9935X88051000000',
'9923X88126000000', '0079L00166000000', '9929X00346000000',
'9929X83352000000', '9946X82585000000', '9935X88129000000',
'9946X50197000000', '9946X84281000000', '9946X83439000000',
'9929X87613000000', '9910X82602000000', '9946X84022000000',
'0255G00250000000', '9946X84023000000', '9935X87980000000',
'9910X84448000000', '9809X83021000000', '9910X00536000000',
'9923X87905000000', '0001P00031000000', '9946X00087000000',
'9935X82337000000', '9923X87807000000', '9809X00030000000',
'9946X00977000000', '9946X01087000000', '9929X87382000000',
'9905X00824000000', '0668L00006000000', '9929X82825000000',
'9946X85635000000', '9905X01781000000', '9946X83610000000',
'9809X00165000000', '9910X00889000000', '9935X00638000000',
'9910X82578000000', '9841X00073000001', '9946X50247000000',
'9905X00378000000', '9905X82376000000', '9923X87790000000',
'9910X84160000000', '0298S00100000000', '9929X87955000000',
'9929X01282000000', '9935X01234000000', '0124J00124000000',
'8000T02047000000', '9905X83406000000', '9929X00894000000',
'9935X87960000000', '9935X83818000000', '9946X00961000000',
'9935X82838000000', '9910X84180000000', '9929X87575000000',
'9929X83410000000', '9844X00494000000', '9929X01183000000',
'9935X83034000000', '9929X01331000000', '9929X86824000000',
'9946X85512000000', '9841X00098000000', '9946X85020000000',
'9946X82533000000', '9946X88550000000', '9905X83275000000',
'9946X00880000000', '9809X00260000000', '9809X00318000000',
'9946X50271000000', '9910X01305000000', '9935X50031000000',
'9809X00119000000', '9923X84460000000', '9946X87917000000',
'8000T00472000000', '9946X85629000000', '9910X84275000000',
'9910X00049000000', '9929X00824000000', '0716R00378000000',
'9905X83236000000', '9923X82161000000', '9946X84780000000',
'9910X01334000000', '9935X83733000000', '0669D00200000100',
'9929X88309000000', '9929X85012000000', '9935X83424000000',
'0125M00387000000', '9946X50516000000', '9923X00812000000',
'9809X83027000000', '9935X88087000000', '9929X00644000000',
'9809X00031000000', '9929X85887000000', '9946X83502000000',
'9929X86134000000', '0130P00268000000', '8000T00420000000',
'9935X83831000000', '9910X84327016500', '0129E00149000000',
'9946X50570000000', '9935X82765000000', '9905X01311000000',
'9910X82176000000', '9929X84749000000', '9910X00810000000',
'9946X84179000000', '0450P00635000000', '9935X87801000000',
'9905X01225000000', '9929X85987000000', '9905X82715000000',
'0267C00331000000', '9905X00577000000', '9929X86056000000',
'9905X82814000000', '9935X00279000000', '0176P00279000100',
'9946X01445000000', '9935X82971000000', '9935X82305000000',
'9946X01318000000', '9923X50053000000', '9929X86823000000',
'9929X00522000000', '9946X85215000000', '9844X00402000000',
'0669N00107000000', '9809X00234000000', '9935X87990000000',
'9946X84242000000', '8000T01889000000', '9929X84123000000',
'9935X50213000000', '9946X82627000000', '9946X83158000000',
'9841X00076000000', '9910X84230000000', '9946X84896000000',
'9946X87777000000', '9929X85429000000', '9935X87791000000',
'0010J00335000000', '0175C00218000000', '0011M00185000000',
'9935X01204000000', '9946X84376000000', '0002L00001000A00',
'9946X85265000000', '9929X00854000000', '9923X88072000000',
'0087A00266000000', '9905X83750000000', '9929X86812000000',
'0255R00307000000', '0291K00098000000', '0273S00041000000',
'9929X87627000000', '0249B001530A2400', '9929X85320000000',
'9905X82990000000', '9910X00080000000', '9929X84234000000',
'9929X01538000000', '9910X84551000000', '9935X00162000000',
'9946X50115000000', '9946X84312000000', '9923X87946000000',
'9910X01300000000', '8000T01841000000', '9935X00487000000',
'0190C00040000000', '0361D00034000000', '9929X01918000000',
'9946X88170000000', '9809X00328000000', '9935X88229000000',
'9923X88128000000', '9910X00532000000', '9929X86352000000',
'9946X50552000000', '9946X00202000000', '9929X86874000000',
'9935X82446000000', '9905X01373000000', '9946X83835000000',
'9935X88006000000', '9935X00401000000', '9929X85102000000',
'9923X88014000000', '0177K00084000001', '9935X83692000000',
'8000T01869000000', '0050K00007000000', '9946X00890000000',
'8000T04413000000', '9946X01402000000', '0121F00092000000',
'9946X84400000000', '0007N00143000000', '0066E00149000000',
'9929X01848000000', '9809X00022000000', '9905X82077000000',
'9923X87903000000', '9923X00640000000', '9910X83965000000',
'0125M00389000000', '9929X85685000000', '9946X00608000000',
'9946X88163000000', '9946X01367000000', '9946X84276000000',
'9905X84005003A00', '9946X00516000000', '9929X83830000000',
'9844X00014000000', '9929X83525000000', '8000T00296000000',
'9923X87763000000', '9929X86378000000', '9923X00440000000',
'9946X80036000000', '9908X82931000000', '9935X82697000000',
'8000T00411000000', '9935X82822000000', '9946X84069000000',
'9946X82312000000', '9946X85143000000', '9946X00859000000',
'9905X01959000000', '9809X83058000000', '9935X83340000000',
'2011A00326161600', '9929X87430000000', '0152A00011000000',
'9946X83214000000', '0117N00024000000', '9946X84996000000',
'9946X85602000000', '9908X82869000000', '9929X85329000000',
'9946X87995000000', '9929X83228000000', '9929X82850000000',
'9923X01005000000', '9905X01765000000', '9910X00291000000',
'9935X83731000000', '9946X50427000000', '9929X87882000000',
'9910X00201000000', '9946X88416000000', '8000T03071000000',
'9929X84503000000', '9923X82465000000', '9946X82579000000',
'8000T00228000000', '9905X83485000000', '0625K00019000000',
'9905X50111000000', '9910X00133000000', '9923X00170000000',
'9923X87628000000', '9929X87453000000', '9935X82557000000',
'8000T00540000000', '9923X88532000000', '9910X84422000000',
'9905X00913000000', '8000T00580000000', '9935X82963000000',
'9929X00898000000', '9946X00868000000', '9910X00045000000',
'9929X84057000000', '9929X85571000000', '9905X01586000000',
'9935X87931000000', '0125M00392000000', '9946X82881000000',
'9929X87477000000', '0004K00242000000', '0103P00024000000',
'9946X82303000000', '1106M00148000000', '0131C00030000000',
'9910X82336000000', '9946X82598000000', '9935X83165000000',
'0525H00015000000', '9935X83820000000', '9905X01267000000',
'9929X01728000000', '0079R00094000000', '9809X84061000000',
'9946X82213000000', '8000T03166000000', '9844X00323000000',
'9929X83922000000', '9935X88126000000', '9905X83772000000',
'9905X82840000000', '0083S00323000000', '9929X01902000000',
'9946X84147000000', '9929X86844000000', '9809X84005000000',
'9946X83222000000', '9905X01412000000', '9929X88323000000',
'8000T01873000000', '9929X85985000000', '0738H00048000000',
'9923X87906000000', '9910X84528000000', '9935X83071000000',
'9923X84322000000', '9809X00110000000', '9946X88303000000',
'0434P00006000000', '9946X50316000000', '9923X88037000000',
'9929X87355000000', '9929X84150000000', '9935X82977000000',
'9905X83994000000', '9923X87785000000', '9929X00758000000',
'9910X00366000000', '9946X84776000000', '9946X82684000000',
'9905X00761000000', '9923X87590000000', '9935X00989000000',
'1211R00158000000', '0054S00039000000', '9946X83434000000',
'9905X82473000000', '9844X82011000000', '9935X88198000000',
'9946X84240000000', '0307P00380000000', '9905X83705000000',
'9844X00146000000', '9923X00155000000', '9910X84185000000',
'0352S00135000000', '9946X50022000000', '9910X00692000000',
'9923X00190000000', '0235N00070000000', '9929X01541000000',
'9844X00346000000', '9923X00524000000', '9935X82529000000',
'0023H00367000000', '9946X00876000000', '9946X82863000000',
'9946X50008000000', '0363J00327000000', '9923X00387000000',
'9946X88378000000', '9905X01063000000', '9905X83258000000',
'9935X83392000000', '0193C00022000000', '9929X87632000000',
'9946X83721000000', '9905X00329000000', '9910X00703000000',
'9923X84323000000', '9910X01643000000', '0083F00306000000',
'9929X01033000000', '9946X85636000000', '9841X82006000000',
'9946X50565000000', '9935X82423000000', '9935X83019000000',
'9946X84318000000', '9935X87813000000', '9905X82057000000',
'9946X85007000000', '9946X50368000000', '9929X82544000000',
'9929X83913000000', '9929X87318000000', '9929X00619000000',
'9935X82911000000', '9929X01084000000', '9929X86288000000',
'0011A00141000000', '9905X83691000000', '9905X00961000000',
'9935X82144000000', '9844X00601000000', '9946X82473000000',
'9929X87642000000', '9923X00963000000', '9809X00142000000',
'9844X82023000000', '9946X84207000000', '9929X88224000000',
'9929X50030000000', '9929X87248000000', '9841X00133000000',
'9905X82531000000', '0289M00157000000', '9935X01020000000',
'9929X01116000000', '8000T00150000000', '9946X00392000000',
'9946X50291000000', '9935X00425000000', '9946X00748000000',
'9935X83697000000', '9946X85453000000', '9929X00128000000',
'9923X88005000000', '9910X84429000000', '0023G00345000000',
'9935X88588000000', '9929X86763000000', '9946X83942000000',
'0036P00048000000', '9929X87750000000', '9929X84346000000',
'9929X00576000000', '9910X00423000000', '9929X87902000000',
'9946X84998000000', '0284L00181000100', '9946X85088000000',
'9946X83159000000', '9910X82263000000', '9923X82448000000',
'9946X01362000000', '0361L00026000000', '9844X00754000000',
'9923X87912014600', '9923X00189000000', '9946X83731000000',
'9935X83736000000', '9929X86340000000', '9935X82196000000',
'9935X88188000000', '9910X01440000000', '9905X82870000000',
'9946X00082000000', '9929X86173000000', '9929X00675000000',
'9946X50116000000', '9929X82161000000', '9910X00564000000',
'0010J00078000000', '9946X88450000000', '9923X84552000000',
'0660N00106000000', '9946X50016000000', '9923X50009000000',
'9923X88243000000', '9923X84664000000', '9929X83501000000',
'1354N00250000000', '0049C00246000000', '9923X88194000000',
'9905X01071000000', '9923X00038000000', '9946X82528000000',
'9946X82284000000', '9923X00026000000', '9935X82140000000',
'1272P00360000000', '9935X83205000000', '0874P00022000000',
'9935X88069000000', '9935X83688000000', '9844X00626000000',
'9935X00670000000', '9935X01295000000', '9946X83223000000',
'9946X00441000000', '0023M00168000000', '9946X00224000000',
'9946X50389000000', '9929X87161000000', '9923X84593000000',
'9923X87444000000', '0450P00466000000', '9946X50210000000',
'9905X00120000000', '9923X84452000000', '9935X82827000000',
'9935X83003000000', '9935X00043000000', '0121J00217000000',
'9929X86802000000', '0351G00116000000', '9905X01643000000',
'9946X82052000000', '9946X80037000000', '0083S00149000000',
'9929X86830000000', '9946X84387000000', '9923X00073000000',
'9935X83734000000', '1352F00327000000', '9910X82195000000',
'9935X82114000000', '9905X01807000000', '9923X87823000000',
'9935X00198000000', '9910X00308000000', '9841X82001000000',
'9935X00147000000', '9946X87996000000', '9923X84654000000',
'9929X86346000000', '9946X50288000000', '9946X83358000000',
'9929X86045000000', '9946X87896000000', '9946X00019000000',
'9905X84005001C00', '9929X01026000000', '9923X87989000000',
'9929X83843000000', '9905X00579000000', '9844X00410000000',
'9929X83092000000', '9929X83237000000', '9905X00700000000',
'9929X00703000000', '9905X82274000000', '9923X82436000000',
'0230J00041000001', '9929X01170000000', '9935X88033000000',
'9905X50121000000', '9929X50078000000', '0048A00130000000',
'9935X01199000000', '9946X84988000000', '9946X01568000000',
'9923X00907000000', '9946X83258000000', '9905X01187000000',
'9929X50061000000', '9923X84667000000', '9946X84093000000',
'9929X00358000000', '9929X87287000000', '9929X00866000000',
'9946X84195000000', '9929X88178000000', '9844X00467000000',
'0458E00048000000', '9929X85884000000', '9923X88350000000',
'9905X83899000000', '9929X87597000000', '9946X88287000000',
'9929X87883000000', '9905X00844000000', '9946X85300000000',
'9905X82896000000', '9946X88306000000', '9905X00045000000',
'8000T00326000000', '9809X00067000000', '9905X00348000000',
'9923X88015000000', '9905X84092000000', '9929X83494000000',
'9929X87683000000', '9908X82895000000', '9929X01078000000',
'9946X00821000000', '0300H00071000000', '9929X84023000000',
'9910X82357000000', '9935X00746000000', '9946X83067000000',
'9935X83337000000', '9809X83017000000', '9929X86277000000',
'9905X83237000000', '9929X80036000000', '9946X83104000000',
'8000T02045000000', '9935X83702000000', '0007P00004000000',
'2372M00056000000', '9905X83503000000', '9905X83666000000',
'9935X88042000000', '9946X82628000000', '9923X87503000000',
'9935X50158000000', '9946X82767000000', '9929X84393000000',
'9929X87603000000', '9929X84911000000', '9929X85488000000',
'0640N00381000000', '9809X82062000000', '8000T01420000000',
'0011A00160000000', '9929X00691000000', '9929X85827000000',
'9946X82645000000', '9905X01663000000', '9935X82198000000',
'9910X82489000000', '9923X84510000000', '9905X83442000000',
'9935X82162000000', '9929X88071000000', '9929X84617000000',
'0190M00157000000', '1068G00150000000', '0048M00035000A00',
'9923X88458000000', '0055D00001000000', '9929X85021000000',
'9946X84676000000', '9946X00432000000', '9929X83912000000',
'9946X82476000000', '9929X87491000000', '9929X50199000000',
'9809X00254000000', '9946X84707000000', '9935X01161000000',
'9935X00641000000', '9910X01212000000', '9923X88190000000',
'9929X86280000000', '9910X00329000000', '9905X82682000000',
'9929X50031000000', '9935X82041000000', '0299F00064000000',
'9935X88118000000', '9935X83286000000', '0175C00220000000',
'9929X87989000000', '9929X85075000000', '9929X00297000000',
'9946X84967000000', '9946X01211000000', '9946X85216000000',
'9910X00507000000', '9910X84415000000', '9929X85043000000',
'9844X00082000000', '9946X85544000000', '9935X82823000000',
'9929X87755000000', '9929X83467000000', '0309D00303000000',
'9910X84281000000', '9929X83070000000', '9923X88069000000',
'9929X01472000000', '9910X84500000000', '9929X86332000000',
'9923X00076000000', '9929X86058000000', '9905X83585000000',
'9935X82113000000', '9910X00025000000', '9946X50159000000',
'9935X00365000000', '9905X01764000000', '9935X82748000000',
'9935X83096000000', '9910X84427000000', '9910X00320000000',
'9923X00974000000', '9910X82231000000', '0025M00092000000',
'8000T01690000000', '0339A00050000000', '9929X01969000000',
'9929X50222000000', '9910X01536000000', '9929X87070000000',
'9935X88031000000', '9929X87932000000', '9910X82326000000',
'9844X00704000000', '9946X88100000000', '9935X82988000000',
'9935X88526000000', '9946X84209000000', '9929X84658000000',
'9929X87662000000', '9910X84401000000', '9844X00304000000',
'0096F00105000000', '9929X00356000000', '9935X83491000000',
'9946X84724000000', '9946X87720000000', '9935X00033000000',
'9946X82729000000', '0131C00147000000', '9929X87661000000',
'0024D00279000000', '9929X50027000000', '9946X88148000000',
'9923X87794000000', '9946X84275000000', '9905X00025000000',
'9929X01323000000', '9946X87846000000', '9905X01710000000',
'0050K00052000000', '9946X85037000000', '9910X00064000000',
'9929X86678000000', '9929X86648000000', '9844X00657000000',
'9929X87058000000', '9905X01244000000', '0050K00157000000',
'9935X83304000000', '9844X00418000000', '9929X00183000000',
'9929X86746000000', '9946X83388000000', '9910X82739000000',
'9929X85900000000', '9929X83080000000', '9923X00247000000',
'9935X82663000000', '9935X83030000000', '0421F00093000000',
'9905X82146000000', '9935X83700000000', '0011A00166000000',
'8000T01785000000', '0942L00335000000', '9929X84159000000',
'9905X50248000000', '9935X83272000000', '0241K00291000000',
'9935X00364000000', '9935X88304000000', '9923X87766000000',
'9905X83021000000', '9935X83330000000', '9929X87484000000',
'9935X82893000000', '9946X88302000000', '9929X00076000000',
'9929X84335000000', '0050L00270000000', '9935X83510000000',
'0086N00185000200', '8000T00281000000', '9910X82538000000',
'0018A00252000000', '0052G00150000000', '9946X88177000000',
'9911X85897000000', '9923X87447000000', '9905X83462000000',
'9946X01819000000', '9946X84286000000', '0222N00047000000',
'9905X01845000000', '9910X82359000000', '9935X50185000000',
'9910X82789000000', '9935X88316000000', '9910X00592000000',
'9809X84062000000', '9946X83763000000', '8000T00424000000',
'9923X87810000000', '9935X82414000000', '9946X85387000000',
'1100B00155000000', '9946X82676000000', '9841X00141000000',
'9910X00619000000', '9935X00911000000', '9946X00068000000',
'9946X81026000000', '9910X84625000000', '0098P00064000000',
'1658M00433000000', '9910X00956000000', '9946X00322000000',
'9946X83853000000', '9929X84399000000', '9844X00507000000',
'9841X00169000000', '9809X84060000000', '9905X83786000000',
'9923X84338000000', '9935X82471000000', '9923X00571000000',
'9910X84231000000', '0034K00043000000', '1104S00179000000',
'9809X00109000000', '9910X82031000000', '0997C00237000001',
'1658M00026000000', '9929X83910000000', '9946X83396000000',
'9946X88539000000', '9946X82565000000', '9935X88719000000',
'9929X00629000000', '9923X82068000000', '9910X82170000000',
'9923X82073000000', '9905X00191000000', '9946X87845000000',
'9946X85595000000', '9929X88347000000', '9946X84194000000',
'9923X00449000000', '9910X84272000000', '9946X84338000000',
'9935X87839000000', '9946X00489000000', '9946X83403000000',
'0510C00030000000', '0348P00370000000', '0022M00038000000',
'9929X01371000000', '9929X87307000000', '9946X88408000000',
'9910X83998000000', '9929X85861000000', '9905X00779000000',
'9935X82671000000', '0156C00168000000', '9946X01612000000',
'9929X83097000000', '9929X01055000000', '9905X00123000000',
'9923X87949000000', '9946X00570000000', '9946X83168000000',
'0507D00010000000', '9946X88420000000', '9841X00101000000',
'9905X83749000000', '9935X82049000000', '9844X00476000000',
'9946X82860000000', '9905X00200000000', '9946X88465000000',
'9935X83756000000', '9946X01101000000', '9923X00490000000',
'9929X86282000000', '9946X84029000000', '9929X00766000000',
'9923X84644000000', '9923X00120000000', '0284L00184000100',
'9929X86373000000', '9929X01617000000', '9929X84912000000',
'9946X50494000000', '9946X82086000000', '9935X83469000000',
'9905X01862000000', '9905X00109000000', '9929X83702000000',
'9910X00709000000', '0042B00020000000', '9905X00331000000',
'9844X00504000000', '9946X82467000000', '9809X83048000000',
'9923X00246000000', '9946X82644000000', '9946X88468000000',
'9946X50294000000', '9910X00104000000', '9946X88470000000',
'9905X00027000000', '0716R00378000200', '9905X82582000000',
'9946X83175000000', '9844X00101000000', '9946X85173000000',
'9844X80006000000', '9923X00827000000', '9935X83685000000',
'0050K00119000000', '9946X85035000000', '9929X85971000000',
'9935X83036000000', '9946X00491000000', '9923X00759000000',
'1846C00215000000', '0083K00323000000', '9923X00294000000',
'8000T00376000000', '9929X01534000000', '9935X88005000000',
'9946X82078000000', '9910X00841000000', '9905X00578000000',
'9929X01388000000', '9946X87903000000', '9923X84673000000',
'0608G00042000000', '0162G00150000000', '8000T03026000000',
'9946X00909000000', '9923X88341000000', '1203H00130000000',
'9935X83314000000', '9905X00951000000', '0391S00042000000',
'9905X00243000000', '9929X00401000000', '0156B00314000000',
'9929X01425000000', '9929X86778000000', '9929X87807000000',
'9935X83346000000', '9935X82376000000', '8000T02037000000',
'9935X83546000000', '9935X82577000000', '9929X83071000000',
'8000T03573000000', '0080H00007000000', '9946X84672000000',
'9935X88264000000', '9946X88380000000', '8000T01382000000',
'9946X01338000000', '2018S00100000100', '9946X88693000000',
'9929X87175000000', '0222N00033000000', '0388L00098000000',
'9946X85168000000', '9946X82638000000', '9946X00298000000',
'0564S00031000000', '9935X83367000000', '0050K00100000A00',
'9946X50465000000', '9844X00483000000', '9905X83648000000',
'9946X01755000000', '9946X01216000000', '9910X00894000000',
'9929X01839000000', '9929X87751000000', '9935X82223000000',
'9929X01554000000', '9935X88714000000', '1203A00107000000',
'9908X82856000000', '9935X83246000000', '0049R00220000000',
'0925G00053000100', '0002K00010000001', '9910X82494000000',
'0662L00109000000', '9905X50113000000', '9929X87589000000',
'9923X87452000000', '9946X85179000000', '9910X84202000000',
'9910X82428000000', '9923X87443000000', '9946X84188000000',
'9946X01726000000', '9905X01414000000', '9946X85267000000',
'9946X83322000000', '9929X00169000000', '9929X85844000000',
'9929X86829000000', '9935X83033000000', '0310F00026000000',
'9910X01057000000', '9905X83907000000', '9923X82404000000',
'9946X83019000000', '9935X00152000000', '0570F00400000000',
'9910X82349000000', '9910X82419000000', '9946X82801000000',
'9844X00663000000', '9929X01206000000', '9905X01344000000',
'9905X83606000000', '9935X82994000000', '9923X00854000000',
'9923X00388000000', '9935X82753000000', '0084L00068000B00',
'9946X84870000000', '9929X85750000000', '9910X84377000000',
'0716R00378000100', '9905X82175000000', '9910X84362000000',
'9929X82202000000', '9946X82892000000', '9946X01204000000',
'0014E00240000000', '9905X01449000000', '8000T01381000000',
'9935X83502000000', '9905X82723000000', '0614N00076000000',
'9946X84303000000', '0027B00102000000', '9923X00522000000',
'9905X84030000000', '0028A00124000000', '9946X85154000000',
'9929X85483000000', '9929X84722000000', '9935X83228000000',
'9905X83159000000', '9935X88254000000', '9905X84064000000',
'9908X82946000000', '9929X85734000000', '0326D00012000000',
'9929X01460000000', '9929X84430000000', '9946X83272000000',
'9929X83485000000', '9841X82009000000', '9809X00141000000',
'9935X88362000000', '9935X82889000000', '9935X80008000002',
'9905X00920000000', '9929X87619000000', '0131C00165000000',
'9929X81154000000', '9946X82646000000', '9929X87219000000',
'0738M00192000000', '9880X50062000001', '0049N00140000D00',
'0125R00220000000', '9905X83538000000', '9935X83250000000',
'9935X50195000000', '9910X84017000000', '1223R00279000000',
'0506N00003000000', '9905X83955000000', '9923X00572000000',
'9910X01622000000', '9929X83873000000', '9910X00975000000',
'9946X84733000000', '9844X00127000000', '9935X00360000000',
'9910X84466000000', '9929X87794000000', '9929X50190000000',
'0395L00207000000', '0084M00336000000', '0048S00266000000',
'9946X88626000000', '9946X83719000000', '9905X00270000000',
'9905X82396000000', '9905X83717000000', '0460P00259000000',
'9923X00659000000', '9929X83238000000', '0066E00158000000',
'9935X82545000000', '9844X00628000000', '9844X82025000000',
'9910X81054000000', '9935X82202000000', '2009R00325000000',
'0002M00284000000', '9935X82938000000', '9946X87832000000',
'9929X86004000000', '9946X82209000000', '9910X83974000000',
'9935X83097000000', '9935X00322000000', '0009A00007000B00',
'9809X84038000000', '9935X82406000000', '9905X80014000000',
'0525G00070000000', '9929X87988000000', '9929X86218000000',
'0103L00209000000', '9929X88243000000', '9923X01081000000',
'9923X84570000000', '9923X88231000000', '9923X00385000000',
'9929X87579000000', '9929X01392000000', '9929X83107000000',
'9929X83073000000', '0066E00046000000', '9910X84622000000',
'8000T00693000000', '9935X82323000000', '9946X00449000000',
'9923X88349000000', '9923X87917000000', '9910X01595000000',
'9841X00151000000', '0718B00092000000', '9935X83757000000',
'9809X84024000000', '9923X00150000000', '9809X83019000000',
'9935X83580000000', '9946X82346000001', '9946X82346000000',
'9946X83654000000', '9946X85496034600', '9946X01874000000',
'9929X50159000000', '9946X83739000000', '9809X84049000000',
'9946X83549000000', '9923X00324000000', '9908X82945000000',
'9946X50020000000', '0084A00077000000', '9935X83511000000',
'9946X50255000000', '9946X01777000000', '9923X87919000000',
'9946X84849000000', '9935X82995000000', '9946X84784000000',
'9910X01534000000', '0162P00112000000', '9910X00625000000',
'9935X87912000000', '9923X88073000000', '9935X83679011200',
'9809X84012000000', '9929X86679000000', '9946X84025000000',
'9946X00818000000', '9809X00203000000', '9929X00321000000',
'9905X83143000000', '9946X82211000000', '9929X84593000000',
'9946X85034000000', '9946X01164000000', '9946X00736000000',
'9946X88249000000', '0310R00264000000', '9929X86200000000',
'9929X87494000000', '0999B00009000000', '9946X01728000000',
'9946X82671000000', '9929X87865000000', '9946X84736000000',
'9935X00636000000', '1421C00171000000', '9929X00858000000',
'9935X88143000000', '9935X00051000000', '9946X00995000000',
'9910X84018000000', '9935X00474000000', '9946X83706000000',
'9929X84709000000', '9929X00227000000', '0050K00265000000',
'8000T00167000000', '9908X82858000000', '9809X50012000000',
'9910X01250000000', '9923X88076000000', '9929X87806000000',
'9946X88595000000', '9929X00242000000', '9923X84573000000',
'9905X01662000000', '9929X01309000000', '8000T02380000000',
'9905X01582000000', '9905X83491000000', '9929X87971000000',
'9946X50033000000', '9929X87313000000', '9923X87680000000',
'9910X00758000000', '9946X88185000000', '9935X88699000000',
'9929X88221000000', '9923X84529000000', '9910X84621000000',
'9929X01148000000', '9946X83907000000', '9910X82468000000',
'9905X50039000000', '9935X82355000000', '9923X00003000000',
'9929X00571000000', '9946X88156000000', '9929X00428000000',
'9946X82986000000', '9923X84310000000', '9910X00705000000',
'9923X00784000000', '9929X87570000000', '0382G00202000000',
'9905X83647000000', '8000T02050000000', '9844X00235000000',
'0119S00103000100', '0611C00220000000', '0811F00284000001',
'9929X00345000000', '8000T01477000000', '9910X82601000000',
'9935X82601000000', '9929X83087000000', '9929X00106000000',
'0020R00309000000', '9905X00286000000', '9935X01152000000',
'9929X84061000000', '9935X50020000000', '9935X88431000000',
'0175C00225000A00', '9905X83739000000', '0050K00028000000',
'9946X01139000000', '9946X84787000000', '9905X83515000000',
'0078S00214000000', '9946X01629000000', '9935X82743000000',
'9844X00245000000', '9905X01655000000', '9946X84333000000',
'9935X82710000000', '9946X01571000000', '9929X00717000000',
'9946X00474000000', '9905X83895000000', '9905X83277000000',
'9946X88254000000', '9923X82040000000', '9809X83034000000',
'9946X84432000000', '9935X82496000000', '9935X87816000000',
'0175P00290000000', '1223R00282000000', '9809X00135000000',
'0084G00047000A00', '9935X00526000000', '9910X83857000000',
'0883A00025000100', '9910X84176000000', '9905X82791000000',
'9935X50146000000', '9910X01163000000', '9946X82851000000',
'9929X01812000000', '9923X88453000000', '9929X86967000000',
'9910X01053000000', '9929X01086000000', '9910X83800000000',
'9923X00625000000', '9946X84835000000', '9946X01738000000',
'9929X88159000000', '1078P00260000000', '9905X01875000000',
'9809X00090000000', '9935X87830000000', '9844X00656000000',
'9929X01326000000', '9929X01413000000', '9935X50291000000',
'9929X83824000000', '9929X85482000000', '9929X84964000000',
'9910X82637000000', '9910X84020000000', '9946X83277000000',
'9929X82627000000', '9910X84335000000', '0050J00027000000',
'9946X50323000000', '9923X87566000000', '9923X84465000000',
'9908X82947000000', '9905X83551000000', '9946X83577000000',
'9935X88712000000', '9935X01140000000', '9905X82929000000',
'9929X50073000000', '8000T03249000000', '9935X82158000000',
'9923X00400000000', '9841X00139000000', '9946X00108000000',
'9946X85004000000', '1223R00276000000', '9923X88079000000',
'9929X85751000000', '9946X87987000000', '8000T02041000000',
'0026P00065000000', '9946X88276000000', '9946X00642000000',
'0048S00267000000', '9905X00983000000', '9923X88179000000',
'9935X83605000000', '9929X87860000000', '9844X00200000000',
'9935X82760000000', '9905X00574000000', '9910X80027000000',
'9923X88102000000', '1999K00014000000', '9946X82279000000',
'9841X50003000000', '9929X85904000000', '9946X84399000000',
'9946X01321000000', '9946X85068000000', '9946X84294000000',
'9910X00909000000', '9935X01033000000', '9935X00177000000',
'9929X00020000000', '9946X00668000000', '9935X82825000000',
'9935X83489000000', '9923X00048000000', '9905X01047000000',
'9910X00614000000', '9923X87947000000', '9946X87975000000',
'0122C00069000000', '9935X83112000000', '9935X83834000000',
'0050K00271000000', '9946X00502000000', '9935X88026000000',
'9844X00548000000', '9929X00349000000', '9923X84571000000',
'9935X83233000000', '9935X83478000000', '9935X00375000000',
'9946X84084000000', '9929X00549000000', '9809X83041000000',
'9923X88020000000', '9946X87681000000', '1003L00275000000',
'9935X88647000000', '0815A00131000000', '9929X86964000000',
'9946X50153000000', '9923X84665000000', '9935X82199000000',
'9910X84623000000', '9935X82214000000', '9929X87423000000',
'9905X50101000001', '9923X00253000000', '9844X00321000000',
'9929X83224000000', '9946X00448000000', '9923X87547000000',
'9929X00054000000', '9923X88056000000', '9905X84020007A00',
'0382A00254000000', '9946X01457000000', '9905X01870000000',
'9905X50033000000', '0024N00043000A00', '9929X01700000000',
'9935X88094000000', '9929X82851000000', '9946X84112000000',
'0297J00150000000', '0162R00237000000', '9923X00245000000',
'9905X01730000000', '9935X87870000000', '9946X83363000000',
'9946X84089000000', '9844X00427000000', '9929X86061000000',
'0141C00180000000', '9946X88248000000', '9905X00190000000',
'9946X82711000000', '0138K00150000000', '9929X00979000000',
'0001C01662010600', '9841X50014000000', '9946X88102000000',
'9946X84785000000', '9946X85565000000', '9809X84066000000',
'9946X82105000000', '9935X83765000000', '9946X88648000000',
'9935X00340000000', '9908X82860000000', '9908X82901000000',
'9841X00157000000', '9946X85557000000', '9929X86322000000',
'0940K00279000000', '9923X87760000000', '9935X83382000000',
'9946X82682000000', '9946X84348000000', '9809X82053000000',
'0023S00258000000', '9905X83576000000', '9910X80031000000',
'9905X84014001D00', '9905X82554000000', '9910X01123000000',
'9946X50149000000', '9946X00590000000', '9946X83738000000',
'9905X83592000000', '0941E00118000000', '8000T00559000000',
'9929X84470000000', '9929X85907000000', '9935X50016000000',
'9946X82534000000', '9910X01055000000', '9910X82627000000',
'9946X87827000000', '9809X00227000000', '9946X85429000000',
'9946X82487000000', '9946X82837000000', '0392C00152000000',
'9929X86315000000', '9946X50518000000', '9929X01576000000',
'9929X87181000000', '9929X85319000000', '9935X01224000000',
'0611B00092000000', '9929X01415000000', '9809X00143000000',
'9905X83170000000', '9946X50412000000', '9929X85480000000',
'9935X83374000000', '9910X80023000000', '0048S00224000000',
'9935X88177000000', '9946X84447000000', '9844X82057000000',
'9809X00062000000', '9929X88180000000', '1104M00308000000',
'9935X83136000000', '9923X82363000000', '0036S00224000000',
'9946X00799000000', '9946X00303000000', '9923X82177000000',
'9946X83273000000', '0022M00033000000', '9910X84128000000',
'0011M00178000000', '9946X83446000000', '9923X00215000000',
'9905X00795000000', '0972R00200000000', '0154S00033000000',
'9946X84423000000', '0343B00023000100', '9910X82491000000',
'9929X86600000000', '9946X81021000000', '0205H00259000000',
'9935X50279000000', '9946X88062000000', '9905X84095000000',
'9935X00349000000', '9908X82867000000', '9910X81086000000',
'9946X88288000000', '9905X83388000000', '0023F00060000B00',
'9923X00057000000', '0209C00069000000', '9929X85558000000',
'0033D00203000000', '9905X82023000000', '9929X00692000000',
'9923X88410000000', '9946X84332000000', '9905X82134000000',
'9946X88116000000', '9809X83003000000', '9929X84013000000',
'9935X88319000000', '0191N00046000000', '9946X83068000000',
'9841X00106000000', '9910X84560000000', '0348N00211000000',
'9844X00046000000', '9809X83053000000', '9946X88172000000',
'9946X82694000000', '9946X82557000000', '0198H00030000000',
'0808N00260000000', '9929X87387000000', '9929X87081000000',
'9946X00941000000', '9929X00552000000', '9929X86617000000',
'9929X87757000000', '9923X87826000000', '9935X87827000000',
'9844X00621000000', '9929X86966000000', '9908X83030000000',
'9910X01348000000', '8000T00034000000', '9946X83667000000',
'9946X01756000000', '0544M00132000000', '9929X84606000000',
'9905X83824000000', '9809X80000000000', '1510R00318000000',
'9946X00495000000', '9910X01151000000', '0363C00140000100',
'9929X00028000000', '9809X84026000000', '9929X86368000000',
'9929X01788000000', '9946X50357000000', '9946X00875000000',
'9929X00395000000', '9923X87470000000', '9935X82304000000',
'9935X82884000000', '9929X87404000000', '9935X83364000000',
'9844X00155000000', '9935X01126000000', '9923X00510000000',
'9935X88306000000', '9923X84596000000', '9946X84750000000',
'9905X82258000000', '9929X87295000000', '0831A00305000000',
'0829N00025000100', '9929X87670000000', '9923X84410000000',
'9923X82165000001', '0222N00091000000', '9905X82256000000',
'0738A00162000000', '9844X00744000000', '9923X82354000000',
'0052B00012000001', '9929X83362000000', '9929X85859000000',
'9910X01288000000', '9923X00287000000', '9923X00498000000',
'9935X82912000000', '9905X82812000000', '9910X80014000000',
'9905X84033000000', '9935X83270000000', '0024H00100000000',
'0451B00646000000', '9929X86748000000', '9946X82168000000',
'9905X83206000000', '9923X00998000000', '9935X00809000000',
'9946X82535000000', '9946X50196000000', '9905X01035000000',
'0281M00068000000', '9946X83855000000', '0292C00191000000',
'9929X00710000000', '9946X01320000000', '9946X85069000000',
'8000T00358000000', '9929X01465000000', '9929X86569000000',
'9929X00021000000', '9905X00223000000', '9844X00299000000',
'0050K00155000000', '9905X01656000000', '9910X00157000000',
'9946X84049000000', '9946X01129000000', '9905X82271000000',
'9929X83408000000', '9905X00863000000', '9929X01879000000',
'9946X00691000000', '9905X01557000000', '9905X82726000000',
'9929X87973000000', '9929X00686000000', '9946X82451000000',
'9935X82391000000', '9809X00278000000', '9935X82516000000',
'9946X87843000000', '9935X00503000000', '9923X88169000000',
'9923X88114000000', '9929X00439000000', '9946X88365000000',
'9905X01550000000', '9946X83178000000', '8000T01779000000',
'9935X83015000000', '9929X82520000000', '9946X87809000000',
'9935X50039000000', '9905X01694000000', '1274H00165000000',
'9935X83558000000', '0119S00102000000', '9929X85857000000',
'9946X84117000000', '9923X82179000000', '9946X82725000000',
'9841X00107000000', '9910X84126000000', '9905X01964000000',
'9946X83998000000', '9946X84297000000', '0010P00082000000',
'9905X82545000000', '9946X00913000000', '9929X00206000000',
'9905X00976000000', '9905X01872000000', '9905X83834000000',
'9946X01138000000', '0009N00156000000', '0556B00262000000',
'9923X00739000000', '9910X82365000000', '9929X87405000000',
'8000T00037000000', '9946X87916000000', '9905X83173000000',
'9929X84021000000', '9923X88094000000', '9910X00676000000',
'9923X82293000000', '9923X87422000000', '9929X86180000000',
'0301N00129000000', '1076R00261000000', '9946X50462000000',
'9946X87881000000', '9929X86822000000', '0087G00294000002',
'9809X82056000000', '9946X01682000000', '0083K00210000000',
'0749H00171000000', '0475F00262000000', '0291G00048000000',
'9935X88918000000', '0130P00314000001', '8000T00615000000',
'9935X88048000000', '9905X82448000000', '9929X86172000000',
'9946X88132000000', '9929X84370000000', '9929X87167000000',
'8000T02934000000', '9905X50025000000', '9809X00233000000',
'9923X00706000000', '9946X82310000000', '9844X00276000000',
'9935X50065000000', '9946X00027000000', '9935X82679000000',
'9910X83831000000', '9935X82688000000', '9946X87689000000',
'9929X84940000000', '9946X50220000000', '9905X00503000000',
'9910X84597000000', '9910X84550000000', '9946X01512000000',
'9905X01153000000', '9946X01060000000', '9809X00242000000',
'9905X83368000000', '9929X87184000000', '9946X82680000000',
'9935X50137000000', '9946X85164000000', '9946X88180000000',
'9923X00624000000', '9905X01691000000', '9929X85783000000',
'9946X00493000000', '9929X86834000000', '9946X84051000000',
'9929X88359000000', '9946X50455000000', '9923X87414000000',
'9905X00104000000', '9923X82050000000', '0016K00129000000',
'0365E00097000000', '9905X00724000000', '9929X85686000000',
'0236S00341000000', '9935X88299000000', '9946X87750000000',
'9910X00554000000', '9910X01286000000', '9905X00811000000',
'9923X82362000000', '8000T00371000000', '1355H00100000000',
'9923X87431000000', '9935X82240000000', '9929X01205000000',
'0056P00048000A00', '9844X00404000000', '9946X82294000000',
'9946X82849000000', '9935X00132000000', '9946X82094000000',
'9946X83972000000', '9905X01684000000', '0050K00100000000',
'0443K00002000000', '9946X83080000000', '9929X87841000000',
'9929X50087000000', '9905X01301000000', '0704F00242000000',
'9935X82997000000', '9923X88173000000', '9935X88539000000',
'9910X84325000000', '9923X00864000000', '9946X88128000000',
'9929X86100000000', '0010N00104000000', '9929X01628000000',
'9923X88385000000', '9910X00773000000', '9910X84242000000',
'9935X82084000000', '9923X82394000000', '0124J00104000000',
'9929X01463000000', '8000T02092000000', '9929X83254000000',
'9929X87386000000', '9910X84352000000', '9910X00043000000',
'9946X83107000000', '9946X82906000000', '0140R00283000000',
'9910X00836000000', '9844X00047000000', '9935X00142000000',
'9929X87617000000', '9844X00659000000', '9946X50380000000',
'0305H00166000000', '0194L00176000000', '9946X85338000000',
'9908X83046000000', '9935X88458000000', '9923X00732000000',
'9929X83570000000', '9946X83657000000', '9946X84678000000',
'9946X00619000000', '9923X87469000000', '8000T02033000000',
'8000T00035000000', '9910X00454000000', '9935X82064000000',
'9923X84422000000', '9935X82905000000', '9946X00944000000',
'9935X88318000000', '9946X84971000000', '9923X88057000000',
'9929X01948000000', '9923X00293000000', '9946X00972000000',
'9946X01809000000', '0510J00003000000', '2012M00060000000',
'9910X82360000000', '9905X00941000000', '9946X82151000000',
'9946X82940000000', '9946X84113000000', '9946X83748000000',
'9905X83198000000', '9929X86365000000', '9935X87890000000',
'9935X83039000000', '9929X01441000000', '9905X82640000000',
'8000T00121000000', '9929X86296000000', '9929X01285000000',
'0831P00111000000', '9946X82341000000', '9935X82917000000',
'0050K00177000000', '9923X88195000000', '9929X88226000000',
'9844X00698000000', '9946X84818000000', '9910X84183000000',
'9905X00982000000', '1242L00115000000', '9923X88025000000',
'9910X84383000000', '9946X00603000000', '9935X82787000000',
'9841X00206000000', '9910X84019000000', '9935X83300000000',
'9929X82349000000', '9946X87755000000', '9929X00153000000',
'9844X00121000000', '9929X86073000000', '9929X84543000000',
'9905X00443000000', '9929X83749000000', '9946X50349000000',
'0381B00259000000', '9946X01870000000', '9946X85601000000',
'9844X00303000000', '9809X00290000000', '9929X00476000000',
'9905X82904000000', '9910X82556000000', '9935X82826000000',
'1757D00136000000', '9905X00415000000', '9929X01894000000',
'9923X88606000000', '0026E00321000000', '9923X88197000000',
'9929X83973000000', '9946X85281000000', '9929X86060000000',
'9923X00984000000', '0180E00168000000', '9946X85527000000',
'9929X84906000000', '9905X00630000000', '9929X87245000000',
'9935X83604000000', '0131J00319000000', '9946X88360000000',
'9929X01620000000', '0049N00131000000', '9946X85600000000',
'0125M00388000000', '9946X50317000000', '0560B00122000000',
'9935X01088000000', '9910X00892000000', '9929X00233000000',
'0426M00225000000', '9946X85273000000', '9929X00122000000',
'9946X83508000000', '9946X83142000000', '9910X01349000000',
'9910X00832000000', '9929X87599000000', '9946X87898000000',
'9910X83883000000', '9935X83767000000', '9929X00165000000',
'9910X00613000000', '9905X01253000000', '9929X86024000000',
'9929X87146000000', '9946X84245000000', '9923X87868000000',
'9935X00685000000', '9929X88048000000', '9923X82202000000',
'9923X87912015100', '9946X01028000000', '9809X00176000000',
'9905X82070000000', '9946X88436000000', '9946X88429000000',
'9910X01167000000', '9946X01839000000', '9935X82404000000',
'9946X50546000000', '9809X00076000000', '9929X00118000000',
'0050K00240000000', '9929X85025000000', '9809X82047000000',
'9946X01389000000', '9946X82814000000', '9929X83240000000',
'9929X85014000000', '1676A00068000000', '1241L00380000000',
'9929X84420000000', '9929X84373000000', '9929X82853000000',
'9929X01171000000', '9910X82267000000', '9946X85619000000',
'9946X84213000000', '0035R00120000001', '9946X82063000000',
'9935X83207000000', '9929X85247000000', '9935X82716000000',
'9905X00381000000', '9809X83049000000', '9929X82247000000',
'0117N00027000100', '9910X00569000000', '9929X84668000000',
'9935X83755000000', '9929X80097000000', '9946X83444000000',
'0067P00332000000', '9905X83756000000', '9923X82453000000',
'9908X82943000000', '9923X00070000000', '9905X00670000000',
'9946X85114000000', '1346N00275000000', '9905X01496000000',
'9929X85832000000', '9923X87827000000', '0222E00193000000',
'9844X00045000000', '9935X01268000000', '2372M00010000000',
'9910X84592000000', '0775D00075000000', '9946X00026000000',
'9905X01859000000', '9923X88588000000', '9908X82909000000',
'0049N00074000000', '9946X00726000000', '9923X84710000000',
'9946X83983000000', '9929X88225000000', '9923X87644000000',
'9946X82512000000', '9929X00319000000', '9905X01915000000',
'9929X84555000000', '9910X00217000000', '9929X01789000000',
'9946X00539000000', '9935X88359000000', '9910X82415000000',
'9923X87678000000', '9946X82918000000', '9946X85490000000',
'8000T01846000000', '9946X85418000000', '9946X84092000000',
'9935X88421000000', '9929X01173000000', '8000T00271000000',
'9910X84509000000', '9946X00874000000', '9929X85474000000',
'9923X88454000000', '9923X88265000000', '9910X84449000000',
'9923X82459000000', '9935X00214000000', '9910X83880000000',
'9946X82011000000', '9935X01051000000', '9929X84152000000',
'9946X00694000000', '9929X87348000000', '9935X00771000000',
'9935X88281000000', '8000T00161000000', '9923X88140000000',
'9935X82243000000', '9935X00342000000', '9929X86327000000',
'0305R00500000000', '9946X88484000000', '9935X82171000000',
'9905X00495000000', '9923X84575000000', '9905X00816000000',
'9935X88648000000', '9809X84030000000', '0645E00256000000',
'0023F00247000A00', '0669N00111000000', '9905X82819000000',
'9809X81002000000', '9946X82922000000', '9923X00222000000',
'9935X83737000000', '9910X84627000000', '9929X01281000000',
'9809X84018000000', '9935X82913000000', '9929X87885000000',
'9929X01639000000', '9946X84191000000', '9905X83514000000',
'9905X83751000000', '9929X85244000000', '0849J00110000000',
'9929X86202000000', '9908X82887000000', '9905X01408000000',
'9910X82567000000', '9929X87908000000', '9946X83813000000',
'9946X85103000000', '9935X00479000000', '9935X82418000000',
'9923X88240000000', '0233C00275000001', '9910X00250000000',
'8000T00622000000', '9910X82069000000', '9908X00180000000',
'9929X83718000000', '9946X00718000000', '1209D00031000000',
'9935X83324000000', '9929X87754000000', '9946X85451000000',
'0049E00031000A00', '9908X82852000000', '9910X82695000000',
'8000T02034000000', '9935X01292000000', '9929X84471000000',
'9929X00478000000', '9929X87218000000', '9935X01206000000',
'9935X87907000000', '9946X84781000000', '9935X88283000000',
'9929X82511000000', '9935X88310000000', '9935X81004000000',
'9905X84022000000', '9905X82453000000', '9923X82419000000',
'9905X83769000000', '9946X50171000000', '9910X00721000000',
'9923X82418000000', '9946X01281000000', '9946X83726000000',
'9946X88437000000', '9935X83234000000', '9946X84755000000',
'9929X87532000000', '9923X88161000000', '9923X87486000000',
'9946X85183000000', '9935X87895000000', '9935X83158000000',
'9946X87991000000', '9929X84636000000', '9935X88054000000',
'9923X87436000000', '8000T00316000000', '0006S00080000000',
'9905X83795000000', '9946X00111000000', '8000T02018000000',
'9923X82215000000', '9929X01337000000', '9910X84331000000',
'9935X83549000000', '9910X82269000000', '9905X83423000000',
'9905X83624000000', '9946X00738000000', '9923X84688000000',
'9929X87289000000', '0003R00188000000', '0024J00388000000',
'9935X00612000000', '9841X00037000000', '9910X01381000000',
'9946X84457000000', '9910X01079000000', '9809X00194000000',
'9935X82524000000', '0879C00166000000', '0163K00150000000',
'9809X82028000000', '9946X00024000000', '9946X82962000000',
'9905X00794000000', '9923X88443000000', '9946X85579000000',
'9935X87851000000', '9905X83234000000', '9905X82783000000',
'9910X00462000000', '9923X84376000000', '9935X50295000000',
'9935X88723000000', '9946X82787000000', '8000T01371000000',
'9946X82618000000', '9946X88068000000', '9929X85216000000',
'9946X01267000000', '1504M00223000000', '9905X82902000000',
'9929X83261000000', '9923X82303000000', '8000T03640000000',
'0321S00025000000', '9935X88451000000', '9905X50122000000',
'0856K00008000000', '9923X87549000000', '9935X83518000000',
'9946X84999000000', '9929X87026000000', '9935X01192000000',
'9946X00348000000', '9910X82535000000', '9923X84608000000',
'9923X00871000000', '9946X50039000000', '9929X01430000000',
'9935X83343000000', '9929X85019000000', '9929X87852000000',
'9929X87849000000', '9923X84686000000', '9905X00182000000',
'9905X00094000000', '9946X00209000000', '9946X85410000000',
'9929X00026000000', '9910X00951000000', '9946X84687000000',
'9946X00791000000', '0222A00112000000', '9929X85342000000',
'8000T03096000000', '9910X82335000000', '9923X88267000000',
'9935X00626000000', '9929X00465000000', '9910X84620000000',
'9905X00108000000', '9929X86008000000', '9923X88538000000',
'9946X83250000000', '0758K00098000000', '9905X83414000000',
'9929X86857000000', '9935X88151000000', '9905X82697000000',
'9929X86783000000', '9905X83566000000', '9910X82218000000',
'9929X86767000000', '9929X86103000000', '9923X82378000000',
'9905X83556000000', '9935X83523000000', '9923X82444000000',
'9910X00958000000', '9929X84662000000', '9946X01798000000',
'0140G00124000000', '9946X01214000000', '9905X50031000000',
'9923X82125000000', '9929X85698000000', '9923X00996000000',
'9946X85584000000', '9946X83794000000', '9923X88605000000',
'0084A00079000000', '9929X00483000000', '9935X82170000000',
'9923X82481000000', '9923X00221000000', '9935X01342000000',
'9929X00449000000', '9946X88039000000', '9905X83017000000',
'9905X84077000000', '9946X84145000000', '9935X88059000000',
'9929X86955000000', '1911H00335000000', '0130P00275000000',
'9929X83503000000', '9929X01932000000', '9905X00137000000',
'9946X01637000000', '9946X00020000000', '9929X85599000000',
'9910X84316000000', '9929X01721000000', '9911X85894000000',
'9946X83581000000', '9929X84283000000', '9929X01921000000',
'9946X01642000000', '9929X83426000000', '9905X82219000000',
'9946X85386000000', '9905X01526000000', '0010P00084000000',
'9935X82019000000', '0080N00118000000', '9923X00485000000',
'1130H00327000000', '9910X01308000000', '9905X00226000000',
'9935X83409000000', '9935X83535000000', '0954E00205000000',
'9905X82629000000', '9935X82921000000', '9929X84544000000',
'9923X82409000000', '9923X87820000000', '0365J00079000000',
'9923X82225000000', '9935X88287000000', '9844X00272000000',
'9946X83860000000', '0131D00375000002', '8000T00267000000',
'9923X00306000000', '1355R00260000000', '9905X82233000000',
'0130R00306000000', '9923X00905000000', '9935X88093000000',
'9910X84376000000', '9905X01444000000', '9929X87866000000',
'9905X01551000000', '9905X01600000000', '9946X50325000000',
'9929X85332000000', '9923X88198000000', '9935X83041000000',
'9946X85142000000', '9929X85603000000', '9946X83630000000',
'0668L00026000000', '0046E00065000000', '9946X88184000000',
'0433K00181000000', '0048S00228000000', '1365L00323000000',
'9929X85860000000', '9905X01536000000', '0084K00028000200',
'9946X87857000000', '0381E00112000000', '9946X50391000000',
'9929X83370000000', '9923X87942000000', '9910X00460000000',
'9946X87704000000', '9923X82268000000', '9946X82119000000',
'9929X88039000000', '9935X88695000000', '9946X85041000000',
'9946X00034000000', '9935X82110000000', '9929X88070000000',
'0738M00202000000', '9905X84020007B00', '9935X00323000000',
'9809X83047000000', '9910X84341000000', '9946X83556000000',
'9923X88183000000', '9844X00106000000', '0832B00381000000',
'8000T01978000000', '9929X84171000000', '9905X01174000000',
'9929X00732000000', '9929X00339000000', '9929X88365000000',
'9923X84352000000', '0887A00240000G00', '9844X00693000000',
'9935X00328000000', '9905X01527000000', '9929X86536000000',
'9946X85497000000', '9929X86291000000', '9929X83091000000',
'9929X00382000000', '9929X00058000000', '9923X82145000000',
'9935X87825000000', '9923X00320000000', '9946X83904000000',
'9946X01197000000', '9946X83442000000', '9910X01615000000',
'9844X00688000000', '9844X00510000000', '9929X01917000000',
'9929X00660000000', '9923X88374000000', '9905X01908000000',
'9910X83922000000', '9910X83918000000', '9946X84229000000',
'9923X00919000000', '9929X01531000000', '9841X00055000000',
'8000T03095000000', '1832L00017000000', '9935X87876000000',
'0234L00225000000', '9946X84907000000', '9935X50201000000',
'9929X86249000000', '9929X83249000000', '0231N00156000000',
'9929X01208000000', '9929X86135000000', '9905X83024000000',
'9923X84464000000', '9929X88072000000', '9910X80066000000',
'9935X83777000000', '9844X81006000000', '8000T01433000000',
'9923X00326000000', '9910X01489000000', '9923X82475000000',
'9905X83710000000', '9908X82904000000', '9946X00562000000',
'9929X88017000000', '9910X82496000000', '9844X00152000000',
'9935X82744000000', '9923X50005000000', '9929X00341000000',
'9923X00553000000', '9929X00360000000', '0050L00274000000',
'9946X01483000000', '9935X87845000000', '9946X87762000000',
'9935X82975000000', '9923X82334000000', '9935X83316000000',
'9929X00788000000', '9910X01319000000', '9910X83864000000',
'9910X00188000000', '9935X88393000000', '9946X00152000000',
'9946X00730000000', '9910X50038000000', '0434S00100000000',
'9946X83119000000', '0063D00012000000', '9929X83558000000',
'9905X01116000000', '9946X84038000000', '0092P00125000000',
'9946X85249000000', '9935X01184000000', '9929X00624000000',
'0011A00191000A00', '9905X00350000000', '0810F00259000000',
'9923X00666000000', '9929X01625000000', '9929X87321000000',
'9923X01052000000', '9946X87715000000', '9910X82536000000',
'9946X50497000000', '9946X83980000000', '9923X00870000000',
'9905X82956000000', '0461C00117000000', '9929X85220000000',
'9908X83035000000', '9935X00679000000', '8000T01789000000',
'9844X82032000000', '9905X01577000000', '9929X83448000000',
'9929X84611000000', '9946X87958000000', '9929X84704000000',
'9935X83635000000', '9946X82822000000', '0716C00126000000',
'9929X01794000000', '9929X88360000000', '9923X88331000000',
'8000T03313000000', '9844X00169000000', '9935X83383000000',
'9929X00789000000', '0648R00401000000', '9929X01855000000',
'9908X82961000000', '0351M00360000000', '9910X84348000000',
'0121K00142000000', '9929X87951000000', '9946X82848000000',
'9929X84488000000', '9946X85095000000', '0950S00062000000',
'9929X87782000000', '9929X83534000000', '9910X01531000000',
'0056B00158000000', '9908X83045000000', '9929X85372000000',
'9905X00873000000', '9929X84708000000', '9946X50531000000',
'9905X01350000000', '9910X82437000000', '9946X85044000000',
'1519N00030000001', '9910X82582000000', '9946X88202000000',
'9923X88565000000', '9946X85537000000', '0602F00350000000',
'9923X00368000000', '9929X00694000000', '9935X01347000000',
'9905X83725000000', '0513G00018000000', '9905X82283000000',
'9905X01606000000', '9923X88270000000', '9946X83696000000',
'8000T03245000000', '9946X82997000000', '0050K00098000000',
'9946X88400000000', '9910X00435000000', '9946X83758000000',
'9910X00508000000', '9946X82165000000', '0886L00035000000',
'9929X00307000000', '9946X00587000000', '9905X82758000000',
'9946X00938000000', '0124N00215000000', '9946X85610000000',
'9844X00160000000', '9946X00769000000', '9929X84501000000',
'9923X00781000000', '9911X50111000000', '9946X82337000000',
'9946X83773000000', '9935X83764000000', '9910X83910000000',
'9935X82362000000', '9946X84888000000', '9946X00778000000',
'9929X85699000000', '9946X84934000000', '9946X88354000000',
'9929X84229000000', '9905X00854000000', '9935X83614000000',
'9946X82772000000', '9905X01210000000', '9923X88319000000',
'9905X83267000000', '9935X00982000000', '9929X87154000000',
'1506B00246000000', '9929X84873000000', '9929X01533000000',
'9946X84214000000', '9841X50012000000', '0668G00192000000',
'9929X00288000000', '9923X88497000000', '9929X83538000000',
'9929X01528000000', '9923X00369000000', '9910X84463000000',
'9905X83559000000', '9910X00424000000', '9910X82524000000',
'9946X88236000000', '9923X87995000000', '0265A00199000000',
'9929X83019000000', '0023J00104000000', '9905X00372000000',
'9935X83581000000', '9929X88074000000', '9929X85368000000',
'9946X87695000000', '9844X00746000000', '9905X83716000000',
'9946X84968000000', '9905X01178000000', '9929X88127000000',
'9923X88157000000', '9935X01361000000', '9929X84848000000',
'9946X82026000000', '9946X00761000000', '9905X83890000000',
'9844X82026000000', '9923X84331000000', '9923X84564000000',
'9946X83713000000', '9946X00131000000', '9946X84767000000',
'0010J00271000000', '0155L00387000100', '9905X82829000000',
'9935X00238000000', '9923X84463000000', '9946X85047000000',
'0190C00048000000', '9946X83005000000', '9935X83042000000',
'9809X00291000000', '9935X82047000000', '9946X84007000000',
'9910X84632000000', '9946X87775000000', '9809X00264000000',
'9935X83413000000', '9923X84528000000', '9929X50574000000',
'9946X50104000000', '9923X84636000000', '9929X01041000000',
'0362F00218000000', '0307M00267000000', '9910X01562000000',
'9923X84544000000', '9905X00959000000', '9946X82355000000',
'9910X84226000000', '9935X83149000000', '9929X87946000000',
'9929X84228000000', '9905X00675000000', '9935X82704000000',
'9935X88482000000', '9905X82161000000', '9923X87605000000',
'9905X83366000000', '9946X83685000000', '9844X00734000000',
'9923X82195000000', '9905X82108000000', '9809X84081000000',
'9946X01140000000', '9905X00865000000', '9929X00281000000',
'9929X87143000000', '9935X87819000000', '9905X82220000000',
'9905X00325000000', '9929X01106000000', '9946X83672000000',
'9923X87859000000', '9929X00841000000', '9809X00236000000',
'9929X00048000000', '9923X00799000000', '9935X83119000000',
'9946X01434000000', '9946X85627000000', '9946X84790000000',
'9844X00395000000', '0050K00183000100', '9809X00134000000',
'9923X87857000000', '0083K00275000000', '9908X82853000000',
'0663C00210000000', '9905X82918000000', '9946X88187000000',
'9908X82942000000', '0083S00159000000', '9929X88188000000',
'9935X88255000000', '9946X83989000000', '9929X84622000000',
'9809X00101000000', '9911X85898000000', '9929X86866000000',
'9935X00751000000', '9929X87979000000', '9929X86295000000',
'0741D00030000000', '9905X00473000000', '9929X88170000000',
'9905X00938000000', '9910X01191000000', '9946X81054000000',
'9809X84063000000', '9929X87294000000', '9946X87926000000',
'9946X87984000000', '9929X87255000000', '9929X88109000000',
'9946X83762000000', '9946X01421000000', '9844X00385000000',
'9946X87757000000', '9935X82430000000', '9935X00351000000',
'9905X00805000000', '9910X84080000000', '9935X00049000000',
'9809X84040000000', '9929X84971000000', '9929X00946000000',
'9935X50043000000', '9946X83585000000', '9929X88200000000',
'0131R00032000000', '9946X83087000000', '9946X88198000000',
'9841X82004000000', '9929X86278000000', '9929X83845000000',
'9946X82794000000', '9923X88444000000', '9946X85169000000',
'9910X84043000000', '9946X88402000000', '9946X00194000000',
'9905X83688000000', '9935X01284000000', '0272B00152000000',
'9905X83731000000', '9929X86323000000', '9929X85575000000',
'9929X01355000000', '9946X84302000000', '8000T01963000000',
'9910X83889000000', '9946X85358000000', '9923X82371000000',
'9910X00911000000', '9809X84045000000', '0101K00096000000',
'9844X00162000000', '9923X00677000000', '9929X84218000000',
'9923X84574000000', '9935X88494000000', '9905X83912000000',
'9946X84751000000', '9844X00585000000', '9905X00277000000',
'8000T02202000000', '9935X83582000000', '9929X00551000000',
'9910X01607000000', '9946X83281000000', '9929X82686000000',
'0080H00304000000', '9929X85825000000', '9905X00114000000',
'0039R00002000000', '9905X00362000000', '9929X00429000000',
'9946X00813000000', '0343B00023000000', '9946X82956000000',
'9946X82896000000', '9844X00167000000', '9923X00451000000',
'9946X50496000000', '9929X84877000000', '9923X87999000000',
'0382L00283000000', '9935X83086000000', '9946X88247000000',
'9946X82769000000', '9929X00995000000', '9923X82017000000',
'9946X85555000000', '9923X00077000000', '9910X01461000000',
'9910X84206000000', '9923X84478000000', '9905X82187000000',
'9905X01206000000', '9946X84976000000', '9935X01011000000',
'9929X85147000000', '9929X88209000000', '9929X88160000000',
'9929X50212000000', '9905X00359000000', '9910X84225000000',
'9923X88167000000', '9946X82344000001', '9844X00331000000',
'9910X82392000000', '9946X82820000000', '9905X82618000000',
'9946X01210000000', '0507L00012000000', '0524S00001000000',
'0717D00351000000', '9946X85045000000', '8000T01912000000',
'9905X00680000000', '9929X87758000000', '9929X85776000000',
'9935X01023000000', '9946X88382000000', '9935X82930000000',
'9935X83224000000', '9946X50064000000', '9935X88003000000',
'8000T01679000000', '8000T01348000000', '9929X87080000000',
'9935X01115000000', '9946X84749000000', '9935X83661000000',
'9910X84626000000', '9923X87864000000', '9908X82960000000',
'9929X87306000000', '9946X82088000000', '9929X83386000000',
'9910X01395000000', '9844X00627000000', '9905X83294000000',
'9929X01502000000', '9923X00412000000', '0382L00306000000',
'9946X80009000000', '9946X83935000000', '9929X87034000000',
'9923X88062000000', '9905X01024000000', '0422H00295000000',
'9946X87954000000', '9905X83887000000', '0236S00213000000',
'9935X83373000000', '9929X86641000000', '9809X00120000000',
'0195F00078000000', '9929X86203000000', '9929X85481000000',
'9929X01406000000', '9946X83355000000', '9905X83747000000',
'9935X82987000000', '9946X84778000000', '9929X00565000000',
'9935X88584000000', '9905X82286000000', '9946X01176000000',
'9905X00312000000', '9935X83135000000', '0280C00254000000',
'9946X83579000000', '9905X01618000000', '9935X00699000000',
'9923X87994000000', '9910X83797000000', '0738M00190000000',
'9923X88366000000', '0276F00144000000', '9910X01639000000',
'2275K00238000000', '1354H00083000100', '9946X87838000000',
'9935X82069000000', '9905X83990000000', '0163D00045000000',
'9929X00100000000', '9946X85347000000', '9844X00381000000',
'9946X00090000000', '9929X85691000000', '9935X82480000000',
'9935X01089000000', '9935X88395000000', '9929X88058000000',
'9923X88207000000', '9905X00551000000', '9923X84705000000',
'9935X83166000000', '9946X87810000000', '9935X00036000000',
'9809X00292000000', '9946X82917000000', '9844X00580013100',
'9923X82222000000', '9946X84216000000', '9935X82370000000',
'9935X82566000000', '9929X87338000000', '9946X83846000000',
'9946X82137000000', '0056P00071000000', '9923X00408000000',
'9905X01392000000', '9929X50106000000', '9923X82382000000',
'9905X00337000000', '9929X00844000000', '9910X01080000000',
'9946X84453000000', '9946X01847000000', '0154S00036000000',
'9946X85430000000', '8000T00506000000', '9923X88016000000',
'9935X83281000000', '9946X50150000000', '8000T01362000000',
'9923X87601000000', '9929X85259000000', '8000T00564000000',
'9923X84440000000', '1577N00048000000', '9910X84131000000',
'9946X84766000000', '0444J00009000000', '9923X82121000000',
'0025G00225000A00', '9929X85328000000', '9935X83652000000',
'9923X00517000000', '0997B00231000001', '0029G00241000000',
'9946X82843000000', '9923X82300000000', '9905X01019000000',
'9910X82178000000', '0450P00456000000', '9923X84314000000',
'9935X00750000000', '9910X82404000000', '9929X01345000000',
'9946X85090000000', '9946X82025000000', '9910X00114000000',
'9935X82664000000', '2090D00262000000', '9910X84643000000',
'9935X82313000000', '9905X00521000000', '9946X87859000000',
'2015D00267000000', '9935X88075000000', '9905X00007000000',
'9929X87009000000', '9844X00529000000', '9929X80062000000',
'9809X82004000000', '9905X01293000000', '9946X83186000000',
'9929X01051000000', '9946X82980000000', '9910X84081000000',
'9910X82202000000', '9923X88545000000', '9923X50039000000',
'9929X86772000000', '9923X00020000000', '9929X87016000000',
'9946X00800000000', '9809X84067000000', '9910X83924000000',
'9946X82229000000', '9946X82560000000', '9929X84968000000',
'9935X00645000000', '9929X01914000000', '0661A00195000000',
'9923X00174000000', '9905X83161000000', '9929X85574000000',
'9844X00539000000', '9946X84721000000', '9923X84442000000',
'9946X00246000000', '0124J00104000A00', '8000T03602000000',
'9946X01275000000', '9935X87940000000', '0732F00045000000',
'9923X00208000000', '9809X83051000000', '9935X88237000000',
'9935X83375000000', '9910X82377000000', '9923X87424000000',
'9946X83975000000', '0276L00098000000', '9910X00963000000',
'9910X82275000000', '9908X83036000000', '0357H00002021500',
'9946X01440000000', '0118G00221000000', '9910X82614000000',
'9908X82884000000', '9923X88338000000', '9935X88165000000',
'9809X82026000000', '9935X00725000000', '0297C00292000000',
'9935X88332000000', '9905X50095000000', '9905X01094000000',
'9923X00339000000', '9929X87400000000', '9935X83593000000',
'9935X00074000000', '9935X82960000000', '8000T00452000000',
'9929X01970000000', '9929X87528000000', '9923X00737000000',
'9905X00485000000', '9910X01529000000', '9946X00460000000',
'9935X01202021900', '9946X85189000000', '9946X84073000000',
'9935X88366000000', '9946X88061000000', '9929X87253000000',
'9935X83168000000', '9946X82027000000', '9910X01586000000',
'9910X80074000000', '9929X80099000000', '9946X83892000000',
'9910X00195000000', '9844X00532000000', '8000T02164000000',
'9923X88463000000', '9946X84331000000', '9923X82306000000',
'0060L00208000001', '0103H00274000000', '0001C01662J01700',
'9946X00254000000', '9935X88544000000', '9946X85402000000',
'9935X82221000000', '9809X00296000000', '9905X01668000000',
'9946X01653000000', '0033D00204000000', '9929X83472000000',
'9929X50019000000', '9929X85952000000', '9923X00371000000',
'9935X82678000000', '9929X83003000000', '9905X82024000000',
'9946X82881000001', '0256M00016000000', '9923X87812000000',
'9910X01423000000', '9946X85231000000', '9946X01515000000',
'9844X00695000000', '9946X82731000000', '0102C00246000000',
'9905X00404000000', '9929X86289000000', '9929X88016000000',
'0035D00035000000', '0549L00079000000', '9929X88014000000',
'9841X00081000000', '0024L00083000000', '9946X83035000000',
'9935X83264000000', '0111S00381000000', '9905X84029000000',
'9905X84005002B00', '9929X88125000000', '9946X83246000000',
'9929X01305000000', '0167K00263000000', '9923X87776000000',
'9935X50179000000', '8000T02303000000', '9923X88196000000',
'9946X84135000000', '9923X82209000000', '9910X83822000000',
'9946X88649000000', '9923X84656000000', '9935X87886000000',
'9929X83939000000', '9910X82341000000', '9809X82006000000',
'9923X87940000000', '9905X00134000000', '9935X00335000000',
'9910X84083000000', '0250D00064000000', '9929X88059000000',
'9946X83900000000', '9946X83620000000', '9935X83020000000',
'9910X84421000000', '9929X01506000000', '1136B00205000000',
'9935X50075000000', '9905X83205000000', '9929X85009000000',
'9946X84436000000', '0626L00214000000', '9929X87612000000',
'9910X01384000000', '9929X01837000000', '9929X01964000000',
'9910X01075000000', '9946X83131000000', '9946X01137000000',
'0079R00088000000', '0086R00314000000', '9929X87429000000',
'8000T02650000000', '0085G00004116300', '9923X87449000000',
'9946X82254000000', '9946X50105000000', '9946X85650000000',
'0375K00275000000', '9905X00487000000', '0176H00156000000',
'9946X85017000000', '9946X85229000000', '0524M00300000000',
'9929X00591000000', '9946X87938000000', '9946X00244000000',
'9929X86037000000', '9946X82304000000', '0387H00142000000',
'9923X00497000000', '0607J00130000100', '9935X83087000000',
'9929X86666000000', '9905X82277000000', '9929X86572000000',
'0758G00025000000', '9905X83054000000', '9809X84072000000',
'9905X82255000000', '9946X85503000000', '9946X01011000000',
'8000T01607000000', '9929X00422000000', '9929X00550000000',
'9946X85622000000', '0117B00114000000', '9905X01316000000',
'9905X83656000000', '9910X00470000000', '9910X00472000000',
'9935X88540000000', '9923X84545000000', '9946X85583000000',
'9923X50025000000', '9946X88154000000', '9905X83529000000',
'9946X84919000000', '9946X82889000000', '9935X50007000000',
'0065C00140000000', '9946X00912000000', '9908X82938000000',
'9935X82727000000', '9929X84344000000', '9910X84404000000',
'9905X00136000000', '0141P00395000000', '9946X50007000000',
'9946X82842000000', '9946X00617000000', '9910X82179000000',
'9908X82910000000', '0125L00289000000', '9929X86252000000',
'8000T00555000000', '9844X00236000000', '9946X83082000000',
'9929X83253000000', '9880X50054000000', '9910X83834000000',
'9929X80063000000', '9910X00993000000', '9946X85253000000',
'9935X83040000000', '9841X00207000000', '9929X01030000000',
'9844X00118000000', '0435R00290000000', '9935X88113000000',
'0084M00360000000', '9905X83501000000', '9910X01421000000',
'9946X87707000000', '9844X00074000000', '8000T00102000000',
'9946X82090000000', '9946X82912000000', '9929X86006000000',
'9946X00837000000', '9841X00195000000', '9946X01188000000',
'9905X01152000000', '8000T01393000000', '0086R00311000000',
'9946X85155000000', '8000T00264000000', '9946X83441000000',
'9923X00980000000', '9946X50091000000', '0214L00237000000',
'0430A00007000000', '0361F00070000100', '9929X01063000000',
'0236S00212000000', '0011A00148000000', '0737A00256000000',
'9905X50090000000', '9923X87723000000', '9844X00472000000',
'1361S00339000000', '9946X87804000000', '9910X83900000000',
'8000T00678000000', '9905X83742000000', '9946X83251000000',
'9923X82117000000', '9946X82876000000', '0176L00063000000',
'9923X88209000000', '9844X00691000000', '9929X86534000000',
'9946X87749000000', '9946X85206000000', '0059F00172000000',
'0702M00224000000', '9905X01911000000', '9935X87977000000',
'9923X84306000000', '9946X85535000000', '9910X00029000000',
'9946X85001000000', '9946X50359000000', '9910X50025000000',
'9946X01009000000', '9923X82432000000', '9946X01282000000',
'9946X00703000000', '9905X00807000000', '9929X82696000000',
'9935X83134000000', '8000T00444000000', '9929X01242000000',
'0084K00028000100', '9946X01521000000', '9910X84457000000',
'9946X01744000000', '9923X84450000000', '9935X83566000000',
'9946X83002000000', '9935X88689000000', '9929X87529000000',
'8000T01957000000', '0050L00078000000', '9809X00004000000',
'9923X84350000000', '9929X83820000000', '9910X84423000000',
'9935X00754000000', '9935X87944000000', '9929X86759000000',
'9905X01513000000', '9841X00063000000', '9946X84944000000',
'9929X00840000000', '9935X82935000000', '9935X88573000000',
'0005L00151000000', '9910X00861000000', '9946X00401000000',
'0189E00004000000', '9923X82395000000', '9905X50024000000',
'9905X82912000000', '8000T00453000000', '9935X82087000000',
'9841X00002000000', '9929X86833000000', '9929X87968000000',
'9935X88333000000', '9946X00508000000', '9929X85389000000',
'9946X01179000000', '9929X87237000000', '0826D00005000000',
'9910X01556000000', '9946X87735000000', '9923X84364000000',
'8000T00451000000', '9844X00044000000', '9946X83105000000',
'9946X82944000000', '9929X00252000000', '8000T02509000000',
'9946X85241000000', '9929X83540000000', '9946X84250000000',
'9935X00026000000', '9905X00880000000', '9929X01661000000',
'9935X82463000000', '9935X88424000000', '9923X00185000000',
'9929X85837000000', '9935X81026000000', '9929X86766000000',
'9935X82549000000', '9929X00781000000', '9929X85475000000',
'9935X00219000000', '0775D00101000000', '9910X82416000000',
'8000T03338000000', '9905X83561000000', '9946X83099000000',
'0204M00345000000', '8000T00274000000', '9935X83739000000',
'9905X83880000000', '0299F00068000000', '9946X88406000000',
'9910X82124000000', '9929X00335000000', '9910X82343000000',
'9929X00631000000', '9929X86702000000', '9905X82066000000',
'9929X88176000000', '9946X84146000000', '9946X87941000000',
'9910X82198000000', '8000T02676000000', '9946X88108000000',
'9929X83011000000', '9946X82623000000', '9935X82154000000',
'9910X82545000000', '9946X88581000000', '9910X82090000000',
'0222E00184000000', '0175P00309000200', '9923X84640000000',
'9841X82008000000', '9946X50538000000', '9935X50259000000',
'9910X84182000000', '9923X88068000000', '9910X83957000000',
'9946X85232000000', '9935X83010000000', '9929X87831000000',
'9910X82669000000', '9929X80061000000', '9929X83517000000',
'9923X00661000000', '9929X84768000000', '9946X83500000000',
'9946X83134000000', '9910X82444000000', '9935X83779000000',
'9935X83113000000', '9946X87960000000', '9929X83104000000',
'9929X01379000000', '9946X00037000000', '9935X87859000000',
'9935X87932000000', '0548R00117000000', '0768R00059000100',
'9929X00238000000', '9910X00858000000', '9929X01668000000',
'9946X85398000000', '0025G00222000000', '9946X85157000000',
'9929X84654000000', '0232D00238000000', '9905X01323000000',
'9809X00059000000', '9923X88484000000', '9946X82933000000',
'9905X01170000000', '9905X01898000000', '9929X01484000000',
'9946X01648000000', '9929X85313000000', '9910X82265000000',
'9809X82010000000', '9905X82636000000', '0421A00180041200',
'9946X50132000000', '9935X88665000000', '9935X83784000000',
'0124J00167000000', '9910X00150000000', '9905X83765000000',
'8000T00616000000', '0083M00071000000', '0024J00211000000',
'9946X50085000000', '9935X88205000000', '9946X85516000000',
'9905X00536000000', '9809X84022000000', '9946X83653000000',
'0023M00322000A00', '9929X87165000000', '9910X84389000000',
'9905X83532000000', '9929X00237000000', '9929X87855000000',
'8000T01964000000', '9929X87431000000', '9923X84685000000',
'9946X85373000000', '9929X86341000000', '9905X00013000000',
'9923X87783000000', '9923X88427000000', '1569K00135000000',
'9935X50128000000', '9844X00371000000', '0222E00255000000',
'8000T01983000000', '9946X00794000000', '1663R00129000000',
'9929X01085000000', '9946X00918000000', '9929X00590000000',
'9910X80043000000', '9946X83885000000', '9935X83237000000',
'9935X88436000000', '9946X88210000000', '9905X83557000000',
'0024L00065000000', '9905X83364000000', '9946X84929000000',
'9910X01181000000', '9844X00552000000', '9923X00006000000',
'9935X83440000000', '9946X82948000000', '9946X85350000000',
'9929X84374000000', '9905X00476000000', '9841X00034000000',
'0450P00464000000', '9923X87944000000', '9910X84220000000',
'9929X00605000000', '9929X84168000000', '9905X01891000000',
'9929X88133000000', '9946X87664000000', '0618A00361000000',
'9809X84006000000', '9923X00590000000', '9910X00879000000',
'9905X82765000000', '9929X84809000000', '9923X87638000000',
'0436A00095000000', '0050K00016000000', '0050K00009000000',
'9905X01777000000', '9929X00997000000', '9935X83514000000',
'9929X86366000000', '9929X00389000000', '9946X83314000000',
'9935X01148000000', '9923X00088000000', '8000T02308000000',
'9946X82947000000', '9946X82241000000', '9935X83835000000',
'9946X00025000000', '9910X84193000000', '9929X86110000000',
'9946X50222000000', '9905X82995000000', '9905X01878000000',
'9935X82346000000', '9935X01063000000', '9929X01634000000',
'0066E00138000000', '9946X87842000000', '9905X01801000000',
'9905X83191000000', '9929X84157000000', '9905X00493000000',
'9935X88715000000', '9935X88181000000', '9946X50506000000',
'9923X84677000000', '9929X01356000000', '1678C00323000100',
'8000T03228000000', '0163K00248000000', '9910X83887000000',
'0025M00195000000', '9923X87421000000', '9935X83247000000',
'9841X00020000000', '0010L00136000000', '0050F00009000000',
'9946X82987000000', '9910X00100000000', '9929X83112000000',
'0050F00018000000', '9905X82684000000', '9929X88172000000',
'9923X82039000000', '9929X00308000000', '9935X82450000000',
'0430L00065000000', '9910X84006000000', '9946X84893000000',
'9929X00016000000', '0055D00335000A00', '9910X84420000000',
'9946X85434000000', '9946X83880000000', '9809X00215000000',
'0218S00154000000', '9946X82660000000', '0269S00022000000',
'9910X82761000000', '0600M00345000000', '0314G00058000002',
'9935X87936000000', '9905X01938000000', '9910X83873000000',
'9929X01053000000', '9910X00518000000', '9946X83376000000',
'9929X88314000000', '9935X83679011700', '0067P00330000000',
'0450P00474000000', '9935X82424000000', '9809X00158000000',
'9908X83043000000', '9946X83130000000', '0619J00320000000',
'9935X82686000000', '9923X88387000000', '0523P00316000000',
'9929X85099000000', '9923X82433000000', '9946X83543000000',
'9929X87962000000', '9905X82202000000', '9910X00745000000',
'9905X01951000000', '9910X84101000000', '9946X82118000000',
'9946X85340000000', '0087B00001000000', '9905X83992000000',
'9905X82456000000', '9910X84151000000', '9923X82096000000',
'2180P00123000000', '9844X00634000000', '9905X01769000000',
'8000T03164000000', '9905X83735000000', '0024H00101000000',
'9905X00311000000', '9923X00867000000', '9935X00163000000',
'9946X88280000000', '9935X00716000000', '8000T01698000000',
'9929X87476000000', '0465R00299000001', '8000T01702000000',
'9935X83109000000', '9929X83081000000', '9929X83499000000',
'9935X88201000000', '9923X88239000000', '0999B00197000000',
'9923X87676000000', '9923X84535000000', '9946X82614000000',
'9905X82032000000', '0291R00202000000', '9946X84253000000',
'9946X87811000000', '0051K00247000000', '9809X82009000000',
'9935X83782000000', '0018G00060000000', '9935X82232000000',
'9905X82130000000', '9946X83257000000', '9905X83540000000',
'9905X83415000000', '9910X83878000000', '9935X01232000000',
'9946X88109000000', '9910X00582000000', '9905X00743000000',
'9946X85282000000', '9935X87967000000', '9905X82062000000',
'9935X01022000000', '9923X87681000000', '8000T01926000000',
'0010C00019000000', '9910X83956000000', '9905X01611000000',
'9910X82484000000', '9946X00110000000', '8000T02822000000',
'9905X82764000000', '0150P00063000000', '8000T03323000000',
'9923X87804000000', '9929X87288000000', '0507L00006000000',
'9929X86253000000', '9910X82260000000', '8000T02183000000',
'9905X00456000000', '9929X83516000000', '9946X00200000000',
'9935X88020000000', '9946X80045000000', '9905X00146000000',
'9935X82129000000', '9946X00986000000', '9935X88557000000',
'9946X84417000000', '0077H00100000002', '0084G00047000000',
'9946X87935000000', '9935X83359000000', '9929X86797000000',
'8000T02945000000', '9929X84939000000', '9905X83396000000',
'9946X83583000000', '9929X88037000000', '9929X83106000000',
'9935X88271000000', '0718H00034000000', '9946X01323000000',
'9946X82746000000', '9905X83513000000', '9946X00690000000',
'9935X82879000000', '9946X87892406D00', '9929X86198000000',
'0105M00020000001', '9935X83729000000', '9946X82471000000',
'9910X01663000000', '9929X87640000000', '9929X86743000000',
'0383B00134000000', '9923X00236000000', '9809X00283000000',
'9923X88097000000', '8000T02955000000', '9935X00773000000',
'9929X87856000000', '9929X88165000000', '9946X83956000000',
'0175H00027000000', '0046N00072000000', '9905X01574000000',
'9935X00591000000', '0390B00220000100', '9905X01601000000',
'9946X01263000000', '9946X83344000000', '9935X00947000000',
'9844X00351000000', '0124J00099000000', '9809X00116000000',
'9929X85733000000', '9929X82548000000', '9910X00722000000',
'0718H00040000000', '9923X00031000000', '9946X83722000000',
'0466F00190000000', '9929X85910000000', '9923X88500000000',
'9929X86550000000', '9946X85432000000', '0010J00159000000',
'9929X83504000000', '9929X00362000000', '9923X88185000000',
'9905X00874000000', '9905X83517000000', '9935X87873000000',
'9946X82662000000', '0301L00172000000', '9929X00298000000',
'9923X88415000000', '9923X01084000000', '9910X82633000000',
'9809X84003000000', '9929X88217000000', '9929X82803000000',
'9946X84012000000', '9946X84406000000', '9935X00321000000',
'9946X00665000000', '0134A00228000000', '9905X82728000000',
'9935X00073000000', '9929X85326000000', '0718H00030000000',
'9910X82742000000', '0087B00149000000', '9929X82859000000',
'9935X00421000000', '9946X84314000000', '9935X82458000000',
'9905X84073000000', '1075M00268000000', '9910X00103000000',
'9905X00529000000', '9935X83442000000', '9946X87671000000',
'9923X84661000000', '9935X88597000000', '9935X00977000000',
'9946X00036000000', '9935X88415000000', '0101B00270000000',
'0253H00171000000', '9905X82822000000', '0361F00067000100',
'9923X87567000000', '9923X87598000000', '9841X00125000000',
'9844X00465000000', '9935X83475000000', '9841X82023000000',
'9910X82426000000', '9946X82525000000', '9946X82176000000',
'9929X86537000000', '9935X88452000000', '9910X82079000000',
'9910X83841000000', '0856P00128000000', '9929X84243000000',
'9935X00099000001', '9910X82417000000', '8000T00052000000',
'9910X84441000000', '9910X84169000000', '9910X01058000000',
'9908X82854000000', '9929X00877000000', '0250D00058000000',
'0254N00200000100', '9923X84388000000', '9946X87716000000',
'9935X82316000000', '9809X00087000000', '9946X84235000000',
'9905X50054000000', '9929X86351000000', '9905X83235000000',
'9905X83860000000', '9905X82144000000', '9946X88499000000',
'9929X86867000000', '9929X87474000000', '0831M00066000000',
'9935X82014000000', '9946X88533000000', '0874D00156000000',
'9905X01690000000', '9910X84189000000', '9929X85854000000',
'9910X01137000000', '9910X83824000000', '9929X01016000000',
'9905X82533000000', '9923X00266000000', '9923X82244000000',
'9929X00248000000', '9946X50237000000', '9935X00145000000',
'9946X83587000000', '9935X82451000000', '9929X00928000000',
'9929X86317000000', '9929X84549000000', '9935X83275000000',
'9923X00791000000', '9946X85437000000', '9935X82381000000',
'9923X82296000000', '9929X87892000000', '8000T00361000000',
'9910X84311000000', '9946X88003000000', '9929X86196000000',
'9946X83310000000', '9946X88438000000', '9929X00514000000',
'9935X01247000000', '0069R00227000000', '9923X88269000000',
'0050K00056000000', '9910X00672000000', '9946X85199000000',
'9910X83938000000', '9935X82723000000', '9905X82985000000',
'9905X00593000000', '9929X85312000000', '0222J00062000000',
'9946X83301000000', '9929X50163000000', '0507L00073000000',
'9910X01064000000', '9929X85310000000', '0042D00138000000',
'9935X83721000000', '9929X84028000000', '9923X00958000000',
'9929X88210000000', '9923X88432000000', '9929X81216000000',
'9946X85624000000', '0004J00071000000', '0616M00105000000',
'9923X88162000000', '9905X82155000000', '9935X82669000000',
'9910X80042000000', '9880X02956000000', '9935X83050000000',
'9929X83028000000', '9923X00691000000', '8000T03181000000',
'0050L00271000000', '9929X00650000000', '0190H00058000000',
'9910X00504000000', '9905X83365000000', '9910X84416000000',
'9923X84684000000', '9841X00057000000', '9923X88131000000',
'9905X82033000000', '9946X50275000000', '9844X82017000000',
'9929X01852000000', '9946X84918000000', '9946X88399000000',
'9929X87256000000', '0124J00166000000', '9946X82847000000',
'9923X88132000000', '9929X87555000000', '9923X87474000000',
'9929X87297000000', '9923X00436000000', '9935X83678000000',
'9929X82879000000', '9946X84223000000', '9935X83530000000',
'9946X85283000000', '9910X00552000000', '9923X87912015500',
'9905X82330000000', '0125L00213000000', '0083L00292000000',
'9946X85439000000', '9929X82336000000', '9929X83256000000',
'9910X01342000000', '9929X84431000000', '9929X85357000000',
'0887A00240006600', '9946X83569000000', '1224G00089000000',
'9905X01660000000', '0222N00051000000', '9946X84842000000',
'0716R00375000000', '9929X01461000000', '9935X88629000000',
'0050K00154000200', '9946X01374000000', '9946X87930000000',
'9946X80044000000', '0019J00300000000', '9910X82149000000',
'9929X85346000000', '9905X00126000000', '9946X83591000000',
'9946X01099000000', '9929X87819000000', '9946X50192000000',
'9946X82160000000', '9929X85243000000', '9905X00997000000',
'9935X83252000000', '9929X01082000000', '9910X82379000000',
'1130P00185000000', '9910X00572000000', '9935X83187000000',
'9923X00202000000', '8000T00464000000', '9923X88568000000',
'9910X80026000000', '9905X01571000000', '9905X01277000000',
'9946X82249000000', '9929X86545000000', '9946X83668000000',
'9923X88112000000', '9946X83957000000', '9929X83273000000',
'9905X00801000000', '0225S00320000000', '9946X84037000000',
'9905X82169000000', '9911X50168000000', '9841X00093000000',
'9905X00627000000', '9844X00098000000', '9935X88180000000',
'9935X87879000000', '9923X84434000000', '9946X84184000000',
'9946X01752000000', '9910X83990000000', '9946X50526000000',
'9844X00752000000', '9929X01387000000', '9929X01916000000',
'9929X01799000000', '9935X82933000000', '9905X00877000000',
'9946X00329000000', '0291R00153000000', '9929X87213000000',
'9929X85559000000', '9946X85547000000', '9929X87985000000',
'9946X01257000000', '8000T00140000000', '9809X00306000000',
'9929X85137000000', '0220P00310000000', '9929X84907000000',
'9946X01702000000', '8000T02023000000', '9929X83964000000',
'0243A00006000000', '9935X83069000000', '9935X88711000000',
'9923X84554000000', '0083L00286000000', '9910X84302000000',
'9923X87927000000', '9910X84294000000', '9910X82215000000',
'9905X83753000000', '9910X84521000000', '9844X00332000000',
'9946X50333000000', '9923X82315000000', '9910X84268000000',
'9905X83763000000', '9923X00200000000', '9946X50335000000',
'9929X01368000000', '9929X87944000000', '9946X00225000000',
'9910X84228000000', '9946X01165000000', '9929X84742000000',
'9946X82504000000', '9946X83467000000', '9929X01841000000',
'9923X87603000000', '0719F00099000000', '9809X84015000000',
'9946X85620000000', '0463H00050000000', '9929X87781000000',
'8000T00017000000', '9929X00837000000', '9929X00821000000',
'9905X82299000000', '9946X88377000000', '9923X87527000000',
'9905X00419000000', '0040F00103000000', '9841X82014000000',
'9929X84676000000', '9935X01341000000', '9929X85809000000',
'8000T01927000000', '9946X82883000000', '9946X83822000000',
'9929X86936000000', '9910X83944000000', '9923X00695000000',
'9929X83421000000', '9946X85532000000', '9929X87622000000',
'9946X01704000000', '9929X84183000000', '9910X83960000000',
'9929X84136000000', '9935X00488000000', '9935X01323000000',
'9929X86128000000', '9908X82918000000', '2020C00132000000',
'9841X00103000000', '9929X86864000000', '9841X00194000000',
'9910X84313000000', '9946X88532000000', '9910X01362000000',
'9910X84188000000', '9929X87252000000', '9844X00384000000',
'9935X01307000000', '9946X87691000000', '9905X00721000000',
'9935X82804000000', '9844X82041000000', '9905X83231000000',
'9929X85225000000', '9929X00655000000', '9946X84373000000',
'9946X50314000000', '9923X84519000000', '9946X85268000000',
'9929X87314000000', '9910X00821000000', '9923X84404000000',
'9923X88081000000', '0382G00203000000', '9946X83196000000',
'0119S00104000000', '9910X00701000000', '9905X82234000000',
'9929X83357000000', '0251E00190000000', '9923X84709000000',
'9929X87033000000', '9935X50034000000', '9935X82683000000',
'8000T02026000000', '9841X00111000000', '9929X00461000000',
'9905X00071000000', '9910X00529000000', '9946X80046000000',
'9946X50488000000', '9923X82219000000', '9935X82490000000',
'9923X88423000000', '9935X82698000000', '9929X00779000000',
'0125M00369000000', '9935X82720000000', '9946X00589000000',
'9946X88329000000', '9910X00441000000', '9929X87643000000',
'0136A00217000000', '9929X87884000000', '9946X87746000000',
'9946X83268000000', '9905X00369000000', '9905X01216000000',
'9923X00265000000', '9923X84384000000', '9946X00963000000',
'0372F00016000002', '9844X00278000000', '9910X01511000000',
'9910X80061000000', '9946X87892406C00', '8000T03260000000',
'0997G00227000001', '9946X50219000000', '9929X84375000000',
'9929X01909000000', '9946X83096000000', '9929X85731000000',
'9910X84050000000', '9844X82020000000', '0829N00039000000',
'9910X00021000000', '9910X00576000000', '9946X50100000000',
'8000T00378000000', '0071J00176000000', '9935X01139000000',
'0173F00333000000', '9923X87848000000', '9905X01927000000',
'9946X82158000000', '9844X00201000000', '9946X83955000000',
'9946X82850000000', '9929X00368000000', '0128E00088000000',
'9935X50249000000', '9910X00009000000', '9905X01160000000',
'0049F00011000000', '9923X82305000000', '9935X00057000000',
'9923X82338000000', '9946X50374000000', '9929X81008000000',
'9946X84708000000', '9910X00057000002', '9929X88155000000',
'9946X84241000000', '9905X00945000000', '9935X83715000000',
'9935X82786000000', '9929X88027000000', '9946X50302000000',
'9946X85572000000', '0083K00278000000', '9935X01025000000',
'9923X87979000000', '9946X84267000000', '9946X84019000000',
'9935X83531000000', '9910X84418000000', '9946X82925000000',
'9905X01123000000', '9929X00254000000', '9929X01936000000',
'8000T00414000000', '9935X82937000000', '9905X00980000000',
'9946X50143000000', '9946X84273000000', '9929X87439000000',
'9809X00136000000', '9935X88293000000', '9935X83573000000',
'8000T01914000000', '9935X82984000000', '9910X82185000000',
'9929X82496000000', '9946X01156000000', '9910X01240000000',
'0034H00180000000', '1468D00002000000', '9935X83243000000',
'9905X83451000000', '9946X87980000000', '9844X00194000000',
'9923X82424000000', '9929X86187000000', '0562D00084000000',
'9929X01087000000', '9910X84633000000', '9910X00068000000',
'9929X01680000000', '9946X88091000000', '9929X00455000000',
'9905X01644000000', '0225N00095041100', '9905X50069000000',
'9946X00985000000', '9929X50370000000', '9935X87882000000',
'8000T02692000000', '9929X88346000000', '9946X83634000000',
'9935X82300000000', '9946X84771000000', '9910X84191000000',
'0004G00013000000', '9946X00443000000', '9905X83524000000',
'0760R00321000000', '9923X01048000000', '9929X84871000000',
'0050K00242000000', '9905X00900000000', '9946X82069000000',
'9809X84042000000', '9935X82399000000', '9910X01390000000',
'9935X00456000000', '9935X50212000000', '9946X84173000000',
'9923X88262000000', '9905X00324000000', '9929X86326000000',
'9946X00196000000', '9935X50149000000', '9929X84805000000',
'0887A00240000E00', '9905X83861000000', '9910X00223000000',
'9929X85139000000', '9946X85329000000', '9929X86676000000',
'9946X84791000000', '9841X00196000000', '9946X82764000000',
'9929X00394000000', '9923X82163000000', '9809X00302000000',
'9946X87906000000', '9946X83784000000', '9946X84812000000',
'9946X00436000000', '9929X85775000000', '9910X82205000000',
'9923X00358000000', '9946X00545000000', '9929X87322000000',
'9946X00218000000', '9905X83673000000', '9946X83228000000',
'9905X00072000000', '9946X85360000000', '9946X83136000000',
'0235N00038000000', '9905X80003000000', '9946X01157000000',
'0292C00270000000', '9946X84798000000', '9935X82314000000',
'9923X82360000000', '0608J00200000000', '9910X84001000000',
'9946X83198000000', '8000T02969000000', '9905X01423000000',
'9935X87927000000', '9910X82758000000', '1349N00190000000',
'9929X85096000000', '9946X84310000000', '9908X82966000000',
'0299F00068000100', '9929X83965000000', '9910X00668000000',
'9946X83979000000', '9910X01619000000', '9929X01351000000',
'1658M00024000000', '9946X83698000000', '0600F00319000000',
'9844X00335000000', '9910X80028000000', '0189E00299000000',
'9946X88321000000', '9946X85543000000', '9935X83485000000',
'0001N00163000000', '9929X84869000000', '9905X01254000000',
'9935X88207000000', '9935X82536000000', '8000T00012000000',
'9905X83232000000', '9923X87717000000', '9946X00212000000',
'9908X82857000000', '9910X01515000000', '9946X00707000000',
'9905X01686000000', '9935X87844000000', '9910X83860000000',
'9929X00070000000', '9910X84385000000', '9946X87948000000',
'9929X87309000000', '9946X83176000000', '9905X84034210500',
'9946X01830000000', '0462E00147000002', '9905X01238000000',
'9946X82547000000', '9946X88129000000', '0249A00279000000',
'9946X83834000000', '0448M00146000000', '0023B00227000A00',
'9905X00408000000', '9929X87357000000', '9929X82697000000',
'9809X82036000000', '8000T00180000000', '9946X85097000000',
'9946X82235000000', '9946X50299000000', '9935X82867000000',
'9946X84975000000', '9905X01446000000', '9929X00871000000',
'9946X85024000000', '0011A00173000000', '9935X83403000000',
'0290P00069000000', '9905X82279000000', '9946X82804000000',
'9905X82292000000', '9929X01115000000', '9923X88188000000',
'9905X01965000000', '9923X00004000000', '9929X85224000000',
'9946X83353000000', '9929X87282000000', '9844X00449000000',
'9910X81069000002', '0302E00111000000', '1670F00040000000',
'9946X82073000000', '9910X84602000000', '9935X00957000000',
'9905X82550000000', '9929X88213000000', '9946X82195000000',
'9923X88244000000', '9929X50321000000', '9929X00672000000',
'8000T02615000000', '9905X82552000000', '9905X00887000000',
'9929X00114000000', '9935X83245000000', '9905X00561000000',
'9929X87336000000', '9946X85038000000', '0562N00024000100',
'9946X82285000000', '9935X82819000000', '9910X00853000000',
'9929X84813000000', '9923X88420000000', '9935X83584000000',
'9910X00860000000', '9935X88343000000', '9946X85120000000',
'9946X88097000000', '9929X00170000000', '0103E00005000000',
'9935X88062000000', '9923X87956000000', '9929X87352000000',
'9935X83694000000', '1358J00369000000', '9946X88103000000',
'9923X00209000000', '9910X01285000000', '9929X87530000000',
'0887D00090000000', '9923X87477000000', '0660A00020000200',
'9935X82185000000', '9935X88162000000', '9935X87832000000',
'0653G00263000000', '9946X82894000000', '9935X82828000000',
'9923X00858000000', '9935X87905000000', '9935X88363000000',
'9910X84139000000', '0119S00157000000', '0607J00075000100',
'9946X82610000000', '9946X88357000000', '9946X50281000000',
'9923X87817000000', '8000T03282000000', '9844X00442000000',
'9910X84153000000', '9946X01649000000', '9929X85288000000',
'9946X50068000000', '9929X86001000000', '9935X83520000000',
'9929X88166000000', '9929X83265000000', '0003S00011000000',
'0080G00187000000', '9946X84187000000', '9929X86608000000',
'9946X84974000000', '9844X00228000000', '9935X82863000000',
'9905X83889000000', '9923X82271000000', '9929X01908000000',
'9946X50267000000', '9929X83486000000', '9946X83411000000',
'1358C00103000000', '9929X86138000000', '0617H00314000000',
'9946X88506000000', '9923X00667000000', '9935X82550000000',
'9935X01127000000', '9935X00427000000', '9929X85990000000',
'9946X00469000000', '9946X85454000000', '9946X88623000000',
'9946X82823000000', '9905X01498000000', '0236P00048000000',
'9946X84231000000', '9946X82777000000', '9946X85348000000',
'8000T03464000000', '9910X82577000000', '0004E00022000000',
'9935X83338000000', '0012N00272000000', '9935X83240000000',
'9946X84723000000', '9946X01071000000', '9910X00092000000',
'9946X83365000000', '9935X83161000000', '9923X82064000000',
'9905X01263000000', '9929X82137000000', '9946X88181000000',
'9923X84313000000', '9923X00779000000', '9946X01857000000',
'9929X87498000000', '9946X88304000000', '9929X83834000000',
'0888K00006000000', '9946X88309000000', '9923X88000000000',
'9905X83146000000', '9935X82836000000', '9946X88417000000',
'9929X01446000000', '9809X00039000000', '9946X85205000000',
'9946X85130000000', '9946X00193000000', '0050K00056000A00',
'0136A00395000100', '9905X82782000000', '9946X83944000000',
'9929X87005000000', '9929X88098000000', '9910X00176000000',
'0024N00043000000', '0068H00070000000', '9946X85109000000',
'9844X00480000000', '0156C00234000000', '9946X83229000000',
'8000T02425000000', '0011A00146000000', '9910X83795000000',
'9946X50491000000', '9929X00922000000', '9929X88012000000',
'9929X87633000000', '9946X85500000000', '1202D00222000000',
'9946X00204000000', '9929X00811000000', '8000T00323000000',
'9910X00526000000', '9929X87610000000', '9946X01447000000',
'9946X87808000000', '0232D00240000000', '9908X82880000000',
'9929X83529000000', '9910X00820000000', '9929X87847000000',
'9923X84518000000', '9929X84970000000', '9905X00499000000',
'9935X00653000000', '9935X82925000000', '9929X84872000000',
'9946X01741000000', '9929X00460000000', '9935X88330000000',
'9910X84291000000', '9905X50172000000', '9905X82295000000',
'9923X88218000000', '9946X82886000000', '9929X87312000000',
'9946X87965000000', '0068H00068000000', '9935X82871000000',
'9946X88204000000', '9923X84458000000', '9910X84559000000',
'9935X82077000000', '9946X50131000000', '9935X87913000000',
'8000T01343000000', '9929X87648000000', '9929X87358000000',
'9923X87571000000', '0024F00342000001', '0563H00400000000',
'9946X01825000000', '9929X88324000000', '9929X82805000000',
'0604J00291000000', '9929X84154000000', '9910X01507000000',
'9905X82210000000', '9935X82229000000', '9935X88289000000',
'9910X84640000000', '9946X83402000000', '9905X83441000000',
'0041L00157000000', '9946X01036000000', '0253K00200000000',
'9910X01068000000', '9929X85077000000', '9935X83601000000',
'9929X50136000000', '9946X84764000000', '9935X00155000000',
'9929X00875000000', '0050F00016000000', '9841X00047000000',
'9929X86102000000', '0024L00087000000', '9946X87970000000',
'9923X88174000000', '9946X00167000000', '9946X88186000000',
'0049E00217000000', '9935X87952000000', '0132S00074000000',
'9929X86376000000', '9929X84417000000', '9935X87857000000',
'8000T02498000000', '9946X50373000000', '9844X00352000000',
'9935X83695000000', '0235S00500000000', '9929X84933000000',
'9929X87826000000', '0079R00048000000', '9844X82044000000',
'9905X00403000000', '9905X82207000000', '9935X82802000000',
'9844X00654000000', '0668G00194000000', '0002K00006000001',
'0002K00006000000', '9905X83160000000', '9946X01350000000',
'9905X83266000000', '9929X82549000000', '0541A00240000000',
'9929X87522000000', '9809X84001000000', '9929X01835000000',
'9946X00994000000', '9923X87473000000', '9935X83445000000',
'9923X84516000000', '9929X82631000000', '9929X87308000000',
'9929X88077000000', '9844X00636000000', '9935X82440000000',
'9910X01100000000', '9946X87692000000', '9905X00642000000',
'9844X00541000000', '9905X84020007C00', '9929X85962000000',
'9905X00385000000', '9935X00118000000', '9946X00966000000',
'9905X82680000000', '9935X50293000000', '9946X85400000000',
'9946X01759000000', '0084D00125000000', '9929X83361000000',
'9946X84684000000', '9935X83044000000', '9923X84496000000',
'1128G00036000000', '9946X00789000000', '8000T00574000000',
'9929X01383000000', '9923X88315000000', '9929X00365000000',
'9946X82266000000', '0717M00396100300', '9946X84693000000',
'9923X82280000000', '9935X83496000000', '9946X83352000000',
'9905X00637000000', '0050L00164000000', '0024H00103000000',
'9935X88110000000', '9929X00309000000', '9905X83652000000',
'9935X82332000000', '0063B00291000000', '9935X82146000000',
'9929X87740000000', '9809X00324000000', '9946X85443000000',
'0512L00016000100', '0022M00031000000', '9929X86669000000',
'9946X87687000000', '9905X00591000000', '9923X87697000000',
'9929X86099000000', '8000T01403000000', '9946X84861000000',
'9929X50010000000', '9841X00113000000', '0388S00013000100',
'9946X01601000000', '9905X01511000000', '9809X00085000000',
'9905X01689000000', '9946X82832000000', '0003N00218000000',
'9929X82017000000', '9935X00379000000', '1507S00250000000',
'9935X00550000000', '9946X84086000000', '9935X87975000000',
'9929X85284000000', '9929X00593000000', '9910X82162000000',
'9929X00920000000', '8000T01427000000', '9935X88063000000',
'0821S00262000000', '9910X01493000000', '9929X84217000000',
'9935X83572000000', '9929X00727000000', '9905X01126000000',
'9946X83199000000', '9935X82709000000', '9946X82356000000',
'9946X83938000000', '9946X84425000000', '9844X00714000000',
'0289S00100000000', '9929X84320000000', '8000T02368000000',
'9929X87809000000', '9946X88598000000', '0163K00151000000',
'9910X00848000000', '9905X01894000000', '0023M00273000000',
'9946X85648000000', '9935X00585000000', '9935X50063000000',
'0112E00254000000', '9929X84974000000', '0450P00645000000',
'9923X01088000000', '9946X88351000000', '9935X82553000000',
'9946X88074000000', '9923X87451000000', '9923X01006000000',
'9929X01180000000', '9935X88554000000', '9946X83327000000',
'9929X00194000000', '9946X50499000000', '9844X00366000000',
'9910X00981000000', '9910X82346000000', '0246K00138000000',
'9946X88488000000', '9910X01618000000', '9929X86524000000',
'9946X88536000000', '9929X84562000000', '9946X82008000000',
'9844X00212000000', '9929X88122000000', '9946X82939000000',
'9844X00440000000', '9905X50247000000', '9905X83444000000',
'0639L00253000000', '9844X00697000000', '9929X83835000000',
'9946X83679000000', '9946X82215000000', '9946X83459000000',
'1909E00172000000', '9935X83792000000', '9946X85200000000',
'9946X87767000000', '9809X82051000000', '9929X83514000000',
'9935X01197000000', '9929X84670000000', '9935X82488000000',
'0221G00129000000', '9929X00967000000', '9905X84002000000',
'9946X00241000000', '9935X00020000000', '9946X50402000000',
'9905X00617000000', '9946X50414000000', '9905X83404000000',
'9905X82205000000', '9809X00327000000', '0175C00163000000',
'9929X84472000000', '9910X01398000000', '9929X84618000000',
'9905X83690000000', '8000T00776000000', '9923X00171000000',
'9946X84108000000', '9929X01029000000', '9929X85390000000',
'9844X00232000000', '9905X82772000000', '9929X50288000000',
'9905X83745000000', '8000T01948000000', '9841X00014000000',
'9905X01723000000', '9946X85027000000', '9929X50156000000',
'9809X00148000000', '9946X50450000000', '9946X50490000000',
'9929X01178000000', '9946X83242000000', '9923X00585000000',
'9946X01598000000', '9929X01160000000', '9935X82397000000',
'9946X50025000000', '9935X01266000000', '9923X88358000000',
'9910X82714000000', '9923X88537000000', '0189E00002000000',
'2181M00443000000', '0415F00144000000', '9935X82685000000',
'9935X88694000000', '9946X00301000000', '0708N00025000000',
'9923X84467000000', '0422D00150000000', '9929X87235000000',
'9905X82610000000', '9946X82977000000', '9929X85279000000',
'9923X87791000000', '9923X82430000000', '9809X00099000000',
'9935X83825000000', '0751A00190000000', '9946X88356000000',
'9946X82521000000', '9929X87965000000', '9929X87501000000',
'0010J00107000000', '9935X82600000000', '9946X85243000000',
'8000T00166000000', '9946X83170000000', '9935X88687000000',
'9905X82172000000', '9946X84713000000', '9929X00516000000',
'9946X83503000000', '9946X83218000000', '8000T00801000000',
'0022K00329000000', '9910X83796000000', '9946X01092000000',
'9929X87587000000', '0625K00017000000', '9923X00298000000',
'0012R00003000000', '9935X88204000000', '0007P00003000000',
'9923X00299000000', '9935X50058000000', '9910X84027000000',
'9929X50392000000', '9809X00078000000', '8000T00265000000',
'9935X88112000000', '9935X00884000000', '9905X83689000000',
'9935X83095000000', '9929X01978000000', '9935X83157000000',
'9935X88548000000', '9844X00110000000', '9809X00239000000',
'9935X82045000000', '9905X00846000000', '9929X86643000000',
'0833F00376000100', '9910X00622000000', '9923X87912014800',
'9841X00144000000', '9908X82908000000', '9905X00075000000',
'9929X84058000000', '0222E00254000000', '9929X84124000000',
'9923X82158000000', '9946X83538000000', '9946X82247000000',
'9844X00086000000', '9923X87708000000', '8000T02141000000',
'0421G00046000000', '9946X50180000000', '9946X84149000000',
'9929X86256000000', '9946X84095000000', '0222A00110000000',
'0738H00046000000', '9946X82043000000', '2395N00006000000',
'9946X85587000000', '0646E00243000000', '9844X00137000000',
'9929X87377000000', '9929X84148000000', '9905X83303000000',
'9946X00115000000', '9946X00468000000', '8000T01778000000',
'9923X01021000000', '9910X50022000000', '9905X83594000000',
'9905X00991000000', '9935X82886000000', '9929X01163000000',
'0101L00158000000', '9905X01948000000', '0050K00120000000',
'9946X84414000000', '9905X01250000000', '9923X87992000000',
'9908X03396000001', '0125L00219000000', '9935X00252000000',
'9946X00638000000', '9910X84079000000', '8000T01541000000',
'9929X80006000000', '9946X82747000000', '9935X88381000000',
'9905X00942000000', '9946X84711000000', '9929X01366000000',
'9905X01931000000', '9905X82644000000', '9929X86871000000',
'9946X81033000000', '9946X50436000000', '9946X00628000000',
'1224G00257000000', '9946X83815000000', '9905X83947000000',
'9946X84344000000', '9929X85554000000', '9935X00447000000',
'9910X00571000000', '9946X83968000000', '9929X01444000000',
'0179J00309000000', '9910X01664000000', '9929X83837000000',
'8000T01398000000', '9935X82380000000', '9946X82326000000',
'9929X88042000000', '9905X83018000000', '9910X00977000000',
'9946X85638000000', '9929X00734000000', '9946X00455000000',
'9905X01131000000', '9946X82858000000', '9935X88259000000',
'0124J00164000000', '9929X88093000000', '9929X01600000000',
'9929X01631000000', '9935X83023000000', '9935X01035000000',
'9910X82463000000', '9929X50575000000', '9809X00325000000',
'9946X01573000000', '0997F00232000001', '9929X85373000000',
'9929X85564000000', '9935X00555000000', '9929X00596000000',
'9841X00079000000', '8000T02731000000', '9946X88069000000',
'9946X83406000000', '9935X82514000000', '9946X01735000000',
'9946X83000000000', '0024D00292000000', '9935X82776000000',
'9929X87246000000', '9935X82131000000', '9929X86596000000',
'0395F00074000000', '0373E00268000000', '9946X00999000000',
'9923X88409000000', '9923X88535000000', '0760M00075000000',
'9946X85270000000', '0092M00008000000', '9910X84061000000',
'9923X80011000000', '0775H00069000000', '9923X84649000000',
'0941K00274000000', '9910X84543000000', '9910X00708000000',
'9935X83599000000', '9946X01077000000', '9935X82157000000',
'9910X84288000000', '0299F00064000100', '9910X82631000000',
'9929X00771000000', '9929X86668000000', '9935X83668000000',
'9935X88733000000', '9946X84924000000', '9935X83827000000',
'9923X82254000000', '1077L00181000000', '9935X82945000000',
'9929X01481000000', '9929X88033000000', '0856A00290000000',
'9946X82566000000', '9946X82724000000', '9809X82002000000',
'9905X82451000000', '9905X00413000000', '9935X00719000000',
'8000T00132000000', '9910X84393000000', '9910X84087000000',
'9923X00303000000', '9910X84234000000', '9935X50098000000',
'1357F00156000000', '9946X82813000000', '9910X01452000000',
'9935X01279000000', '9946X83267000000', '8000T03341000000',
'9935X88447000000', '9935X00258000000', '9946X00088000000',
'9910X84544000000', '9929X87674000000', '9946X83781000000',
'9929X88130000000', '9946X00252000000', '9935X82342000000',
'9844X00246000000', '9844X00740000000', '9910X01513000000',
'9946X82287000000', '9905X83896000000', '9946X85152000000',
'9910X82217000000', '9929X01436000000', '9910X01346000000',
'9923X84543000000', '9929X01004000000', '9946X84237000000',
'9905X82763000000', '9905X00047000000', '0999B00198000000',
'9929X83508000000', '9929X84961000000', '9946X82985000000',
'9946X00240000000', '9946X84026000000', '9946X00717000000',
'9929X87378000000', '9946X83716000000', '9946X87699000000',
'9946X82613000000', '9929X01295000000', '9935X83619000000',
'9929X82691000001', '0156G00330000000', '9929X88174000000',
'0878N00378000000', '9946X84670000000', '9905X01583000000',
'0235P00222000000', '9844X00725000000', '9929X82530000000',
'9905X00036000000', '0024N00049000000', '9905X83823000000',
'9923X84622000000', '9929X84669000000', '9910X84207000000',
'9929X83269000000', '9905X83454000000', '9946X83290000000',
'9841X00188000000', '9946X87805000000', '9946X84247000000',
'9929X84678000000', '9929X83399000000', '9935X83269000000',
'9923X84522000000', '9929X87718000000', '9935X88344000000',
'9844X00694000000', '9929X87839000000', '9910X00122000000',
'9946X83185000000', '0307N00158000000', '9905X01914000000',
'0061H00143000001', '9946X84717000000', '9929X01568000000',
'9935X82949000000', '9935X82767000000', '9946X01192000000',
'9935X83608000000', '9935X50262000000', '0124J00108000000',
'9929X00912000000', '0054P00110000000', '9809X84017000000',
'9935X82155000000', '9929X86837000000', '9929X00611000000',
'9929X87966000000', '9905X00736000000', '9905X82810000000',
'9946X50336000000', '8000T00478000000', '1098R00181000000',
'9929X00562000000', '0094C00245000000', '9946X84921000000',
'9946X85488000000', '9929X01786000000', '9910X00830000000',
'9923X01040000000', '9946X01155000000', '0079L00174000000',
'0124K00165000001', '9935X00969000000', '9923X82106000000',
'9946X83589000000', '9935X88605000000', '9929X83731000000',
'1345R00254000000', '0467M00172000000', '9905X50093000000',
'9946X01497000000', '9935X01062000000', '9841X00152000000',
'0342F00369000000', '9946X84058000000', '9935X83305000000',
'9946X84277000000', '9923X88345000000', '9946X88174000000',
'9929X87316000000', '0235P00224000000', '9844X00117000000',
'0024J00226000000', '9929X85420000000', '9929X01895000000',
'1909A00339000000', '9946X88660000000', '9935X00183000000',
'9935X01202022500', '9809X00274000000', '9929X86771000000',
'9935X00551000000', '9935X82568000000', '9809X82003000000',
'0513G00055000000', '9844X00433000000', '9935X88017000000',
'9946X84409000000', '9929X85677000000', '9929X84348000000',
'9946X83648000000', '9935X00507000000', '9910X84021000000',
'9809X84002000000', '9946X01862000000', '9905X83016000000',
'9905X83300000000', '0973B00100000000', '0018A00102000000',
'9946X00015000000', '9910X84009000000', '9929X84620000000',
'9946X82156000000', '9946X50234000000', '9946X85536000000',
'9929X87780000000', '9910X82347000000', '9946X83280000000',
'9946X83645000000', '9946X01459000000', '9946X82699000000',
'9929X88149000000', '0141C00182000000', '0460D00375000000',
'9923X00617000000', '9929X00150000000', '0170P00030000000',
'9946X84345000000', '9929X85106000000', '9935X00189000000',
'9923X00555000000', '0103P00188000000', '9929X86859000000',
'0461H00175000000', '9929X85489000000', '9905X81024000000',
'0284L00184000200', '9935X82124000000', '9946X82480000000',
'9935X00495000000', '0178A00131000000', '9929X86091000000',
'9809X00009000000', '9905X00512000000', '9946X85446000000',
'9946X85244000000', '9935X82561000000', '9935X00332000000',
'9946X83050000000', '9929X83554000000', '9809X00118000000',
'9946X85367000000', '9929X84433000000', '9905X82800000000',
'9929X86855000000', '0884A00032000000', '9929X50089000000',
'9929X85838000000', '9929X85168000000', '9910X01085000000',
'9946X82635000000', '9946X85382000000', '9905X82168000000',
'9910X84332000000', '8000T03021000000', '9910X84436000000',
'8000T00182000000', '0205G00162000000', '9935X82073000000',
'9929X87541000000', '9929X85663000000', '9910X00520000000',
'9844X82034000000', '9929X88121000000', '9935X82588000000',
'9929X83500000000', '9905X01485000000', '9844X00680000000',
'9929X88362000000', '9935X82434000000', '9905X00457000000',
'9923X87874000000', '9946X82692000000', '9935X82235000000',
'9935X82466000000', '9935X00985000000', '9946X87718000000',
'9946X88281000000', '9935X83047000000', '9946X82606000000',
'9929X01701000000', '9935X83785000000', '9946X84877000000',
'9929X85533000000', '9946X00151000000', '9929X84828000000',
'9910X84297000000', '9923X88012000000', '9935X00825000000',
'9905X82065000000', '0232P00093000000', '9910X83817000000',
'9946X82817000000', '9929X00188000000', '9905X83720000000',
'9910X00003000000', '9946X01732000000', '9905X82080000000',
'9929X01800000000', '9946X84081000000', '9935X82396000000',
'9929X00134000000', '9929X83457000000', '9923X82347000000',
'9910X01453000000', '9923X82451000000', '9946X83125000000',
'0048N00160000000', '9910X82154000000', '9946X83664000000',
'9929X86096000000', '9935X01118000000', '9929X87615000000',
'9923X00211000000', '9935X83528000000', '9929X86639000000',
'9929X84125000000', '1832S00028000000', '9905X01156000000',
'9946X83578000000', '0055S00161000000', '9910X82401000000',
'9935X83750000000', '9923X84472000000', '9946X01227000000',
'9844X00274000000', '9910X00567000000', '9935X83083000000',
'0638S00018000000', '0176F00095000000', '9946X00899000000',
'9923X88133000000', '9905X83199000000', '9910X80006000000',
'9946X82208000000', '9946X88083000000', '9946X84730000000',
'9905X82790000000', '9844X82042000000', '9935X83411000000',
'9905X82211000000', '8000T00062000000', '0167C00026000000',
'9935X88398000000', '9935X00867000000', '9923X88494000000',
'9929X87290000000', '9946X82172000000', '9946X83873000000',
'9905X83190000000', '9935X83216000000', '9935X82858000000',
'9929X87851000000', '9923X88011000000', '9946X88576000000',
'9905X50119000000', '9946X01159000000', '9910X84431000000',
'9935X00174000000', '0363E00366000000', '9905X83734000000',
'9946X83792000000', '9946X82592000000', '9946X83603000000',
'9946X82134000000', '9935X82591000000', '9946X83381000000',
'9929X86840000000', '0094N00318000000', '0881A00120000000',
'9910X01280000000', '9929X87894000000', '9923X82441000000',
'9946X83022000000', '0088E00306000000', '9929X00510000000',
'9935X83321000000', '9935X88152000000', '9935X87999000000',
'9946X84390000000', '9935X82737000000', '0564G00200000000',
'9946X82575000000', '9946X82941000000', '9910X84147000000',
'9935X83544000000', '9935X82209000000', '9929X00082000000',
'9929X88177000000', '9929X83924000000', '9910X81050000000',
'9946X83867000000', '8000T02990000000', '9910X01175000000',
'9929X00636000000', '9935X83358000000', '9935X83326000000',
'9910X82470000000', '9929X87547000000', '9929X85885000000',
'9935X82428000000', '9946X82808000000', '9923X84394000000',
'9905X84074000000', '9946X00122000000', '9935X50011000000',
'9929X85668000000', '9905X01570000000', '9946X84254000000',
'0083G00081000000', '9923X82375000000', '0012N00111000000',
'0011E00251000000', '9946X88171000000', '9923X82105000000',
'9929X01859000000', '9844X00662000000', '9841X00138000000',
'9946X83626000000', '9923X82260000000', '9929X82239000000',
'1735P00011000000', '9935X87841000000', '9929X01854000000',
'9905X83393000000', '9946X83221000000', '9923X87465000000',
'9929X84167000000', '9905X00569000000', '9929X83376000000',
'9929X86329000000', '9910X82076000000', '9929X83013000000',
'9905X00685000000', '9946X82102000000', '9929X85028000000',
'9929X01629000000', '8000T03333000000', '9946X50569000000',
'9935X50281000000', '9905X82173000000', '9946X00705000000',
'9935X82075000000', '9935X87849000000', '1129B00279000000',
'9929X87015000000', '9935X88270000000', '9946X83383000000',
'9946X82051000000', '0014A00394000000', '9809X00275000000',
'9946X83824000000', '9946X00292000000', '9929X88322000000',
'9923X84424000000', '9910X01376000000', '9905X00781000000',
'9935X83534000000', '9935X82589000000', '9946X83777000000',
'1202D00220000000', '9929X87845000000', '9929X84972000000',
'9910X82628000000', '9923X01039000000', '0045M00086000000',
'9910X01130000000', '9946X88556000000', '9935X87800000000',
'9946X84305000000', '0083M00064000000', '9841X50005000000',
'9946X83252000000', '9910X84293000000', '9905X00090000000',
'9946X82818000000', '9929X84659000000', '0051K00248000000',
'9905X00999000000', '9929X86314000000', '0218S00150000000',
'9844X00359000000', '9910X84392000000', '9946X83414000000',
'9946X84139000000', '9908X82556000000', '9929X85082000000',
'0083H00021000000', '9946X84799000000', '0362A00023000000',
'9935X00301000000', '9910X83877000000', '9905X83467000000',
'9929X85676000000', '9946X83631000000', '9946X88113000000',
'9935X00131000000', '0701J00050000000', '9923X88224000000',
'0710E00008000100', '9910X83987000000', '9910X01505000000',
'0023G00013000000', '9946X85467000000', '9935X82847000000',
'0423A00002000000', '9935X88391000000', '9946X83821000000',
'9946X01685000000', '9905X82226000000', '9923X84469000000',
'9929X81015000000', '9935X01241000000', '9809X83052000000',
'0124J00161000000', '9935X88349000000', '9929X82248000000',
'9946X87929000000', '9946X84131000000', '9905X82308000000',
'9929X85011000000', '8000T00437000000', '0163S00182000000',
'9935X88080000000', '9935X82773000000', '9946X00096000000',
'9905X01704000000', '9929X00425000000', '9929X87189000000',
'9929X87544000000', '9946X82240000000', '9929X85814000000',
'9946X84686000000', '9929X86872000000', '9844X82046000000',
'9905X83821000000', '8000T00538000000', '9935X83310000000',
'9923X88373000000', '9935X88392000000', '9935X82070000000',
'9929X87028000000', '9929X01390000000', '9946X50095000000',
'9905X01678000000', '0233E00262000800', '9905X83953000000',
'0124J00125000000', '9905X01761000000', '0125L00270000000',
'9905X01522000000', '1211R00009000000', '9935X83471000000',
'9905X00958000000', '9929X00351000000', '9946X01534000000',
'0629G00301000000', '0083L00293000000', '9905X82101000000',
'1240H00299000000', '9905X83089000000', '9935X01030000000',
'9939X82686000000', '9910X84300000000', '9910X80058000000',
'9929X01869000000', '9946X84035000000', '9946X50030000000',
'9809X82041000000', '9910X50074000000', '9935X82201000000',
'9910X00143000000', '9809X83050000000', '0012J00265000000',
'9946X01273000000', '9929X87035000000', '9946X83987000000',
'9946X82065000000', '9908X83028000000', '9935X82320000000',
'9935X88191000000', '9929X00086000000', '9905X50110000000',
'0775D00080000000', '9923X88096000000', '9905X83145000000',
'9946X50346000000', '0159M00044000000', '9910X01510000000',
'9910X84497000000', '9905X83450000000', '9809X83026000000',
'9908X82524000000', '9946X85626000000', '0520C00022000000',
'9929X01110000000', '9935X01119000000', '0046E00063000000',
'0175C00226000000', '9910X00770000000', '9910X83865000000',
'9946X50272000000', '9923X00693000000', '9905X01091000000',
'9946X84129000000', '9929X86566000000', '9935X83017000000',
'9935X82907000000', '9929X00883000000', '9946X88060000000',
'9946X83385000000', '0233E00262000100', '9946X00311000000',
'9929X86028000000', '8000T01864000000', '0670M00100000000',
'9929X84553000000', '9946X00893000000', '9809X00277000000',
'9935X87875000000', '9946X82199000000', '0510C00119000000',
'9923X00361000000', '0055P00334000000', '9923X84474000000',
'9905X00831000000', '9929X85221000000', '9908X82911000000',
'0242P00062000000', '9946X84739000000', '9905X00853000000',
'9946X84118000000', '9929X00705000000', '9905X83207000000',
'9935X82534000000', '9929X86821000000', '9905X83280000000',
'9905X00651000000', '9935X82479000000', '9946X82292000000',
'9935X88090000000', '1507M00064000000', '9929X50005000000',
'9809X00321000000', '9905X82603000000', '9935X82472000000',
'8000T02567000000', '9905X00870000000', '9946X82164000000',
'9844X80001000000', '1211M00100000000', '9905X00239000000',
'8000T03130000000', '9946X85262920100', '9935X83178000000',
'9946X85618000000', '9923X82423000000', '9841X00156000000',
'9910X83879000000', '9946X84153000000', '9910X81051000000',
'9946X88106000000', '9929X84908000000', '9929X00447000000',
'0099B00175001900', '9910X84357000000', '9910X82473000000',
'9946X84440000000', '9905X00950000000', '9923X00134000000',
'9910X84065000000', '9923X50026000000', '9946X83619000000',
'9946X85202000000', '9905X00755000000', '9910X50086000000',
'0882M00060000000', '9935X82174000000', '9929X84220000000',
'9929X01207000000', '0011M00189000000', '9946X83165000000',
'9929X87472000000', '9935X00601000000', '9946X82543000000',
'9929X00040000000', '9946X84330000000', '9946X83195000000',
'0214K00188000000', '9905X84024000000', '9923X87499000000',
'9809X00083000000', '9946X83960000000', '9946X88051000000',
'9946X85250000000', '0436J00326000000', '9929X88025000000',
'9905X82320000000', '9923X88375000000', '9911X01422000000',
'9935X83361000000', '9946X88233000000', '9935X50148000000',
'9929X84673000000', '9910X84351000000', '9946X84137000000',
'9946X83060000000', '0050K00063000000', '9910X00138000000',
'9923X87963000000', '9929X50251000000', '9935X82931000000',
'9929X88239000000', '9929X87990000000', '9923X00235000000',
'9923X84655000000', '9946X88471000000', '9946X81024000000',
'9905X82780000000', '9929X86863000000', '9929X50056000000',
'9910X81047000000', '9905X82305000000', '9935X82666000000',
'8000T00122000000', '0010P00094000000', '9844X00191000000',
'9929X00654000000', '9929X00299000000', '9905X00859000000',
'9844X82018000000', '9935X01144000000', '9929X86675000000',
'9905X00829000000', '0880K00085000000', '0025P00147000000',
'9910X80048000000', '9844X00007000000', '9929X83510000000',
'9946X00484000000', '9923X88273000000', '9946X50144000000',
'0083M00070000000', '9929X88206000000', '9946X50348000000',
'9908X82922000000', '0307N00142000000', '9929X00953000000',
'9929X01596000000', '9935X82835000000', '9946X82305000000',
'9905X00866000000', '0084A00123000000', '9923X87602000000',
'9946X84048000000', '9935X83790000000', '9946X82791000000',
'9923X00923000000', '9929X85314000000', '9910X00418000000',
'9935X83063000000', '9946X87910000000', '8000T01809000000',
'9905X01455000000', '9946X01815000000', '9923X82056000000',
'0633N00298000000', '9935X50124000000', '9935X83505000000',
'9929X83405000000', '0616C00300000000', '9923X88473000000',
'9929X87986000000', '9929X87466000000', '9935X00381000000',
'9905X82639000000', '9929X86175000000', '9929X86184000000',
'9905X00966000000', '9946X88582000000', '9905X83582000000',
'0749S00225000000', '9923X82492000000', '9946X82713000000',
'9905X00840000000', '9935X83474000000', '9946X85050000000',
'9935X88192000000', '9929X87402000000', '9929X85059000000',
'9923X82193000000', '9929X87521000000', '9946X84375000000',
'9929X01845000000', '9935X83176000000', '9946X84908000000',
'9935X01078000000', '9935X88235000000', '0170C00118000000',
'9946X84030000000', '9935X88641000000', '9935X88153000000',
'0762R00067000000', '9844X00314000000', '9946X83924000000',
'9905X01515000000', '9929X01065000000', '9946X84132000000',
'9935X82807000000', '9929X00159000000', '9905X83645000000',
'9935X82918000000', '9929X83221000000', '9946X50209000000',
'9910X00405000000', '0050K00154000400', '9929X87346000000',
'9929X85868000000', '9946X83750000000', '9946X87851000000',
'9946X84761000000', '0663A00012000100', '9935X87809000000',
'9905X84075000000', '9946X82898000000', '9905X83009000000',
'9929X86270000000', '9910X84196000000', '9946X84311000000',
'9946X01630000000', '9929X00338000000', '9935X87840000000',
'9905X83908000000', '9844X00623000000', '9929X88009000000',
'9946X82237000000', '9844X00355000000', '9935X50160000000',
'9935X01017000000', '9935X87914000000', '8000T01684000000',
'9929X87432000000', '9935X00557000000', '9841X00015000000',
'9923X01038000000', '9844X00435000000', '9935X83213000000',
'9946X82953000000', '9923X88099000000', '9929X82351000000',
'9905X00237000000', '9923X00881000000', '9910X01666000000',
'9929X01529000000', '8000T01468000000', '9929X81023000000',
'9935X50275000000', '9905X82623000000', '9923X00002000000',
'0727S00130000000', '9946X88169000000', '9935X83208000000',
'9905X82458000000', '9935X82725000000', '9935X82410000000',
'9946X85625000000', '9929X00171000000', '9841X00193000000',
'9905X82466000000', '9905X01494000000', '9905X83535000000',
'9929X83904000000', '9946X84395000000', '9923X00690000000',
'9905X82004000000', '9946X88459000000', '8000T00237000000',
'9929X00336000000', '9929X01093000000', '9905X01010000000',
'9929X87157000000', '9905X01711000000', '9844X82016000000',
'9946X85040000000', '0050K00029000000', '1138C00092000000',
'0085D00062A21600', '9935X00195000000', '9946X83602000000',
'9923X87454000000', '9946X84859000000', '0612R00002000000',
'9905X83471000000', '9910X00046000000', '9905X82137000000',
'9946X85079000000', '9923X87658000000', '9910X83876000000',
'9905X00751000000', '9946X85440000000', '9905X00138000000',
'9946X83351000000', '0070M00168000000', '0609P00174000000',
'0422K00270000000', '0375K00259000000', '9946X85577000000',
'9910X01246000000', '9929X83356000000', '9929X87743000000',
'9923X00019000000', '9929X86258000000', '9910X00416000000',
'9946X00936000000', '9946X85089000000', '9929X00301000000',
'9935X83664000000', '9929X87027000000', '9923X84468000000',
'9929X86325000000', '0121G00034000000', '0660B00048000000',
'9946X83164000000', '9946X01375000000', '9946X01557000000',
'9929X82545000000', '9946X84164000000', '9905X01255000000',
'9910X84400000000', '0066E00044000000', '9946X88054000000',
'9946X01671000000', '9923X80016000000', '9929X00730000000',
'1241L00347000000', '9935X50165000000', '9935X88060000000',
'9946X00536000000', '9923X84687000000', '9908X82963000000',
'8000T00270000000', '9929X87442000000', '9809X82035000000',
'9929X87604000000', '0516M00036000000', '9946X84814000000',
'9905X84005002C00', '9946X83948000000', '9935X83141000000',
'0083M00073000000', '9935X00697000000', '9923X87824000000',
'9929X00210000000', '2019F00299000001', '9946X82578000000',
'9929X87408000000', '9929X87448000000', '9923X84397000000',
'9923X88134000000', '9841X00064000000', '9910X82658000000',
'0606J00098000000', '9923X84651000000', '9946X87729000000',
'9905X84023000000', '9946X00851000000', '0301N00100000000',
'9923X82437000000', '9923X88566000000', '9844X00638000000',
'9905X01612000000', '8000T03265000000', '9935X83182000000',
'9946X84734000000', '9929X86137000000', '9935X01286000000',
'9910X00356000000', '2381K00008000000', '9935X87973000000',
'0615A00084000000', '0001N00281004B00', '9946X88229000000',
'9923X82152000000', '9946X50203000000', '9844X00262000000',
'9946X82204000000', '0766M00138000000', '9935X82830000000',
'9923X00379000000', '9923X82381000000', '9923X82443000000',
'9929X83451000000', '9844X00614000000', '9910X00933000000',
'9946X82130000000', '9935X82932000000', '9946X85049000000',
'9929X88141000000', '9923X84346000000', '9946X88002000000',
'9905X50079000000', '8000T02174000000', '9946X84040000000',
'9905X83356000000', '0115C00317000000', '9946X83209000000',
'0502M00216000000', '9946X82583000000', '9923X00285000000',
'9923X00866000000', '9905X00946000000', '9929X82684000000',
'9929X00228000000', '0727S00025000000', '9935X83703000000',
'9923X84590000000', '9910X00928000000', '0010J00159000A00',
'9929X87458000000', '9923X88335000000', '9935X83032000000',
'9935X83167000000', '9946X82587000000', '9946X50495000000',
'9929X83869000000', '0083L00018000000', '9905X83732000000',
'9929X87923000000', '9946X83635000000', '9910X00289000000',
'9929X86698000000', '9923X00822000000', '9946X82189000000',
'9910X84525000000', '9946X82943000000', '9905X82923000000',
'9929X00477000000', '9935X83470000000', '9946X83476000000',
'9946X84377000000', '9946X87939000000', '0647E00096000000',
'9946X88218000000', '9910X00115000000', '9809X00162000000',
'9923X82141000000', '9923X84356000000', '9923X84652000000',
'9929X01067000000', '9905X83762000000', '9929X86369000000',
'9923X87569000000', '9809X00074000000', '0321H00070000031',
'9946X82819000000', '9946X88333000000', '8000T02733000000',
'9923X00370000000', '9905X82131000000', '9905X01610000000',
'9946X00514000000', '9935X82429000000', '9929X87596000000',
'9910X84187000000', '9929X88205000000', '9809X83020000000',
'9905X01756000000', '9946X01564000000', '9935X83550000000',
'9946X85266000000', '9929X83412000000', '9923X82311000000',
'9946X50429000000', '9929X87212000000', '9946X00571000000',
'9905X01246000000', '9946X82466000000', '9935X88193000000',
'9946X83117000000', '9946X82537000000', '9929X84547000000',
'9935X83482000000', '9946X87733000000', '9905X83668905D00',
'9929X87639000000', '0466B00170000100', '9935X82059000000',
'9929X87497000000', '9935X00417000000', '9946X50189000000',
'9905X01879000000', '9946X50489000000', '9946X84424000000',
'9946X85518000000', '9910X00464000000', '9935X88426000000',
'9946X87952000000', '9929X87533000000', '9929X84844000000',
'9844X00356000000', '9809X84029000000', '8000T04165000000',
'9946X84378000000', '9946X88428000000', '0024J00227000000',
'9910X84092000000', '0719F00012000000', '9905X83095000000',
'9935X00079000000', '9935X82966000000', '9910X82276000000',
'8000T01815000000', '0025H00113000000', '9946X01494000000',
'9946X84021000000', '9841X82011000000', '0236K00238000000',
'9929X85081000000', '9910X00303000000', '9905X82799000000',
'9905X00517000000', '9935X87902000000', '9923X87782000000',
'9929X88256000000', '9946X82967000000', '9910X00806000000',
'9929X86862000000', '9841X00192000000', '9844X00547000000',
'9946X85098000000', '1670G00191000000', '9935X83005000000',
'9905X01922000000', '9929X87650000000', '9946X83891000000',
'9946X84732000000', '9844X00050000000', '9939X50416000000',
'9946X85078000000', '9939X50640000000', '9946X84826000000',
'9910X84516000000', '9946X85092000000', '9929X01598000000',
'9935X83431000000', '9946X88393000000', '9935X50247000000',
'9905X00547000000', '9844X82019000000', '1002B00030000400',
'8000T00576000000', '9809X00077000000', '9946X85118000000',
'9929X86626000000', '9946X83354000000', '9946X88643000000',
'0273G00050000000', '9935X88357000000', '9946X85201000000',
'9946X00403000000', '9946X83614000000', '0004B00224000000',
'9929X88080000000', '9946X00257000000', '9946X82651000000',
'9929X87746000000', '9929X01011000000', '9905X83469000000',
'9905X82196000000', '9946X83862000000', '9946X84127000000',
'9905X00409000000', '9929X85507000000', '9923X84581000000',
'8000T01418000000', '8000T01365000000', '9946X83741000000',
'9905X82868000000', '9929X87150000000', '9935X82775000000',
'9946X00451000000', '9929X85850000000', '9935X88065000000',
'9946X82246000000', '9929X87637000000', '9929X87880000000',
'9929X87859000000', '8000T01548000000', '9929X01339000000',
'9935X82840000000', '0249B001530C2400', '9929X87921000000',
'9946X85193000000', '9809X84023000000', '0270K00021000000',
'9905X82892000000', '9929X86601000000', '9908X82927000000',
'9946X01167000000', '9929X80034000000', '9923X88247000000',
'9929X01254000000', '9946X87833000000', '0130R00252000000',
'9946X82225000000', '9910X00051000000', '9905X00864000000',
'9946X00745000000', '9946X87997000000', '9923X50074000000',
'9905X83361000000', '9935X88736000000', '9929X01857000000',
'0549N00126000000', '9841X00065000000', '9946X84458000000',
'9809X83056000000', '9935X82468000000', '9929X00587000000',
'9929X87017000000', '9809X82007000000', '9910X84082000000',
'9929X88308000000', '0329L00005000000', '9946X01429000000',
'9929X00065000000', '9929X84014000000', '9946X82269000000',
'0850C00110000000', '9946X01186000000', '9946X83138000000',
'0050K00154000100', '9929X84442000000', '0004B00224000200',
'8870X00014000001', '0140G00144000000', '9841X00143000000',
'0549H00045000000', '9910X82125000000', '9946X82133000000',
'0997B00214000000', '9929X84130000000', '0066E00124000000',
'9910X83848000000', '9923X84606000000', '9905X01855000000',
'9905X83680000000', '9935X50143000000', '9946X88165000000',
'9929X00950000000', '9946X00245000000', '9946X01430000000',
'9935X00902000000', '0236H00153000000', '9910X82441000000',
'0080F00112000000', '9910X01617000000', '9910X82759000000',
'9929X85473000000', '9946X81053000000', '9935X00085000000',
'2204B0003200A400', '0670L00040000000', '9946X83028000000',
'9910X82571000000', '9946X85495000000', '9929X86293000000',
'9905X00832000000', '9929X01036000000', '9935X01015000000',
'9946X82157000000', '9910X82455000000', '9844X00408000000',
'0124C00015000000', '9946X00915000000', '9910X82324000000',
'9910X01062000000', '9946X82328000000', '1272N00100000000',
'9910X01138000000', '9908X82903000000', '0882C00010000000',
'8000T00523000000', '9910X84653000000', '0236F00041000000',
'9923X82488000000', '8000T00824000000', '9946X50221000000',
'9946X00959000000', '9935X00537000000', '9929X88010000000',
'8000T03417000000', '0024D00275000000', '9929X83907000000',
'0469A00100000000', '9946X00949000000', '9935X82578000000',
'9935X87921000000', '9929X86785000000', '9946X87830000000',
'9946X85568000000', '9946X88642000000', '9946X84183000000',
'9923X82231000000', '9809X00121000000', '9910X84265000000',
'9923X82140000000', '9905X01541000000', '9929X01730000000',
'9946X85254000000', '9929X85942000000', '9935X88261000000',
'9929X50046000000', '9929X85392000000', '8000T03182000000',
'0007B00207000000', '9929X00987000000', '9923X84383000000',
'9905X00088000000', '9946X87700000000', '8000T03038000000',
'9946X82988000000', '9929X84666000000', '9923X50019000000',
'9929X85872000000', '0450P00472000000', '9905X08242000000',
'9910X00778000000', '9844X00319000000', '8000T00566000000',
'9929X01179000000', '9905X00051000000', '9935X88009000000',
'9946X83350000000', '0827E00162000000', '9929X85505000000',
'0166C00180000000', '9905X82614000000', '9844X00471000000',
'9923X88098000000', '9929X87742000000', '9923X88359000000',
'9923X00628000000', '0414E00261000000', '9905X01241000000',
'9929X00884000000', '9905X00103000000', '9946X84674000000',
'9929X00597000000', '9929X86191000000', '9946X82673000000',
'2001G00004000000', '9929X00739000000', '9935X00686000000',
'9910X01632000000', '0050P00050000100', '9946X50486000000',
'9923X87577000000', '9929X84429000000', '9923X00133000000',
'9946X87840000000', '9935X82771000000', '9946X85289000000',
'9946X01871000000', '9910X82374000000', '0131C00081000000',
'9929X86680000000', '0718G00250000000', '0556C00387000000',
'9946X88127000000', '9929X00515000000', '9844X00753000000',
'9935X50012000000', '9929X00007000000', '9929X84288000000',
'9946X85228000000', '9929X85080000000', '9935X00368000000',
'9929X85107000000', '9946X50243000000', '9946X00920000000',
'9905X83669000000', '9935X83693000000', '9929X86968000000',
'9923X87912013300', '9946X83437000000', '9946X50530000000',
'8000T01384000000', '9844X00116000000', '9935X82043000000',
'9905X83966000000', '9946X85022000000', '9935X83021000000',
'9946X83974000000', '9946X84943000000', '9935X82794000000',
'9929X87284000000', '9910X80038000000', '9935X83254000000',
'9905X83855000000', '9905X82633000000', '9929X86171000000',
'9946X83908000000', '9929X87629000000', '9929X87428000000',
'9923X87687000000', '0048M00200000000', '0775D00136000000',
'9946X83611000000', '0264H00238000000', '1999L00016000000',
'9929X00474000000', '9946X83015000000', '9929X85273000000',
'9935X88257000000', '9809X00029000000', '9946X85016000000',
'9929X87397000000', '9946X83193000000', '9935X83355000000',
'9935X88385000000', '9910X84545000000', '9935X82369000000',
'9929X84847000000', '0096M00112000100', '9946X84677000000',
'9935X82564000000', '0131C00022000000', '9946X82183000000',
'9905X83055000000', '9929X83004000000', '9946X85549000000',
'0251R00125000000', '9910X01540000000', '9935X88100000000',
'9935X88273000000', '9946X88548000000', '8000T01391000000',
'9929X85443000000', '9935X50209000000', '9923X87895000000',
'9841X00072000000', '9929X80084000000', '9929X85842000000',
'9923X87736000000', '9946X84446000000', '9923X88475000000',
'9946X82667000000', '9946X01345000000', '1507S00323000000',
'0204K00244000000', '0430R00252000000', '9946X00922000000',
'0066E00148000000', '9923X82088000000', '9935X82952000000',
'9929X85359000000', '9929X85976000000', '9905X82926000000',
'9935X00441000000', '9929X83967000000', '8000T03456000000',
'0248N00160000000', '9935X00649000000', '9841X00074000000',
'8000T00445000000', '9946X00427000000', '9935X83257000000',
'9929X87449000000', '9929X83544000000', '9929X85890000000',
'9946X84439000000', '9923X87526000000', '0718K00048000000',
'9905X83785000000', '9935X88244000000', '9929X84327000000',
'9923X82036000000', '9910X82199000000', '9923X82142000001',
'9905X82457000000', '9935X00561000000', '9946X83075000000',
'9935X88735000000', '0010J00339000000', '9935X00249000000',
'0857C00399000000', '0141K00011000000', '9935X83418000000',
'9946X84168000000', '0049L00336000000', '9935X83024000000',
'0011E00284000000', '9929X80060000000', '9935X00407000000',
'9923X82471000000', '9929X84648000000', '8000T00486000000',
'9923X82340000000', '9935X88515000000', '9929X88051000000',
'1211R00152000000', '9929X01960000000', '9946X80001000000',
'9929X01215000000', '9809X84046000000', '9923X87684000000',
'9946X82652000000', '9929X50022000000', '9809X00344000000',
'9910X84117000000', '9946X83836000000', '9929X01311000000',
'9946X82054000000', '9946X85156000000', '9929X50286000000',
'9905X83353000000', '9946X82803000000', '9809X50003000000',
'9929X85427000000', '9929X83231000000', '9923X87734000000',
'9935X88032000000', '9809X83039000000', '9910X82422000000',
'9905X00024000000', '0130R00271000000', '9935X83215000000',
'9923X87754000000', '9929X01516000000', '9923X00824000000',
'9908X82933000000', '9910X84049000000', '9946X82762000000',
'9946X50251000000', '9910X00406000000', '9946X83265000000',
'9946X83519000000', '9946X88125000000', '9809X00200000000',
'9935X50052000000', '9923X00519000000', '9935X00639000000',
'9809X00179000000', '9929X83563000000', '9929X88079000000',
'0348N00103000000', '9910X00900000000', '9935X01270000000',
'9946X80023000000', '9905X00532000000', '9946X84393000000',
'0361F00078000200', '9929X82802000000', '9910X82126000000',
'9910X84345000000', '9929X00659000000', '0024D00307000000',
'9935X00149000000', '9905X82163000000', '9929X00540000000',
'9905X00248000000', '9923X87572000000', '9946X85316000000',
'9946X83160000000', '9844X82010000000', '9910X00978000000',
'9923X82469000000', '9923X82207000000', '9844X00699000000',
'9935X00453000000', '9935X50107000000', '9929X86177000000',
'9929X88342000000', '9946X85257000000', '9905X83290000000',
'9935X83335000000', '9923X84483000000', '9935X82687000000',
'9923X01042000000', '0175P00309000300', '9935X82253000000',
'9946X87703000000', '9946X82852000000', '9946X00864000000',
'9946X82705000000', '9935X88546000000', '9910X84440000000',
'9946X83112000000', '9935X83822000000', '9946X00483000000',
'9929X83545000000', '9923X00578000000', '9946X00256000000',
'9935X82143000000', '9923X88544000000', '9946X50553000000',
'9923X00396000000', '9844X00204000000', '9935X00257000000',
'9935X88233000000', '9923X88326000000', '9905X01372000000',
'9929X83006000000', '0046E00062000000', '9910X00410000000',
'9910X83818000000', '9946X50167000000', '9905X00289000000',
'9929X88011000000', '0062B00082000000', '9905X82026000000',
'9929X88212000000', '9935X50282000000', '9935X82504000000',
'9946X83528000000', '9946X85414000000', '9923X87904000000',
'9935X83541000000', '9935X82345000000', '9935X88279000000',
'9935X82183000000', '0022K00033000000', '9946X83432000000',
'9935X83816000000', '9946X82934000000', '9946X00924000000',
'0957C00204000000', '9946X00968000000', '9946X82333000000',
'9844X00491000000', '9923X88471000000', '9929X86005000000',
'9905X82471000000', '9946X85364000000', '9923X84319000000',
'9929X01692000000', '9923X00333000000', '9908X82930000000',
'9910X84343000000', '9946X01089000000', '9935X82301000000',
'9905X00175000000', '9946X83927000000', '9946X84177000000',
'9910X82504000000', '9929X00004000000', '9910X84247000000',
'9910X00058000000', '9929X01277000000', '9929X84467000000',
'9929X00324000000', '9923X87813000000', '9946X01228000000',
'9946X01787000000', '9910X82024000000', '9935X82486000000',
'0458F00051000000', '9905X00098000000', '9935X82250000000',
'9923X88343000000', '9946X84823000000', '9905X01575000000',
'9946X84032000000', '9935X83503000000', '9905X83951000000',
'9935X83390000000', '9929X01098000000', '9946X85023000000',
'9946X83485000000', '9880X85090000000', '9946X83069000000',
'9946X00500000000', '9923X88467000000', '9923X01058000000',
'1210G00008000000', '9905X83464000000', '9946X00524000000',
'9923X00079000000', '9946X00731000000', '9946X01025000000',
'9905X84031000000', '9946X82516000000', '0131E00041000000',
'9929X87562000000', '0357H00150003100', '9946X84060000000',
'9935X83548000000', '9841X00086000000', '9910X00643000000',
'9910X50034000000', '9946X85093000000', '9910X84461000000',
'0011A00253000000', '9910X01624000000', '9935X83770000000',
'9946X83536000000', '9929X50057000000', '9946X87907000000',
'9929X87961000000', '9929X87815000000', '9910X01168000000',
'9929X00277000000', '0232A00176000000', '9910X82440000000',
'9929X86262000000', '0008H00200000000', '9946X01082000000',
'9929X83098000000', '0551E00138000000', '9946X82532000000',
'9910X00153000000', '9923X87880000000', '9946X01420000000',
'9946X01413000000', '9910X00712000000', '9929X83389000000',
'9809X82011000000', '9935X88602000000', '9935X83620000000',
'9935X88116000000', '9935X87869000000', '9929X01595000000',
'9905X82446000000', '0512L00010000100', '9935X87835000000',
'0050F00004000000', '9905X83681000000', '9935X87942000000',
'9929X82546000000', '0050K00154000500', '0086P00283000001',
'9935X82375000000', '9929X50079000000', '9946X00767000000',
'9809X83025000000', '9946X83844000000', '9910X82320000000',
'9905X83944000000', '9935X82851000000', '9905X01596000000',
'0220P00242000000', '9923X88587000000', '9844X00040000000',
'9946X84397000000', '9905X84038000000', '9929X85891000000',
'9929X87614000000', '0450P00465000000', '9946X87918000000',
'9946X84324000000', '9935X82703000000', '9946X82354000000',
'9923X82205000000', '9946X00402000000', '9923X84698000000',
'9929X88340000000', '0002M00308000000', '9910X84493000000',
'8000T00388000000', '9946X01288000000', '9935X88450000000',
'9929X01410000000', '9935X00459000000', '9946X83571000000',
'9946X83895000000', '9929X85393000000', '9929X87198000000',
'9946X50114000000', '9905X82773000000', '9946X84258000000',
'9946X83194000000', '9935X82555000000', '9923X82343000000',
'9935X82145000000', '0010J00334000000', '9935X01129000000',
'9910X00551000000', '9905X01370000000', '9929X84318000000',
'9946X81038000000', '9946X82621000000', '9946X85639000000',
'0052E00081050500', '9910X01026000000', '9923X00787000000',
'9935X82684000000', '9905X83279000000', '9946X83211000000',
'9910X83813000000', '9929X84859000000', '9935X88384000000',
'9946X84372000000', '9929X88222000000', '1104P00273000000',
'9946X83982000000', '9946X50086000000', '9946X50099000000',
'9923X00034000000', '9905X01132000000', '0717M00021000100',
'9929X84359000000', '9935X87918000000', '9935X82377000000',
'9935X83451000000', '9929X88218000000', '9929X85276000000',
'9923X82408000000', '9935X00014000000', '9905X83740000000',
'9910X01660000000', '9929X83833000000', '9946X82364000000',
'9929X85495000000', '9844X00015000000', '9935X88258000000',
'9946X83260000000', '9905X00855000000', '9929X01802000000',
'0134F00218000000', '9910X82461000000', '9908X82932000000',
'9946X88286000000', '0392C00185000000', '9946X88318000000',
'0083M00219000000', '9935X82700000000', '9929X84810000000',
'9929X88307000000', '0083S00145000000', '9946X87925000000',
'9923X00435000000', '9929X84395000000', '0829N00045000100',
'9935X50130000000', '9935X83813000000', '9946X87994000000',
'9935X50239000000', '9929X85823000000', '9946X88243000000',
'9946X82264000000', '0885B00160000000', '9935X83670000000',
'9935X50236000000', '9929X87877000000', '9946X88124000000',
'0011A00134000000', '9929X87572000000', '9923X87635000000',
'0182R00020000000', '8000T00418000000', '9910X82200000000',
'9910X50090000000', '9946X87937000000', '0450P00460000000',
'9905X83505000000', '9910X84022000000', '9935X00627000000',
'9905X82278000000', '9923X84309000000', '9946X82913000000',
'9905X82793000000', '9935X82023000000', '9935X82405000000',
'9935X82832000000', '1077G00045000000', '9923X00582000000',
'9910X01197000000', '9910X01597000000', '9935X83823000000',
'9946X88188000000', '9935X83220000000', '1136A00066000000',
'9923X01043000000', '9935X00599000000', '9910X00317000000',
'9946X84097000000', '9935X83538000000', '0155H00059000000',
'9905X84100000000', '9910X82074000000', '9935X82513000000',
'9946X84415000000', '9946X50166000000', '9935X83153000000',
'9946X50264000000', '9923X88604000000', '9935X82860000000',
'9910X00888000000', '9946X01763000000', '9905X00828000000',
'9929X00221000000', '9929X82854000000', '9946X01444000000',
'9910X00187000000', '0131C00206000000', '9923X87784000000',
'9905X82031000000', '9905X82909000000', '0421F00307000000',
'9923X00606000000', '9923X84627000000', '8000T02698000000',
'9929X85701000000', '9929X81022000000', '9935X83726000000',
'0010J00124000000', '9929X87519000000', '9929X83383000000',
'9946X84105000000', '9910X00716000000', '9935X87867000000',
'9946X84230000000', '0309G00158000000', '9929X00633000000',
'9905X83257000000', '9929X88123000000', '9946X00050000000',
'9929X01543000000', '9905X82461000000', '9929X01986000000',
'9905X83497000000', '9946X88473000000', '0069M00277000000',
'9935X83824000000', '9905X83685000000', '9929X84284000000',
'9946X83486000000', '0023F00257000000', '0256M00101000000',
'9929X86114000000', '9841X50007000000', '9809X84000000000',
'9910X00723000000', '0059F00157000100', '9905X00297000000',
'9946X85576000000', '8000T01925000000', '9929X85893000000',
'0076J00045000000', '9929X83100000000', '9910X84295000000',
'9946X50300000000', '9935X01029000000', '9841X00216000000',
'0512L00018000100', '9946X01008000000', '9910X83955000000',
'9935X01330000000', '9929X85446000000', '9929X86777000000',
'9929X87024000000', '9946X00704000000', '9935X83391000000',
'9910X80022000000', '1203F00127000300', '8000T03487000000',
'9946X82971000000', '9910X01156000000', '0131C00204000000',
'9923X84565000000', '9905X83981000000', '9929X83515000000',
'9935X00066000000', '9905X00760000000', '9905X01345000000',
'9935X87872000000', '9946X01057000000', '9929X01072000000',
'9905X82198000000', '9929X01360000000', '9946X84985000000',
'9946X00063000000', '9923X88431000000', '1222D00095000000',
'9946X85170000000', '9946X84441000000', '0008H00202000000',
'0525J00200000000', '0422D00200000000', '9905X82152000000',
'9935X83378000000', '9929X85311000000', '9929X85032000000',
'9929X83509000000', '9946X00268000000', '0124J00165000000',
'9946X01144000000', '9929X85497000000', '9935X83301000000',
'9935X00594000000', '9910X00031000000', '9923X84395000000',
'9905X83458000000', '9935X88160000000', '9844X82040000000',
'9935X82010000000', '9809X00071000000', '0083L00085000000',
'9929X87913000000', '8000T03186000000', '9929X01775000000',
'9935X83103000000', '9929X85108000000', '9929X00557000000',
'9923X87630000000', '9946X00336000000', '0236R00128000000',
'9923X82102000000', '9946X83264000000', '9923X01002000000',
'1671B00260000000', '9923X87479000000', '9946X83584000000',
'9910X82139000000', '9946X82616000000', '1077F00336000000',
'0478K00032000000', '9905X83767000000', '9946X85548000000',
'9935X00054000000', '9929X85501000000', '9946X88256000000',
'1345M00233000000', '9946X88075000000', '9929X83229000000',
'9844X00732000000', '9935X83090000000', '9905X00095000000',
'9910X00440000000', '9946X84028000000', '9923X00044000000',
'9946X88554000000', '0604J00135000000', '9946X84024000000',
'9923X88428000000', '0008H00201000000', '9905X01937000000',
'9935X50001000000', '9935X82096000000', '1077L00100000000',
'9844X00133000000', '0087C00243000000', '9910X00474000000',
'2372R00516000000', '8000T00164000000', '9935X83682000000',
'0125L00288000000', '9946X00281000000', '9929X87663000000',
'9935X82246000000', '9905X01876000000', '9905X83474000000',
'9946X83356000000', '9935X83045000000', '9929X85149000000',
'9929X83083000000', '9946X85510000000', '9946X82961000000',
'9923X84521000000', '9929X83164000000', '9946X88050000000',
'9935X83251000000', '8000T00944000000', '0083S00152000000',
'9923X00752000000', '9946X83283000000', '9923X87798000000',
'9923X00873000000', '9908X83027000000', '9910X00501000000',
'9946X50018000000', '9946X84410000000', '9910X82398000000',
'9946X83812000000', '9946X88424000000', '9946X88414000000',
'9910X84498000000', '9905X83837000000', '9929X84661000000',
'0560F00008000000', '9905X83682000000', '9905X01389000000',
'9946X83384000000', '9946X83852000000', '9935X82344000000',
'9946X88541000000', '9905X83370000000', '9946X50005000000',
'9946X82952000000', '9946X85590000000', '9946X01482000000',
'9935X82848000000', '9923X80007000000', '9923X87851000000',
'9910X84129000000', '9935X82897000000', '9905X83813000000',
'9935X01131000000', '9929X85010000000', '9929X87569000000',
'9929X87399000000', '0713G00605030400', '9946X50152000000',
'9910X83838000000', '9905X82245000000', '9946X82815000000',
'9935X87795000000', '9905X83307000000', '9923X82118000000',
'9923X88156000000', '9946X83586000000', '9929X01293000000',
'9910X82203000000', '9929X01382000000', '9844X00309000000',
'9935X82672000000', '9935X00173000000', '9905X00784000000',
'9929X01027000000', '9923X87732000000', '9935X83263000000',
'8000T00145000000', '9935X83115000000', '9923X87699000000',
'9946X82718000000', '9935X87974000000', '9923X88086000000',
'9910X83975000000', '9923X84551000000', '9946X50013000000',
'9946X84291000000', '9929X85260000000', '9905X83079000000',
'9946X01697000000', '9946X83056000000', '9905X82992000000',
'9923X00556000000', '9905X01272000000', '9929X83535000000',
'9923X88323000000', '9929X01697000000', '9929X83450000000',
'9929X87556000000', '9929X84819000000', '9929X87660000000',
'9905X01442000000', '9946X01761000000', '9905X01738000000',
'9923X87619000000', '9929X87960000000', '9946X87988000000',
'9935X82509000000', '9841X00019000000', '9946X88346000000',
'9946X87836000000', '9923X00955000000', '0010J00118000000',
'9929X87591000000', '9910X84539000000', '9905X00677000000',
'9905X82897000000', '9923X81016000000', '9929X01643000000',
'9946X88398000000', '9905X01547000000', '9923X84337000000',
'0611C00213000000', '9929X86813000000', '9905X82322000000',
'9946X01132000000', '0255B00018000000', '9929X82533000000',
'9935X88305000000', '9946X82162000000', '0356G00320000000',
'9946X01784000000', '9946X85476000000', '0003N00030000000',
'9929X00873000000', '9946X88096000000', '9946X82550000000',
'9905X01517000000', '9929X01231000000', '9910X84635000000',
'0027B00104000000', '9923X50024000000', '9923X84444000000',
'9946X00892000000', '9935X82435000000', '0039R00009000000',
'9929X87416000000', '9946X88537000000', '9946X88077000000',
'0624D00059000000', '9905X00757000000', '9946X85560000000',
'9929X85133000000', '9946X84031000000', '9905X83903000000',
'9935X83181000000', '9946X82864000000', '9946X00942000000',
'9923X87548000000', '9929X84910000000', '9929X86204000000',
'0267G00290000000', '9946X84327000000', '9809X82063000000',
'9946X85388000000', '9841X00026000000', '9923X00904000000',
'9844X00196000000', '9946X80022000000', '9946X88121000000',
'9910X83943000000', '9905X00981000000', '9935X50280000000',
'9929X01563000000', '9809X00246000000', '9946X82307000000',
'9935X83344000000', '9923X87962000000', '9935X83567000000',
'9935X00811000000', '9905X82617000000', '8000T03144000000',
'9929X82261000000', '9923X87843000000', '9905X01783000000',
'9910X82216000000', '9929X85739000000', '9929X00577000000',
'9935X00473000000', '9946X83034000000', '9946X82693000000',
'9946X85177000000', '9946X82946000000', '9841X00017000000',
'9935X83327000000', '9923X84358000000', '9935X88168000000',
'0362F00180000000', '0512L00153000000', '8000T00124000000',
'0010N00106000000', '9910X84296000000', '9929X87051000000',
'9929X83203000000', '9946X82219000000', '9929X00603000000',
'9844X82052000000', '9905X83853000000', '9935X83795000000',
'9910X01661000000', '9910X84312000000', '9929X01525000000',
'0316J00080000000', '0353C00172000000', '9910X83826000000',
'9905X01395000000', '9946X88478000000', '9946X87725000000',
'9929X00729000000', '9935X82395000000', '9935X82257000000',
'0088D00112000000', '9929X86819000000', '0223C00056000000',
'9929X50175000000', '9929X86190000000', '9929X50413000000',
'9946X88227000000', '9923X87768000000', '0083K00089000000',
'9910X84155000000', '9923X82156000000', '9929X81016000000',
'9905X82807000000', '9946X83449000000', '9929X88230000000',
'9946X87989000000', '9929X85386000000', '9929X83970000000',
'9923X87858000000', '9905X83664000000', '9923X84693000000',
'9935X88046000000', '9910X01588000000', '1356A00200000001',
'0131C00163000000', '9946X82780000000', '9923X82398000000',
'9908X83038000000', '9935X83793000000', '9929X87893000000',
'9910X00957000000', '9923X87960000000', '9946X83088000000',
'9929X00092000000', '9929X01968000000', '9929X87982000000',
'9929X87420000000', '9910X00650000000', '0543G00151000100',
'0473B00105000000', '9946X85632000000', '9910X84406000000',
'9946X50523000000', '9946X84366000000', '9844X00277000000',
'9929X87563000000', '9935X00273000000', '9935X50154000000',
'9946X83054000000', '9923X00337000000', '9935X00565000000',
'9929X84290000000', '9929X87193000000', '9905X50046000000',
'0620R00223000000', '2011A00326161200', '9946X88631000000',
'9923X87489000000', '9935X50015000000', '9935X88190000000',
'9946X01803000000', '9946X88340000000', '9910X01527000000',
'9905X82232000000', '9923X00437000000', '9929X82260000000',
'0717M00007000100', '0668L00040000000', '9946X01301000000',
'9910X00657000000', '9935X83255000000', '9946X88458000000',
'9923X00367000000', '9910X00443000000', '9929X83870000000',
'9946X88555000000', '9910X83941000000', '9946X82103000000',
'9929X87534000000', '9946X82228000000', '9929X87538000000',
'9929X84376000000', '9923X00284000000', '9946X01582000000',
'0006G00231000000', '9935X00210000000', '9929X83393000000',
'9946X83149000000', '9923X88115000000', '9946X82869000000',
'9923X88091000000', '9905X01134000000', '9923X88496000000',
'9905X00040000000', '9910X84649000000', '9923X87912013400',
'9923X87682000000', '9946X84104000000', '9923X82181000000',
'9946X88146000000', '9910X00377000000', '9935X82927000000',
'9935X87883000000', '9905X01609000000', '9910X01316000000',
'8000T02608000000', '9929X85845000000', '9809X50005000000',
'9946X84385000000', '0012N00224000000', '9946X83684000000',
'9844X00132000000', '9841X00197000000', '9844X00129000000',
'9946X82334000000', '9923X00823000000', '9923X84588000000',
'9946X84825000000', '9910X84190000000', '0881B00191000000',
'9905X83942000000', '9946X85051000000', '9935X00232000000',
'9844X00658000000', '0125L00273000000', '9935X83185000000',
'9929X86273000000', '8000T02249000000', '9929X01099000000',
'9923X88572000000', '9946X85628000000', '9946X83203000000',
'9905X50178000000', '9923X87649000000', '9923X50023000000',
'0463D00322000000', '9905X83596000000', '9946X84083000000',
'0045S00150000000', '9946X84170000000', '9910X81030000000',
'9905X83006000000', '9946X82522000000', '9929X00693000000',
'9905X01121000000', '9935X82699000000', '9929X85740000000',
'9910X00503000000', '9935X82551003800', '0157R00225000000',
'9905X82831000000', '9929X83391000000', '9946X00846000000',
'8000T03288000000', '9809X00261000000', '9923X88168000000',
'9929X84975000000', '9844X82037000000', '9910X00376000000',
'9929X86248000000', '9844X81007000000', '9929X88358000000',
'9929X01637000000', '9929X01123000000', '9946X83861000000',
'9929X83867000000', '9946X85260000000', '9935X01057000000',
'9946X83151000000', '9910X00022000000', '0301N00097000000',
'9923X80012000000', '8000T00784000000', '9905X00491000000',
'9910X83890000000', '9923X87698000000', '9910X00128000000',
'8000T03755000000', '9929X84725000000', '9946X84252000000',
'9923X84675000000', '9946X01835000000', '9935X82251000000',
'0476G00300000000', '9935X88716000000', '0316J00084000000',
'9935X82943000000', '9946X82108000000', '0292C00251000000',
'0362A00022000000', '9946X85223000000', '9923X50021000000',
'9935X82417000000', '9929X87853000000', '9935X00242000000',
'0103E00100000000', '9923X88356000000', '9809X82054000000',
'9946X83934000000', '9935X82519000000', '0715G00070000000',
'9905X83719000000', '9905X01006000000', '9905X01448000000',
'9946X01414000000', '9946X87885000000', '9929X01244000000',
'0048A00131000000', '0030E00307000000', '9946X83910000000',
'9946X01386000000', '9809X00273000000', '9905X01336000000',
'9929X85024000000', '9935X82705000000', '9946X83027000000',
'9946X88620000000', '9946X85314000000', '9946X88332000000',
'9910X01462000000', '9910X82214000000', '9935X82169000000',
'9923X80017000000', '9946X85533000000', '9935X82095000000',
'9935X83370000000', '9844X00482000000', '9929X85395000000',
'0048S00249000000', '9905X82775000000', '9929X00725000000',
'0382G00209000000', '9929X87186000000', '9908X82936000000',
'9929X82495000000', '9946X01332000000', '9935X88556000000',
'9929X50011000000', '0377N00163000000', '9929X84814000000',
'9935X82565000000', '9929X84416000000', '9946X85172000000',
'9935X01171000000', '9910X01458000000', '9946X00220000000',
'9929X83456000000', '9946X82888000000', '9946X00304000000',
'9923X87657000000', '9923X88067000000', '0341G00319000000',
'0084M00346000000', '9929X84560000000', '0287R00160000000',
'9946X87752000000', '0307N00145000000', '0436J00165000000',
'0768K00015000000', '9946X50045000000', '8000T00225000000',
'0627S00239000000', '9946X85483000000', '9946X85009000000',
'9946X83976000000', '9929X85534000000', '9905X00711000000',
'9905X83544000000', '9923X87839000000', '9935X01096000000',
'9923X88447000000', '9910X01245000000', '9946X82064000000',
'9841X00025000000', '9946X83810000000', '9935X88292000000',
'9923X88095000000', '9946X87905000000', '9905X01880000000',
'9946X83558000000', '0129N00031000000', '9935X82254000000',
'9929X86818000000', '0948R00332000000', '0083M00068000000',
'9905X81006000000', '9946X01620000000', '9946X83291000000',
'9929X00583000000', '9809X00168000000', '9910X00531000000',
'9935X01265000000', '0051K00180000000', '9935X82801000000',
'9905X83736000000', '9929X01670000000', '9929X83489000000',
'9946X00533000000', '0125M00383000000', '0036H00140000000',
'1072L00365000000', '9935X50228000000', '9935X82904000000',
'9946X00667000000', '9923X84582000000', '9929X87896000000',
'9929X87323000000', '9935X82864000000', '9946X84821000000',
'9935X00621000000', '9929X87438000000', '0883N00312000000',
'9929X85257000000', '9946X82586000000', '9923X84621000000',
'9905X83360000000', '9923X88397000000', '0056P00071000C00',
'9910X00243000000', '0023G00006000000', '9910X01154000000',
'9946X87660000000', '9946X85442000000', '9929X87969000000',
'9929X87495000000', '9935X83190000000', '9923X84396000000',
'9946X84973000000', '0732F00040000000', '0125L00272000000',
'9905X83082000000', '9935X82970000000', '9923X87832000000',
'9935X87910000000', '9946X85481000000', '9946X01046000000',
'9905X01073000000', '9905X00132000000', '0103E00300000000',
'9946X01300000000', '8000T02003000000', '9935X83179000000',
'9929X85597000000', '9929X01073000000', '9910X82281000000',
'9929X82504000000', '9935X50159000000', '9929X00041000000',
'0251D00253000000', '9905X83874000000', '9946X01002000000',
'9910X00437000000', '8000T00291000000', '9946X01622000000',
'9929X87702000000', '9935X88064000000', '0126F00130000100',
'0536J00061000000', '9905X01053000000', '8000T02217000000',
'9929X84363000000', '8000T00007000000', '9905X84017000000',
'8000T02310000000', '9935X83227000000', '9905X01454000000',
'9946X84746000000', '9946X82836000000', '9935X00062000000',
'0255S00067000000', '9929X82678000000', '9946X84046000000',
'9910X00270000000', '9841X81001000000', '9935X88021000000',
'9844X00367000000', '9935X88530000000', '0692A00107000000',
'2194S00216000000', '9929X01324000000', '0023M00253000000',
'9809X82012000000', '9929X00008000000', '9905X01966000000',
'8000T02921000000', '9905X83729000000', '1203C00036000300',
'9929X86112000000', '9905X83468000000', '9910X00497000000',
'9910X83978000000', '9946X84301000000', '9929X00808000000',
'0124J00093000000', '9929X00616000000', '9946X01757000000',
'9844X00468000000', '0062G00194000000', '9905X83238000000',
'9910X01248000000', '9935X88587000000', '9946X88362000000',
'9929X88124000000', '9905X00336000000', '9923X87789000000',
'9929X85728000000', '9946X88274000000', '9935X88121000000',
'9905X83815000000', '9946X00407000000', '9905X82994000000',
'9946X84950000000', '9923X84579000000', '0241F00244000000',
'9923X87955000000', '9809X84033000000', '8000T01352000000',
'9910X84289000000', '0051S00021000000', '9929X84418000000',
'9946X01751000000', '9929X86703000000', '9910X00880000000',
'9946X84979000000', '9929X84619000000', '9935X83732000000',
'9910X50017000000', '9946X83547000000', '9905X83811000000',
'9935X82102000000', '9905X82798000000', '8000T00673000000',
'0165E00003000000', '9946X83123000000', '9935X00150000000',
'9809X84014000000', '9923X88043000000', '9905X00742000000',
'9910X01484000000', '9935X00618000000', '0390B00220000200',
'9905X83788000000', '9910X83891000000', '9905X83466000000',
'9929X01552000000', '9946X83262000000', '9946X82816000000',
'8000T00809000000', '9935X83348000000', '9935X00586000000',
'9946X83865000000', '9929X01540000000', '9935X88039000000',
'9935X83420000000', '9946X83717000000', '9923X82070000000',
'9946X85184000000', '9923X82160000000', '9935X87854000000',
'9905X00690000000', '9935X88351000000', '0455S00127000000',
'9929X50176000000', '9910X01199000000', '9923X84595000000',
'9929X82006000000', '9946X83230000000', '9935X82518000000',
'9929X00843000000', '9844X00443000000', '9905X82084000000',
'9929X86002000000', '9935X82862000000', '9905X82839000000',
'9946X00144000000', '9929X01349000000', '9946X82752000000',
'9923X87651000000', '9935X82116000000', '0231N00040000000',
'0692A00108000000', '9923X88405000000', '9946X50122000000',
'9935X82745000000', '9905X82585000000', '9929X87443000000',
'9910X84549000000', '9946X88232000000', '9905X83311000000',
'9923X88395000000', '9946X85163000000', '9946X82903000000',
'9935X50131000000', '9929X50098000000', '0191J00190000001',
'9905X01831000000', '9935X83339000000', '9923X84527000000',
'9841X00030000000', '9923X82256000000', '9935X82986000000',
'9923X00043000000', '9946X83807000000', '9946X83690000000',
'8000T01632000000', '0011M00168000000', '9946X85395000000',
'9923X00811000000', '9905X00357000000', '9929X86360000000',
'9929X50059000000', '9946X88277000000', '9910X84424000000',
'8000T03257000000', '1357F00150000000', '9946X01302000000',
'9935X83177000000', '9946X01758000000', '9946X83407000000',
'9929X88035000000', '9910X01659000000', '9935X00800000000',
'9908X82951000000', '8000T03079000000', '9929X83084000000',
'9910X84360000000', '9929X00271000000', '9935X82173000000',
'9923X84632000000', '9946X00544000000', '9946X85471000000',
'9946X83715000000', '9935X83016000000', '9946X50111000000',
'9809X00287000000', '0393G00214000000', '9946X00807000000',
'9929X01928000000', '9946X00770000000', '9935X83577000000',
'9946X01743000000', '0829D00096000000', '9905X80002000000',
'9929X87518000000', '9935X82497000000', '9905X01585000000',
'9844X00466000000', '9946X00207000000', '9910X84156000000',
'9923X00608000000', '9935X88367000000', '9929X00921000000',
'9946X00870000000', '9929X85737000000', '0050L00209000000',
'9935X83265000000', '9844X00361000000', '0119N00046000200',
'9935X82412000000', '9905X83373000000', '9844X00177000000',
'9946X82597000000', '9929X86275000000', '9946X83858000000',
'9929X00197000000', '9910X00463000000', '9905X83477000000',
'9946X84077000000', '0115B00054000000', '9929X86026000000',
'8000T00306000000', '9923X88384000000', '0236S00096000000',
'9946X87675000000', '9923X88120000000', '9905X00448000000',
'9905X83459000000', '9946X82757000000', '9923X87466000000',
'9905X82260000000', '9905X50076000000', '9935X33680000000',
'9905X82916000000', '0355C00060000000', '9841X00108000000',
'9935X00703000000', '9905X83526000000', '9929X87191000000',
'9929X88163000000', '9910X84224000000', '9923X84455000000',
'9923X82261000000', '0028A00125000000', '9905X82816000000',
'9935X00531000000', '9923X01020000000', '9923X00953000000',
'9946X83169000000', '9923X00201000000', '9946X84418000000',
'9946X01047000000', '9946X83113000000', '0301N00156000000',
'9929X86255000000', '9935X00779000000', '9946X83666000000',
'9935X82777000000', '9935X00992000000', '0454C00008000000',
'9946X84066000000', '9923X84539000000', '9905X00535000000',
'9946X85575000000', '9946X00927000000', '9929X84137000000',
'9946X85182000000', '9929X86615000000', '9935X00061000000',
'9935X88004000000', '9929X86189000000', '9946X00943000000',
'9905X82634000000', '9905X83607000000', '9946X01147000000',
'9929X01890000000', '9910X01052000000', '0050K00174000000',
'9929X82346000000', '9946X85441000000', '9935X83011000000',
'8000T01386000000', '9929X85280000000', '9923X82230000000',
'9935X88533000000', '9935X00970000000', '9844X00290000000',
'9935X83398000000', '9929X01325000000', '9929X01412000000',
'9946X83386000000', '1077G00182000000', '9935X50111000000',
'8000T01985000000', '9935X50297000000', '9946X87677000000',
'9946X88553000000', '9935X01359000000', '9905X82906000000',
'9935X82016000000', '2012M00049000000', '9946X50456000000',
'9905X83003000000', '9946X84071000000', '9910X84577000000',
'9946X81064000000', '9946X82710000000', '9946X01643000000',
'0381L00011000000', '9905X01159000000', '9910X00999000000',
'9923X88042000000', '9923X84317000000', '9929X83902000000',
'9929X84595000000', '9923X82287000000', '9929X88063000000',
'9905X01603000000', '9935X83059000000', '9946X01148000000',
'9929X86331000000', '9905X00687000000', '9946X82695000000',
'9946X83535000000', '9946X88275000000', '9809X00330000000',
'9809X00113000000', '9929X87810000000', '9923X01000000000',
'9929X00643000000', '9935X00709000000', '9910X84541000000',
'0049E00033000000', '9929X85331000000', '9935X88050000000',
'9946X84853000000', '8000T00585000000', '9844X00544000000',
'9929X85840000000', '9929X00849000000', '9923X00554000000',
'0050K00101000A00', '9935X50090000000', '0301N00092000000',
'9929X83936000000', '9910X00877000000', '0055A00110000000',
'9910X82056000000', '9935X83655000000', '9935X00010000000',
'9923X00806000000', '9946X85296000000', '9929X00323000000',
'9929X85818000000', '9844X00669000000', '9946X82663000000',
'9935X82393000000', '8000T02812000000', '9923X88528000000',
'9946X85226000000', '1077L00100000100', '9923X87821000000',
'9946X83617000000', '9946X83429000000', '9935X88291000000',
'9908X82871000000', '9929X86087000000', '9946X83939000000',
'9946X85187000000', '9929X83543000000', '9910X84236000000',
'9923X00199000000', '8000T03165000000', '9946X85378000000',
'9946X82031000000', '8000T02025000000', '9905X84014001C00',
'9929X87328000000', '9905X82792000000', '9923X00118000000',
'9910X00872000000', '9946X82775000000', '9946X82214000000',
'0182R00018000000', '0431C00375000000', '9946X83307000000',
'9935X88303000000', '9923X88216000000', '9910X00471000000',
'9946X50481000000', '9946X84444000000', '9946X50057000000',
'9935X82728000000', '0010J00110000000', '9946X01767000000',
'9935X50152000000', '9929X85780000000', '9946X83418000000',
'9923X82167000000', '9929X01005000000', '0130P00274000000',
'9923X84451000000', '9910X84028000000', '9929X86567000000',
'9844X00613000000', '9935X82751000000', '9935X00435000000',
'9910X00728000000', '9905X83171000000', '9910X84194000000',
'9946X00428000000', '9923X88321000000', '9929X01197000000',
'8000T01749000000', '9935X50221000000', '9910X00794000000',
'9923X00203000000', '9905X83580000000', '9905X84006044A00',
'1354N00254000000', '9946X01045000000', '9905X00005000000',
'9905X01270000000', '9841X00172000000', '9910X00159000000',
'9929X00411000000', '0119S00159000000', '8000T00687000000',
'9946X83453000000', '8000T01872000000', '9910X00726000000',
'9923X82263000000', '8000T01440000000', '9929X87711000000',
'9946X84119000000', '9929X83836000000', '0193D00014000100',
'9935X83452000000', '9910X84505000000', '9923X87539000000',
'9929X84139000000', '9935X83388000000', '9946X84102000000',
'9809X00320000000', '9946X01069000000', '0395D00050000000',
'9905X01168000000', '9946X83755000000', '9929X85816000000',
'9929X86125000000', '9946X87766000000', '9929X84019000000',
'0141A00042000000', '9905X82230000000', '1358J00079000000',
'9929X01929000000', '0765F00150000000', '9929X85745000000',
'9844X00188000000', '9923X00648000000', '9935X83054000000',
'9923X87636000000', '9946X84150000000', '0718H00032000000',
'9910X00989000000', '9905X83420000000', '9929X86539000000',
'9923X87968000000', '9923X84512000000', '9935X82061000000',
'9935X88138000000', '9923X82467000000', '2011A00326161400',
'9946X00602000000', '9929X88181000000', '9935X83640000000',
'9905X00371000000', '0551A00040000000', '9935X82239000000',
'9929X01517000000', '9929X87925000000', '9946X88652000000',
'0705L00194000000', '9929X87168000000', '9946X87971000000',
'1355M00200000000', '0374A00102000000', '9929X84950000000',
'9841X00185000000', '9929X86319000000', '8000T03461000000',
'0190H00052000000', '9905X82037000000', '9905X00607000000',
'9905X00424000000', '9935X00341000000', '9923X88461000000',
'9935X00255000000', '8000T03582000000', '9935X82482000000',
'9935X83826000000', '0957C00208000000', '9935X88732000000',
'9935X88646000000', '9946X50172000000', '9935X88056000000',
'9935X00161000000', '9929X00568000000', '9929X00940000000',
'0121J00212000000', '9929X00366000000', '9935X82050000000',
'9929X85988000000', '9935X01227000000', '9946X82344000000',
'0175G00009000000', '9946X85323000000', '9905X82641000000',
'9929X84010000000', '9929X88136000000', '9910X82210000000',
'9946X82146000000', '9929X88126000000', '9923X84461000000',
'9946X82198000000', '9910X81068000000', '9935X50062000000',
'9905X00599000000', '9923X84302000000', '9929X85421000000',
'9929X00711000000', '9910X01608000000', '9946X50187000000',
'9935X82363000000', '9910X83982000000', '9905X82637000000',
'9935X00529000000', '9929X00504000001', '9946X00716000000',
'9844X82006000000', '0062D00179000000', '9844X00350000000',
'9929X87583000000', '9946X88000000000', '9946X00494000000',
'8000T01939000000', '9935X88111000000', '9923X00291000000',
'9946X87710000000', '9935X00637000000', '9910X00923000000',
'9929X82499000000', '9905X01718000000', '9935X01019000000',
'9905X01607000000', '9841X00010000000', '9844X00193000000',
'9946X50356000000', '9946X01492000000', '9809X00043000000',
'9946X82650000000', '9923X88164000000', '0083L00007000000',
'9905X00494000000', '9935X82774000000', '9935X88197000000',
'9935X83394000000', '9929X87023000000', '9929X00895000000',
'9929X00563000000', '9910X82623000000', '9929X86832000000',
'9905X01930000000', '9929X84561000000', '9844X00492000000',
'9923X00252000000', '9923X87673000000', '9905X82704000000',
'0268N00370000000', '9929X83903000000', '9929X85565000000',
'8000T00282000000', '9946X83530000000', '9905X82608000000',
'9946X50240000000', '9946X82624000000', '9929X87590000000',
'9946X82486000000', '9935X83774000000', '9946X88006000000',
'9946X84002000000', '1075C00305000100', '9809X82034000000',
'9923X00445000000', '9946X01804000000', '9929X84705000000',
'9923X82246000000', '9905X00739000000', '9929X84008000000',
'9905X83662000000', '0263S00001000000', '9946X01464000000',
'9929X85897000000', '9935X83117000000', '0116D00064000001',
'9923X00365000000', '9929X84371000000', '9946X82853000000',
'9935X83412000000', '9923X87965000000', '9935X01348000000',
'9935X50040000000', '9946X83261000000', '9935X83217000000',
'0124J00113000000', '9905X00125000000', '0741L00177000100',
'9809X83004000000', '9946X00725000000', '9946X84210000000',
'9935X83104000000', '9946X88151000000', '9905X01548000000',
'9946X82062000000', '9910X01575000000', '9929X87947000000',
'9908X82883000000', '9946X83757000000', '9946X88348000000',
'9923X87705000000', '9905X82083000000', '9929X00869000000',
'0810F00255000000', '9809X82033000000', '9929X01025000000',
'9929X00649000000', '9946X50351000000', '0734A00034000000',
'9905X83354000000', '9935X83769000000', '9946X84391000000',
'9923X87633000000', '9923X88023000000', '9844X50021000000',
'9946X85517000000', '9905X00031000000', '9935X82902000000',
'9929X87329000000', '9935X00226000000', '9935X00836000000',
'9946X83641000000', '9923X87632000000', '9946X01714000000',
'9946X84178000000', '9935X01198000000', '9929X87630000000',
'9905X82468000000', '0051L00239000000', '9923X82403000000',
'9905X82050000000', '0232A00357000000', '9910X01442000000',
'9905X01834000000', '9946X83309000000', '9935X82311000000',
'9929X82541000000', '9929X84127000000', '0046N00073000000',
'9929X00113000000', '9923X88554000000', '9923X84524000000',
'9935X50230000000', '9809X00156000000', '9935X01039000000',
'9923X82449000000', '9905X50087000000', '9946X83695000000',
'9923X88074000000', '9935X82400000000', '0851E00034000000',
'8000T02994000000', '9935X83448000000', '9905X00714000000',
'0233E00262000600', '9923X82104000000', '9946X88029000000',
'9935X83746000000', '9946X82329000000', '9929X50048000000',
'9946X82790000000', '9935X83624000000', '0615F00234000100',
'9935X87964000000', '9809X83006000000', '9905X83367000000',
'9929X88013000000', '8000T03140000000', '0011A00132000A00',
'9905X83637000000', '9946X84379000000', '9946X88335000000',
'0102E00052000001', '0776C00220000000', '9929X87915000000',
'9935X82465000000', '9910X84637000000', '8000T02051000000',
'9905X00147000000', '9946X84740000000', '9923X84414000000',
'9946X01474000000', '1066K00349000000', '9923X84304000000',
'9946X01736000000', '9910X00673000000', '9935X82689000000',
'9935X83585000000', '0081E00123000000', '9923X00477000000',
'9923X00676000000', '9929X01432000000', '0124N00231000000',
'9935X01240000000', '9946X84389000000', '9910X83902000000',
'9946X84402000000', '9929X88211000000', '9929X83072000000',
'9946X01555000000', '9929X01817000000', '9929X01633000000',
'9929X87359000000', '9923X87816000000', '9910X01606000000',
'9935X83406000000', '9935X00196000000', '0321H00084000000',
'9935X00028000000', '9946X84956000000', '9946X84054000000',
'9929X85422000000', '9946X83191000000', '9905X50036000000',
'0624H00107000000', '9844X00181000000', '9923X84707000000',
'9946X01749000000', '0084A00091000000', '9923X88361000000',
'9946X84795000000', '9910X80068000000', '9946X50318000000',
'9935X82385000000', '9946X85288000000', '9905X83015000000',
'9946X82834000000', '0832E00040000000', '9935X83248000000',
'9910X83895000000', '9844X00013000000', '9923X82101000000',
'0111S00380000000', '9905X01037000000', '9929X83548000000',
'9935X83031000000', '9929X85176000000', '9929X83557000000',
'9946X81078000000', '9935X00434000000', '9946X83008000000',
'9935X82063000000', '9946X88630000000', '9929X85567000000',
'9935X83231000000', '0629C00135000000', '9844X00239000000',
'9905X83528000000', '9929X85824000000', '9946X00588000000',
'9935X83073000000', '0520E00202000000', '9935X82782000000',
'9923X82032000000', '9923X82146000000', '9908X82864000000',
'9923X82374000000', '9946X83234000000', '9929X84672000000',
'9929X83417000000', '9910X01456000000', '9946X82721000000',
'0050K00210000000', '9929X00441000000', '9946X50466000000',
'9905X00726000000', '0718C00170000000', '9929X87455000000',
'9923X82344000000', '9929X01188000000', '0358A00150000000',
'9923X87508000000', '9946X85101000000', '9946X88145000000',
'9910X00511000000', '9923X87462000000', '9844X00312000000',
'9923X00935000000', '9946X84221000000', '9910X82213000000',
'9910X00710000000', '9923X84311000000', '9935X50237000000',
'9929X85166000000', '9844X00252000000', '9946X50527000000',
'9923X88077000000', '9923X87621000000', '9946X82527000000',
'9929X82205000000', '9935X01125000000', '1080C00075000000',
'9935X88414000000', '0050K00013000000', '0063D00018000000',
'9946X83540000000', '9929X85285000000', '9946X88343000000',
'9929X00350000000', '9929X84815000000', '9929X84605000000',
'1204L00166000000', '9946X83305000000', '9905X01284000000',
'0049J00233000000', '9935X82788000000', '8000T01946000000',
'9946X83575000000', '9946X88319000000', '9929X86183000000',
'9923X82048000000', '9946X84807000000', '9844X00464000000',
'0139R00080000000', '0668E00189000000', '9905X01413000000',
'9946X84817000000', '9923X00662000000', '9923X87752000000',
'0530M00181000000', '9946X84445000000', '9935X83591000000',
'9946X83999000000', '9910X00589000000', '0270R00101000000',
'0162N00100000000', '9946X84050000000', '9946X82181000000',
'0851E00036000000', '9946X50366000000', '0715F00049000000',
'9809X82061000000', '9910X01178000000', '9929X00149000000',
'9935X01289000000', '9946X83482000000', '9910X84527000000',
'9809X00133000000', '9946X85571000000', '9844X00256000000',
'9946X50038000000', '0006F00180000000', '9946X82523000000',
'9946X01212000000', '9905X01788000000', '9935X83171000000',
'9929X88157000000', '9946X84013000000', '9946X84220000000',
'9929X87038000000', '9844X00005000000', '9905X83631000000',
'0236K00242000000', '9929X85164000000', '9923X00583000000',
'9946X01376000000', '9929X01621000000', '9923X84526000000',
'9910X83923000000', '9946X82607000000', '9935X83159000000',
'9905X01941000000', '9923X82028000000', '1355L00155000000',
'9929X01306000000', '9905X01593000000', '9929X84225000000',
'9905X00686000000', '9929X84361000000', '9946X85102000000',
'9809X84009000000', '9935X83107000000', '9929X01898000000',
'9946X84744000000', '9841X00231000000', '9905X00581000000',
'9946X82461000000', '9929X87634000000', '9935X50199000000',
'9946X87676000000', '9946X83573000000', '0056P00071000B00',
'9905X83325000000', '9946X83306000000', '9946X83616000000',
'9841X00220000000', '9923X84421000000', '9935X00810000000',
'9929X85744000000', '9946X00984000000', '9910X00523000000',
'9946X01574000000', '9946X00836000000', '0165B00050000000'
]
update_centroids(centroids_missing_arr)


Skipping 9923X82120000000: Raw property addr = ' NEELY SCHOOL RD  '
Skipping 0008H00207000000: Raw property addr = '22 GEN ROBINSON ST                PA '
Skipping 9923X88213000000: Raw property addr = ' WARREN RD                PA '
Skipping 9929X86742000000: Raw property addr = '928 FAIRFIELD LANE                PA '
Skipping 0102B00350000001: Raw property addr = ' 5TH AVE CARNEGIE       PA 15106'
Skipping 9946X85474000000: Raw property addr = ' BELLE TERRE CT                PA '
Skipping 9935X83214000000: Raw property addr = '2033 WEST GROVE DR                PA '
Skipping 9910X82175000000: Raw property addr = '44 ESCALON DR  '
Skipping 9923X00741000000: Raw property addr = '2686 WEINMAN RD  '
Skipping 9923X00961000000: Raw property addr = '210 PEAK DR  '
Skipping 0334H00209000000: Raw property addr = ' CAMPBELLS RUN RD  '
Skipping 0773C00150000000: Raw property addr = ' WOODCOCK COURT BETHEL PARK    PA 15102'
Skipping 9935X88055000000: Raw property addr = '1127 BAY HILL DR 127 GIBS

Google: Fetch '501 TIMBER TRAIL  ' seemed to succeed, but results empty or non-unique
Skipping 9929X84954000000: Raw property addr = '501 TIMBER TRAIL  '
Updating 9923X00774000000 from census: u'151 WARREN RD, WARRENDALE, PA, 15086' (-80.073586, 40.657100)
Updating 9929X88312000000 from census: u'203 PINE VALLEY DR, IMPERIAL, PA, 15126' (-80.216980, 40.445120)
Updating 9946X82666000000 from census: u'742 WHEATLAND CIR, BRIDGEVILLE, PA, 15017' (-80.133710, 40.328300)
Google: Fetch '125 HIDDEN LANE  ' seemed to succeed, but results empty or non-unique
Skipping 9923X00430000000: Raw property addr = '125 HIDDEN LANE  '
Updating 9946X88092000000 from census: u'8035 SADDLEWOOD DR, BRIDGEVILLE, PA, 15017' (-80.135980, 40.322180)
Updating 9935X88285000000 from census: u'2022 CONDOR LN, GIBSONIA, PA, 15044' (-80.018180, 40.667503)
Skipping 9946X00664000000: Raw property addr = ' MARTHA ST  '
Updating 9935X82575000000 from census: u'113 FOX MEADOW DR, WEXFORD, PA, 15090' (-80.044205, 40.638893)


Skipping 9929X86704000000: Raw property addr = ' OAKDALE RD  '
Updating 9910X01164000000 from census: u'127 NANCY ST, IMPERIAL, PA, 15126' (-80.249960, 40.452900)
Updating 9929X83940000000 from census: u'36 FOREST GLEN DR, IMPERIAL, PA, 15126' (-80.226220, 40.446500)
Skipping 9910X01490000000: Raw property addr = ' SPRING RUN RD EXT  '
Updating 9946X01316000000 from census: u'401 HOOK ST, BRIDGEVILLE, PA, 15017' (-80.134964, 40.355278)
Updating 9946X82318000000 from census: u'667 DEER WATCH RD, BRIDGEVILLE, PA, 15017' (-80.131670, 40.328330)
Skipping 9905X82834000000: Raw property addr = '2150 ENGLISH TURN DR                PA '
Updating 9935X88057000000 from census: u'1131 BAY HILL DR, GIBSONIA, PA, 15044' (-80.023224, 40.669933)
Updating 0052H00268000000 from census: u'5311 5TH AVE, PITTSBURGH, PA, 15232' (-79.935130, 40.448116)
Skipping 9946X83711000000: Raw property addr = '4197 BATTLE RIDGE RD  '
Google: Fetch ' BLAIRMONT DR  ' seemed to succeed, but results empty or non-unique
Sk

Skipping 9905X82683000000: Raw property addr = '214 MEADOWGROVE CIRCLE                PA '
Updating 9929X83552000000 from census: u'517 WALDEN WAY, IMPERIAL, PA, 15126' (-80.221950, 40.446903)
Updating 0084E00302041300 from census: u'5850 CENTRE AVE, PITTSBURGH, PA, 15206' (-79.930980, 40.458170)
Skipping 0079R00106000000: Raw property addr = ' FEILBACH ST PITTSBURGH     PA 15209'
Updating 0350A00029000000 from census: u'305 GOLF DR, PITTSBURGH, PA, 15229' (-80.048546, 40.528545)
Skipping 9905X83001000000: Raw property addr = ' BOYDS RUN RD                PA '
Updating 9929X85089000000 from census: u'718 GROVE ST, MC DONALD, PA, 15057' (-80.212430, 40.385406)
Skipping 0751F00006000000: Raw property addr = ' LOGAN RD N VERSAILES    PA 15137'
Updating 0282B00342I22000 from census: u'220 QUEENSBERRY CT, PITTSBURGH, PA, 15237' (-79.990630, 40.516506)
Skipping 0175C00227000000: Raw property addr = ' TIOGA ST PITTSBURGH     PA 15208'
Skipping 0225G00175000000: Raw property addr = '354 HUNT R

Google: Fetch '2649 BROOKLEDGE RD  ' failed
Skipping 9946X83146000000: Raw property addr = '2649 BROOKLEDGE RD  '
Google: Fetch '906 MILL COURT  ' seemed to succeed, but results empty or non-unique
Skipping 9946X82551000000: Raw property addr = '906 MILL COURT  '
Updating 0359N00029000000 from census: u'15 TRILLIUM LN, PITTSBURGH, PA, 15238' (-79.902040, 40.525433)
Updating 9923X88017000000 from census: u'202 WARREN RD, WARRENDALE, PA, 15086' (-80.071860, 40.658085)
Updating 9935X82189000000 from census: u'105 NORTHBROOK DR, GIBSONIA, PA, 15044' (-80.009735, 40.642506)
Updating 0070K00044000000 from census: u'228 W PROSPECT AVE, PITTSBURGH, PA, 15205' (-80.074450, 40.447506)
Google: Fetch '18 CAROL DR  ' seemed to succeed, but results empty or non-unique
Skipping 9905X00188000000: Raw property addr = '18 CAROL DR  '
Google: Fetch '  110 STONEBRIDGE DR  ' seemed to succeed, but results empty or non-unique
Skipping 9929X87292000000: Raw property addr = '  110 STONEBRIDGE DR  '
Updating 9

...

Skipping 9910X01608000000: Raw property addr = '1705 RTE 30 IMPERIAL       PA 15126'
Updating 9946X50187000000 from census: u'506 5TH AVE, BRIDGEVILLE, PA, 15017' (-80.136580, 40.357480)
Updating 9935X82363000000 from census: u'112 PINEHURST LN, GIBSONIA, PA, 15044' (-80.023940, 40.672005)
Google: Fetch '912 LODGEPOLE DR  ' seemed to succeed, but results empty or non-unique
Skipping 9910X83982000000: Raw property addr = '912 LODGEPOLE DR  '
Updating 9905X82637000000 from census: u'729 STONEGATE DR, OAKDALE, PA, 15071' (-80.143610, 40.404545)
Updating 9935X00529000000 from census: u'151 LIMERICK RD, WEXFORD, PA, 15090' (-80.057620, 40.624325)
Skipping 9929X00504000001: Raw property addr = '21 DEMPE RD  '
Updating 9946X00716000000 from census: u'304 GRANT ST, MORGAN, PA, 15064' (-80.146170, 40.354446)
Updating 9844X82006000000 from census: u'4004 NOBLESTOWN RD, OAKDALE, PA, 15071' (-80.180800, 40.399544)
Updating 0062D00179000000 from census: u'2035 WOODWARD AVE, PITTSBURGH, PA, 15226' (

Skipping 9946X88151000000: Raw property addr = '624 TURNBERRY LANE BRIDGEVILLE PA 15017'
Updating 9905X01548000000 from census: u'51 SUNNYSIDE AVE, CARNEGIE, PA, 15106' (-80.142050, 40.397140)
Updating 9946X82062000000 from census: u'317 RIDGE POINT CIR, BRIDGEVILLE, PA, 15017' (-80.125200, 40.326176)
Google: Fetch '15 SUNSET DR                PA ' seemed to succeed, but results empty or non-unique
Skipping 9910X01575000000: Raw property addr = '15 SUNSET DR                PA '
Updating 9929X87947000000 from census: u'202 COMMODORE DR, MC DONALD, PA, 15057' (-80.259926, 40.403225)
Skipping 9908X82883000000: Raw property addr = ' COAL  '
Updating 9946X83757000000 from census: u'210 STUART CIR, MC DONALD, PA, 15057' (-80.166780, 40.377552)
Updating 9946X88348000000 from census: u'6108 CALEDONIA CT, BRIDGEVILLE, PA, 15017' (-80.139730, 40.349000)
Updating 9923X87705000000 from census: u'203 PINE RD, GROVE CITY, PA, 16127' (-80.143160, 41.153190)
Skipping 9905X82083000000: Raw property add

Google: Fetch '14 ALLISON TRAILER CT PITTSBURGH     PA 15225' seemed to succeed, but results empty or non-unique
Skipping 8000T02051000000: Raw property addr = '14 ALLISON TRAILER CT PITTSBURGH     PA 15225'
Skipping 9905X00147000000: Raw property addr = ' BOYDS RUN RD                PA '
Updating 9946X84740000000 from census: u'258 PORTMAN LN, BRIDGEVILLE, PA, 15017' (-80.115005, 40.339745)
Skipping 9923X84414000000: Raw property addr = '223 SEASONS DR  '
Skipping 9946X01474000000: Raw property addr = '4180 BATTLE RIDGE RD                PA '
Skipping 1066K00349000000: Raw property addr = ' MAGEE RD SEWICKLEY      PA 15143'
Updating 9923X84304000000 from census: u'825 HILLCREST CIR, WEXFORD, PA, 15090' (-80.086105, 40.620632)
Updating 9946X01736000000 from census: u'3467 WASHINGTON PIKE, BRIDGEVILLE, PA, 15017' (-80.133570, 40.333010)
Updating 9910X00673000000 from census: u'51 BUGAY LN, IMPERIAL, PA, 15126' (-80.290300, 40.432354)
Updating 9935X82689000000 from census: u'626 KARRASTY

Skipping 9929X00441000000: Raw property addr = '251 DAMSKY ST IMPERIAL PA 15126'
Updating 9946X50466000000 from census: u'135 MELROSE CT, BRIDGEVILLE, PA, 15017' (-80.117850, 40.343803)
Updating 9905X00726000000 from census: u'106 JONES DR, BRIDGEVILLE, PA, 15017' (-80.117220, 40.368180)
Skipping 0718C00170000000: Raw property addr = ' SADDLE DR                PA '
Updating 9929X87455000000 from census: u'209 WOODCREST DR, CORAOPOLIS, PA, 15108' (-80.226280, 40.455097)
Skipping 9923X82344000000: Raw property addr = '504 KNOLL CT                PA '
Skipping 9929X01188000000: Raw property addr = '7137 NOBLESTOWN RD  '
Updating 0358A00150000000 from census: u'214 BROWNSHILL RD, PITTSBURGH, PA, 15238' (-79.916480, 40.530230)
Skipping 9923X87508000000: Raw property addr = '821 ARBORDALE LANE  '
Updating 9946X85101000000 from census: u'331 RIDGE POINT CIR, BRIDGEVILLE, PA, 15017' (-80.126030, 40.325570)
Updating 9946X88145000000 from census: u'627 TURNBERRY LN, OAKDALE, PA, 15071' (-80.1770

Skipping 9929X87038000000: Raw property addr = '1104 FAIRFIELD LANE                PA '
Updating 9844X00005000000 from census: u'104 1ST ST, OAKDALE, PA, 15071' (-80.185100, 40.398907)
Updating 9905X83631000000 from census: u'1231 MERIDIAN DR, PRESTO, PA, 15142' (-80.122086, 40.377400)
Updating 0236K00242000000 from census: u'22 FLEET ST, RANKIN, PA, 15104' (-79.876980, 40.407307)
Skipping 9929X85164000000: Raw property addr = ' RTE 22  '
Updating 9923X00583000000 from census: u'2185 RIDGE DR, MARS, PA, 16046' (-80.084880, 40.667576)
Updating 9946X01376000000 from census: u'16 WABASH AVE, MORGAN, PA, 15064' (-80.144810, 40.353565)
Updating 9929X01621000000 from census: u'240 WHITTENGALE RD, OAKDALE, PA, 15071' (-80.209700, 40.412823)
Updating 9923X84526000000 from census: u'23 BLUEBERRY LN, WEXFORD, PA, 15090' (-80.091965, 40.640453)
Skipping 9910X83923000000: Raw property addr = '709 TAMARACK DR                PA '
Updating 9946X82607000000 from census: u'401 LARK TREE CIR, BRIDGEVILL

In [386]:
result=geocode_address_google('COCHRAN ST SEWICKLEY      PA 15143')
addr_comps = result['results'][0]['address_components']
#    for i in range(0, len(addr_comps)):
#        if('location' in addr_comps[i]['types']):
#            return addr_comps[i]['short_name']
#addr_comps
result['results'][0]['geometry']['location']

{u'lat': 40.5377722, u'lng': -80.17400409999999}

In [358]:
parid = parid2centroid.keys()[0]
print '%s: %r (%f, %f)' % (parid, parid2centroid[parid], parid2centroid[parid].x, parid2centroid[parid].y)

: <shapely.geometry.point.Point object at 0x7f542fedc090> (-80.050660, 40.521093)


In [368]:
from shapely.geometry import Point
ret = geocode_address_census('13 NOBLESTOWN RD, CARNEGIE, PA, 15106')
coords = ret['result']['addressMatches'][0]['coordinates']
point = Point(coords['x'], coords['y'])
print '%r (%f, %f)' % (point, point.x, point.y)

<shapely.geometry.point.Point object at 0x7f538c82ac90> (-80.112434, 40.395950)


In [372]:
apd_2017[apd_2017.PROPERTYOWNER.str.contains("OLENIACZ")]

PROPERTYOWNER  \
PARID                                                                    
0034K00284000000  EDWARD J OLENIACZ & ELIZABETH J OLENIACZLIVING TRUST   
1356K00345000000                     OLENIACZ KEITH M & KIMBERLY J (W)   
0539A00174000000                                    OLENIACZ ELEANOR P   
1216M00037000000                         OLENIACZ DAVID R & MARY K (W)   
1216M00093000000                     OLENIACZ RUDOLPH J JR & DOLORES A   
0029C00099000000                                       OLENIACZ MARK S   

                 PROPERTYHOUSENUM PROPERTYFRACTION            PROPERTYADDRESS  \
PARID                                                                           
0034K00284000000              758                                    LINDA DR   
1356K00345000000             3243                                E HARDIES RD   
0539A00174000000              250                                     CLAY DR   
1216M00037000000               20                                  DEERTON ST   
1216M00093000000               66                   RUSSELLTON DORSEYVILLE RD   
0029C00099000000             3249                                   JULIET ST   

                 PROPERTYCITY PROPERTYSTATE PROPERTYUNIT PROPERTYZIP  \
PARID                                                                  
0034K00284000000   PITTSBURGH            PA                    15226   
1356K00345000000     GIBSONIA            PA                    15044   
0539A00174000000   PITTSBURGH            PA                    15235   
1216M00037000000     CHESWICK            PA                    15024   
1216M00093000000     CHESWICK            PA                    15024   
0029C00099000000   PITTSBURGH            PA                    15213   

                  MUNICODE                MUNIDESC  SCHOOLCODE  \
PARID                                                            
0034K00284000000       119  19th Ward - PITTSBURGH          47   
1356K00345000000       914               Hampton            20   
0539A00174000000       934            Penn Hills            30   
1216M00037000000       952             West Deer            12   
1216M00093000000       952             West Deer            12   
0029C00099000000       104   4th Ward - PITTSBURGH          47   

                          SCHOOLDESC  \
PARID                                  
0034K00284000000  City Of Pittsburgh   
1356K00345000000    Hampton Township   
0539A00174000000      Penn Hills Twp   
1216M00037000000          Deer Lakes   
1216M00093000000          Deer Lakes   
0029C00099000000  City Of Pittsburgh   

                                                           LEGAL1  \
PARID                                                               
0034K00284000000  PIONEER VILLAGE 3RD PLAN 343 LOT 47.11XAVG128.0   
1356K00345000000  1.158 ALD E HARDIES RD                            
0539A00174000000  CHURCHILL MANOR 2ND PLAN 150 LOT 49X120X58.62 C   
1216M00037000000  DEERTON 2ND PLAN 28 LOT 125XAVG248.36X55.01 DEE   
1216M00093000000  DEERTON 2ND PLAN 5 LOT 105.8XAVG196.23X110 RUSS   
0029C00099000000  LINDEN LAND CO PLAN PT K 2 LOT 24X115 JULIET ST   

                                                           LEGAL2  \
PARID                                                               
0034K00284000000  2X59.37 LINDA DR                                  
1356K00345000000  2 STY BRK & ALUM HSE-INT GAR #3243                
0539A00174000000  LAY DR                                            
1216M00037000000  RTON RD                                           
1216M00093000000  ELLTON RD COR DEERTON RD                          
0029C00099000000                       3 STY M BRK HSE & STO 3249   

                                                           LEGAL3 NEIGHCODE  \
PARID                                                                         
0034K00284000000  1 STY BRK VEN BUNG-GAR #758                         11902   
1356K00345000000                             

In [440]:
apd_20.SALEDESC.value_counts()

VALID SALE                          141204
LOVE AND AFFECTION SALE             109656
UNVERIFIED DECLARED VALID SALE       40437
OTHER INVALID SALES INDICATED        36991
BRAND NEW SALE NOT ANALYZED          24141
MULTI-PARCEL SALE                    18471
THE FLAG CANNOT BE DETERMINED        15589
NOT APPLICABLE                        9730
SHERIFF SALE                          5224
OUTLIER SALE                          3255
COMBINATIONS AND SPLITS               2155
CITY TREASURER SALE                   1446
VACANT LAND SALE                      1110
CHANGED AFTER SALE                     862
UNVERIFIED DECLARED VALID SALE X       436
INTERIM                                193
OWNER SUPPLIED AND VALID               167
VALID SALE excluded from MKT            95
??                                      94
OWNER SUPPLIED SALE                      4
Name: SALEDESC, dtype: int64

In [340]:
apd_2015.SALECODE.value_counts()

AttributeError: 'DataFrame' object has no attribute 'SALECODE'

In [327]:
apd_2017.loc['0084J00185000000']

PROPERTYOWNER                   SEABROOKE J THOMAS
PROPERTYHOUSENUM                              5825
PROPERTYFRACTION                                  
PROPERTYADDRESS                          PIERCE ST
PROPERTYCITY                            PITTSBURGH
PROPERTYSTATE                                   PA
PROPERTYUNIT                                      
PROPERTYZIP                                  15232
MUNICODE                                       107
MUNIDESC                     7th Ward - PITTSBURGH
SCHOOLCODE                                      47
SCHOOLDESC                      City Of Pittsburgh
LEGAL1                PT 51 LOT 16.18X63 PIERCE ST
LEGAL2                         2 STY BRK HSE #5825
LEGAL3                                         NaN
NEIGHCODE                                    10703
NEIGHDESC                                SHADYSIDE
TAXCODE                                          T
TAXDESC                               20 - Taxable
TAXSUBCODE                     

In [204]:
property_map['0029C00050000000']

[{'asofdate': '1999-01-01',
  'canonical_owner_address': u'3512 FRAZIER ST, PITTSBURGH, PA, 15213',
  'changeaddr': u'3512 FRAZIER STREET PITTSBURGH PA 15213',
  'date': '1977-01-01',
  'event_type': 'PURCHASE',
  'ownername': u'PRYOR WILLIAM D'},
 {'asofdate': '2009-09-01',
  'canonical_owner_address': u'1914 WATSON ST, PITTSBURGH, PA, 15219',
  'changeaddr': ' 1914 WATSON ST PITTSBURGH, PA 15219-5828 ',
  'date': u'1977-01-20',
  'event_type': 'PURCHASE',
  'fm_total': 46300.0,
  'ownerdesc': 'Regular',
  'ownername': 'PRYOR WILLIAM D',
  'saledesc': 'VALID SALE'},
 {'asofdate': '2017-10-01',
  'canonical_owner_address': u'414 GRANT ST, PITTSBURGH, PA, 15219',
  'changeaddr': '414 GRANT ST RM 200 CITY-COUNTY BUILDING PITTSBURGH PA 15219',
  'date': u'2017-04-28',
  'event_type': 'PURCHASE',
  'fm_total': 1000,
  'ownerdesc': 'CORPORATION',
  'ownername': 'CITY OF PITTSBURGH',
  'saledesc': 'GOVT SALE'}]

In [205]:
property_map['2018H00310000000']

[{'asofdate': '2017-10-01',
  'canonical_owner_address': u'817 E HILL DR, NEW KENSINGTON, PA, 15068',
  'changeaddr': '817 E HILL DR NEW KENSINGTON PA 15068',
  'date': u'1993-10-04',
  'event_type': 'PURCHASE',
  'fm_total': 30100,
  'ownerdesc': 'REGULAR',
  'ownername': 'CARNEY CHARLENE P & CHARLES K CARNEY',
  'saledesc': 'OTHER'},
 {'asofdate': '2009-09-01',
  'changeaddr': ' 1194 DONNELLSVILLE RD NATRONA HEIGHTS, PA 15065-3007 ',
  'date': u'1993-10-04',
  'event_type': 'PURCHASE',
  'fm_total': 25700.0,
  'ownerdesc': 'Regular',
  'ownername': 'CARNEY CHARLENE P & CHARLES K CARNEY',
  'saledesc': 'THE FLAG CANNOT BE DETERMINED'}]

In [315]:
property_map['0028H00014000000']=[{'changeaddr': '3535 BLVD OF THE ALLIES, PITTSBURGH, PA 15213',
  'date': u'1986-08-25',
  'event_type': 'PURCHASE',
  'ownername': 'KELLY ROBERT E JR & KELLY ROBERT E JR WILLIAM W RIELLY ROBERT B NELL JR & HOMER E STOTLER'},
 {'changeaddr': '3535 BLVD OF THE ALLIES, PITTSBURGH, PA 15213',
  'date': u'1986-08-25',
  'event_type': 'PURCHASE',
  'ownername': 'KELLY ROBERT E JR & RIELLY WILLIAM W & NELL ROBE'},
 {'changeaddr': '3535 BLVD OF THE ALLIES, PITTSBURGH, PA 15213',
  'date': u'2012-12-18',
  'event_type': 'PURCHASE',
  'ownername': 'ROBERT E KELLY JR REVOCABLE TRUST'},
 {'changeaddr': '3535 BLVD OF THE ALLIES, PITTSBURGH, PA 15213',
  'date': u'2012-12-18',
  'event_type': 'PURCHASE',
  'ownername': 'ROBERT E KELLY JR REVOCABLE TRUST & WILLIAM W RIELLY REVOCABLE TRU'},
 {'changeaddr': '3535 BLVD OF THE ALLIES, PITTSBURGH, PA 15213',
  'date': u'2012-12-18',
  'event_type': 'PURCHASE',
  'ownername': 'ROBERT E KELLY JR REVOCABLE TRUST ROBERT E KELLY JR TRUSTEE & WIL'}]

In [316]:
owner_map['ROBERT E KELLY JR REVOCABLE TRUST ROBERT E KELLY JR TRUSTEE & WIL']=owner_map['ROBERT E KELLY JR REVOCABLE TRUST ROBERT E KELLY JR \xce\x93\xc3\x87\xc3\xb4 TRUSTEE & WIL']

In [127]:
changeaddr_map['8 WATSON ST, CARNEGIE, PA 15106']

KeyError: '8 WATSON ST, CARNEGIE, PA 15106'

In [206]:
owner_map['STANDARD REALTY GROUP LP']

[{'date': u'2003-12-12',
  'event_type': 'PURCHASE',
  'parid': '0084J00135000000'},
 {'date': u'2003-12-12',
  'event_type': 'PURCHASE',
  'parid': '0084J00206000000'},
 {'date': u'2004-11-19',
  'event_type': 'PURCHASE',
  'parid': '0084J00153000000'},
 {'date': u'2004-12-23',
  'event_type': 'PURCHASE',
  'parid': '0025D00155000400'},
 {'date': u'2004-12-23',
  'event_type': 'PURCHASE',
  'parid': '0025D00155000900'},
 {'date': u'2004-12-23',
  'event_type': 'PURCHASE',
  'parid': '0048M00024000000'},
 {'date': u'2004-12-23',
  'event_type': 'PURCHASE',
  'parid': '0084J00172000000'},
 {'date': u'2004-12-23',
  'event_type': 'PURCHASE',
  'parid': '0084J00207000000'},
 {'date': u'2004-12-23',
  'event_type': 'PURCHASE',
  'parid': '0084J00178000000'},
 {'date': u'2004-12-23',
  'event_type': 'PURCHASE',
  'parid': '0084J00210000000'},
 {'date': u'2004-12-23',
  'event_type': 'PURCHASE',
  'parid': '0084J00211000000'},
 {'date': u'2004-12-23',
  'event_type': 'PURCHASE',
  'parid': '

In [207]:
# Sanity check it's working
next_date = '1970-01-01'
parid='0084J00135000000'
print property_map[parid]
while(next_date<this_date):
    ret=get_related_parids(parid, next_date)
    print "%s: %s - %s = %d" % (parid, ret['start_date'], ret['next_date'], ret['parcount'])
    next_date=ret['next_date']

[{'event_type': 'PURCHASE', 'asofdate': '1999-01-01', 'canonical_owner_address': u'996 ORANMORE ST, PITTSBURGH, PA, 15201', 'changeaddr': u'996 ORANMORE ST PITTSBURGH PA 15201', 'ownername': u'MARSHALL CLARENCE G & JENNIE', 'date': '1967-04-01'}, {'canonical_owner_address': u'4124 BUTLER ST, PITTSBURGH, PA, 15201', 'event_type': 'PURCHASE', 'asofdate': '2017-10-01', 'fm_total': 60000, 'changeaddr': '4124 BUTLER ST PITTSBURGH PA 15201', 'ownername': 'STANDARD REALTY GROUP LP', 'date': u'2003-12-12', 'saledesc': 'OTHER INVALID', 'ownerdesc': 'CORPORATION'}, {'canonical_owner_address': u'4124 BUTLER ST, PITTSBURGH, PA, 15201', 'event_type': 'PURCHASE', 'asofdate': '2009-09-01', 'fm_total': 45000.0, 'changeaddr': ' 4124 BUTLER ST PITTSBURGH, PA 15201-3118 ', 'ownername': 'STANDARD REALTY GROUP LP', 'date': u'2003-12-12', 'saledesc': 'OTHER INVALID SALES INDICATED', 'ownerdesc': 'Corporation'}]
0084J00135000000: 1970-01-01 - 1978-06-01 = 1
0084J00135000000: 1978-06-01 - 1994-10-03 = 2
0084J

In [208]:
# TORKEO ROBERT V
next_date = '1970-01-01'
parid='0029H00175000000'
print property_map[parid]
while(next_date<this_date):
    ret=get_related_parids(parid, next_date)
    print "%s: %s - %s = %d" % (parid, ret['start_date'], ret['next_date'], ret['parcount'])
    next_date=ret['next_date']

[{'event_type': 'PURCHASE', 'asofdate': '1999-01-01', 'canonical_owner_address': u'3319 JULIET ST, PITTSBURGH, PA, 15213', 'changeaddr': u'3319 JULIET ST PITTSBURGH PA 15213', 'ownername': u'TORKEO ROBERT V', 'date': '1996-09-01'}, {'canonical_owner_address': u'3152 GRIFFITHS ST, PITTSBURGH, PA, 15213', 'event_type': 'PURCHASE', 'asofdate': '2017-10-01', 'fm_total': 45000, 'changeaddr': '3152 GRIFFITH ST PITTSBURGH PA 15213', 'ownername': 'TORKEO ROBERT V', 'date': u'2001-09-13', 'saledesc': 'SHERIFF SALE', 'ownerdesc': 'REGULAR'}, {'canonical_owner_address': u'3152 GRIFFITHS ST, PITTSBURGH, PA, 15213', 'event_type': 'PURCHASE', 'asofdate': '2009-09-01', 'fm_total': 42400.0, 'changeaddr': ' 3152 GRIFFITH ST PITTSBURGH, PA 15213-4510 ', 'ownername': 'TORKEO ROBERT V', 'date': u'2001-09-13', 'saledesc': 'SHERIFF SALE', 'ownerdesc': 'Regular'}]
0029H00175000000: 1996-09-01 - 2000-08-18 = 6
0029H00175000000: 2000-08-18 - 2001-09-13 = 7
0029H00175000000: 2001-09-13 - 2002-06-07 = 13
0029H00

In [210]:
print property_map.keys()[1]
property_map[property_map.keys()[1]]

0056F00154000000


[{'asofdate': '1999-01-01',
  'changeaddr': u'CITY COUNTY BLDG PITTSBURGH PA 19',
  'date': '1961-11-01',
  'event_type': 'PURCHASE',
  'ownername': u'THREE TAXING BODIES'},
 {'asofdate': '2017-10-01',
  'canonical_owner_address': u'140 TECUMSEH ST, PITTSBURGH, PA, 15207',
  'changeaddr': '140 TECUMSEH ST PITTSBURGH PA 15207',
  'date': u'1961-11-02',
  'event_type': 'PURCHASE',
  'fm_total': 3800,
  'ownerdesc': 'REGULAR',
  'ownername': 'THIRY JOHN P & HELEN M',
  'saledesc': 'LOVE&AFFECTION'},
 {'asofdate': '2009-09-01',
  'canonical_owner_address': u'140 TECUMSEH ST, PITTSBURGH, PA, 15207',
  'changeaddr': ' 140 TECUMSEH ST PITTSBURGH, PA 15207-1682 ',
  'date': u'1961-11-02',
  'event_type': 'PURCHASE',
  'fm_total': 4900.0,
  'ownerdesc': 'Regular',
  'ownername': 'THIRY JOHN P & HELEN M',
  'saledesc': 'LOVE AND AFFECTION SALE'}]

In [148]:
apd_2009[apd_2009.PROPERTYOWNER.str.contains('WYDRENSKI ')]

MAPBLOCKLO  MUNICODE PSEUDONO  \
PARID                                            
0432C00117000000  432-C-117     940.0      NaN   
0218L00034000000   218-L-34     940.0      NaN   
0162D00020000000   162-D-20     126.0      NaN   

                                        PROPERTYOWNER  PROPERTYFRACTION  \
PARID                                                                     
0432C00117000000  WYDRENSKI STANLEY A & PAULINE J (W)               NaN   
0218L00034000000   WYDRENSKI SUSAN M & LAWRENCE E (H)               NaN   
0162D00020000000     WYDRENSKI ROBERT A & DARLENE (W)               NaN   

                 PROPERTYHOUSENUM        PROPERTYADDRESS PROPERTYUNIT  \
PARID                                                                   
0432C00117000000              105    BERKELEY MEADOWS CT          NaN   
0218L00034000000              141              GAYMOR DR          NaN   
0162D00020000000             4466         RODENBAUGH AVE          NaN   

                 PROPERTYCITY   PROPERTYSTATE PROPERTYZIP  FAIRMARKET  \
PARID                                                                   
0432C00117000000               PITTSBURGH, PA       15237    126400.0   
0218L00034000000               PITTSBURGH, PA       15214    102600.0   
0162D00020000000               PITTSBURGH, PA       15214     53800.0   

                  FAIRMARK_1  FAIRMARKETTOTAL  COUNTYLAND  COUNTYBUIL  \
PARID                                                                   
0432C00117000000     29000.0         155400.0     29000.0    111400.0   
0218L00034000000     24500.0         127100.0     24500.0     87600.0   
0162D00020000000     17900.0          71700.0     17900.0     38800.0   

                  EXEMPTAMOU  PRIORMARKE                 MUNDESC  SCHOOLCODE  \
PARID                                                                          
0432C00117000000         0.0    155400.0                    ROSS        28.0   
0218L00034000000         0.0    127100.0                    ROSS        28.0   
0162D00020000000         0.0     71700.0  PITTSBURGH - 26TH WARD        47.0   

                          SCHOOLDESC TAXCODE  TAXDESC  OWNERCODE OWNERDESC  \
PARID                                                                        
0432C00117000000         North Hills       T  Taxable       12.0   Regular   
0218L00034000000         North Hills       T  Taxable       12.0   Regular   
0162D00020000000  City Of Pittsburgh       T  Taxable       12.0   Regular   

                 STATECODE    STATEDESC  USECODE        USEDESC  \
PARID                                                             
0432C00117000000         R  Residential     10.0  SINGLE FAMILY   
0218L00034000000         R  Residential     10.0  SINGLE FAMILY   
0162D00020000000         R  Residential     10.0  SINGLE FAMILY   

                 CHANGENOTICEADDRESS1       CHANGENOTICEADDRESS2  \
PARID                                                              
0432C00117000000                       105   BERKELEY MEADOWS CT   
0218L00034000000                                 141   GAYMOR DR   
0162D00020000000                           4466   RODENBAUGH AVE   

                       CHANGENOTICEADDRESS3 CHANGENOTICEADDRESS4  \
PARID                                                              
0432C00117000000  PITTSBURGH, PA 15237-3937                        
0218L00034000000  PITTSBURGH, PA 15214-1346                        
0162D00020000000  PITTSBURGH, PA 15214-1242                        

                                            AGENTNAME SERVICECOD  \
PARID                                                              
0432C00117000000  WYDRENSKI STANLEY A & PAULINE J (W)        NaN   
0218L00034000000         WELLS FARGO R E TAX SERVICES        NaN   
0162D00020000000     WYDRENSKI ROBERT A & DARLENE (W)        NaN   

                      TAXBILLFUL                 TAXBILLF_1  \
PARID                                                         
0432C0011700000

In [155]:
apd_2009.loc['0163B00066000000']

MAPBLOCKLO                                             163-B-66
MUNICODE                                                    126
PSEUDONO                                                    NaN
PROPERTYOWNER                     SCHUELER ERIC B & LINDA J (W)
PROPERTYFRACTION                                            NaN
PROPERTYHOUSENUM                                           4570
PROPERTYADDRESS                                      ZANE PLACE
PROPERTYUNIT                                                NaN
PROPERTYCITY                                                   
PROPERTYSTATE                                    PITTSBURGH, PA
PROPERTYZIP                                               15214
FAIRMARKET                                                39300
FAIRMARK_1                                                 9300
FAIRMARKETTOTAL                                           48600
COUNTYLAND                                                 9300
COUNTYBUIL                              

In [150]:
apd_2017.loc['0162D00020000000']

PROPERTYOWNER                                          BARCUS MATTHEW L
PROPERTYHOUSENUM                                                   4466
PROPERTYFRACTION                                                       
PROPERTYADDRESS                                          RODENBAUGH AVE
PROPERTYCITY                                                 PITTSBURGH
PROPERTYSTATE                                                        PA
PROPERTYUNIT                                                           
PROPERTYZIP                                                       15214
MUNICODE                                                            126
MUNIDESC                                         26th Ward - PITTSBURGH
SCHOOLCODE                                                           47
SCHOOLDESC                                           City Of Pittsburgh
LEGAL1                  RODFNBAUGH PL PLAN 167-168 LOT 60X100 IN ALL RO
LEGAL2                  DENBAUGH AV                             

In [154]:
apd_2009[~apd_2009.index.str.contains('000000$',regex=True)]

MAPBLOCKLO  MUNICODE PSEUDONO  \
PARID                                                 
0385E00101000400     385-E-101-4     870.0      NaN   
0385E00101000200     385-E-101-2     870.0      NaN   
0385E00109000100     385-E-109-1     870.0      NaN   
0040B00229000100      40-B-229-1     128.0      NaN   
0385E00300061000   385-E-300-610     870.0      NaN   
0385E00300120200  385-E-300-1202     870.0      NaN   
0385E00300080200   385-E-300-802     870.0      NaN   
0385E00300080000   385-E-300-800     870.0      NaN   
1675A00125000001  1675-A-125-0-1     909.0      NaN   
0385E00101000300     385-E-101-3     870.0      NaN   
0701F00210173500  701-F-210-1735     906.0      NaN   
0085P00027000A00       85-P-27-A     114.0      NaN   
0701F00200177800  701-F-200-1778     906.0      NaN   
0701F00230179400  701-F-230-1794     906.0      NaN   
0701F00200177200  701-F-200-1772     906.0      NaN   
0701F00230178800  701-F-230-1788     906.0      NaN   
0701F00200176000  701-F-200-1760     906.0      NaN   
0701F00200177000  701-F-200-1770     906.0      NaN   
0701F00230174500  701-F-230-1745     906.0      NaN   
0701F00200176800  701-F-200-1768     906.0      NaN   
0701F00200175200  701-F-200-1752     906.0      NaN   
0701F00200177400  701-F-200-1774     906.0      NaN   
0701F00200176400  701-F-200-1764     906.0      NaN   
0701F00230179000  701-F-230-1790     906.0      NaN   
0385E00105000100     385-E-105-1     870.0      NaN   
0385E00300120400  385-E-300-1204     870.0      NaN   
0385E00300060800   385-E-300-608     870.0      NaN   
0385E00300080400   385-E-300-804     870.0      NaN   
0385E00350020000   385-E-350-200     870.0      NaN   
0085P00045000100       85-P-45-1     114.0      NaN   
0701F00210173900  701-F-210-1739     906.0      NaN   
0385E00300060200   385-E-300-602     870.0      NaN   
0701F00200177600  701-F-200-1776     906.0      NaN   
0701F00210173300  701-F-210-1733     906.0      NaN   
0701F00230178600  701-F-230-1786     906.0      NaN   
0385E00101000100     385-E-101-1     870.0      NaN   
0040C00253000A00      40-C-253-A     128.0      NaN   
0701F00230179200  701-F-230-1792     906.0      NaN   
0701F00200176200  701-F-200-1762     906.0      NaN   
0385E00350011100   385-E-350-111     870.0      NaN   
0385E00350040400   385-E-350-404     870.0      NaN   
0385E00350030900   385-E-350-309     870.0      NaN   
0385E00350020600   385-E-350-206     870.0      NaN   
0385E00350010900   385-E-350-109     870.0      NaN   
0385E00350040600   385-E-350-406     870.0      NaN   
0385E00350021000   385-E-350-210     870.0      NaN   
0701F00230178000  701-F-230-1780     906.0      NaN   
0385E00350040200   385-E-350-402     870.0      NaN   
0701F00230178400  701-F-230-1784     906.0      NaN   
0701F00200175600  701-F-200-1756     906.0      NaN   
...                          ...       ...      ...   
0701C00007140300    701-C-7-1403     906.0      NaN   
0701C00007080100     701-C-7-801     906.0      NaN   
0701C00007080400     701-C-7-804     906.0      NaN   
0701C00007150200    701-C-7-1502     906.0      NaN   
0701C00007090400     701-C-7-904     906.0      NaN   
0701C00007110400    701-C-7-1104     906.0      NaN   
0701C00007170300    701-C-7-1703     906.0      NaN   
0701C00007080200     701-C-7-802     906.0      NaN   
0701C00007160400    701-C-7-1604     906.0      NaN   
0701C00120070300   701-C-120-703     906.0      NaN   
0701C00007140200    701-C-7-1402     906.0      NaN   
0701C00007170400    701-C-7-1704     906.0      NaN   
0701C00007130100    701-C-7-1301     906.0      NaN   
0701C00007110300    701-C-7-1103     906.0      NaN   
0701C00007110200    701-C-7-1102     906.0      NaN   
0701C00007120100    701-C-7-1201     906.0      NaN   
0701C00007160200    701-C-7-1602     906.0      NaN   
0701C00007090300     701-C-7-903     906.0      NaN   
0701C00007100200    701-C-7-1002     906.0      NaN   
0701C00120070200   701-C-120-702     906.0      NaN   
0701C00

In [157]:
apd_2009

MAPBLOCKLO  MUNICODE PSEUDONO  \
PARID                                               
0040A00310000000      40-A-310     835.0      NaN   
0040A00352000000      40-A-352     835.0      NaN   
0040B00110000000      40-B-110     128.0      NaN   
1671S00064000000     1671-S-64     952.0      NaN   
0040B00041000000       40-B-41     128.0      NaN   
0040B00119000000      40-B-119     128.0      NaN   
0542C00094000000      542-C-94     953.0      NaN   
1673A00116000000    1673-A-116     913.0      NaN   
0040A00330000000      40-A-330     818.0      NaN   
1672J00051000000     1672-J-51     952.0      NaN   
1672J00075000000     1672-J-75     952.0      NaN   
0542C00106000000     542-C-106     953.0      NaN   
0040A00304000000      40-A-304     835.0      NaN   
0040B00009000000        40-B-9     128.0      NaN   
1673G00199000000    1673-G-199     913.0      NaN   
1671N00055000000     1671-N-55     952.0      NaN   
1672J00045000000     1672-J-45     952.0      NaN   
1673G00194000000    1673-G-194     913.0      NaN   
0040A00318000000      40-A-318     835.0      NaN   
0040A00332000000      40-A-332     818.0      NaN   
0040A00344000000      40-A-344     835.0      NaN   
0040B00011000000       40-B-11     128.0      NaN   
1673C00321000000    1673-C-321     913.0      NaN   
1673C00321000000    1673-C-321     913.0      NaN   
1673G00196000000    1673-G-196     913.0      NaN   
1672N00179000000    1672-N-179     952.0      NaN   
1673G00165000000    1673-G-165     913.0      NaN   
1673G00188000000    1673-G-188     913.0      NaN   
1671H00055000000     1671-H-55     952.0      NaN   
1671M00248000000    1671-M-248     952.0      NaN   
0542E00012000000      542-E-12     953.0      NaN   
0040B00113000000      40-B-113     128.0      NaN   
1672P00331000000    1672-P-331     952.0      NaN   
1672N00316000000    1672-N-316     952.0      NaN   
1673G00206000000    1673-G-206     913.0      NaN   
0040A00345000000      40-A-345     835.0      NaN   
1671N00067000000     1671-N-67     952.0      NaN   
0040B00118000000      40-B-118     128.0      NaN   
0542C00102000000     542-C-102     953.0      NaN   
0040A00336000000      40-A-336     835.0      NaN   
0040A00351000000      40-A-351     835.0      NaN   
1671J00368000000    1671-J-368     952.0      NaN   
1672J00084000000     1672-J-84     952.0      NaN   
0040B00012000000       40-B-12     128.0      NaN   
1671G00380000000    1671-G-380     952.0      NaN   
1671G00395000000    1671-G-395     952.0      NaN   
1672K00348000000    1672-K-348     952.0      NaN   
0040A00312000000      40-A-312     835.0      NaN   
0040B00073000000       40-B-73     128.0      NaN   
0040B00037000000       40-B-37     128.0      NaN   
...                        ...       ...      ...   
0251G00010000000      251-G-10     926.0      NaN   
0384K00027000000      384-K-27     870.0      NaN   
0701C00016000000      701-C-16     906.0      NaN   
0701C00120000000     701-C-120     906.0      NaN   
0541N00078000000      541-N-78     953.0      NaN   
0085N00227000000      85-N-227     114.0      NaN   
0085N00229000000      85-N-229     114.0      NaN   
0542A00160000000     542-A-160     953.0      NaN   
0251F00212000000     251-F-212     926.0      NaN   
0701C00007090200   701-C-7-902     906.0      NaN   
0085N00101000000      85-N-101     114.0      NaN   
0251F00112000000     251-F-112     926.0      NaN   
0085N00149000000      85-N-149     114.0      NaN   
0085N00178000000      85-N-178     114.0      NaN   
0251F00036000000      251-F-36     926.0      NaN   
0251G00205000000     251-G-205     926.0      NaN   
0085N00180000000      85-N-180     114.0      NaN   
0085N00053000000       85-N-53     114.0      NaN   
0085N00176000000      85-N-176     114.0      NaN   
0251F00149000000     251-F-149     926.0      NaN   
0251G00076000000      251-G-76     926.0      NaN   
0251G00221000000     251-G-221     926.0      NaN   
0384L00112000000     384-L-112     829.0     

# Process geometries to be able to record lat/lon for properties

In [71]:
#with open("assessments/Allegheny_County_Parcel_Boundaries.geojson") as f:
#    parcel_json = json.load(f)
#len(parcel_json['features'])
g = gpd.read_file('assessments/Allegheny_County_Parcel_Boundaries.geojson')

g=g.set_index('PIN')

# Calculate the centroid for each row and store in a new column called centroid
g['centroid']=g['geometry'].centroid

In [72]:
# Create a map from PARID to centroid
parid2centroid = {g.index[i]:g['centroid'].iloc[i] for i in range(0, len(g.index))}

In [ ]:
# Given a list of parcel ids, add a centroid to parid2centroid from the property address if we have a good one
def update_centroids(parid_arr):
    for parid in parid_arr:
        # Check if we already know this centroid
        if(parid in parid2centroid):
            continue
        # Don't know the centroid yet.  First try census
        if parid in canonical_property_address_map:
            addr = canonical_property_address_map[parid]
            coords = get_canonical_coords(addr)
            if(coords):
                print "Updating %s from census: %r (%f, %f)" % (parid, addr, coords.x, coords.y)
                parid2centroid[parid]=coords
                continue
        if parid in raw_property_address_map:
            addr = raw_property_address_map[parid]
            coords = get_canonical_coords_google(addr)
            if(coords):
                print "Updating %s from google: %r (%f, %f)" % (parid, addr, coords.x, coords.y)
                parid2centroid[parid]=coords
                continue
            print "Skipping %s: Raw property addr = %r" % (parid, raw_property_address_map[parid])
        else:
            print "Skipping %s: No raw property addr" % (parid)


# New volume animation

In [73]:
def color_from_floats(r,g,b):
    return r + g * 256.0 + b * 256.0 * 256.0

def pack_color(color):
    return color['r'] + color['g'] * 256.0 + color['b'] * 256.0 * 256.0;

def parse_color(color):
    color = color.strip()
    c = color
    try:
        if c[0] == '#':
            c = c[1:]
        if len(c) == 3:
            return pack_color({'r': 17 * int(c[0:1], 16),
                               'g': 17 * int(c[1:2], 16),
                               'b': 17 * int(c[2:3], 16)})
        if len(c) == 6:
            return pack_color({'r': int(c[0:2], 16),
                               'g': int(c[2:4], 16),
                               'b': int(c[4:6], 16)})
    except:
        pass
    raise InvalidUsage('Cannot parse color <code><b>%s</b></code> from spreadsheet.<br><br>Color must be in standard web form, <code><b>#RRGGBB</b></code>, where RR, GG, and BB are each two-digit hexadecimal numbers between 00 and FF.<br><br>See <a href="https://www.w3schools.com/colors/colors_picker.asp">HTML Color Picker</a>' % color)

def parse_colors(colors):
    packed = [parse_color(color) for color in colors]
    return numpy.array(packed, dtype = numpy.float32)

In [400]:
#out_suffix="_09_10_11_13_14_15_17"
#out_suffix="_15213_17"
#out_suffix="_99_09_17"
#out_suffix="_99_04b_09_17"
#out_suffix="_99_04_05_09_17"
out_suffix="_99_04_05_09_10_17"

In [423]:
start=arrow.now()

# Use the property_map, owner_map, and changeaddr_map to generate a new type of volume animation
# Write out a binary file with the volume colors
vol_colors = ['#a50026','#cd2827','#e75436','#f7804b','#fdad61','#fed788','#ffffbf','#b9e0ed','#8dc0db','#699fca','#4d7db9','#3e5aa7','#313695']
def volume_to_color(volume):
    if (volume < 2):
        return parse_color(vol_colors[0]) 
    #elif (volume < 3):
    #    return parse_color(vol_colors[1]) 
    #elif (volume < 4):
    #    return parse_color(vol_colors[2]) 
    elif (volume < 5):
        return parse_color(vol_colors[3]) 
    elif (volume < 10):
        return parse_color(vol_colors[4]) 
    elif (volume < 20):
        return parse_color(vol_colors[5]) 
    elif (volume < 40):
        return parse_color(vol_colors[6]) 
    elif (volume < 60):
        return parse_color(vol_colors[7]) 
    elif (volume < 80):
        return parse_color(vol_colors[8]) 
    elif (volume < 150):
        return parse_color(vol_colors[9]) 
    elif (volume < 300):
        return parse_color(vol_colors[10]) 
    elif (volume < 500):
        return parse_color(vol_colors[11]) 
    else:
        return parse_color(vol_colors[12]) 

def output_volume_dots():
    # Write out volume of ownership for each residential non-vacant land property
    points = []
    i=0
    start=arrow.now()
    chunk_start_time=arrow.now()
    chunk_size=1000

    for parid in property_map.keys():
        centroid=None
        try:
            centroid = parid2centroid[parid]
        except:
            print "%s is missing from centroids, skipping" % (parid)
            continue

        try:
            # Handle periodic debug message
            if((i%chunk_size)==0 and i>0):
                print "%d-%d: processing %r, %s time elapsed" %(i-(chunk_size-1), i, parid, arrow.now()-chunk_start_time)
                addcnt=0
                chunk_start_time=arrow.now()

            # Nominally start at 1950
            next_date = '1950-01-01'

            while(next_date<this_date):
                volume_map=get_related_parids(parid, next_date)

                next_date=volume_map['next_date']
                color = volume_to_color(volume_map['parcount'])
                if((i%chunk_size)==0):
                    print "  %s: %s - %s = %d" % (parid, volume_map['start_date'], volume_map['next_date'], volume_map['parcount'])
                saledate = SaledateToEpoch(volume_map['start_date'])
                enddate = SaledateToEpoch(next_date)
                if(color != None):
                    points += PointToPixelXY(centroid)     
                    points.append(color)
                    # Put epoch time for SALEDATE as start valid time, and next_date as end valid time
                    points.append(float(saledate))
                    points.append(float(enddate))
                else:
                    print "Color of " + str(volume_map['parcount']) + " is None"
        except:
            print "Unexpected error processing %s, next_date=%s:" % (parid, next_date), sys.exc_info()[0]
            #raise

        #Increment debug message counter
        i=i+1

    array.array('f', points).tofile(open(('assessments/res_volume_color_m_epoch%s.bin'%out_suffix), 'wb'))

    end=arrow.now()
    print "Processing took %s" % (str(end-start))
    
#import cProfile
#cProfile.run('output_volume_dots()')
output_volume_dots()


  0011F00188000000: 2008-11-17 - 2009-10-06 = 34
  0011F00188000000: 2009-10-06 - 2010-02-16 = 35
  0011F00188000000: 2010-02-16 - 2011-02-08 = 36
  0011F00188000000: 2011-02-08 - 2012-01-11 = 37
  0011F00188000000: 2012-01-11 - 2012-09-12 = 48
  0011F00188000000: 2012-09-12 - 2012-10-26 = 52
  0011F00188000000: 2012-10-26 - 2013-04-26 = 57
  0011F00188000000: 2013-04-26 - 2013-10-25 = 59
  0011F00188000000: 2013-10-25 - 2014-10-24 = 60
  0011F00188000000: 2014-10-24 - 2015-02-04 = 66
  0011F00188000000: 2015-02-04 - 2015-09-22 = 69
  0011F00188000000: 2015-09-22 - 2015-10-30 = 70
  0011F00188000000: 2015-10-30 - 2016-04-29 = 72
  0011F00188000000: 2016-04-29 - 2016-08-19 = 75
  0011F00188000000: 2016-08-19 - 2017-04-28 = 79
  0011F00188000000: 2017-04-28 - 2018-08-11 = 80
1-1000: processing '0051P00166000000', 0:00:00.399189 time elapsed
  0051P00166000000: 2001-07-20 - 2006-08-04 = 2
  0051P00166000000: 2006-08-04 - 2010-08-02 = 3
  0051P00166000000: 2010-08-02 - 2013-11-20 = 4
  005

In [71]:
start=arrow.now()

single_property_color = '#a50026'
corporate_color = '#ffffbf'
unknown_color = '#303030'

def ownertype_to_color(parid, property_event):
    # Check if property and owner canonical addresses are both known
    property_canonical_addr=get_canonical_property_addr(parid)
    owner_canonical_addr=None
    if('canonical_owner_address' in property_event.keys()):
        owner_canonical_addr=property_event['canonical_owner_address']
    # Check if both addresses are identical.  If so, use single_property_color
    # since it's owner occupied, even if the owner is a multiple or corporate owner
    # in general
    if(property_canonical_addr and owner_canonical_addr and property_canonical_addr == owner_canonical_addr):
        return single_property_color

    ownerdesc = 'REGULAR'
    if('ownerdesc' in property_event.keys()):
       ownerdesc = property_event['ownerdesc']
    volume_map=get_related_parids(parid, property_event['date'])
    volume = volume_map['parcount']
    if ('CORPORATION' in ownerdesc or 'Corporation' in ownerdesc):
        # Ivory 
        return corporate_color
    elif ('homesteadflag' in property_event.keys() and 
          (property_event['homesteadflag'].strip()=='HOM' or property_event['homesteadflag'].strip()=='C')):
        # If homestead flag set, use single property color regardless of volume
        return single_property_color
    elif ('REGULAR' in ownerdesc or 'Regular' in ownerdesc):
        # Regular owner, what volume?
        if(volume == 1):
            # Same color as 1 in volume view
            return single_property_color
        else:
            # Same color as other in class view
            return '#02ca75'
    else:
        print "Unrecognized owner type: %s, %d" % (ownerdesc,volume)
        return unknown_color

def output_ownertype_dots(parid_arr, suffix):
    # If parid_arr not specified, do all of the keys in property_map
    if(len(parid_arr)==0):
        parid_arr=property_map.keys()
        
    # Write out volume of ownership for each residential non-vacant land property
    points = []
    start=arrow.now()
    chunk_start_time=arrow.now()
    chunk_size=1000
    chunk_cnt=0
    
    for parid in parid_arr:
        centroid=None
        did_output_dot=False
        try:
            centroid = parid2centroid[parid]
        except:
            print "%s is missing from centroids, skipping" % (parid)
            continue

        try:
            # Handle periodic debug message
            if((chunk_cnt%chunk_size)==0 and chunk_cnt>0):
                print "%d-%d: processing %r, %s time elapsed" %(chunk_cnt-(chunk_size-1), chunk_cnt, parid, arrow.now()-chunk_start_time)
                addcnt=0
                chunk_start_time=arrow.now()

            # Get list of property events or this property
            property_events = property_map[parid]

            # Keep track of the date of the last datapoint. 
            last_date = '1900-01-01'
            last_color=0
            
            for i in range(0,len(property_events)):
                event_date = property_events[i]['date']
                # Get color for this property event
                color = ownertype_to_color(parid, property_events[i])
                # Check if the date and color haven't changed, if so skip to the next event
                if(color == last_color and last_date == event_date):
                    # Nothing new here, move along
                    continue
                elif(last_date==event_date and i>0):
                    # Color changed without the sale date changing, possibly flag this as an issue
                    # If this new color is unknown, skip it
                    # If the last color was unknown, delete it and use this one
                    # Otherwise, this might be a change in homesteadflag.  If so, single_property_color takes precedence.
                    # Corporate takes priority between multi and corporate
                    # If neither has single_property_color, raise an exception
                    if(color==unknown_color):
                        # Ok, just skip this one
                        continue
                    elif(last_color==unknown_color):
                        # Pop the previous point off (5 floats) and use this new one
                        for j in range(0,5):
                            del points[-1]
                        #print "  REMOVED %s: %s = %s (len %d)" % (parid, event_date,last_color, len(points))
                    elif(last_color==single_property_color):
                        # Ok, just skip this one
                        continue
                    elif(color == single_property_color):
                        # Pop the previous point off (5 floats) and use this new one
                        for j in range(0,5):
                            del points[-1]
                        #print "  REMOVED %s: %s = %s (len %d)" % (parid, event_date,last_color, len(points))
                    elif(last_color==corporate_color):
                        # Ok, just skip this one
                        continue
                    elif(color==corporate_color):
                        # Pop the previous point off (5 floats) and use this new one
                        for j in range(0,5):
                            del points[-1]
                        #print "  REMOVED %s: %s = %s (len %d)" % (parid, event_date,last_color, len(points))
                    else:
                        print " PROBLEM %s: %s changed color on same date %s->%s" % (parid, event_date, last_color, color)
                        raise
                        
                if((chunk_cnt%chunk_size)==0):
                    print "  %s: %s = %s" % (parid, event_date, color)
                
                # Get range of dates for this color
                saledate = SaledateToEpoch(event_date)
                next_date = get_next_sale_date(parid, event_date)
                if(next_date == None):
                    # No new owner after this, set end date to the end of time
                    enddate = float(1e38)
                    next_date=this_date
                else:
                    enddate = SaledateToEpoch(next_date)
                if(color != None):
                    points += PointToPixelXY(centroid)     
                    points.append(parse_color(color))
                    # Put epoch time for SALEDATE as start valid time, and next_date as end valid time
                    points.append(float(saledate))
                    points.append(float(enddate))
                    #print "  %s: %s - %s = %s (len %d)" % (parid, event_date, next_date, color, len(points))
                else:
                    print "Color of " + str(volume_map['parcount']) + " is None"

                # Set last_date and last_color for next loop
                last_date = event_date
                last_color= color
                did_output_dot=True
        except:
            print "Unexpected error processing %s:" % (parid), sys.exc_info()[0]
            raise

        #Increment debug message counter
        if(did_output_dot):
            chunk_cnt = chunk_cnt+1

    array.array('f', points).tofile(open(('assessments/ownertype_color_m_epoch%s.bin'%suffix), 'wb'))

    end=arrow.now()
    print "Processing took %s for %d dots" % (str(end-start), chunk_cnt)
    

In [600]:
#import cProfile
#cProfile.run('output_volume_dots()')
output_ownertype_dots([],out_suffix)

  0177N00269000000: 2007-03-02 = #a50026
  0177N00269000000: 2011-02-28 = #a50026
  REMOVED 0104P00058000000: 1999-09-08 = #02ca75 (len 185)
  REMOVED 0023L00150000000: 2001-01-04 = #02ca75 (len 235)
  REMOVED 0046A00067000000: 2004-06-03 = #02ca75 (len 595)
  REMOVED 0117A00030000000: 2012-07-11 = #02ca75 (len 1035)
  REMOVED 0445J00217000000: 2004-11-10 = #02ca75 (len 1045)
  REMOVED 0826D00101000000: 2013-07-02 = #02ca75 (len 1115)
  REMOVED 0568K00082000000: 1982-02-03 = #02ca75 (len 1415)
  REMOVED 0048F00113000000: 2007-04-24 = #02ca75 (len 1550)
  REMOVED 0071G00130000000: 2013-01-31 = #02ca75 (len 1590)
  REMOVED 0070M00241000000: 2011-09-20 = #02ca75 (len 2850)
  REMOVED 0775K00070000000: 2013-09-13 = #02ca75 (len 3040)
  REMOVED 0432L00244000000: 2012-04-12 = #02ca75 (len 4905)
  REMOVED 0165B00095000000: 2008-10-07 = #02ca75 (len 4910)
  REMOVED 0381B00012000000: 2001-01-29 = #02ca75 (len 5380)
  REMOVED 0004A00164000000: 1978-05-25 = #02ca75 (len 7415)
1-1000: processing u'

  REMOVED 0457N00256000000: 2012-05-29 = #02ca75 (len 67415)
  REMOVED 0372M00260000000: 2008-10-08 = #02ca75 (len 67430)
  REMOVED 0736D00013000000: 2013-09-06 = #02ca75 (len 67945)
  REMOVED 0386H00233000000: 2013-08-02 = #02ca75 (len 68370)
  REMOVED 0082A00234000000: 2010-02-01 = #02ca75 (len 68560)
  REMOVED 1906B00172000000: 2014-05-30 = #02ca75 (len 68630)
  REMOVED 0454K00252000000: 2010-02-24 = #02ca75 (len 68725)
  REMOVED 0276K00076000000: 2005-09-08 = #02ca75 (len 69085)
  REMOVED 0849R000250H1A00: 2013-10-21 = #02ca75 (len 69975)
  REMOVED 0124K00170000000: 2014-05-29 = #02ca75 (len 70125)
  REMOVED 0033N00073000000: 2013-06-11 = #02ca75 (len 70615)
  REMOVED 0375B00092000000: 2009-02-12 = #02ca75 (len 71475)
  REMOVED 0023K00291000000: 2008-11-19 = #02ca75 (len 71685)
  REMOVED 0944N00358000000: 2005-10-05 = #02ca75 (len 71790)
  REMOVED 0305R00228000000: 1994-02-17 = #02ca75 (len 71855)
  REMOVED 0131G00098000000: 2011-01-19 = #02ca75 (len 71940)
  REMOVED 0144N000140000

  REMOVED 0098K00286000000: 2008-08-05 = #02ca75 (len 136060)
  REMOVED 0088M00146000000: 2013-07-09 = #02ca75 (len 136290)
  REMOVED 1206H00269000000: 1984-02-23 = #02ca75 (len 137035)
  REMOVED 0062E00112000000: 2010-02-12 = #02ca75 (len 137285)
  REMOVED 0168M00189000000: 2014-12-19 = #02ca75 (len 137375)
  REMOVED 0162R00054000000: 2010-12-29 = #02ca75 (len 138635)
  REMOVED 0094F00245000000: 2004-11-01 = #02ca75 (len 138745)
  REMOVED 0421J00249000600: 2014-12-23 = #02ca75 (len 139240)
  REMOVED 0448A00261000000: 2004-09-09 = #02ca75 (len 139785)
  REMOVED 0167F00250000000: 1999-06-16 = #02ca75 (len 140180)
  REMOVED 0230S00029000000: 2012-11-09 = #02ca75 (len 140905)
  REMOVED 0099K00047000000: 2013-04-24 = #02ca75 (len 141065)
0351B00248000000 is missing from centroids, skipping
18001-19000: processing u'0279R00265002500', 0:00:00.262302 time elapsed
  0279R00265002500: 2010-10-29 = #ffffbf
  REMOVED 0354D00097000000: 2010-12-29 = #02ca75 (len 142330)
  REMOVED 0386S00033000000:

  REMOVED 1134G00225000000: 2010-10-13 = #02ca75 (len 206005)
  REMOVED 0060J00305000000: 2009-07-17 = #02ca75 (len 206600)
  REMOVED 0111L00232000000: 1998-12-09 = #02ca75 (len 207365)
  REMOVED 8000T02333000000: 2010-01-06 = #02ca75 (len 207830)
  REMOVED 0012J00435000000: 2011-08-19 = #02ca75 (len 208375)
0299F00066000200 is missing from centroids, skipping
  REMOVED 0032E00147000000: 2009-06-12 = #02ca75 (len 208625)
27001-28000: processing u'1271A00349000000', 0:00:00.294742 time elapsed
  1271A00349000000: 1950-05-05 = #a50026
  1271A00349000000: 1971-07-14 = #a50026
  REMOVED 0163A00143000000: 2012-01-12 = #02ca75 (len 209995)
  REMOVED 0660N00107000000: 2005-08-08 = #02ca75 (len 211640)
  REMOVED 0251B00216000000: 2010-10-15 = #02ca75 (len 213780)
  REMOVED 0116J00281000000: 2005-07-21 = #02ca75 (len 215785)
  REMOVED 0667B00072000000: 2010-03-01 = #02ca75 (len 216725)
28001-29000: processing u'0180F00081000000', 0:00:00.292779 time elapsed
  0180F00081000000: 1950-05-05 = #a50

  REMOVED 0383M00093000000: 2009-08-24 = #02ca75 (len 275150)
0564S00033000000 is missing from centroids, skipping
36001-37000: processing u'0061B00061000000', 0:00:00.301289 time elapsed
  0061B00061000000: 2003-12-24 = #02ca75
  REMOVED 0081C00232000000: 2010-01-20 = #02ca75 (len 278430)
  REMOVED 0628A00067000000: 1969-08-01 = #02ca75 (len 278630)
  REMOVED 0430A00319000000: 1978-07-12 = #02ca75 (len 279655)
  REMOVED 0071S00192000000: 2014-12-30 = #02ca75 (len 279670)
  REMOVED 1828L00001000000: 2012-12-28 = #02ca75 (len 280090)
0851E00032000000 is missing from centroids, skipping
  REMOVED 0821N00085070100: 2014-01-06 = #02ca75 (len 281315)
  REMOVED 0097E00154000000: 2011-12-08 = #02ca75 (len 281375)
  REMOVED 0321R00194000000: 2009-02-24 = #02ca75 (len 281395)
  REMOVED 0279G00144000000: 2008-01-11 = #02ca75 (len 281405)
  REMOVED 0060A00163000000: 1983-05-23 = #02ca75 (len 282480)
  REMOVED 0022B00238000000: 2013-10-11 = #02ca75 (len 282595)
  REMOVED 1352P00041000000: 2011-11-

...

  REMOVED 0238H00040000000: 2010-01-22 = #02ca75 (len 3532205)
  REMOVED 0168J00077000000: 2010-10-01 = #02ca75 (len 3532425)
  REMOVED 0178G00168000000: 2010-04-29 = #02ca75 (len 3533330)
0050F00004000000 is missing from centroids, skipping
  REMOVED 0036D00100000000: 2013-08-23 = #02ca75 (len 3535450)
  REMOVED 0184A00278000000: 1997-03-14 = #02ca75 (len 3535550)
  REMOVED 0167L00061000000: 2003-07-01 = #02ca75 (len 3536170)
  REMOVED 0084J00100000000: 2009-05-04 = #02ca75 (len 3536440)
  REMOVED 0467S00245000000: 2009-01-14 = #02ca75 (len 3536570)
  REMOVED 0654J00055000000: 2009-08-11 = #02ca75 (len 3536825)
  REMOVED 0028P00126027100: 2013-08-01 = #02ca75 (len 3537075)
471001-472000: processing u'0039J00076000000', 0:00:00.286632 time elapsed
  0039J00076000000: 1950-05-05 = #a50026
  0039J00076000000: 1962-05-14 = #a50026
  REMOVED 0115A00097000000: 2011-10-12 = #02ca75 (len 3538265)
  REMOVED 0470D00292000000: 2014-01-30 = #02ca75 (len 3539445)
  REMOVED 0297H00020000000: 2005-0

  REMOVED 0301N00323000000: 2012-08-24 = #02ca75 (len 3590375)
478001-479000: processing u'0522C00109000000', 0:00:00.289314 time elapsed
  0522C00109000000: 2009-01-22 = #a50026
  REMOVED 0469D00137000000: 2002-09-09 = #02ca75 (len 3591230)
  REMOVED 0951M00227000000: 2013-03-07 = #02ca75 (len 3591660)
  REMOVED 0143P00210000000: 2009-10-21 = #02ca75 (len 3591705)
  REMOVED 1367G00149000000: 1975-12-03 = #02ca75 (len 3591735)
  REMOVED 0980B00112000000: 2010-03-26 = #02ca75 (len 3591805)
  REMOVED 0980B00112000000: 2012-07-26 = #02ca75 (len 3591810)
  REMOVED 1270G00013000000: 2008-07-23 = #ffffbf (len 3592695)
1365G00118000000 is missing from centroids, skipping
  REMOVED 0828N00343000000: 2002-06-25 = #02ca75 (len 3593005)
  REMOVED 0279A00332000000: 2010-04-27 = #02ca75 (len 3593795)
  REMOVED 0176J00172000000: 2013-06-10 = #02ca75 (len 3594070)
  REMOVED 0717J00052000000: 2011-12-14 = #02ca75 (len 3594770)
  REMOVED 1996A00030000000: 2011-06-22 = #02ca75 (len 3594875)
  REMOVED 02

  REMOVED 0049J00272000000: 2012-01-06 = #02ca75 (len 3653465)
  REMOVED 0181B00150000000: 2009-02-09 = #02ca75 (len 3653605)
  REMOVED 1067B00004000000: 2013-08-19 = #02ca75 (len 3653735)
  REMOVED 0513S00023000000: 2013-07-18 = #02ca75 (len 3655080)
  REMOVED 0454L00188000000: 2007-07-18 = #02ca75 (len 3656520)
0084M00346000000 is missing from centroids, skipping
  REMOVED 0045E00203000000: 2011-03-02 = #02ca75 (len 3657170)
  REMOVED 0019S00008000000: 1978-12-31 = #02ca75 (len 3657240)
  REMOVED 0084A00275000000: 2005-11-03 = #02ca75 (len 3657635)
  REMOVED 0100C00050800500: 2004-01-14 = #02ca75 (len 3658025)
487001-488000: processing u'0649C00004000000', 0:00:00.280211 time elapsed
  0649C00004000000: 1998-07-16 = #a50026
  REMOVED 1216H00187000000: 2014-11-03 = #02ca75 (len 3659020)
  REMOVED 0429M00231000000: 2012-12-07 = #02ca75 (len 3659420)
  REMOVED 0311N00312000000: 2015-01-29 = #02ca75 (len 3659740)
  REMOVED 0191P00044000000: 2009-05-26 = #02ca75 (len 3659990)
  REMOVED 03

  REMOVED 0467F00079000000: 2014-05-22 = #02ca75 (len 3712725)
  REMOVED 0252K00306000000: 1961-11-28 = #02ca75 (len 3712820)
0119S00157000000 is missing from centroids, skipping
  REMOVED 0464L00027000000: 1987-01-28 = #02ca75 (len 3715920)
  REMOVED 0145D00027000000: 2008-02-26 = #02ca75 (len 3715970)
  REMOVED 0746H00376000000: 1980-09-04 = #02ca75 (len 3716310)
  REMOVED 0167F00312000000: 2013-10-02 = #02ca75 (len 3718070)
  REMOVED 0100K00172000000: 2012-01-06 = #02ca75 (len 3718185)
  REMOVED 0879N00046000200: 2007-04-02 = #02ca75 (len 3718370)
495001-496000: processing u'0102K00142000000', 0:00:00.282301 time elapsed
  0102K00142000000: 1993-10-15 = #ffffbf
  REMOVED 1355F00138510900: 2012-04-04 = #02ca75 (len 3718795)
  REMOVED 1203N00018000000: 2012-04-13 = #02ca75 (len 3721840)
2012M00049000000 is missing from centroids, skipping
  REMOVED 0467R00021000000: 2013-04-04 = #02ca75 (len 3721865)
  REMOVED 0033L00039000000: 2004-07-30 = #02ca75 (len 3721910)
  REMOVED 0162J0018300

  REMOVED 0138C00034000000: 2011-02-18 = #02ca75 (len 3774180)
  REMOVED 0737D00328000000: 2014-05-27 = #02ca75 (len 3774715)
  REMOVED 0464G00034000000: 1998-02-27 = #02ca75 (len 3774800)
  REMOVED 0054R00249000000: 2008-08-28 = #02ca75 (len 3776035)
  REMOVED 0596D00031000000: 2013-08-12 = #02ca75 (len 3776090)
  REMOVED 0691E00006000000: 2014-05-29 = #02ca75 (len 3776330)
  REMOVED 0124N00371000000: 2006-03-01 = #02ca75 (len 3776675)
  REMOVED 1494L00003000000: 2009-08-11 = #02ca75 (len 3777010)
  REMOVED 0741K00017000000: 2012-10-23 = #02ca75 (len 3777230)
  REMOVED 0823S00076000000: 2012-12-05 = #02ca75 (len 3777625)
  REMOVED 0229S00393000000: 2015-01-27 = #02ca75 (len 3777655)
0051L00239000000 is missing from centroids, skipping
503001-504000: processing u'0232R00300000000', 0:00:00.287264 time elapsed
  0232R00300000000: 1950-05-05 = #02ca75
  REMOVED 0341D00135000000: 2014-03-10 = #02ca75 (len 3779535)
  REMOVED 0464G00383000000: 2009-08-25 = #02ca75 (len 3780030)
  REMOVED 06

In [35]:
parids_15213=apd_2017[apd_2017.PROPERTYZIP=='15213'].index

In [43]:
valid_parids_15213=list(set(parids_15213) & set(property_map.keys()) & set(parid2centroid.keys()))

In [44]:
len(valid_parids_15213)

4806

In [72]:
output_ownertype_dots(valid_parids_15213,"_d4_15213")

  0011F00188000000: 2008-11-17 = #ffffbf
1-1000: processing '0052F00008000000', 0:00:00.258180 time elapsed
  0052F00008000000: 2016-01-07 = #a50026
1001-2000: processing '0028A00271000000', 0:00:00.246129 time elapsed
  0028A00271000000: 2007-09-07 = #a50026
2001-3000: processing '0029D00104000000', 0:00:00.265822 time elapsed
  0029D00104000000: 2007-11-07 = #a50026
3001-4000: processing '0028S00127000000', 0:00:00.251807 time elapsed
  0028S00127000000: 1983-07-05 = #a50026
Processing took 0:00:01.217544 for 4806 dots


In [637]:
start=arrow.now()

single_property_color = '#a50026'
corporate_color = '#ffffbf'
unknown_color = '#303030'

# Distressed sales are:
distressed_saledescs=['SHERIFF SALE', 'CITY TREASURER SALE','CITY TREASURER',
                      'PREV FORECLOSE','GOVT SALE','BANK SALE']
#affection_saledescs=['LOVE AND AFFECTION SALE','LOVE&AFFECTION']
affection_saledescs=[]

#distressed_colors=["#ff0000","#00ff00"]
#affection_colors=["#FA00D4","#15FA00"]
distressed_colors=["#FA00D4","#15FA00"]
affection_colors=[]

single_property_colors=[single_property_color, "#ff0000", "#FA00D4"]
def saletype_to_color(parid, property_event):
    try:
        ownerdesc = 'REGULAR'
        if('ownerdesc' in property_event.keys()):
           ownerdesc = property_event['ownerdesc']
        saledesc = 'VALID'
        if('saledesc' in property_event.keys()):
            saledesc = property_event['saledesc']
        volume_map=get_related_parids(parid, property_event['date'])
        volume = volume_map['parcount']

        # Check if homestead flag is set
        homesteadflag=False
        if('homesteadflag' in property_event.keys() and 
          (property_event['homesteadflag'].strip()=='HOM' or property_event['homesteadflag'].strip()=='C')):
            homesteadflag=True
        # Check if property went to a single owner or not
        single_owner = True
        if ('CORPORATION' in ownerdesc or 'Corporation' in ownerdesc or (volume>1 and not homesteadflag)):
            single_owner=False
        
        
        # Check for distressed sale
        if(saledesc in distressed_saledescs):
            # Is distressed sale, check if it went to a single owner or not
            if(single_owner):
                # Set to bright pink
                return "#FA00D4"
            else:
                # Return fluorescent green
                return "#15FA00"
#            if(single_owner):
#                # Set to bright red
#                return "#ff0000"
#            else:
#                # Return bright green
#                return "#00ff00"
#        elif(saledesc in affection_saledescs):
#            # Is affection sale, check if it went to a single owner or not
#            if(single_owner):
#                # Set to bright pink
#                return "#FA00D4"
#            else:
#                # Return fluorescent green
#                return "#15FA00"
        else:
            # Normal sale
#            if ('CORPORATION' in ownerdesc or 'Corporation' in ownerdesc):
#                # Ivory 
#                return '#ffffbf'
            if (single_owner):
                # Same color as 1 in volume view
                return single_property_color
            else:
                # Non-corporate multi-owner, reguarl sale
                # Same color as other in class view
                return '#02ca75'
    except:
        print "Exception processing saletype: %s" % (parid), sys.exc_info()[0]
        raise
        return '#303030'

def output_saletype_dots(parid_arr, suffix):
    # If parid_arr not specified, do all of the keys in property_map
    if(len(parid_arr)==0):
        parid_arr=property_map.keys()
    # Write out volume of ownership for each residential non-vacant land property
    points = []
    start=arrow.now()
    chunk_start_time=arrow.now()
    chunk_size=1000
    chunk_cnt=0
    
    for parid in parid_arr:
        centroid=None
        did_output_dot=False
        try:
            centroid = parid2centroid[parid]
        except:
            print "%s is missing from centroids, skipping" % (parid)
            continue

        try:
            # Handle periodic debug message
            if((chunk_cnt%chunk_size)==0 and chunk_cnt>0):
                print "%d-%d: processing %r, %s time elapsed" %(chunk_cnt-(chunk_size-1), chunk_cnt, parid, arrow.now()-chunk_start_time)
                addcnt=0
                chunk_start_time=arrow.now()

            # Get list of property events or this property
            property_events = property_map[parid]

            # Keep track of the date of the last datapoint. 
            last_date = '1900-01-01'
            last_color=0
            
            for i in range(0,len(property_events)):
                event_date = property_events[i]['date']
                # Get color for this property event
                color = saletype_to_color(parid, property_events[i])
                # Check if the date and color haven't changed, if so skip to the next event
                if(color == last_color and last_date == event_date):
                    # Nothing new here, move along
                    continue
                elif(last_date==event_date and i>0):
                    # Color changed without the sale date changing, possibly flag this as an issue
                    # If this new color is unknown, skip it
                    # If the last color was unknown, delete it and use this one
                    # Otherwise, distressed_colors take precedence if present, 
                    # if not, this might be a change in homesteadflag.  If so, single_property_color takes precedence.
                    # Corporate takes priority between multi and corporate
                    # If neither has single_property_color, raise an exception
                    if(color==unknown_color):
                        # Ok, just skip this one
                        continue
                    elif(last_color==unknown_color):
                        # Pop the previous point off (5 floats) and use this new one
                        for j in range(0,5):
                            del points[-1]
                    elif(last_color in distressed_colors):
                        # Ok, just skip this one
                        continue
                    elif(color in distressed_colors):
                        # Pop the previous point off (5 floats) and use this new one
                        for j in range(0,5):
                            del points[-1]
                    elif(last_color in affection_colors):
                        # Ok, just skip this one
                        continue
                    elif(color in affection_colors):
                        # Pop the previous point off (5 floats) and use this new one
                        for j in range(0,5):
                            del points[-1]
                    elif(color in single_property_colors):
                        # Pop the previous point off (5 floats) and use this new one
                        for j in range(0,5):
                            del points[-1]
                    elif(last_color in single_property_colors):
                        # Ok, just skip this one
                        continue
                    elif(last_color==corporate_color):
                        # Ok, just skip this one
                        continue
                    elif(color==corporate_color):
                        # Pop the previous point off (5 floats) and use this new one
                        for j in range(0,5):
                            del points[-1]
                    else:
                        print " PROBLEM %s: %s changed color on same date %s->%s" % (parid, event_date, last_color, color)
                        raise

                if((chunk_cnt%chunk_size)==0):
                    print "  %s: %s = %s" % (parid, event_date, color)
                
                # Get range of dates for this color
                saledate = SaledateToEpoch(event_date)
                next_date = get_next_sale_date(parid, event_date)
                if(next_date == None):
                    # No new owner after this, set end date to the end of time
                    enddate = float(1e38)
                    next_date=this_date
                else:
                    enddate = SaledateToEpoch(next_date)
                if(color != None):
                    points += PointToPixelXY(centroid)     
                    points.append(parse_color(color))
                    # Put epoch time for SALEDATE as start valid time, and next_date as end valid time
                    points.append(float(saledate))
                    points.append(float(enddate))
                    #print "  %s: %s - %s = %s (len %d)" % (parid, event_date, next_date, color, len(points))
                else:
                    print "Color of " + str(volume_map['parcount']) + " is None"

                # Set last_date and last_color for next loop
                last_date = event_date
                last_color= color
                did_output_dot=True
        except:
            print "Unexpected error processing %s:" % (parid), sys.exc_info()[0]
            raise

        #Increment debug message counter
        if(did_output_dot):
            chunk_cnt = chunk_cnt+1

    array.array('f', points).tofile(open(('assessments/saletype_color_m_epoch%s.bin'%suffix), 'wb'))

    end=arrow.now()
    print "Processing took %s for %d dots" % (str(end-start), chunk_cnt)
    

In [ ]:
output_saletype_dots([],out_suffix)

  0177N00269000000: 2007-03-02 = #a50026
  0177N00269000000: 2011-02-28 = #a50026
1-1000: processing u'0981J00102000000', 0:00:00.430800 time elapsed
  0981J00102000000: 2008-04-21 = #02ca75
  0981J00102000000: 2010-07-08 = #a50026
1001-2000: processing u'0252H00202000000', 0:00:00.331908 time elapsed
  0252H00202000000: 2004-03-02 = #a50026
2001-3000: processing u'0362G00145000000', 0:00:00.329856 time elapsed
  0362G00145000000: 2000-05-03 = #02ca75
  0362G00145000000: 2015-04-10 = #02ca75
0178J00009000000 is missing from centroids, skipping
3001-4000: processing u'0878N00182000000', 0:00:00.314119 time elapsed
  0878N00182000000: 1999-12-29 = #02ca75
0024N00055000000 is missing from centroids, skipping
4001-5000: processing u'0435G00198000000', 0:00:00.313595 time elapsed
  0435G00198000000: 2002-05-14 = #a50026
  0435G00198000000: 2010-03-19 = #a50026
  0435G00198000000: 2013-05-23 = #a50026
0175C00169000000 is missing from centroids, skipping
0564S00037000000 is missing from centr

46001-47000: processing u'0517H00030240400', 0:00:00.282306 time elapsed
  0517H00030240400: 2009-08-06 = #a50026
0084M00362000000 is missing from centroids, skipping
47001-48000: processing u'0129G00202000000', 0:00:00.292338 time elapsed
  0129G00202000000: 1985-03-28 = #a50026
  0129G00202000000: 2014-05-21 = #a50026
0010C00013000000 is missing from centroids, skipping
48001-49000: processing u'0255E00082000000', 0:00:00.282780 time elapsed
  0255E00082000000: 1956-06-19 = #a50026
0178J00017000000 is missing from centroids, skipping
49001-50000: processing u'0551C00277000000', 0:00:00.287053 time elapsed
  0551C00277000000: 1950-05-05 = #a50026
  0551C00277000000: 1959-07-06 = #a50026
  0551C00277000000: 2011-12-13 = #02ca75
0349F00197000000 is missing from centroids, skipping
50001-51000: processing u'0692R00044000000', 0:00:00.285093 time elapsed
  0692R00044000000: 1950-05-05 = #02ca75
  0692R00044000000: 2003-08-22 = #02ca75
51001-52000: processing u'0634D00110000000', 0:00:00.2

89001-90000: processing u'0025N00080021900', 0:00:00.307087 time elapsed
  0025N00080021900: 2011-01-14 = #02ca75
  0025N00080021900: 2017-05-12 = #a50026
0175C00167000000 is missing from centroids, skipping
90001-91000: processing u'1357C00166000000', 0:00:00.287104 time elapsed
  1357C00166000000: 2001-02-27 = #a50026
1999L00012000000 is missing from centroids, skipping
91001-92000: processing u'0426D00233000000', 0:00:00.294100 time elapsed
  0426D00233000000: 2012-03-23 = #a50026
  0426D00233000000: 2015-06-18 = #a50026
8000T03141000000 is missing from centroids, skipping
1203F00095000300 is missing from centroids, skipping
0049C00209000000 is missing from centroids, skipping
92001-93000: processing '0268K00080000000', 0:00:00.290802 time elapsed
  0268K00080000000: 2014-12-31 = #a50026
  0268K00080000000: 2015-12-31 = #a50026
0024N00048000000 is missing from centroids, skipping
93001-94000: processing u'0087H00011000000', 0:00:00.292285 time elapsed
  0087H00011000000: 1998-07-15 

133001-134000: processing u'0014E00220000000', 0:00:00.280660 time elapsed
  0014E00220000000: 2006-08-29 = #02ca75
  0014E00220000000: 2013-03-05 = #02ca75
134001-135000: processing u'0341H00269000000', 0:00:00.286062 time elapsed
  0341H00269000000: 2007-08-29 = #02ca75
135001-136000: processing u'0042N00177000000', 0:00:00.289147 time elapsed
  0042N00177000000: 2003-03-05 = #02ca75
136001-137000: processing u'0003N00066000000', 0:00:00.286086 time elapsed
  0003N00066000000: 1991-01-02 = #a50026
  0003N00066000000: 2010-11-18 = #02ca75
137001-138000: processing u'0507S00164000000', 0:00:00.281678 time elapsed
  0507S00164000000: 2005-08-18 = #a50026
  0507S00164000000: 2014-06-02 = #a50026
  0507S00164000000: 2017-04-26 = #a50026
0023M00269000000 is missing from centroids, skipping
0081A00128000000 is missing from centroids, skipping
138001-139000: processing u'1242C00314000000', 0:00:00.280577 time elapsed
  1242C00314000000: 2003-07-08 = #a50026
  1242C00314000000: 2013-12-02 = #

181001-182000: processing u'0077B00151000000', 0:00:00.286298 time elapsed
  0077B00151000000: 2008-08-22 = #a50026
182001-183000: processing u'1354E00255000000', 0:00:00.278794 time elapsed
  1354E00255000000: 1997-08-11 = #02ca75
8000T03070000000 is missing from centroids, skipping
1735P00025000000 is missing from centroids, skipping
183001-184000: processing u'1355F00138512900', 0:00:00.291710 time elapsed
  1355F00138512900: 2008-12-05 = #a50026
0023M00247000000 is missing from centroids, skipping
0131E00042000000 is missing from centroids, skipping
0050K00060000000 is missing from centroids, skipping
184001-185000: processing u'0040B00232000000', 0:00:00.287649 time elapsed
  0040B00232000000: 1976-06-09 = #a50026
  0040B00232000000: 2016-09-30 = #02ca75
185001-186000: processing u'0299F00151000000', 0:00:00.302115 time elapsed
  0299F00151000000: 2006-07-13 = #a50026
0001N00281004B00 is missing from centroids, skipping
186001-187000: processing u'0305N00043000000', 0:00:00.277306

1834D00046000000 is missing from centroids, skipping
225001-226000: processing u'0344L00060000000', 0:00:00.284510 time elapsed
  0344L00060000000: 1996-05-06 = #a50026
  0344L00060000000: 2013-10-22 = #02ca75
226001-227000: processing u'0019D00211000000', 0:00:00.279635 time elapsed
  0019D00211000000: 2007-07-05 = #02ca75
1999P00022000000 is missing from centroids, skipping
0512L00014000100 is missing from centroids, skipping
227001-228000: processing u'0516B00165000000', 0:00:00.247704 time elapsed
  0516B00165000000: 1950-05-05 = #a50026
8000T00534000000 is missing from centroids, skipping
228001-229000: processing u'0206C00007000000', 0:00:00.218144 time elapsed
  0206C00007000000: 1993-12-21 = #a50026
  0206C00007000000: 2010-08-10 = #a50026
  0206C00007000000: 2017-06-26 = #a50026
229001-230000: processing u'0364M00249000000', 0:00:00.228667 time elapsed
  0364M00249000000: 1971-12-08 = #a50026
9946X50070000000 is missing from centroids, skipping
230001-231000: processing u'0960

In [143]:
parid='0121K00245000000'
print canonical_property_address_map[parid]
print property_map[parid]
for j in range(0,len(property_map[parid])):
    print '%r: %s\n' % (property_map[parid][j], ownerprox_to_color(parid, property_map[parid][j]))

1704 CHISLETT ST, PITTSBURGH, PA, 15206
[{'event_type': 'PURCHASE', 'canonical_owner_address': u'1019 PAINTERTOWN RD, IRWIN, PA, 15642', 'changeaddr': '1019 PAINTERTOWN RD IRWIN PA 15642', 'ownername': 'BRADY MARK & LYNN (W)', 'date': u'2007-09-18', 'saledesc': 'LOVE&AFFECTION', 'ownerdesc': 'REGULAR-ETUX OR ET VIR'}, {'event_type': 'PURCHASE', 'canonical_owner_address': u'132 VERLINDEN DR, MONROEVILLE, PA, 15146', 'changeaddr': ' 132 VERLINDEN DR MONROEVILLE, PA 15146-2051 ', 'ownername': 'BRADY MARK & LYNN (W)', 'date': u'2007-09-18', 'saledesc': 'LOVE AND AFFECTION SALE', 'ownerdesc': 'Regular'}]
{'event_type': 'PURCHASE', 'canonical_owner_address': u'1019 PAINTERTOWN RD, IRWIN, PA, 15642', 'changeaddr': '1019 PAINTERTOWN RD IRWIN PA 15642', 'ownername': 'BRADY MARK & LYNN (W)', 'date': u'2007-09-18', 'saledesc': 'LOVE&AFFECTION', 'ownerdesc': 'REGULAR-ETUX OR ET VIR'}: #8dc0db

{'event_type': 'PURCHASE', 'canonical_owner_address': u'132 VERLINDEN DR, MONROEVILLE, PA, 15146', 'chang

In [628]:
'#a50026'  in single_property_colors

True

In [632]:
output_saletype_dots(['0028L00264000000'],"_d1")

  0028L00264000000: 1986-06-11 = #a50026
  0028L00264000000: 1986-06-11 - 2010-07-30 = #a50026 (len 5)
  0028L00264000000: 2010-07-30 = #15FA00
  0028L00264000000: 2010-07-30 - 2018-08-11 = #15FA00 (len 10)
Processing took 0:00:00.005889 for 1 dots


In [638]:
output_saletype_dots(valid_parids_15213,"_15213")

  0011F00188000000: 2008-11-17 = #15FA00
1-1000: processing '0026L00164000000', 0:00:00.363045 time elapsed
  0026L00164000000: 1978-10-02 = #02ca75
  0026L00164000000: 2013-10-04 = #02ca75
  0026L00164000000: 2013-12-26 = #02ca75
1001-2000: processing '0029B00145000000', 0:00:00.322082 time elapsed
  0029B00145000000: 1989-12-21 = #02ca75
  0029B00145000000: 2013-10-25 = #15FA00
2001-3000: processing '0028H00016000000', 0:00:00.305576 time elapsed
  0028H00016000000: 1950-05-05 = #a50026
  0028H00016000000: 1967-08-22 = #a50026
3001-4000: processing '0028G00064000000', 0:00:00.314717 time elapsed
  0028G00064000000: 1988-12-19 = #02ca75
Processing took 0:00:01.555014 for 4797 dots


# Owner proximity

In [75]:
# Create a cache of zip code to proximity. 
# If zip is in PA, but not Allegheny county, value will be 'PA'
# If zip is in Allegheny county, value will be 'Allegheny'
zip_map={}

In [76]:
# Read in US zips, subset on PA
us_zips = pd.read_csv("allegheny_county/zip/us-national-zips-2010.csv",dtype={'zipcode':numpy.str})
pa_zips = us_zips[us_zips.state=='PA']

In [77]:
for zipcode in pa_zips['zipcode']:
    zip_map[zipcode]='PA'

In [78]:
# List of Allegheny county zipcodes adapted from https://clicknathan.com/2012/10/10/csv-of-all-zip-codes-in-allegheny-county-and-pittsburgh/
ac_zips = [15006,15007,15101, 15006,15102,15014,15104,15015,15017,15106,15024,15025,15026,15108,15030,15046,15034,15110,15035,15112,15037,15044,15045,15116,15120,15126,15056,15129,15136,15130,15131,15132,15133,15135,15146,15064,15065,15137,15071,15139,15140,15201,15202,15203,15204,15205,15206,15207,15208,15209,15210,15211,15212,15213,15214,15215,15216,15217,15218,15219,15220,15221,15222,15223,15224,15225,15226,15227,15228,15229,15232,15233,15234,15235,15236,15237,15238,15239,15241,15242,15243,15275,15276,15142,15076,15143,15144,15084,15145,15147,15086,15122,15123,15090,15148]
for zipcode in ac_zips:
    zip_map[str(zipcode)]='Allegheny'

In [176]:
def get_simultaneous_property_events(prop_ev_list, start_index):
    eval_date=prop_ev_list[start_index]['date']
    start_date = eval_date
    next_date = this_date

    # Keep a list of the equivalent transactions.  Seed it with the start_index'th item in prop_ev_list
    equiv_transactions=[prop_ev_list[start_index]]
    # Check if this is the last transaction in prop_ev_list
    if(start_index+1>=len(prop_ev_list)):
        return equiv_transactions
    
    # At least one left
    for i in range(start_index+1,len(prop_ev_list)):
        # See if this new transaction is equivalent to the last item in the current list
        if(is_same_transaction(prop_ev_list[i],equiv_transactions[-1]) and 
           prop_ev_list[i]['date']==eval_date):
            equiv_transactions.append(prop_ev_list[i])
            #print "  %d still equivalent %r" %(i, equiv_transactions)
        elif(prop_ev_list[i]['date']>eval_date):
            #print "  %d after timespan (%r), process current set" %(i,prop_ev_list[i])
            break
        else:
            # We haven't hit the end of the timespan yet, but the ownership has changed.
            # Reset equiv_transactions starting from the current event
            break
            
    # We've got all the equivalent transactions, sort them according to asofdate
    return sorted(equiv_transactions, key=lambda ev: ev['asofdate'])

In [211]:
parid = '2018H00310000000'
sevs = get_simultaneous_property_events(property_map[parid],0)
colors = map(lambda ev: ownerprox_to_color(parid, ev), sevs)
colors

['#a50026', '#8dc0db']

In [401]:
start=arrow.now()

vol_colors = ['#a50026','#cd2827','#e75436','#f7804b','#fdad61','#fed788','#ffffbf','#b9e0ed','#8dc0db','#699fca','#4d7db9','#3e5aa7','#313695']

sameaddr_color = vol_colors[0]
samezip_color = vol_colors[3]
allegheny_co_color=vol_colors[6]
in_state_color=vol_colors[8]
out_of_state_color=vol_colors[11]

unknown_color = '#303030'

def ownerprox_to_color(parid, property_event):
    # Record which sort of canonical address we have, as they can't be
    # compared against each other
    use_census_addrs=True
    
    # Check if property and owner canonical addresses are both known
    # to census
    property_canonical_addr=get_canonical_property_addr(parid)
    owner_canonical_addr=None
    if('canonical_owner_address' in property_event.keys()):
        owner_canonical_addr=property_event['canonical_owner_address']
    if(not property_canonical_addr or not owner_canonical_addr):
        # Missing something
        use_census_addrs=False
        if(property_canonical_addr):
            #print "  %r: Census missing owner addr for %r"  % (parid, property_event['date'])
            # Just missing owner_canonical_addr, try google based on the raw owner address in 'changeaddr'
            owner_canonical_addr = get_canonical_address_google(property_event['changeaddr'])
            # If that worked, also get property canonical address from google
            if(owner_canonical_addr):
                #print "  %r: Google has owner addr for %r: %r" % (parid, property_event['date'],owner_canonical_addr)
                property_canonical_addr = get_canonical_address_google(property_canonical_addr)
        else:
            #print "  %r: Census missing property addr, try google" % (parid)
            # Census doesn't know property address 
            property_canonical_addr = get_canonical_address_google(raw_property_address_map[parid])
            if(property_canonical_addr):
                #print "  %r: Google has property addr: %r" % (parid, property_canonical_addr)
                # Get owner address too so they match
                owner_canonical_addr = get_canonical_address_google(property_event['changeaddr'])
                #print "          Google owner addr for %r: %r" % (property_event['date'],owner_canonical_addr)

                # Now that google had a go at it, check again if we have both
        if(not property_canonical_addr or not owner_canonical_addr):
            #print "  %r: Neither census nor google has both addrs for %r, give up" % (parid, property_event['date'])
            # Nope, still missing something
            return unknown_color
    else:
        #print "  %r: Census knows both property and owner addrs for %r" % (parid, property_event['date'])
        pass
        
    # If we get to here, then both property_canonical_addr and owner_canonical_addr are set
    # Check if both addresses are identical.  If so, use sameaddr_color
    if(property_canonical_addr == owner_canonical_addr):
        return sameaddr_color
    
    # Do have both, check for matching zip code
    property_zip=None
    owner_zip=None
    # Check if we should use google or census
    if(use_census_addrs):
        property_zip = get_canonical_zip(property_canonical_addr)
        owner_zip = get_canonical_zip(owner_canonical_addr)
    else:
        # Use google
        property_zip = get_canonical_zip_google(property_canonical_addr)
        owner_zip = get_canonical_zip_google(owner_canonical_addr)
        
    # Double check that owner_zip is valid
    if(not owner_zip):
        # Nope, return unknown
        return unknown_color
    
    # Owner zip is valid, see if it matches property_zip
    if(property_zip == owner_zip):
        return samezip_color
    
    # Check for in county
    zip_level = 'out-of-state'
    if(owner_zip in zip_map.keys()):
        zip_level = zip_map[owner_zip]
    
    if(zip_level=='Allegheny'):
        return allegheny_co_color
    elif(zip_level=='PA'):
        return in_state_color
    else:
        return out_of_state_color

def output_ownerprox_dots(parid_arr, suffix):
    # If parid_arr not specified, do all of the keys in property_map
    if(len(parid_arr)==0):
        parid_arr=property_map.keys()
        
    # Write out volume of ownership for each residential non-vacant land property
    points = []
    start=arrow.now()
    chunk_start_time=arrow.now()
    chunk_size=1000
    chunk_cnt=0
    
    for parid in parid_arr:
        centroid=None
        did_output_dot=False
        try:
            centroid = parid2centroid[parid]
        except:
            print "%s is missing from centroids, skipping" % (parid)
            continue

        try:
            # Handle periodic debug message
            if((chunk_cnt%chunk_size)==0 and chunk_cnt>0):
                print "%d-%d: processing %r, %s time elapsed" %(chunk_cnt-(chunk_size-1), chunk_cnt, parid, arrow.now()-chunk_start_time)
                addcnt=0
                chunk_start_time=arrow.now()

            # Get list of property events or this property
            property_events = property_map[parid]

            # Keep track of the date of the last datapoint. 
            last_date = '1900-01-01'
            last_color=0
            
            # Iterate over the property events.  We need to deal with different instances of the same sale date
            # as a batch because there might be multiple color changes before the next sale
            i=0
            while i < len(property_events):
                event_date = property_events[i]['date']
                # Get the set of simultaneous events in order of asofdate
                sevs = get_simultaneous_property_events(property_events,i)
                # Get color for each of these property events
                scolors = map(lambda ev: ownerprox_to_color(parid, ev), sevs)
                
                # Compute the bookends of this set of events.  The start date of the first 
                # color dot will be the date of this sale.  The end date of the last color
                # dot will be the date of the next sale.  We might have color changes in between
                # due to modifications in change adresses without a sale.  The potential
                # transition points are the asofdate of events where the status changes.
                next_start_date = event_date
                next_sell_date = None
                # Check if there's another event after this batch.  If so, set next_sell_date to be the
                # date of the next item
                if(i+len(sevs)<len(property_events)):
                    next_sell_date = property_events[i+len(sevs)]['date']

                if((chunk_cnt%chunk_size)==0):
                    print "  %s (%d): %s = %s [next_sell_date = %s]" % (parid, i, event_date, scolors, next_sell_date)

                last_color = scolors[0]
                output_color = True
                
                for j in range(0, len(sevs)):
                    color = scolors[j]
                    start_date = next_start_date
                    end_date = next_sell_date
                    # If we're not yet at the end, set end_date to the next asofdate
                    if(j<len(sevs)-1):
                        end_date = sevs[j+1]['asofdate']
                        next_start_date = end_date
                    # Calculate epoch time of start and end 
                    start_e = SaledateToEpoch(start_date)
                    if(end_date == None):
                        # No new owner after this, set end date to the end of time
                        end_e = float(1e38)
                    else:
                        end_e = SaledateToEpoch(end_date)

                    if(color != None):
                        points += PointToPixelXY(centroid)     
                        points.append(parse_color(color))
                        # Put epoch time for SALEDATE as start valid time, and next_date as end valid time
                        points.append(float(start_e))
                        points.append(float(end_e))
                        #print "  %s (%d): %s - %s = %s (len %d)" % (parid, i+j, start_date, end_date, color, len(points))
                    else:
                        print "Color of " + str(volume_map['parcount']) + " is None"


                # Set i, last_date and last_color for next loop
                i = i + len(sevs)
                last_date = event_date
                last_color= color
                did_output_dot=True
        except:
            print "Unexpected error processing %s:" % (parid), sys.exc_info()[0]
            #raise

        #Increment debug message counter
        if(did_output_dot):
            chunk_cnt = chunk_cnt+1

    array.array('f', points).tofile(open(('assessments/ownerprox_color_m_epoch%s.bin'%suffix), 'wb'))

    end=arrow.now()
    print "Processing took %s for %d dots" % (str(end-start), chunk_cnt)
    

In [213]:
test_parids=['2018H00310000000','0026N00263000000', '0010H00190000000', '0428D00080000000',
            '0072B00069000000', '0050P00138000000', '0195A00010000000',
            '0233K00148000000', '0033G00182000000', '0067D00114000000',
            '0079A00094000000', '0006G00201000000', '0555S00258000000',
            '0368N00060000000', '0029M00270000000', '1081P00065000000',
            '0130M00122000000', '1238H00385000000', '0381E00028000000',
            '0235J00250000000', '0013S00060000000', '0019M00033000000',
            '0042K00177000000', '0010D00089000000', '1064J00060000000',
            '0596A00245113500', '0739L00354000000', '0738B00123000000',
            '1099P00017000000', '0471D00291000000', '0632S00257000000',
            '0456H00094000000', '0133L00049000000', '0029G00165000000',
            '1223N00336000000', '0087C00130000000', '2018H00310000000']
output_ownerprox_dots(test_parids,"_test_99_09_17")

  2018H00310000000 (0): 1993-10-04 = ['#a50026', '#8dc0db'] [next_sell_date = None]
Processing took 0:00:06.883168 for 37 dots


In [ ]:
# Process the full set of properties
output_ownerprox_dots([],out_suffix)

  0177N00269000000 (0): 1994-01-18 = ['#3e5aa7', '#a50026'] [next_sell_date = 2007-03-02]
  0177N00269000000 (2): 2007-03-02 = ['#a50026', '#a50026'] [next_sell_date = 2011-02-28]
  0177N00269000000 (4): 2011-02-28 = ['#a50026', '#a50026'] [next_sell_date = None]
9923X82120000000 is missing from centroids, skipping
0008H00207000000 is missing from centroids, skipping
Google: Fetch ' , -0000 ' failed
9923X88213000000 is missing from centroids, skipping
9929X86742000000 is missing from centroids, skipping
9946X83878000000 is missing from centroids, skipping
0102B00350000001 is missing from centroids, skipping
9946X85474000000 is missing from centroids, skipping
9935X83214000000 is missing from centroids, skipping
9910X82175000000 is missing from centroids, skipping
9923X00741000000 is missing from centroids, skipping
9923X00961000000 is missing from centroids, skipping
0334H00209000000 is missing from centroids, skipping
0773C00150000000 is missing from centroids, skipping
9935X880550000

Google: Fetch ' PO BOX 81558 LAS VEGAS, NV 89180-1558 ' seemed to succeed, but results empty or non-unique
0184K00167000000 is missing from centroids, skipping
9946X88160000000 is missing from centroids, skipping
9929X82514000000 is missing from centroids, skipping
9923X87461000000 is missing from centroids, skipping
9929X01297000000 is missing from centroids, skipping
9929X00372000000 is missing from centroids, skipping
9908X82889000000 is missing from centroids, skipping
9929X00803000000 is missing from centroids, skipping
0564S00037000000 is missing from centroids, skipping
0530P00010000000 is missing from centroids, skipping
Google: Fetch ' PO BOX 62336 PITTSBURGH, PA 15241-7336 ' seemed to succeed, but results empty or non-unique
9929X85871000000 is missing from centroids, skipping
2008H00326000100 is missing from centroids, skipping
9905X82719000000 is missing from centroids, skipping
9905X82683000000 is missing from centroids, skipping
0079R00106000000 is missing from centroids,

9946X82760000000 is missing from centroids, skipping
9935X50048000000 is missing from centroids, skipping
9929X84304000000 is missing from centroids, skipping
9929X83812000000 is missing from centroids, skipping
9910X01433000000 is missing from centroids, skipping
0022P00298000000 is missing from centroids, skipping
9929X83380000000 is missing from centroids, skipping
9929X00812000000 is missing from centroids, skipping
9929X84296000000 is missing from centroids, skipping
9905X00255000000 is missing from centroids, skipping
0006M00104000000 is missing from centroids, skipping
9923X00754000000 is missing from centroids, skipping
9929X82493000000 is missing from centroids, skipping
0374G00316000000 is missing from centroids, skipping
10001-11000: processing '0232B00027000000', 0:03:08.484852 time elapsed
  0232B00027000000 (0): 1950-05-05 = ['#a50026', '#a50026'] [next_sell_date = 1970-01-29]
  0232B00027000000 (2): 1970-01-29 = ['#a50026', '#a50026'] [next_sell_date = 1970-02-01]
  0232

9841X00211000000 is missing from centroids, skipping
9923X84335000000 is missing from centroids, skipping
9946X88387000000 is missing from centroids, skipping
9929X01871000000 is missing from centroids, skipping
9923X00815000000 is missing from centroids, skipping
15001-16000: processing '0268K00035000000', 0:03:03.701518 time elapsed
  0268K00035000000 (0): 2015-11-18 = ['#ffffbf', '#ffffbf'] [next_sell_date = None]
9935X83278000000 is missing from centroids, skipping
9910X82460000000 is missing from centroids, skipping
9929X00377000000 is missing from centroids, skipping
9923X00717000000 is missing from centroids, skipping
0443L00218025900 is missing from centroids, skipping
0080G00214000000 is missing from centroids, skipping
9923X87731000000 is missing from centroids, skipping
9905X82281000000 is missing from centroids, skipping
0056J00325000A00 is missing from centroids, skipping
1677K00319000000 is missing from centroids, skipping
9923X87450000000 is missing from centroids, skipp

0418M00018000000 is missing from centroids, skipping
9929X83199000000 is missing from centroids, skipping
9929X00678000000 is missing from centroids, skipping
9946X83592000000 is missing from centroids, skipping
9910X00813000000 is missing from centroids, skipping
9910X82736000000 is missing from centroids, skipping
9946X82041000000 is missing from centroids, skipping
9929X01211000000 is missing from centroids, skipping
9923X88220000000 is missing from centroids, skipping
0643L00081000000 is missing from centroids, skipping
9929X84881000000 is missing from centroids, skipping
9841X82007000000 is missing from centroids, skipping
0766B00220000002 is missing from centroids, skipping
9935X88010000000 is missing from centroids, skipping
9929X86318000000 is missing from centroids, skipping
9905X82817000000 is missing from centroids, skipping
9946X50043000000 is missing from centroids, skipping
9923X87833000000 is missing from centroids, skipping
9905X00198000000 is missing from centroids, sk

...

  0036A00126000000 (2): 2006-08-16 = ['#a50026', '#a50026'] [next_sell_date = 2016-05-13]
  0036A00126000000 (4): 2016-05-13 = ['#a50026', '#a50026'] [next_sell_date = None]
9929X00001000000 is missing from centroids, skipping
Google: Fetch u'297 RIDGE RD, HOMESTEAD, PA, 15120' seemed to succeed, but results empty or non-unique
9929X50028000000 is missing from centroids, skipping
9923X82376000000 is missing from centroids, skipping
9929X01627000000 is missing from centroids, skipping
0049G00319000000 is missing from centroids, skipping
9946X88694000000 is missing from centroids, skipping
9905X00878000000 is missing from centroids, skipping
9929X50244000000 is missing from centroids, skipping
9946X82291000000 is missing from centroids, skipping
9929X85277000000 is missing from centroids, skipping
9935X83122000000 is missing from centroids, skipping
9929X83069000000 is missing from centroids, skipping
9929X86131000000 is missing from centroids, skipping
9946X84420000000 is missing from c

0415L00045000000 is missing from centroids, skipping
9946X88175000000 is missing from centroids, skipping
9935X50100000000 is missing from centroids, skipping
9905X00068000000 is missing from centroids, skipping
9905X01294000000 is missing from centroids, skipping
0101B00266000000 is missing from centroids, skipping
9929X01930000000 is missing from centroids, skipping
8000T00312000000 is missing from centroids, skipping
9905X83684000000 is missing from centroids, skipping
9910X84046000000 is missing from centroids, skipping
9905X83355000000 is missing from centroids, skipping
9929X83093000000 is missing from centroids, skipping
9908X82744000000 is missing from centroids, skipping
9923X87853000000 is missing from centroids, skipping
Google: Fetch 'BUILDING 4 1111 NORTHPOINT DR STE 100 COPPELL, TX 75019- ' seemed to succeed, but results empty or non-unique
Google: Fetch u'143 WILLIAM DR, CORAOPOLIS, PA, 15108' seemed to succeed, but results empty or non-unique
210001-211000: processing '

9929X88382000000 is missing from centroids, skipping
0072C00285000000 is missing from centroids, skipping
9923X84659000000 is missing from centroids, skipping
9935X88390000000 is missing from centroids, skipping
9923X84586000000 is missing from centroids, skipping
9929X00755000000 is missing from centroids, skipping
9910X00666000000 is missing from centroids, skipping
9923X00334000000 is missing from centroids, skipping
9905X08241000000 is missing from centroids, skipping
9923X87758000000 is missing from centroids, skipping
9929X87014000000 is missing from centroids, skipping
9929X86651000000 is missing from centroids, skipping
9905X83386000000 is missing from centroids, skipping
9905X01732000000 is missing from centroids, skipping
9929X01334000000 is missing from centroids, skipping
9935X87815000000 is missing from centroids, skipping
9935X83193000000 is missing from centroids, skipping
0692A00109000000 is missing from centroids, skipping
216001-217000: processing '0174R00150000000', 

Google: Fetch ' PO BOX 426 SMITHFIELD, PA 15110-1274 ' seemed to succeed, but results empty or non-unique
9923X82183000000 is missing from centroids, skipping
9905X50118000000 is missing from centroids, skipping
9946X01410000000 is missing from centroids, skipping
9935X00556000000 is missing from centroids, skipping
9929X01133000000 is missing from centroids, skipping
9923X00656000000 is missing from centroids, skipping
221001-222000: processing '0241N00044000000', 0:06:50.531868 time elapsed
  0241N00044000000 (0): 2007-03-21 = ['#a50026', '#a50026'] [next_sell_date = 2011-06-02]
  0241N00044000000 (2): 2011-06-02 = ['#a50026', '#a50026'] [next_sell_date = None]
9923X82490000000 is missing from centroids, skipping
9929X86533000000 is missing from centroids, skipping
9946X82072000000 is missing from centroids, skipping
9844X00513000000 is missing from centroids, skipping
9929X87195000000 is missing from centroids, skipping
9935X00017000000 is missing from centroids, skipping
9946X00758

  0028S00065000000 (3): 2007-07-03 = ['#a50026', '#a50026', '#a50026', '#a50026'] [next_sell_date = None]
9929X83487000000 is missing from centroids, skipping
8000T03279000000 is missing from centroids, skipping
9905X81004000000 is missing from centroids, skipping
0769P00100000000 is missing from centroids, skipping
2200G00153000000 is missing from centroids, skipping
9946X50066000000 is missing from centroids, skipping
9929X01104000000 is missing from centroids, skipping
9905X82055000000 is missing from centroids, skipping
Google: Fetch ' 72 S MAIN ST 34 YORK NEW SALEM, PA 17371-2003 ' seemed to succeed, but results empty or non-unique
9908X82948000000 is missing from centroids, skipping
9929X86003000000 is missing from centroids, skipping
9923X00809000000 is missing from centroids, skipping
9923X84353000000 is missing from centroids, skipping
9923X00887000000 is missing from centroids, skipping
0773F00112000000 is missing from centroids, skipping
9905X00790000000 is missing from cent

In [286]:
sorted(property_map['0053D00102000000'], key=lambda ev: ''.join([ev['date'],ev['asofdate']]))

[{'asofdate': '1999-01-01',
  'canonical_owner_address': u'363 BUTLER ST, PITTSBURGH, PA, 15223',
  'changeaddr': u'363 BUTLER ST PITTSBURGH PA 15223',
  'date': '1994-08-01',
  'event_type': 'PURCHASE',
  'ownername': u'BARTHOLOMAE DAVID J JOYCE C (W)'},
 {'asofdate': '2004-01-01',
  'canonical_owner_address': u'363 BUTLER ST, PITTSBURGH, PA, 15223',
  'changeaddr': '363 BUTLER ST PITTSBURGH PA 15223',
  'date': '1994-08-19',
  'event_type': 'PURCHASE',
  'fm_total': 286100,
  'ownername': 'BARTHOLOMAE DAVID J'},
 {'asofdate': '2009-09-01',
  'canonical_owner_address': u'5446 PLAINFIELD ST, PITTSBURGH, PA, 15217',
  'changeaddr': ' 5446 PLAINFIELD AVE PITTSBURGH, PA 15217-1146 ',
  'date': u'1994-08-19',
  'event_type': 'PURCHASE',
  'fm_total': 320100.0,
  'homesteadflag': 'C',
  'ownerdesc': 'Regular',
  'ownername': 'BARTHOLOMAE DAVID J & JOYCE C (W)',
  'saledesc': 'VALID SALE'},
 {'asofdate': '2017-10-01',
  'canonical_owner_address': u'5446 PLAINFIELD ST, PITTSBURGH, PA, 15217',

In [281]:
apd_1999.loc['0086E00117000000']

AREA                                                            12713
PERIMETER                                                     481.761
CITYPROP_                                                       80147
CITYPROP_I                                                       2226
MAP                                                                86
BLOCK                                                               E
PARCEL                                                            117
PARSUF                                                           None
CITYPROP_L                                                     86E117
ID                                                              52614
WARD                                                               14
TRACT_                                                             01
BLOCKLOT                                                      086E117
GISLOTBLOC                                                     86E117
REALGIS_LO          

In [246]:
changeaddr_map['2300 E HOLIDAY CT LANSING IL 60438']

[{'date': '1981-11-27', 'event_type': 'PURCHASE', 'parid': '0553N00123000000'}]

In [247]:
owner_map['HRANTICS STEPHEN A']

[{'date': '1981-11-27', 'event_type': 'PURCHASE', 'parid': '0553N00123000000'}]

In [248]:
ownerprox_to_color('0553N00123000000', property_map['0553N00123000000'][0])

KeyError: '0553N00123000000'

In [249]:
raw_property_address_map['0553N00123000000']

KeyError: '0553N00123000000'

In [219]:
property_map['0232C00201000000'] = [{'asofdate': '1999-01-01',
  'canonical_owner_address': u'6255 LIBRARY RD, BETHEL PARK, PA, 15102',
  'changeaddr': u'6255 LIBRARY RD BETHEL PARK PA 1510',
  'date': '1970-11-01',
  'event_type': 'PURCHASE',
  'ownername': u'SEACH CO INC'}]

changeaddr_map['6255 LIBRARY RD BETHEL PARK PA 1510'] = [{'date': '1970-11-01', 'event_type': 'PURCHASE', 'parid': '0232C00201000000'}]

owner_map['SEACH CO INC'] = [{'date': '1970-11-01', 'event_type': 'PURCHASE', 'parid': '0232C00202000000'},
 {'date': '1970-11-01', 'event_type': 'PURCHASE', 'parid': '0232C00201000000'}]


In [175]:
output_ownerprox_dots(valid_parids_15213,"_d3_15213")

  0011F00188000000: 2008-11-17 = #ffffbf
1-1000: processing '0052F00008000000', 0:00:00.519286 time elapsed
  0052F00008000000: 2016-01-07 = #a50026
1001-2000: processing '0028A00271000000', 0:00:00.505276 time elapsed
  0028A00271000000: 2007-09-07 = #a50026
2001-3000: processing '0029D00104000000', 0:00:00.502671 time elapsed
  0029D00104000000: 2007-11-07 = #ffffbf
3001-4000: processing '0028S00127000000', 0:00:00.445039 time elapsed
  0028S00127000000: 1983-07-05 = #a50026
Processing took 0:00:02.316315 for 4806 dots


In [172]:
output_ownerprox_dots(valid_parids_15213[0:100],"_d3_100_15213")

  '0011F00188000000': Census missing property addr, try google
  '0011F00188000000': Google has property addr: u'Wyandotte St, Pittsburgh, PA 15213, USA'
          Google owner addr for u'2008-11-17': u'Pittsburgh City-County Building, 414 Grant St RM 200, Pittsburgh, PA 15219, USA'
  0011F00188000000: 2008-11-17 = #ffffbf
  '0028K00134000000': Census missing property addr, try google
  '0028K00134000000': Google has property addr: u'3336 Niagara St, Pittsburgh, PA 15213, USA'
          Google owner addr for u'1981-06-11': u'836 Meadowbrook Rd, Trafford, PA 15085, USA'
  '0028M00075000000': Google has owner addr for u'2000-11-22': u'Verona, PA 15147, USA'
  '0028J00023000000': Census missing property addr, try google
  '0028J00023000000': Google has property addr: u'Robinson St, Pittsburgh, PA 15213, USA'
          Google owner addr for u'1989-11-20': u'233 Halket St, Pittsburgh, PA 15213, USA'
  '0028G00318000000': Google has owner addr for u'1990-12-11': u'Saratoga, CA 95070, USA'
  

# Graveyard

In [ ]:
# Below is Anne's attempt to put floating point representations of colors into the .bin file for a new 
# shader Randy's writing

In [ ]:
def incrementKey(adict,key):
    if(key == '' or math.isnan(key)):
       return
    if not adict.has_key(key):
        adict[key] = 1
    else:
        adict[key] += 1

In [ ]:
year_built_colors = ['#ffffe0','#ffdaa3','#ffb27c','#fb8768','#eb5f5b','#d3394a','#b3152f','#8b0000']
def year_built_to_color(year):
    if (year <= 1900.0):
        return color_from_floats(64,64,64)
    elif (year < 1916.0):
        return parse_color(year_built_colors[7])       
    elif (year < 1932.0):
        return parse_color(year_built_colors[6])
    elif (year < 1948.0):
        return parse_color(year_built_colors[5])
    elif (year < 1964.0):
        return parse_color(year_built_colors[4])
    elif (year < 1980.0):
        return parse_color(year_built_colors[3])
    elif (year < 1996.0):
        return parse_color(year_built_colors[2])
    elif  (year < 2012.0):
        return parse_color(year_built_colors[1])
    elif  (year < 2016.0):
        return parse_color(year_built_colors[0])
    else:
        return color_from_floats(255,255,255)
 
   
points = []
for i in range(0, len(apd.index)):
    par_id = apd['PARID'][i]
    year_built = apd['YEARBLT'][i]
    if year_built == '' or year_built == '0' or year_built == '0000' or math.isnan(year_built):
        year_built = '0001' # Null Value, -62135596800.0 Epoch
    elif isinstance(year_built, numbers.Number):
        if(year_built < 1):
            year_built = '0001' # Null Value, -62135596800.0 Epoch
        else:
            year_built = "%04d" % (year_built)
    if centroids.has_key(par_id):
        centroid = centroids[par_id]
        points += LonLatToPixelXY(centroid)        
        points.append(year_built_to_color(float(year_built)))
        # Set start valid time as year_built, and max positive float as end valid time
        date = datetime.datetime.strptime(year_built, '%Y')        
        points.append(GetEpoch(date))
        points.append(float(1e38))
array.array('f', points).tofile(open(('assessments/parcels_bltyr_color_epoch%s.bin'%out_suffix), 'wb'))

In [ ]:
# Hightlight based on likelyhood of lead
# <1950 = Probably lead
# 1950-1978 = Maybe lead (not illegal, but being phased out)
# >1978 = Probably not lead (illegal)
year_built_colors = ['#ffffe0','#ffdaa3','#ffb27c','#fb8768','#eb5f5b','#d3394a','#b3152f','#8b0000']
def year_built_to_lead_color(year):
    if (year <= 1900.0):
        return color_from_floats(64,64,64)
    elif (year < 1950.0):
        return parse_color(year_built_colors[7])       
    elif (year < 1979.0):
        return parse_color(year_built_colors[3])
    else:
        return parse_color(year_built_colors[0])
    
points = []
for i in range(0, len(apd.index)):
    par_id = apd['PARID'][i]
    year_built = apd['YEARBLT'][i]
    if year_built == '' or year_built == '0' or year_built == '0000' or math.isnan(year_built):
        year_built = '0001' # Null Value, -62135596800.0 Epoch
    elif isinstance(year_built, numbers.Number):
        if(year_built < 1):
            year_built = '0001' # Null Value, -62135596800.0 Epoch
        else:
            year_built = "%04d" % (year_built)
    if centroids.has_key(par_id):
        centroid = centroids[par_id]
        points += LonLatToPixelXY(centroid)        
        points.append(year_built_to_lead_color(float(year_built)))
        # Set start valid time as year_built, and max positive float as end valid time
        date = datetime.datetime.strptime(year_built, '%Y')        
        points.append(GetEpoch(date))
        points.append(float(1e38))
array.array('f', points).tofile(open(('assessments/parcels_bltyr_lead_color_epoch%s.bin'%out_suffix), 'wb'))

In [ ]:
                                     
fm_colors = ['#a50026','#cd2827','#e75436','#f7804b','#fdad61','#fed788','#ffffbf','#b9e0ed','#8dc0db','#699fca','#4d7db9','#3e5aa7','#313695']
def fm_total_to_color(fm_total):
    if (fm_total < 25000.):
        return parse_color(fm_colors[0]) 
    elif (fm_total < 50000.):
        return parse_color(fm_colors[1]) 
    elif (fm_total < 75000.):
        return parse_color(fm_colors[2]) 
    elif (fm_total < 100000.):
        return parse_color(fm_colors[3]) 
    elif (fm_total < 125000.):
        return parse_color(fm_colors[4]) 
    elif (fm_total < 150000.):
        return parse_color(fm_colors[5]) 
    elif (fm_total < 200000.):
        return parse_color(fm_colors[6]) 
    elif (fm_total < 250000.):
        return parse_color(fm_colors[7]) 
    elif (fm_total < 300000.):
        return parse_color(fm_colors[8]) 
    elif (fm_total < 400000.):
        return parse_color(fm_colors[9]) 
    elif (fm_total < 500000.):
        return parse_color(fm_colors[10]) 
    elif (fm_total < 750000.):
        return parse_color(fm_colors[11]) 
    else:
        return parse_color(fm_colors[12]) 
 
points = []
for i in range(0, len(apd.index)):
    par_id = apd['PARID'][i]
    fm_total = float(apd['FAIRMARKETTOTAL'][i])   
    
    year_built = apd['YEARBLT'][i]
    if year_built == '' or year_built == '0' or year_built == '0000' or math.isnan(year_built):
        year_built = '0001' # Null Value, -62135596800.0 Epoch
    elif isinstance(year_built, numbers.Number):
        if(year_built < 1):
            year_built = '0001' # Null Value, -62135596800.0 Epoch
        else:
            year_built = "%04d" % (year_built)

    if centroids.has_key(par_id):
        centroid = centroids[par_id]
        points += LonLatToPixelXY(centroid)        
        points.append(fm_total_to_color(fm_total))
        # Set start valid time as year_built, and max positive float as end valid time
        date = datetime.datetime.strptime(year_built, '%Y')        
        points.append(GetEpoch(date))
        points.append(float(1e38))
array.array('f', points).tofile(open(('assessments/parcels_fm_color_epoch%s.bin'%out_suffix), 'wb'))

In [ ]:
parcel_colors = ['#fb3059','#fe6b2d','#d1947a','#c6a900','#02ca75','#00a2de','#9529b1']
class_descriptions = sorted(class_descs.keys())

def class_desc_to_color(class_description):
    index = class_descriptions.index(class_description)
    return(parse_color(parcel_colors[index]))

points = []
for i in range(0, len(apd.index)):
    par_id = apd['PARID'][i]
    class_description = apd['CLASSDESC'][i] 
    year_built = apd['YEARBLT'][i]

    if year_built == '' or year_built == '0' or year_built == '0000' or math.isnan(year_built):
        year_built = '0001' # Null Value, -62135596800.0 Epoch
    elif isinstance(year_built, numbers.Number):
        if(year_built < 1):
            year_built = '0001' # Null Value, -62135596800.0 Epoch
        else:
            year_built = "%04d" % (year_built)

    if centroids.has_key(par_id):
        centroid = centroids[par_id]
        points += LonLatToPixelXY(centroid)        
        points.append(class_desc_to_color(class_description))
        # Set start valid time as year_built, and max positive float as end valid time
        date = datetime.datetime.strptime(year_built, '%Y')        
        points.append(GetEpoch(date))
        points.append(float(1e38))
array.array('f', points).tofile(open(('assessments/parcels_class_color_epoch%s.bin'%out_suffix), 'wb'))

In [ ]:
# Highlight vacant lots
points = []
for i in range(0, len(apd.index)):
    par_id = apd['PARID'][i]
    class_description = apd['CLASSDESC'][i] 
    usedesc = apd['USEDESC'][i]

    # default to grey
    color = "#555555"
    if(usedesc =='VACANT LAND'):
        # vacant lot, make it green
        color = "#02ca75"

    if centroids.has_key(par_id):
        centroid = centroids[par_id]
        points += LonLatToPixelXY(centroid)        
        points.append(parse_color(color))
        # Set start valid time as forever, and max positive float as end valid time
        points.append(0)
        points.append(float(1e38))
array.array('f', points).tofile(open(('assessments/vacant_lots%s.bin'%out_suffix), 'wb'))

In [ ]:
# Here are Anne's efforts using the version with owner names to generate volume of properties owned by current owner

In [ ]:
# SALEDATE field is in '%m-%d-%Y' format (ex 10-26-2012) when present
def SaledateToEpoch(datestr):
    return calendar.timegm(time.strptime(datestr, '%m-%d-%Y'))

In [ ]:
# Parse apd table into dictionaries from owner names and change addresses to parid, and from parid to other info
# about the property
owner_names_to_parids = {}
owner_changeaddrs_to_parids = {}
parid_info = {}
volume_counts = {}

# For now, only look at residential properties with known centroids in 15213
for i in range(0, len(apd.index)):
    par_id = apd['PARID'][i]
    zipcode = apd['PROPERTYZIP'][i]
    class_description = apd['CLASSDESC'][i] 
    usedesc = apd['USEDESC'][i] 
    if (usedesc == 'VACANT LAND' or not centroids.has_key(par_id)):
        # skip this one
        continue
    
    # We want to include residential, apartments (usedesc includes APART)
    if(class_description != 'RESIDENTIAL' and (isinstance(usedesc, numbers.Number) or 'APART' not in usedesc)):
        # skip this one
        continue
        
    # This one meets our criteria
    owner_name = apd['PROPERTYOWNER'][i]
    owner_changeaddr = string.strip(str(apd['CHANGENOTICEADDRESS1'][i]))
    c2 = string.strip(str(apd['CHANGENOTICEADDRESS2'][i]))
    c3 = string.strip(str(apd['CHANGENOTICEADDRESS3'][i]))
    c4 = apd['CHANGENOTICEADDRESS4'][i]
    if(c2 != ''):
        owner_changeaddr+=", " + c2
    if(c3 != ''):
        owner_changeaddr+=", " + c3
    if(c4 != ''):
        if(isinstance(c4, numbers.Number)):
            if(not math.isnan(float(c4))):
                owner_changeaddr+=", " + str(int(c4))
        else:
            owner_changeaddr+=", " + c4
        
    if(owner_changeaddr == ''):
        # skip this one
        continue
        
    if(owner_names_to_parids.has_key(owner_name)):
        owner_names_to_parids[owner_name].append(par_id)
    else:
        owner_names_to_parids[owner_name]=[par_id]
        
    if(owner_changeaddrs_to_parids.has_key(owner_changeaddr)):
        owner_changeaddrs_to_parids[owner_changeaddr].append(par_id)
    else:
        owner_changeaddrs_to_parids[owner_changeaddr]=[par_id]

    parid_info[par_id]={'owner_name':owner_name,
                        'owner_changeaddr':owner_changeaddr,
                        'centroid':centroids[par_id],
                        'HOMESTEADFLAG':apd['HOMESTEADFLAG'][i],
                        'USEDESC':apd['USEDESC'][i],
                        'OWNERDESC':apd['OWNERDESC'][i],
                        'SALEDATE':apd['SALEDATE'][i],
                        'OWNERDESC':apd['OWNERDESC'][i],
                        'CLASSDESC':apd['CLASSDESC'][i]
                       }

In [ ]:
# Add counts to parid_info based on max of owner_names_to_parids or owner_changeaddrs_to_parids
# Special case properties with HOMESTEADFLAG set to HOM to be volume=1
for par_id in parid_info.keys():
    volume=1
    if(parid_info[par_id]['HOMESTEADFLAG']!='HOM'):
        ownername_num = len(owner_names_to_parids[parid_info[par_id]['owner_name']])
        ownerchangeaddr_num = len(owner_changeaddrs_to_parids[parid_info[par_id]['owner_changeaddr']])
        volume = max(ownername_num,ownerchangeaddr_num)
    parid_info[par_id]['volume'] = volume
    incrementKey(volume_counts,volume)

In [ ]:
volume_counts

In [ ]:
for ownername in owner_names_to_parids.keys():
    ownername_num = len(owner_names_to_parids[ownername])
    if(ownername_num>10):
        print "%s: %d" % (ownername,ownername_num)

In [ ]:
for ownerchangeaddr in owner_changeaddrs_to_parids.keys():
    ownerchangeaddr_num = len(owner_changeaddrs_to_parids[ownerchangeaddr])
    if(ownerchangeaddr_num>10):
        print "%s: %d" % (ownerchangeaddr,ownerchangeaddr_num)

In [ ]:
for par_id in parid_info.keys():
    if(parid_info[par_id]['volume']>10):
        print parid_info[par_id]

In [ ]:
# Write out a binary file with the volume colors
vol_colors = ['#a50026','#cd2827','#e75436','#f7804b','#fdad61','#fed788','#ffffbf','#b9e0ed','#8dc0db','#699fca','#4d7db9','#3e5aa7','#313695']
def volume_to_color(volume):
    if (volume < 2):
        return parse_color(vol_colors[0]) 
    #elif (volume < 3):
    #    return parse_color(vol_colors[1]) 
    #elif (volume < 4):
    #    return parse_color(vol_colors[2]) 
    elif (volume < 5):
        return parse_color(vol_colors[3]) 
    elif (volume < 10):
        return parse_color(vol_colors[4]) 
    elif (volume < 20):
        return parse_color(vol_colors[5]) 
    elif (volume < 40):
        return parse_color(vol_colors[6]) 
    elif (volume < 60):
        return parse_color(vol_colors[7]) 
    elif (volume < 80):
        return parse_color(vol_colors[8]) 
    elif (volume < 150):
        return parse_color(vol_colors[9]) 
    elif (volume < 300):
        return parse_color(vol_colors[10]) 
    elif (volume < 500):
        return parse_color(vol_colors[11]) 
    else:
        return parse_color(vol_colors[12]) 

# Write out volume of ownership for each residential non-vacant land property
points = []
for par_id in parid_info.keys():
    centroid = parid_info[par_id]['centroid']
    color = volume_to_color(parid_info[par_id]['volume'])
    saledate = SaledateToEpoch('01-01-1900')
    saledate_raw = parid_info[par_id]['SALEDATE']
    if(not(saledate_raw == '' or (isinstance(saledate_raw, numbers.Number) and math.isnan(saledate_raw)))):
        # If not valid, leave as 1900, otherwise parse it into an epoch time
        saledate = SaledateToEpoch(saledate_raw)
        
    if(color != None):
        points += LonLatToPixelXY(centroid)        
        points.append(color)
        # Put epoch time for SALEDATE as start valid time, and max positive float as end valid time
        points.append(float(saledate))
        points.append(float(1e38))
    else:
        print "Color of " + str(parid_info[par_id]['volume']) + " is None"
array.array('f', points).tofile(open(('assessments/res_volume_color_epoch%s.bin'%out_suffix), 'wb'))

In [ ]:
#original version
legend = '<svg width="400" height="30"><rect fill="#a50026" x="0" height="10" width="30"></rect><rect fill="#cd2827" x="30" height="10" width="30"></rect><rect fill="#e75436" x="60" height="10" width="30"></rect><rect fill="#f7804b" x="90" height="10" width="30"></rect><rect fill="#fdad61" x="120" height="10" width="30"></rect><rect fill="#fed788" x="150" height="10" width="30"></rect><rect fill="#ffffbf" x="180" height="10" width="30"></rect><rect fill="#b9e0ed" x="210" height="10" width="30"></rect><rect fill="#8dc0db" x="240" height="10" width="30"></rect><rect fill="#699fca" x="270" height="10" width="30"></rect><rect fill="#4d7db9" x="300" height="10" width="30"></rect><rect fill="#3e5aa7" x="330" height="10" width="30"></rect><text font-size="10.5px" y="29" x="0" fill="#ffffff">1</text><text font-size="10.5px" y="29" x="20"  fill="#ffffff">&nbsp;2</text><text font-size="10.5px" y="29" x="50"  fill="#ffffff">&nbsp;3</text><text font-size="10.5px" y="29" x="80"  fill="#ffffff"> 4</text><text font-size="10.5px" y="29" x="110"  fill="#ffffff"> 5</text><text font-size="10.5px" y="29" x="140"  fill="#ffffff">10</text><text font-size="10.5px" y="29" x="170"  fill="#ffffff">20</text><text font-size="10.5px" y="29" x="200"  fill="#ffffff">40</text><text font-size="10.5px" y="29" x="230"  fill="#ffffff">60</text><text font-size="10.5px" y="29" x="260"  fill="#ffffff">80</text><text font-size="10.5px" y="29" x="290"  fill="#ffffff">150</text><text font-size="10.5px" y="29" x="320"  fill="#ffffff">300</text><text font-size="10.5px" y="29" x="350"  fill="#ffffff">500</text>'
HTML(legend)

In [ ]:
#modified version
legend = '<svg width="400" height="30"><rect fill="#a50026" x="0" height="10" width="30"></rect><rect fill="#f7804b" x="30"  height="10" width="30"></rect><rect fill="#fdad61" x="60"  height="10" width="30"></rect><rect fill="#fed788" x="90"  height="10" width="30"></rect><rect fill="#ffffbf" x="120" height="10" width="30"></rect><rect fill="#b9e0ed" x="150" height="10" width="30"></rect><rect fill="#8dc0db" x="180" height="10" width="30"></rect><rect fill="#699fca" x="210" height="10" width="30"></rect><rect fill="#4d7db9" x="240" height="10" width="30"></rect><rect fill="#3e5aa7" x="270" height="10" width="30"></rect><text font-size="10.5px" y="29" x="0" fill="#ffffff">1</text><text font-size="10.5px" y="29" x="20"  fill="#ffffff">&nbsp;2</text><text Font-size="10.5px" y="29" x="50"   fill="#ffffff"> 5</text><text font-size="10.5px" y="29" x="80"   fill="#ffffff">10</text><text font-size="10.5px" y="29" x="110"  fill="#ffffff">20</text><text font-size="10.5px" y="29" x="140"  fill="#ffffff">40</text><text font-size="10.5px" y="29" x="170"  fill="#ffffff">60</text><text font-size="10.5px" y="29" x="200"  fill="#ffffff">80</text><text font-size="10.5px" y="29" x="230"  fill="#ffffff">150</text><text font-size="10.5px" y="29" x="260"  fill="#ffffff">300</text><text font-size="10.5px" y="29" x="290"  fill="#ffffff">500</text>'
HTML(legend)

In [ ]:
# Write out a binary file with the colors for residential owned by corporate, government, or regular owners
def ownertype_to_color(par_id):
    ownerdesc = parid_info[par_id]['OWNERDESC']
    classdesc = parid_info[par_id]['CLASSDESC']
    volume = parid_info[par_id]['volume']
    if (classdesc == "GOVERNMENT"):
        print "Government: %s, %s, %d" % (ownerdesc, classdesc,volume)
        # Same color as government in property class view
        return parse_color("#d1947a") 
    elif ('CORPORATION' in ownerdesc):
        # Same color as 500+ properties in volume view
        #return parse_color('#313695') 
        return parse_color('#ffffbf')
    elif ('REGULAR' in ownerdesc):
        # Regular owner, what volume?
        if(volume == 1):
            # Same color as 1 in volume view
            return parse_color('#a50026')
        else:
            # Same color as other in class view
            return parse_color('#02ca75')
    else:
        print "Unrecognized owner type: %s, %s, %d" % (ownerdesc, classdesc,volume)
        return parse_color('#303030') 

# Write out volume of ownership for each residential non-vacant land property
points = []
for par_id in parid_info.keys():
    centroid = parid_info[par_id]['centroid']
    color = ownertype_to_color(par_id)
    saledate = SaledateToEpoch('01-01-1900')
    saledate_raw = parid_info[par_id]['SALEDATE']
    if(not(saledate_raw == '' or (isinstance(saledate_raw, numbers.Number) and math.isnan(saledate_raw)))):
        # If not valid, leave as 1900, otherwise parse it into an epoch time
        saledate = SaledateToEpoch(saledate_raw)
        
    if(color != None):
        points += LonLatToPixelXY(centroid)        
        points.append(color)
        # Put epoch time for SALEDATE as start valid time, and max positive float as end valid time
        points.append(float(saledate))
        points.append(float(1e38))
    else:
        print "Color of " + str(parid_info[par_id]['volume']) + " is None"
array.array('f', points).tofile(open(('assessments/ownertype_color_epoch%s.bin'%out_suffix), 'wb'))

In [ ]:
parid_info['0002K00028000000']

In [ ]:
# Foreclosures

In [ ]:
# SALEDATE field is in '%m-%d-%Y' format (ex 10-26-2012) when present
def FilingdateToEpoch(datestr):
    return calendar.timegm(time.strptime(datestr, '%Y-%m-%d'))

In [ ]:
# Read in foreclosure data 
fpath = "assessments/foreclosures-180327.csv"
fapd = pandas.read_csv(fpath)

In [ ]:
# Write out volume of ownership for each residential non-vacant land property
points = []
missing_pin_c=0
found_pin_c=0
missing_pin_a=0
found_pin_a=0
foreclosure_color = '#ff00ff'

for i in range(0, len(fapd.index)):
    par_id = fapd['pin'][i]
    filing_date_raw = fapd['filing_date'][i]
    
    if(filing_date_raw == '' or (isinstance(filing_date_raw, numbers.Number) and math.isnan(filing_date_raw))):
        print "%d: Can't read filing_date %s" % (i, filing_date_raw)
        continue
    filing_date = FilingdateToEpoch(filing_date_raw)
    
    if par_id not in parid_info:
        missing_pin_c+=1
        continue
    found_pin_c+= 1
    
    centroid = parid_info[par_id]['centroid']
    
    if par_id not in parid_info:
        missing_pin_a+=1
    found_pin_a+=1
    
    saledate = SaledateToEpoch('01-01-1900')
    saledate_raw = parid_info[par_id]['SALEDATE']
    if(not(saledate_raw == '' or (isinstance(saledate_raw, numbers.Number) and math.isnan(saledate_raw)))):
        # If not valid, leave as 1900, otherwise parse it into an epoch time
        saledate = SaledateToEpoch(saledate_raw)
        
    startdate = filing_date
    enddate = saledate
    
    if(filing_date<saledate):
        # Sold after foreclosure, who bought it?
        points += LonLatToPixelXY(centroid)        
        points.append(ownertype_to_color(par_id))
        # Put epoch time for SALEDATE as start valid time, and max positive float as end valid time
        points.append(float(filing_date))
        points.append(float(1e38))
    else:
        # Sold before foreclosure, who owned it before?
        points += LonLatToPixelXY(centroid)        
        points.append(ownertype_to_color(par_id))
        # Put epoch time for SALEDATE as start valid time, and max positive float as end valid time
        points.append(float(saledate))
        points.append(float(filing_date))
        # Not sold after foreclosure, show ownership before sale and end foreclosure at end of time
        enddate=float(1e38)
        
    # Output foreclosure dot
    points += LonLatToPixelXY(centroid)        
    points.append(parse_color(foreclosure_color))
    # Put epoch time for SALEDATE as start valid time, and max positive float as end valid time
    points.append(float(startdate))
    points.append(float(enddate))

array.array('f', points).tofile(open(('assessments/foreclosure_color_epoch%s.bin'%out_suffix), 'wb'))

In [ ]:
# Below here are modified versions of the blocks from Gabriel's original python notebook,
# none of which are needed anymore

In [ ]:
sale_prices = {}
for i in range(0, len(apd.index)):
    sale_price = apd['SALEPRICE'][i]
    if not sale_prices.has_key(sale_price):
        sale_prices[sale_price] = 1
    else:
        sale_prices[sale_price] += 1


In [ ]:
len(sale_prices.keys())


In [ ]:
years_built = {}
sale_dates = {}
fairmarket_totals = {}
classes = {}
class_descs = {}

def incrementKey(adict,key):
    if(key == '' or math.isnan(key)):
       return
    if not adict.has_key(key):
        adict[key] = 1
    else:
        adict[key] += 1
    
for i in range(0, len(apd.index)):
    year_built = apd['YEARBLT'][i]
    incrementKey(years_built, year_built)
    sale_date = apd['SALEDATE'][i]
    incrementKey(sale_dates, sale_date)
    fairmarket_total = apd['FAIRMARKETTOTAL'][i]
    incrementKey(fairmarket_totals, fairmarket_total)
    class_ = apd['CLASS'][i]
    incrementKey(classes, class_)
    class_desc = apd['CLASSDESC'][i]
    incrementKey(class_descs, class_desc)


In [ ]:
i

In [ ]:
len(apd.index)

In [ ]:
len(years_built.keys())
years_built['']

In [ ]:
years_built

In [ ]:
points = []
for i in range(0, len(apd.index)):
    par_id = apd['PARID'][i]
    year_built = apd['YEARBLT'][i]
    if year_built == '' or year_built == '0' or year_built == '0000' or math.isnan(year_built):
        year_built = '0001' # Null Value, -62135596800.0 Epoch
    elif isinstance(year_built, numbers.Number):
        if(year_built < 1):
            year_built = '0001' # Null Value, -62135596800.0 Epoch
        else:
            year_built = "%04d" % (year_built)
    if centroids.has_key(par_id):
        centroid = centroids[par_id]
        points += LonLatToPixelXY(centroid)
        date = datetime.datetime.strptime(year_built, '%Y')        
        points.append(GetEpoch(date))
array.array('f', points).tofile(open(('assessments/parcels_yr%s.bin'%out_suffix), 'wb'))


In [ ]:
year_built
date = datetime.datetime.strptime('2000', '%Y')   
GetEpoch(date)

In [ ]:
fairmarket_totals['0']

In [ ]:
classes

In [ ]:
class_descs

In [ ]:
sorted(class_descs.keys())

In [ ]:
no_year_built = 0
no_= 0
for i in range(0, len(apd.index)):
    year_built = apd['YEARBLT'][i]
    class_ = apd['CLASS'][i]
    if year_built == '' and class_ == 'R':
        no_year_built += 1
    elif year_built == '':
        no_ += 1
print no_year_built
print no_

In [ ]:
class_descriptions = sorted(class_descs.keys())
points = []
for i in range(0, len(apd.index)):
    par_id = apd['PARID'][i]
    year_built = apd['YEARBLT'][i]
    class_description = apd['CLASSDESC'][i]  
    if year_built == '' or year_built == '0' or year_built == '0000' or math.isnan(year_built):
        year_built = '0001' # Null Value, -62135596800.0 Epoch
    elif isinstance(year_built, numbers.Number):
        if(year_built < 1):
            year_built = '0001' # Null Value, -62135596800.0 Epoch
        else:
            year_built = "%04d" % (year_built)
    if centroids.has_key(par_id):
        centroid = centroids[par_id]
        points += LonLatToPixelXY(centroid)
        date = datetime.datetime.strptime(year_built, '%Y')        
        points.append(GetEpoch(date))
        points.append(class_descriptions.index(class_description))
array.array('f', points).tofile(open(('assessments/parcels_yrblt%s.bin'%out_suffix), 'wb'))


In [ ]:
foo = sorted(class_descs.keys())

In [ ]:
len(foo)

In [ ]:
parcel_colors = ['#e41a1c','#377eb8','#4daf4a','#984ea3','#ff7f00','#ffff33','#a65628']

In [ ]:
for color in hex_colors:
    rgb_color = HexToRgb(color)
    print "%s,%s,%s" % (rgb_color[0]/255.0, rgb_color[1]/255.0, rgb_color[2]/255.0) 

In [ ]:
hex_colors = ["#fb3059",
"#fe6b2d",
"#d1947a",
"#c6a900",
"#02ca75",
"#00a2de",
"#9529b1"]
for color in hex_colors:
    rgb_color = HexToRgb(color)
    print "%.4f,%.4f,%.4f" % (rgb_color[0]/255.0, rgb_color[1]/255.0, rgb_color[2]/255.0) 

In [ ]:
hex_colors = ['#ffffff','#fffffa','#fffdf5','#fffdf1','#fffcef','#fffbed','#fffbea','#fff9e6','#fff9e3','#fff7e0','#fff7dd','#fff6db','#fff5d8','#fff4d6','#fff3d4','#fff3d2','#fff2d0','#fff0cd','#fff0cb','#ffefc8','#ffeec6','#ffedc3','#ffecc1','#ffeabe','#ffeabc','#ffe9b9','#ffe7b7','#ffe7b4','#ffe6b2','#ffe4b0','#ffe4ad','#ffe3ab','#ffe1a8','#ffe1a6','#ffe0a4','#ffdea1','#ffde9f','#ffdc9d','#ffdc9b','#ffda98','#ffd996','#ffd994','#ffd891','#ffd68f','#ffd68d','#ffd58a','#ffd388','#ffd386','#ffd284','#ffd081','#ffcf7f','#ffcf7d','#ffcd7b','#ffcc78','#ffcc76','#ffca74','#ffc971','#ffc96f','#ffc76d','#ffc76b','#ffc568','#ffc566','#ffc464','#ffc361','#ffc15d','#ffc05a','#ffbf58','#ffbe56','#ffbc53','#ffbc51','#ffba4e','#ffba4c','#ffb849','#ffb747','#ffb644','#ffb53f','#ffb43d','#ffb23a','#ffb237','#ffb134','#ffaf31','#ffaf2e','#ffad2a','#ffab24','#ffab21','#ffa91c','#ffa818','#ffa813','#ffa60b','#ffa400','#ffa300','#ffa200','#ffa100','#ff9f00','#ff9e00','#ff9d00','#ff9c00','#ff9b00','#ff9900','#ff9800','#ff9700','#ff9500','#ff9500','#ff9300','#ff9100','#ff9000','#ff8f00','#ff8d00','#ff8c00','#ff8a00','#ff8a00','#fe8800','#fe8800','#fe8700','#fe8400','#fd8400','#fd8300','#fd8200','#fd8000','#fc7f00','#fc7d00','#fc7c00','#fc7b00','#fb7a00','#fb7900','#fb7800','#fa7700','#fa7400','#fa7400','#f97200','#f97100','#f87000','#f86e00','#f86e00','#f76d00','#f76c00','#f66a00','#f66900','#f56800','#f56600','#f46600','#f46400','#f36400','#f36200','#f36100','#f26000','#f15e00','#f15d00','#f05d00','#ef5b00','#ef5900','#ef5900','#ee5800','#ed5700','#ed5500','#ec5500','#eb5400','#ea5200','#ea5100','#e95000','#e84f00','#e84e00','#e74c00','#e74b00','#e64a00','#e54900','#e44800','#e44700','#e34600','#e34500','#e14400','#e14300','#e04100','#df4000','#de4000','#de3e00','#dd3d00','#dc3d00','#db3c00','#db3a00','#da3900','#d83800','#d83700','#d73600','#d63500','#d63401','#d43301','#d43201','#d23101','#d13001','#d12e01','#d02e01','#d02d01','#ce2c01','#ce2b01','#cd2a01','#cc2901','#ca2801','#c92701','#c92601','#c82501','#c72401','#c62301','#c52201','#c42102','#c32002','#c21f02','#c01e02','#bf1d02','#bf1c02','#be1b02','#bd1a02','#bc1902','#ba1902','#ba1802','#b81702','#b81602','#b71502','#b51402','#b51302','#b41202','#b21202','#b11102','#b01002','#af0e02','#ae0d02','#ac0d02','#ac0c02','#aa0b02','#a90a02','#a80902','#a80902','#a60802','#a50702','#a30602','#a30602','#a20502','#a00502','#a00402','#9e0302','#9c0302','#9b0302','#9b0201','#9a0201','#990201','#970101','#950101','#950101','#940101','#920001','#920001','#900001','#8f0000','#8d0000','#8d0000','#8b0000']

img = Image.new( 'RGB', (255,255), "white") # create a new image
pixels = img.load() # create the pixel map
for i in range(img.size[0]):    # for every pixel:
    for j in range(img.size[1]):
        pixels[i,j] = hex_to_rgb(hex_colors[i]) # set the colour accordingly
img.show
img.save("assessments/year-built-color-map.png")


In [ ]:
hex_stops =  ['#1d1e4e','#482045','#6f1f4b','#8d2747','#aa3f4c','#a9513f','#ba663a','#cf8139','#e59f44','#e9bb76']
hex_colors = ['#1d1e4e','#201e4e','#241e4d','#261e4d','#291e4c','#291f4c','#2b1f4c','#2d1f4b','#301f4b','#331f4a','#341f4a','#371f49','#381f49','#3b1f48','#3d1f48','#3d1f48','#3f2047','#402047','#432046','#452046','#462046','#482045','#492045','#4b2045','#4d2046','#4d2046','#502046','#502046','#522047','#532047','#552047','#562047','#572047','#5a2048','#5b2048','#5c2048','#5d2048','#5e2048','#602049','#622049','#632049','#652049','#65204a','#67204a','#69204a','#6b1f4a','#6b1f4a','#6c1f4b','#6f1f4b','#701f4b','#711f4b','#72204b','#72204b','#75204a','#75214a','#76214a','#77214a','#78214a','#7a224a','#7a224a','#7d2249','#7d2249','#7e2349','#7f2349','#802449','#812449','#832448','#842548','#852548','#862548','#882548','#882648','#892648','#8b2647','#8b2747','#8d2747','#8e2847','#8e2847','#902947','#902948','#912a48','#922b48','#932c48','#932c48','#952d48','#952d48','#952e49','#972f49','#973049','#983049','#993149','#9a3249','#9a3249','#9c334a','#9c334a','#9d354a','#9d354a','#9f364a','#9f364a','#a0374a','#a1384a','#a2384b','#a2394b','#a33a4b','#a43a4b','#a43b4b','#a63c4b','#a73c4b','#a83d4c','#a83d4c','#a93e4c','#a93f4c','#aa414b','#aa424a','#aa4349','#aa4448','#aa4747','#aa4846','#a94b44','#a94b43','#a94d43','#a94e41','#a94f40','#a9513f','#a9523f','#aa523f','#ab533e','#ac543e','#ac543e','#ad563e','#ad563e','#ae573e','#ae583e','#af593d','#b05a3d','#b05a3d','#b15b3d','#b15b3d','#b25d3c','#b35d3c','#b35e3c','#b45f3c','#b55f3c','#b5603c','#b6623b','#b6623b','#b7623b','#b8643b','#b9643b','#b9653a','#ba653a','#ba673a','#bb683a','#bb683a','#bc683a','#bd693a','#bd6a3a','#bd6a3a','#be6c3a','#bf6c3a','#c06d3a','#c16e3a','#c16e3a','#c16f3a','#c2713a','#c2713a','#c3723a','#c4733a','#c5743a','#c5753a','#c5753a','#c6753a','#c7773a','#c8773a','#c87939','#c97939','#c97939','#ca7a39','#ca7b39','#cb7c39','#cc7d39','#cc7e39','#cd7e39','#ce7f39','#ce8039','#cf8139','#cf8139','#d08239','#d0833a','#d1843a','#d2843a','#d2853b','#d2863b','#d3873b','#d4883b','#d5883c','#d5893c','#d58a3c','#d68b3c','#d78c3d','#d78d3d','#d88d3d','#d88d3e','#d98f3e','#da8f3e','#da903f','#da913f','#db923f','#dc933f','#dc9340','#dd9340','#dd9440','#de9641','#df9641','#df9741','#e09741','#e09942','#e19942','#e19a42','#e29a42','#e29c43','#e39d43','#e49d43','#e59e44','#e59e44','#e59f45','#e5a047','#e6a149','#e6a24b','#e6a44c','#e6a54e','#e6a650','#e6a652','#e6a652','#e7a754','#e7a855','#e7aa57','#e7ab59','#e7ab5b','#e7ac5d','#e8ae5e','#e8af60','#e8af62','#e8b063','#e8b165','#e8b265','#e8b367','#e8b469','#e8b56b','#e9b66c','#e9b76e','#e9b870','#e9b872','#e9ba73','#e9ba75','#e9bb76']

In [ ]:
hex_colors.index(hex_stops[9])

In [ ]:
years_built

In [ ]:
hex_stops = ['#f7fbff','#deebf7','#c6dbef','#9ecae1','#6baed6','#4292c6','#2171b5','#08519c','#08306b']

In [ ]:
for i in hex_stops:
  print i + ","

In [ ]:
hex_stops = ['#ffffe0','#dcfac5','#b8f4ab','#90ee90','#6dc88c','#46a386','#008080','#265a81','#233381','#000080']
for color in hex_stops:
    rgb_color = HexToRgb(color)
    print "%.4f,%.4f,%.4f" % (rgb_color[0]/255.0, rgb_color[1]/255.0, rgb_color[2]/255.0) 

In [ ]:
hex_stops = ['#1d1e4e','#5f2049','#8c2747','#aa414b','#ba653a','#d0823a','#e5a045','#ebc07f','#f7e0af','#ffffe0']
years = [1880,1895,1910,1925,1940,1955,1970,1985,2000,2015]

In [ ]:
for i in range(0,10):
    print "if (year < %s) {" % (years[i])
    rgb_color = HexToRgb(hex_stops[i])
    print "  color = vec4(%.4f,%.4f,%.4f,1.0)" % (rgb_color[0]/255.0, rgb_color[1]/255.0, rgb_color[2]/255.0)
    print "}"

In [ ]:
len(years)

In [ ]:
hex_colors = ['#ffffe0','#ffeec1','#ffdea7','#ffcb91','#ffb880','#ffa474','#fe906a','#f87d64','#f06a5e','#e75758','#db4551','#cf3447','#c0223b','#b0122c','#9e051b','#8b0000']
img = Image.new( 'RGB', (255,255), "white") # create a new image
pixels = img.load() # create the pixel map
for i in range(img.size[0]):    # for every pixel:
    for j in range(img.size[1]):
        pixels[i,j] = hex_to_rgb(hex_colors[i/16]) # set the colour accordingly
img.show()
img.save("assessments/year-built-color-map.png")



In [ ]:
parcel_colors = ['#e41a1c','#377eb8','#4daf4a','#984ea3','#ff7f00','#ffff33','#a65628']
parcel_colors = ['#fb3059','#fe6b2d','#d1947a','#c6a900','#02ca75','#00a2de','#9529b1']

year_built_colors = ['#ffffe0','#ffeec1','#ffdea7','#ffcb91','#ffb880','#ffa474','#fe906a','#f87d64','#f06a5e','#e75758','#db4551','#cf3447','#c0223b','#b0122c','#9e051b','#8b0000']
year_built_colors = ['#ffffe0','#ffdaa3','#ffb27c','#fb8768','#eb5f5b','#d3394a','#b3152f','#8b0000']
img = Image.new( 'RGB', (255,255), "white") # create a new image
pixels = img.load() # create the pixel map
for i in range(0,len(parcel_colors)):
    pixels[0,i] = HexToRgb(parcel_colors[i]) # set the colour accordingly
j = 0
for i in list(reversed(range(len(year_built_colors)))):
    pixels[1,j] = HexToRgb(year_built_colors[i]) # set the colour accordingly
    j += 1
#img.show()
img.save("assessments/color-map.png")


In [ ]:
class_descriptions = sorted(class_descs.keys())
points = []
array.array('f', points).tofile(open('parcels_class.bin', 'wb'))
    par_id = apd['PARID'][i]
    year_built = apd['YEARBLT'][i]
    class_description = apd['CLASSDESC'][i]   
    if year_built == '' or year_built == '0':
        year_built = '0001' # Null Value, -62135596800.0 Epoch
    if centroids.has_key(par_id):
        centroid = centroids[par_id]
        points += LonLatToPixelXY(centroid)        
        points.append(float(year_built))
        points.append(class_descriptions.index(class_description)+1.0)
array.array('f', points).tofile(open('assessments/parcels_class.bin', 'wb'))


In [ ]:
sorted(class_descs.keys())

In [ ]:
class_descriptions.index('RESIDENTIAL')

In [ ]:
points[10000:10005]

In [ ]:
def scale_year(year):
    if year < 1800.0: 
        year = 1800.0
    return int(((year - 1800.0) * 8.0) / (2016.0-1800.))


In [ ]:
scale_year(1800.0)

In [ ]:
len(year_built_colors)

In [ ]:
j = 0
for i in list(reversed(range(len(year_built_colors)))):
    print '<rect fill="%s" x="%s" height="10" width="25" stroke-width="1px" stroke="#666"></rect>' % (year_built_colors[i],j*25)
    j += 1
    
j = 0
for i in list(reversed(range(len(year_built_colors)))):
    print '<text font-size="10.5px" fill="%s" y="29" x="%s">%s</text>' % (year_built_colors[i], j*25, 1800)
    j += 1


In [ ]:
list(reversed(range(10)))

In [ ]:
len(fairmarket_totals)

In [ ]:
fm_keys = sorted(map(int,fairmarket_totals.keys()))

In [ ]:
numpy.average(fm_keys)

In [ ]:
numpy.mean(fm_keys)

In [ ]:
numpy.std(fm_keys)

In [ ]:
fairmarket_totals['50000']

In [ ]:
parcel_colors = ['#fb3059','#fe6b2d','#d1947a','#c6a900','#02ca75','#00a2de','#9529b1']
year_built_colors = ['#ffffe0','#ffdaa3','#ffb27c','#fb8768','#eb5f5b','#d3394a','#b3152f','#8b0000']
fm_colors = ['#a50026','#cd2827','#e75436','#f7804b','#fdad61','#fed788','#ffffbf','#b9e0ed','#8dc0db','#699fca','#4d7db9','#3e5aa7','#313695'
]

img = Image.new( 'RGB', (255,255), "white") # create a new image
pixels = img.load() # create the pixel map
for i in range(0,len(parcel_colors)):
    pixels[0,i] = HexToRgb(parcel_colors[i]) # set the colour accordingly
j = 0
for i in list(reversed(range(len(year_built_colors)))):
    pixels[1,j] = HexToRgb(year_built_colors[i]) # set the colour accordingly
    j += 1
for i in range(0,len(fm_colors)):
    pixels[2,i] = HexToRgb(fm_colors[i]) # set the colour accordingly
    
#img.show()
img.save("assessments/color-map.png")


In [ ]:
class_descriptions = sorted(class_descs.keys())
points = []
for i in range(0, len(apd.index)):
    par_id = apd['PARID'][i]
    year_built = apd['YEARBLT'][i]
    class_description = apd['CLASSDESC'][i] 
    fm_total = float(apd['FAIRMARKETTOTAL'][i])    
    if year_built == '' or year_built == '0' or year_built == '0000' or math.isnan(year_built):
        year_built = '0001' # Null Value, -62135596800.0 Epoch
    elif isinstance(year_built, numbers.Number):
        if(year_built < 1):
            year_built = '0001' # Null Value, -62135596800.0 Epoch
        else:
            year_built = "%04d" % (year_built)
    if centroids.has_key(par_id):
        centroid = centroids[par_id]
        points += LonLatToPixelXY(centroid)        
        points.append(float(year_built))
        points.append(class_descriptions.index(class_description)+1.0)
        points.append(fm_total)
array.array('f', points).tofile(open(('assessments/parcels_all%s.bin'%out_suffix), 'wb'))


In [ ]:
sorted(class_descs.keys())

In [ ]:
# Below is Anne's attempt to put floating point representations of colors into the .bin file for a new 
# shader Randy's writing

In [ ]:
parcel_colors = ['#fb3059','#fe6b2d','#d1947a','#c6a900','#02ca75','#00a2de','#9529b1']
class_descriptions = sorted(class_descs.keys())

def class_desc_to_color(class_description):
    index = class_descriptions.index(class_description)
    return(parse_color(parcel_colors[index]))

points = []
for i in range(0, len(apd.index)):
    par_id = apd['PARID'][i]
    class_description = apd['CLASSDESC'][i] 
    if centroids.has_key(par_id):
        centroid = centroids[par_id]
        points += LonLatToPixelXY(centroid)        
        points.append(class_desc_to_color(class_description))
array.array('f', points).tofile(open(('assessments/parcels_class_color%s.bin'%out_suffix), 'wb'))

In [ ]:
len(fm_colors)

In [ ]:
fairmarket_totals['0']

In [ ]:
plt.plot(map(int,fairmarket_totals.keys()), fairmarket_totals.values(), 'ro')
plt.show()

In [ ]:
fm_keys[len(fm_keys) - 100:len(fm_keys)]

In [ ]:
fm_values = ["0", "25K", "50K", "75K", "100K", "125K", "150K", "200K", "250K", "300K", "400K", "500K", "+500K"]
for i in range(len(fm_colors)):
    print '<rect fill="%s" x="%s" height="10" width="30"></rect>' % (fm_colors[i],i*30)
    
for i in range(len(fm_values)):
    print '<text font-size="10.5px" y="29" x="%s">%s</text>' % (i*30, fm_values[i])
